In [1]:
import numpy as np
import xgboost as xgb
import pandas as pd
from IPython.display import display #方便对数据进行可视化
import time
import datetime

根据评审的意见，改良训练集和验证集的划分方式，按照时间进行划分

In [82]:
#训练数据中，数据是从2013-1-1到2015-7-31，跨度是

d1 = datetime.datetime(2015,7,31)
d2 = datetime.datetime(2013,1,1)
print((d1 - d2).days)

941


In [83]:
#选取后20%的天数作为验证集
day = datetime.timedelta(days = int(941 * 0.2))

print(day)
print(d1 - day)

188 days, 0:00:00
2015-01-24 00:00:00


所以我们使用2015/1/24-2015/7/31的日期作为验证集。

In [84]:
#从头开始处理数据

# 导入训练数据
train_data = pd.read_csv(
    "train.csv", 
    low_memory=False)

store_features = pd.read_csv("store.csv")
# 导入测试数据
test_data = pd.read_csv("test.csv")



In [85]:
#此处增加一步，先将验证集划分出来
#打开数据文件，很容易找到，2015/1/24-2015/7/31时间范围内的数据编号为1 - 210736

val_data = train_data[: 210735]
print(val_data['Store'][210734])


display(val_data.head(n=1))


1115


Store  DayOfWeek        Date  Sales  Customers  Open  Promo StateHoliday  \
0      1          5  2015-07-31   5263        555     1      1            0   

   SchoolHoliday  
0              1

In [86]:
train_data = train_data[210735:]
display(train_data.head(n=1))

Store  DayOfWeek        Date  Sales  Customers  Open  Promo  \
210735      1          5  2015-01-23   3586        489     1      0   

       StateHoliday  SchoolHoliday  
210735            0              0

In [87]:
#融合
train_data = pd.merge(train_data, store_features, on = 'Store')
val_data = pd.merge(val_data, store_features, on = 'Store')
test_data = pd.merge(test_data, store_features, on = 'Store')

train_data = train_data.drop('Customers', axis = 1)
sales_train = train_data['Sales']
features_train = train_data.drop('Sales', axis = 1)

val_data = val_data.drop('Customers', axis = 1)
sales_val = val_data['Sales']
features_val = val_data.drop('Sales', axis = 1)

features_test = test_data.drop('Id', axis = 1)

# 对字符串特征进行独热编码
category = ['StoreType', 'Assortment', 'PromoInterval', 'StateHoliday']


#首先将训练集、验证集、测试集合并，然后统一独热编码，然后再拆分为训练集、验证集、测试集

print('合并前：')
print(features_train.shape[0])
print(features_val.shape[0])
print(features_test.shape[0])

data_merge = pd.concat([features_train, features_val], ignore_index = True)
data_merge = pd.concat([data_merge, features_test], ignore_index = True)
data_merge_pd = pd.get_dummies(data_merge, columns = category)

# 需要把NA/NAN的数据转化成0
data_merge_pd.fillna(0, inplace = True)


#增加一步，增加‘Year', 'month', 'day'三个有序分类数据

data_merge_pd['year'] = data_merge_pd['Date'].apply(lambda x: float(x.split('-')[0]))
data_merge_pd['month'] = data_merge_pd['Date'].apply(lambda x: float(x.split('-')[1]))
data_merge_pd['day'] = data_merge_pd['Date'].apply(lambda x: float(x.split('-')[2]))
data_merge_pd = data_merge_pd.drop('Date', axis = 1)


#拆分

features_train = data_merge_pd[ : features_train.shape[0]]
features_val = data_merge_pd[features_train.shape[0] : (features_val.shape[0] + features_train.shape[0])]
features_test = data_merge_pd[ (features_val.shape[0] + features_train.shape[0]) : ]

print('合并后：')
print(features_train.shape[0])
print(features_val.shape[0])
print(features_test.shape[0])



#下面将sales做log处理

sales_train_log = np.log(sales_train + 1) #+1是为了避免log（0）的情况同时使得数据从0开始
sales_val_log = np.log(sales_val + 1)



合并前：
806474
210735
41088
合并后：
806474
210735
41088


In [88]:
display(features_train.head(n=1))
display(features_val.head(n=1))

Store  DayOfWeek  Open  Promo  SchoolHoliday  CompetitionDistance  \
0      1          5   1.0      0              0               1270.0   

   CompetitionOpenSinceMonth  CompetitionOpenSinceYear  Promo2  \
0                        9.0                    2008.0       0   

   Promo2SinceWeek  Promo2SinceYear  StoreType_a  StoreType_b  StoreType_c  \
0              0.0              0.0            0            0            1   

   StoreType_d  Assortment_a  Assortment_b  Assortment_c  \
0            0             1             0             0   

   PromoInterval_Feb,May,Aug,Nov  PromoInterval_Jan,Apr,Jul,Oct  \
0                              0                              0   

   PromoInterval_Mar,Jun,Sept,Dec  StateHoliday_0  StateHoliday_a  \
0                               0               1               0   

   StateHoliday_b  StateHoliday_c    year  month   day  
0               0               0  2015.0    1.0  23.0

Store  DayOfWeek  Open  Promo  SchoolHoliday  CompetitionDistance  \
806474      1          5   1.0      1              1               1270.0   

        CompetitionOpenSinceMonth  CompetitionOpenSinceYear  Promo2  \
806474                        9.0                    2008.0       0   

        Promo2SinceWeek  Promo2SinceYear  StoreType_a  StoreType_b  \
806474              0.0              0.0            0            0   

        StoreType_c  StoreType_d  Assortment_a  Assortment_b  Assortment_c  \
806474            1            0             1             0             0   

        PromoInterval_Feb,May,Aug,Nov  PromoInterval_Jan,Apr,Jul,Oct  \
806474                              0                              0   

        PromoInterval_Mar,Jun,Sept,Dec  StateHoliday_0  StateHoliday_a  \
806474                               0               1               0   

        StateHoliday_b  StateHoliday_c    year  month   day  
806474               0               0  2015.0    7.0  31.0

In [89]:
dtrain = xgb.DMatrix(features_train, label = sales_train_log)
dval = xgb.DMatrix(features_val, label = sales_val_log)

In [111]:
def rmspe(y, y_hat):
    #由于sales取了对数，这里要还原
    y = np.exp(y) - 1
    y_hat = np.exp(y_hat) - 1
    
    #由于有yi=0的情况，直接计算会得出无穷大的结果，所以需要处理一下
    #定义一个y_rev来表示y的倒数，y为0时y_rev也赋值为0（因为在项目中提到“ Any day and store with 0 sales is ignored in scoring.“）
    y_rev = np.zeros(y.shape, dtype = float)
    n_zero = y != 0
    y_rev[n_zero] = 1./y[n_zero]

    rmspe = np.sqrt(np.mean(((y - y_hat)*y_rev)**2))
    return rmspe


#自定义一个评价函数

def rmspe_feval(y_hat, dy):
    y = dy.get_label()
    rmspe_score = rmspe(y, y_hat)
    return 'rmspe', rmspe_score
#定义训练函数
def train(param, dtrain, dval, num_round, feval_c):
    train_time = time.clock()

    model = xgb.train(
        param, dtrain, num_round, feval = feval_c, 
        evals = [(dtrain, 'train'), (dval, 'val')], early_stopping_rounds = 100, 
        verbose_eval = True
    )

    train_time = time.clock() - train_time

    print('The training time of the model is: {:.0f}s'.format(train_time))
    
    return model

#定义一个打分函数
def score(bst, dval):
    y_pred = bst.predict(dval)
#print(y_pred)
    y_val = dval.get_label()
    score = rmspe(y_val, y_pred)
#print(score)
    print('The rmspe of the model on validation data set is {:.6f}'.format(score))
    pass

首先设定较高的eta和较低的迭代次数num_round进行调参，首先找出0.3的eta下最佳迭代次数

In [94]:
#设定参数
param = {'max_depth': 10, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear','min_child_weight': 6,'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 1000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)





[0]	train-rmse:5.27598	val-rmse:5.31696	train-rmspe:0.908052	val-rmspe:0.908712
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:3.69966	val-rmse:3.74083	train-rmspe:0.894064	val-rmspe:0.895385
[2]	train-rmse:2.59856	val-rmse:2.63782	train-rmspe:0.854432	val-rmspe:0.857476
[3]	train-rmse:1.83109	val-rmse:1.86723	train-rmspe:0.780169	val-rmspe:0.785965
[4]	train-rmse:1.29628	val-rmse:1.33087	train-rmspe:0.677827	val-rmspe:0.687088
[5]	train-rmse:0.928176	val-rmse:0.959815	train-rmspe:0.564252	val-rmspe:0.575789
[6]	train-rmse:0.679678	val-rmse:0.708023	train-rmspe:0.459955	val-rmspe:0.471941
[7]	train-rmse:0.510429	val-rmse:0.535935	train-rmspe:0.37578	val-rmspe:0.386088
[8]	train-rmse:0.400413	val-rmse:0.421188	train-rmspe:0.319104	val-rmspe:0.324257
[9]	train-rmse:0.333316	val-rmse:0.349778	train-rmspe:0.287825	val-rmspe:0.286766
[10]	train-rmse:0.291589	val-rmse:0.304815	trai

[98]	train-rmse:0.109856	val-rmse:0.139394	train-rmspe:0.144567	val-rmspe:0.148848
[99]	train-rmse:0.109514	val-rmse:0.139407	train-rmspe:0.144223	val-rmspe:0.148821
[100]	train-rmse:0.109282	val-rmse:0.139436	train-rmspe:0.144609	val-rmspe:0.148793
[101]	train-rmse:0.109044	val-rmse:0.139297	train-rmspe:0.144626	val-rmspe:0.148224
[102]	train-rmse:0.108507	val-rmse:0.139934	train-rmspe:0.144247	val-rmspe:0.148499
[103]	train-rmse:0.108325	val-rmse:0.139875	train-rmspe:0.144076	val-rmspe:0.148487
[104]	train-rmse:0.107885	val-rmse:0.139749	train-rmspe:0.143675	val-rmspe:0.148265
[105]	train-rmse:0.107497	val-rmse:0.139573	train-rmspe:0.143403	val-rmspe:0.14812
[106]	train-rmse:0.10727	val-rmse:0.139819	train-rmspe:0.14294	val-rmspe:0.148275
[107]	train-rmse:0.107131	val-rmse:0.13973	train-rmspe:0.142238	val-rmspe:0.148219
[108]	train-rmse:0.106886	val-rmse:0.139706	train-rmspe:0.142091	val-rmspe:0.148103
[109]	train-rmse:0.106737	val-rmse:0.139625	train-rmspe:0.141957	val-rmspe:0.14804

[197]	train-rmse:0.091779	val-rmse:0.140493	train-rmspe:0.118152	val-rmspe:0.146218
[198]	train-rmse:0.091644	val-rmse:0.140605	train-rmspe:0.117737	val-rmspe:0.146281
[199]	train-rmse:0.091536	val-rmse:0.140678	train-rmspe:0.117549	val-rmspe:0.146378
[200]	train-rmse:0.091378	val-rmse:0.140795	train-rmspe:0.117467	val-rmspe:0.146359
[201]	train-rmse:0.091325	val-rmse:0.140759	train-rmspe:0.11741	val-rmspe:0.146324
[202]	train-rmse:0.091273	val-rmse:0.140748	train-rmspe:0.117366	val-rmspe:0.146302
[203]	train-rmse:0.091171	val-rmse:0.140757	train-rmspe:0.117243	val-rmspe:0.14627
[204]	train-rmse:0.091101	val-rmse:0.140729	train-rmspe:0.117196	val-rmspe:0.146269
[205]	train-rmse:0.091076	val-rmse:0.140648	train-rmspe:0.117183	val-rmspe:0.146175
[206]	train-rmse:0.091021	val-rmse:0.140631	train-rmspe:0.117157	val-rmspe:0.146212
[207]	train-rmse:0.090889	val-rmse:0.140681	train-rmspe:0.117105	val-rmspe:0.146287
[208]	train-rmse:0.090647	val-rmse:0.140739	train-rmspe:0.116857	val-rmspe:0.1

首先调整‘min_child_weight'参数

In [95]:
#设定参数
param = {'max_depth': 10, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear','min_child_weight': 7,'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 167
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)






[0]	train-rmse:5.27598	val-rmse:5.31696	train-rmspe:0.908052	val-rmspe:0.908712
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:3.69966	val-rmse:3.74083	train-rmspe:0.894064	val-rmspe:0.895385
[2]	train-rmse:2.59856	val-rmse:2.63782	train-rmspe:0.854432	val-rmspe:0.857476
[3]	train-rmse:1.83109	val-rmse:1.86723	train-rmspe:0.780169	val-rmspe:0.785965
[4]	train-rmse:1.29628	val-rmse:1.33087	train-rmspe:0.677827	val-rmspe:0.687088
[5]	train-rmse:0.928176	val-rmse:0.959815	train-rmspe:0.564251	val-rmspe:0.575789
[6]	train-rmse:0.67968	val-rmse:0.707966	train-rmspe:0.459956	val-rmspe:0.471923
[7]	train-rmse:0.510431	val-rmse:0.53586	train-rmspe:0.375781	val-rmspe:0.386057
[8]	train-rmse:0.400471	val-rmse:0.421148	train-rmspe:0.319132	val-rmspe:0.324219
[9]	train-rmse:0.333385	val-rmse:0.349746	train-rmspe:0.287873	val-rmspe:0.286731
[10]	train-rmse:0.293345	val-rmse:0.306599	train

[98]	train-rmse:0.110421	val-rmse:0.139431	train-rmspe:0.142451	val-rmspe:0.148795
[99]	train-rmse:0.11002	val-rmse:0.139335	train-rmspe:0.142078	val-rmspe:0.148707
[100]	train-rmse:0.109723	val-rmse:0.139171	train-rmspe:0.141861	val-rmspe:0.148481
[101]	train-rmse:0.109496	val-rmse:0.13929	train-rmspe:0.141682	val-rmspe:0.14844
[102]	train-rmse:0.109052	val-rmse:0.139472	train-rmspe:0.141355	val-rmspe:0.148792
[103]	train-rmse:0.108834	val-rmse:0.139417	train-rmspe:0.141089	val-rmspe:0.148737
[104]	train-rmse:0.10858	val-rmse:0.139407	train-rmspe:0.14064	val-rmspe:0.148704
[105]	train-rmse:0.108243	val-rmse:0.139253	train-rmspe:0.140455	val-rmspe:0.148517
[106]	train-rmse:0.108055	val-rmse:0.139284	train-rmspe:0.140368	val-rmspe:0.14837
[107]	train-rmse:0.107702	val-rmse:0.139399	train-rmspe:0.140144	val-rmspe:0.148463
[108]	train-rmse:0.107225	val-rmse:0.13962	train-rmspe:0.139499	val-rmspe:0.148649
[109]	train-rmse:0.107094	val-rmse:0.139538	train-rmspe:0.139355	val-rmspe:0.148612
[

In [96]:
#设定参数
param = {'max_depth': 10, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear','min_child_weight': 5,'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 167
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)





[0]	train-rmse:5.27598	val-rmse:5.31696	train-rmspe:0.908052	val-rmspe:0.908712
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:3.69966	val-rmse:3.74083	train-rmspe:0.894064	val-rmspe:0.895385
[2]	train-rmse:2.59856	val-rmse:2.63782	train-rmspe:0.854432	val-rmspe:0.857476
[3]	train-rmse:1.83109	val-rmse:1.86723	train-rmspe:0.780169	val-rmspe:0.785965
[4]	train-rmse:1.29628	val-rmse:1.33087	train-rmspe:0.677827	val-rmspe:0.687088
[5]	train-rmse:0.928176	val-rmse:0.959816	train-rmspe:0.564251	val-rmspe:0.57579
[6]	train-rmse:0.679678	val-rmse:0.708023	train-rmspe:0.459954	val-rmspe:0.471941
[7]	train-rmse:0.510429	val-rmse:0.535936	train-rmspe:0.375777	val-rmspe:0.386089
[8]	train-rmse:0.400421	val-rmse:0.421209	train-rmspe:0.319106	val-rmspe:0.324272
[9]	train-rmse:0.333326	val-rmse:0.349809	train-rmspe:0.287826	val-rmspe:0.286788
[10]	train-rmse:0.293265	val-rmse:0.30661	train

[98]	train-rmse:0.110095	val-rmse:0.13954	train-rmspe:0.140465	val-rmspe:0.146048
[99]	train-rmse:0.109674	val-rmse:0.139437	train-rmspe:0.137567	val-rmspe:0.145854
[100]	train-rmse:0.109408	val-rmse:0.139214	train-rmspe:0.137315	val-rmspe:0.145527
[101]	train-rmse:0.109172	val-rmse:0.139048	train-rmspe:0.137069	val-rmspe:0.145414
[102]	train-rmse:0.108954	val-rmse:0.139027	train-rmspe:0.135422	val-rmspe:0.145186
[103]	train-rmse:0.108644	val-rmse:0.13891	train-rmspe:0.135206	val-rmspe:0.145051
[104]	train-rmse:0.108312	val-rmse:0.138805	train-rmspe:0.134824	val-rmspe:0.144987
[105]	train-rmse:0.10807	val-rmse:0.138782	train-rmspe:0.134526	val-rmspe:0.144985
[106]	train-rmse:0.10777	val-rmse:0.138721	train-rmspe:0.134292	val-rmspe:0.144919
[107]	train-rmse:0.107594	val-rmse:0.138708	train-rmspe:0.133932	val-rmspe:0.144751
[108]	train-rmse:0.107342	val-rmse:0.138779	train-rmspe:0.133819	val-rmspe:0.144694
[109]	train-rmse:0.107141	val-rmse:0.138696	train-rmspe:0.133596	val-rmspe:0.14456

In [97]:
#设定参数
param = {'max_depth': 10, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear','min_child_weight': 4,'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 167
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)






[0]	train-rmse:5.27598	val-rmse:5.31696	train-rmspe:0.908052	val-rmspe:0.908712
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:3.69966	val-rmse:3.74083	train-rmspe:0.894064	val-rmspe:0.895385
[2]	train-rmse:2.59856	val-rmse:2.63782	train-rmspe:0.854432	val-rmspe:0.857476
[3]	train-rmse:1.83109	val-rmse:1.86723	train-rmspe:0.780169	val-rmspe:0.785965
[4]	train-rmse:1.29628	val-rmse:1.33087	train-rmspe:0.677827	val-rmspe:0.687088
[5]	train-rmse:0.928176	val-rmse:0.959817	train-rmspe:0.564251	val-rmspe:0.57579
[6]	train-rmse:0.679677	val-rmse:0.708021	train-rmspe:0.459954	val-rmspe:0.47194
[7]	train-rmse:0.510428	val-rmse:0.535934	train-rmspe:0.375778	val-rmspe:0.386088
[8]	train-rmse:0.400412	val-rmse:0.421221	train-rmspe:0.319108	val-rmspe:0.324276
[9]	train-rmse:0.333289	val-rmse:0.349824	train-rmspe:0.287827	val-rmspe:0.286793
[10]	train-rmse:0.293217	val-rmse:0.306624	train

[98]	train-rmse:0.108869	val-rmse:0.142153	train-rmspe:0.148028	val-rmspe:0.151368
[99]	train-rmse:0.108438	val-rmse:0.14223	train-rmspe:0.147853	val-rmspe:0.151355
[100]	train-rmse:0.108249	val-rmse:0.142127	train-rmspe:0.147957	val-rmspe:0.151244
[101]	train-rmse:0.10808	val-rmse:0.142046	train-rmspe:0.147602	val-rmspe:0.151028
[102]	train-rmse:0.107889	val-rmse:0.142024	train-rmspe:0.146557	val-rmspe:0.151005
[103]	train-rmse:0.107727	val-rmse:0.141955	train-rmspe:0.146369	val-rmspe:0.150942
[104]	train-rmse:0.107601	val-rmse:0.141919	train-rmspe:0.146255	val-rmspe:0.151238
[105]	train-rmse:0.107439	val-rmse:0.141865	train-rmspe:0.14753	val-rmspe:0.151141
[106]	train-rmse:0.107042	val-rmse:0.141971	train-rmspe:0.147362	val-rmspe:0.151068
[107]	train-rmse:0.106824	val-rmse:0.142205	train-rmspe:0.146614	val-rmspe:0.151261
[108]	train-rmse:0.106597	val-rmse:0.142097	train-rmspe:0.14651	val-rmspe:0.151201
[109]	train-rmse:0.106212	val-rmse:0.141921	train-rmspe:0.14575	val-rmspe:0.150212

‘min_child_weight'参数的最佳取值是：5

下面调整参数‘colsample_bytree'

In [98]:
#设定参数
param = {'max_depth': 10, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear','min_child_weight': 5,'colsample_bytree': 0.7, 'subsample':0.9}

#设定迭代次数

num_round = 167
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)



[0]	train-rmse:5.27605	val-rmse:5.31705	train-rmspe:0.90805	val-rmspe:0.908711
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:3.69995	val-rmse:3.74085	train-rmspe:0.894035	val-rmspe:0.895352
[2]	train-rmse:2.60367	val-rmse:2.64002	train-rmspe:0.854616	val-rmspe:0.857564
[3]	train-rmse:1.83467	val-rmse:1.86909	train-rmspe:0.780487	val-rmspe:0.786106
[4]	train-rmse:1.30119	val-rmse:1.33362	train-rmspe:0.677751	val-rmspe:0.686478
[5]	train-rmse:0.932518	val-rmse:0.961708	train-rmspe:0.564322	val-rmspe:0.575094
[6]	train-rmse:0.689988	val-rmse:0.73264	train-rmspe:0.46209	val-rmspe:0.479982
[7]	train-rmse:0.517142	val-rmse:0.558143	train-rmspe:0.377657	val-rmspe:0.395326
[8]	train-rmse:0.408094	val-rmse:0.44538	train-rmspe:0.321993	val-rmspe:0.335782
[9]	train-rmse:0.336994	val-rmse:0.371441	train-rmspe:0.288151	val-rmspe:0.296683
[10]	train-rmse:0.298074	val-rmse:0.328202	train-r

[98]	train-rmse:0.113604	val-rmse:0.160204	train-rmspe:0.144863	val-rmspe:0.159751
[99]	train-rmse:0.113213	val-rmse:0.159933	train-rmspe:0.144605	val-rmspe:0.159473
[100]	train-rmse:0.112919	val-rmse:0.159767	train-rmspe:0.144388	val-rmspe:0.159304
[101]	train-rmse:0.112716	val-rmse:0.160175	train-rmspe:0.143884	val-rmspe:0.159066
[102]	train-rmse:0.112391	val-rmse:0.160281	train-rmspe:0.143722	val-rmspe:0.159232
[103]	train-rmse:0.112042	val-rmse:0.160078	train-rmspe:0.143502	val-rmspe:0.159054
[104]	train-rmse:0.111726	val-rmse:0.160163	train-rmspe:0.140515	val-rmspe:0.158992
[105]	train-rmse:0.111359	val-rmse:0.159944	train-rmspe:0.140235	val-rmspe:0.158777
[106]	train-rmse:0.111266	val-rmse:0.159943	train-rmspe:0.140173	val-rmspe:0.158782
[107]	train-rmse:0.11112	val-rmse:0.159904	train-rmspe:0.140056	val-rmspe:0.158731
[108]	train-rmse:0.110868	val-rmse:0.15981	train-rmspe:0.139864	val-rmspe:0.158715
[109]	train-rmse:0.110581	val-rmse:0.159717	train-rmspe:0.139579	val-rmspe:0.158

In [99]:
#设定参数
param = {'max_depth': 10, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear','min_child_weight': 5,'colsample_bytree': 0.9, 'subsample':0.9}

#设定迭代次数

num_round = 167
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)




[0]	train-rmse:5.27591	val-rmse:5.31519	train-rmspe:0.908053	val-rmspe:0.908705
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:3.69958	val-rmse:3.73995	train-rmspe:0.894075	val-rmspe:0.895377
[2]	train-rmse:2.59856	val-rmse:2.63609	train-rmspe:0.854445	val-rmspe:0.857403
[3]	train-rmse:1.83001	val-rmse:1.86584	train-rmspe:0.780493	val-rmspe:0.786276
[4]	train-rmse:1.29634	val-rmse:1.33	train-rmspe:0.677908	val-rmspe:0.68681
[5]	train-rmse:0.927825	val-rmse:0.956109	train-rmspe:0.564554	val-rmspe:0.574665
[6]	train-rmse:0.678686	val-rmse:0.706302	train-rmspe:0.460183	val-rmspe:0.470948
[7]	train-rmse:0.509599	val-rmse:0.53422	train-rmspe:0.376871	val-rmspe:0.384918
[8]	train-rmse:0.401976	val-rmse:0.421901	train-rmspe:0.321429	val-rmspe:0.323313
[9]	train-rmse:0.33191	val-rmse:0.348543	train-rmspe:0.291073	val-rmspe:0.284306
[10]	train-rmse:0.294506	val-rmse:0.307135	train-rms

[98]	train-rmse:0.107892	val-rmse:0.140162	train-rmspe:0.13737	val-rmspe:0.149333
[99]	train-rmse:0.107666	val-rmse:0.140132	train-rmspe:0.137003	val-rmspe:0.149216
[100]	train-rmse:0.107121	val-rmse:0.139852	train-rmspe:0.136525	val-rmspe:0.14899
[101]	train-rmse:0.106855	val-rmse:0.139686	train-rmspe:0.136299	val-rmspe:0.148828
[102]	train-rmse:0.106395	val-rmse:0.139552	train-rmspe:0.135895	val-rmspe:0.148609
[103]	train-rmse:0.106248	val-rmse:0.139488	train-rmspe:0.135431	val-rmspe:0.148581
[104]	train-rmse:0.105816	val-rmse:0.13919	train-rmspe:0.13498	val-rmspe:0.148181
[105]	train-rmse:0.105649	val-rmse:0.139102	train-rmspe:0.134834	val-rmspe:0.147712
[106]	train-rmse:0.10516	val-rmse:0.139497	train-rmspe:0.13373	val-rmspe:0.148005
[107]	train-rmse:0.104865	val-rmse:0.139555	train-rmspe:0.13335	val-rmspe:0.148108
[108]	train-rmse:0.104563	val-rmse:0.13955	train-rmspe:0.133208	val-rmspe:0.147962
[109]	train-rmse:0.104451	val-rmse:0.13953	train-rmspe:0.13308	val-rmspe:0.147962
[110

‘colsample_bytree'最佳取值是0.8

下面调整参数'subsample'

In [100]:
#设定参数
param = {'max_depth': 10, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear','min_child_weight': 5,'colsample_bytree': 0.8, 'subsample':1.0}

#设定迭代次数

num_round = 167
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)





[0]	train-rmse:5.27515	val-rmse:5.31457	train-rmspe:0.908069	val-rmspe:0.908723
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:3.69956	val-rmse:3.73716	train-rmspe:0.894064	val-rmspe:0.895316
[2]	train-rmse:2.59927	val-rmse:2.63542	train-rmspe:0.854285	val-rmspe:0.857144
[3]	train-rmse:1.8313	val-rmse:1.86827	train-rmspe:0.780145	val-rmspe:0.786051
[4]	train-rmse:1.29742	val-rmse:1.3332	train-rmspe:0.677677	val-rmspe:0.687204
[5]	train-rmse:0.928421	val-rmse:0.962576	train-rmspe:0.5643	val-rmspe:0.577129
[6]	train-rmse:0.678216	val-rmse:0.707382	train-rmspe:0.459474	val-rmspe:0.472208
[7]	train-rmse:0.512258	val-rmse:0.538848	train-rmspe:0.377466	val-rmspe:0.388532
[8]	train-rmse:0.403052	val-rmse:0.42457	train-rmspe:0.322205	val-rmspe:0.327813
[9]	train-rmse:0.332601	val-rmse:0.350161	train-rmspe:0.288669	val-rmspe:0.288407
[10]	train-rmse:0.292955	val-rmse:0.307389	train-rm

[98]	train-rmse:0.110099	val-rmse:0.138374	train-rmspe:0.126864	val-rmspe:0.146874
[99]	train-rmse:0.109958	val-rmse:0.138323	train-rmspe:0.126709	val-rmspe:0.146824
[100]	train-rmse:0.10989	val-rmse:0.138332	train-rmspe:0.125343	val-rmspe:0.14687
[101]	train-rmse:0.109743	val-rmse:0.138428	train-rmspe:0.12522	val-rmspe:0.146841
[102]	train-rmse:0.109503	val-rmse:0.138427	train-rmspe:0.125067	val-rmspe:0.146833
[103]	train-rmse:0.109297	val-rmse:0.138292	train-rmspe:0.124842	val-rmspe:0.146694
[104]	train-rmse:0.108931	val-rmse:0.138183	train-rmspe:0.124544	val-rmspe:0.146574
[105]	train-rmse:0.108844	val-rmse:0.138442	train-rmspe:0.122243	val-rmspe:0.146848
[106]	train-rmse:0.108543	val-rmse:0.138342	train-rmspe:0.121999	val-rmspe:0.146802
[107]	train-rmse:0.108211	val-rmse:0.138194	train-rmspe:0.121715	val-rmspe:0.146596
[108]	train-rmse:0.107911	val-rmse:0.138062	train-rmspe:0.121272	val-rmspe:0.146492
[109]	train-rmse:0.107594	val-rmse:0.137921	train-rmspe:0.120973	val-rmspe:0.1463

In [101]:
#设定参数
param = {'max_depth': 10, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear','min_child_weight': 5,'colsample_bytree': 0.8, 'subsample':0.8}

#设定迭代次数

num_round = 167
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)






[0]	train-rmse:5.27612	val-rmse:5.31709	train-rmspe:0.908052	val-rmspe:0.908713
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:3.69981	val-rmse:3.74053	train-rmspe:0.894066	val-rmspe:0.89538
[2]	train-rmse:2.59865	val-rmse:2.63711	train-rmspe:0.854436	val-rmspe:0.857446
[3]	train-rmse:1.83106	val-rmse:1.8673	train-rmspe:0.780226	val-rmspe:0.786033
[4]	train-rmse:1.29707	val-rmse:1.3312	train-rmspe:0.677762	val-rmspe:0.686885
[5]	train-rmse:0.928779	val-rmse:0.958537	train-rmspe:0.564449	val-rmspe:0.575299
[6]	train-rmse:0.679876	val-rmse:0.707382	train-rmspe:0.460522	val-rmspe:0.47204
[7]	train-rmse:0.511049	val-rmse:0.53461	train-rmspe:0.378353	val-rmspe:0.386929
[8]	train-rmse:0.403829	val-rmse:0.422829	train-rmspe:0.324251	val-rmspe:0.327405
[9]	train-rmse:0.337541	val-rmse:0.352909	train-rmspe:0.294715	val-rmspe:0.291882
[10]	train-rmse:0.295459	val-rmse:0.307952	train-rm

[98]	train-rmse:0.11046	val-rmse:0.14217	train-rmspe:0.146496	val-rmspe:0.15462
[99]	train-rmse:0.110106	val-rmse:0.142368	train-rmspe:0.146318	val-rmspe:0.15475
[100]	train-rmse:0.109945	val-rmse:0.142385	train-rmspe:0.146306	val-rmspe:0.154768
[101]	train-rmse:0.109652	val-rmse:0.142305	train-rmspe:0.146122	val-rmspe:0.154652
[102]	train-rmse:0.109355	val-rmse:0.14217	train-rmspe:0.145859	val-rmspe:0.154502
[103]	train-rmse:0.108978	val-rmse:0.142054	train-rmspe:0.145651	val-rmspe:0.154376
[104]	train-rmse:0.108604	val-rmse:0.142004	train-rmspe:0.145056	val-rmspe:0.15438
[105]	train-rmse:0.108286	val-rmse:0.141888	train-rmspe:0.144864	val-rmspe:0.154191
[106]	train-rmse:0.107961	val-rmse:0.142306	train-rmspe:0.143529	val-rmspe:0.154409
[107]	train-rmse:0.107776	val-rmse:0.142231	train-rmspe:0.143289	val-rmspe:0.154357
[108]	train-rmse:0.107547	val-rmse:0.142266	train-rmspe:0.14313	val-rmspe:0.154377
[109]	train-rmse:0.107134	val-rmse:0.142069	train-rmspe:0.142434	val-rmspe:0.153716
[

'subsample'最佳值是0.9

下面调整max_depth

In [104]:
#设定参数
param = {'max_depth': 9, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear','min_child_weight': 5,'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 167
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)







[0]	train-rmse:5.27619	val-rmse:5.31712	train-rmspe:0.908045	val-rmspe:0.908706
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:3.7001	val-rmse:3.74082	train-rmspe:0.894015	val-rmspe:0.895331
[2]	train-rmse:2.59941	val-rmse:2.63744	train-rmspe:0.854256	val-rmspe:0.85725
[3]	train-rmse:1.83183	val-rmse:1.86896	train-rmspe:0.779967	val-rmspe:0.78596
[4]	train-rmse:1.29878	val-rmse:1.33229	train-rmspe:0.677277	val-rmspe:0.686354
[5]	train-rmse:0.931955	val-rmse:0.963391	train-rmspe:0.564036	val-rmspe:0.575538
[6]	train-rmse:0.685541	val-rmse:0.713621	train-rmspe:0.461057	val-rmspe:0.472792
[7]	train-rmse:0.519074	val-rmse:0.543941	train-rmspe:0.379899	val-rmspe:0.389171
[8]	train-rmse:0.410753	val-rmse:0.431779	train-rmspe:0.327	val-rmspe:0.330462
[9]	train-rmse:0.346038	val-rmse:0.361407	train-rmspe:0.299492	val-rmspe:0.29583
[10]	train-rmse:0.30653	val-rmse:0.317907	train-rmspe

[98]	train-rmse:0.120003	val-rmse:0.144297	train-rmspe:0.162256	val-rmspe:0.152252
[99]	train-rmse:0.119815	val-rmse:0.144181	train-rmspe:0.162129	val-rmspe:0.152012
[100]	train-rmse:0.119599	val-rmse:0.144073	train-rmspe:0.162015	val-rmspe:0.151923
[101]	train-rmse:0.119419	val-rmse:0.144115	train-rmspe:0.161888	val-rmspe:0.151718
[102]	train-rmse:0.118884	val-rmse:0.144828	train-rmspe:0.160454	val-rmspe:0.152861
[103]	train-rmse:0.118405	val-rmse:0.144596	train-rmspe:0.15995	val-rmspe:0.152621
[104]	train-rmse:0.118092	val-rmse:0.144476	train-rmspe:0.159719	val-rmspe:0.152505
[105]	train-rmse:0.117804	val-rmse:0.144058	train-rmspe:0.159481	val-rmspe:0.152186
[106]	train-rmse:0.117538	val-rmse:0.144003	train-rmspe:0.159386	val-rmspe:0.151988
[107]	train-rmse:0.117265	val-rmse:0.143816	train-rmspe:0.159247	val-rmspe:0.15184
[108]	train-rmse:0.116944	val-rmse:0.14374	train-rmspe:0.159123	val-rmspe:0.151843
[109]	train-rmse:0.116776	val-rmse:0.143629	train-rmspe:0.158999	val-rmspe:0.1517

最佳‘max_depth'是10

下面找到最佳eta

In [102]:
#设定参数
param = {'max_depth': 10, 'eta': 0.01, 'silent': 0, 'objective': 'reg:linear','min_child_weight': 5,'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)







[0]	train-rmse:7.45325	val-rmse:7.49103	train-rmspe:0.910839	val-rmspe:0.911369
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:7.37887	val-rmse:7.41671	train-rmspe:0.910815	val-rmspe:0.911346
[2]	train-rmse:7.30523	val-rmse:7.34312	train-rmspe:0.910789	val-rmspe:0.911321
[3]	train-rmse:7.23233	val-rmse:7.27025	train-rmspe:0.910762	val-rmspe:0.911295
[4]	train-rmse:7.16016	val-rmse:7.19811	train-rmspe:0.910732	val-rmspe:0.911266
[5]	train-rmse:7.08871	val-rmse:7.12668	train-rmspe:0.910701	val-rmspe:0.911236
[6]	train-rmse:7.01838	val-rmse:7.05624	train-rmspe:0.910667	val-rmspe:0.911204
[7]	train-rmse:6.94835	val-rmse:6.98612	train-rmspe:0.910631	val-rmspe:0.911169
[8]	train-rmse:6.87902	val-rmse:6.9167	train-rmspe:0.910592	val-rmspe:0.911132
[9]	train-rmse:6.81039	val-rmse:6.84811	train-rmspe:0.910551	val-rmspe:0.911093
[10]	train-rmse:6.74274	val-rmse:6.78115	train-rmspe:0.91

[101]	train-rmse:2.72647	val-rmse:2.77589	train-rmspe:0.86193	val-rmspe:0.865146
[102]	train-rmse:2.69952	val-rmse:2.74892	train-rmspe:0.860462	val-rmspe:0.863755
[103]	train-rmse:2.67285	val-rmse:2.72229	train-rmspe:0.858965	val-rmspe:0.862342
[104]	train-rmse:2.64644	val-rmse:2.69589	train-rmspe:0.857438	val-rmspe:0.860897
[105]	train-rmse:2.6203	val-rmse:2.66976	train-rmspe:0.855885	val-rmspe:0.859429
[106]	train-rmse:2.59443	val-rmse:2.64386	train-rmspe:0.854302	val-rmspe:0.857929
[107]	train-rmse:2.56881	val-rmse:2.61821	train-rmspe:0.852691	val-rmspe:0.856402
[108]	train-rmse:2.54347	val-rmse:2.59282	train-rmspe:0.851049	val-rmspe:0.854845
[109]	train-rmse:2.51837	val-rmse:2.56776	train-rmspe:0.849382	val-rmspe:0.85327
[110]	train-rmse:2.49352	val-rmse:2.54296	train-rmspe:0.847686	val-rmspe:0.851669
[111]	train-rmse:2.46892	val-rmse:2.51837	train-rmspe:0.845961	val-rmspe:0.850037
[112]	train-rmse:2.44458	val-rmse:2.49402	train-rmspe:0.844205	val-rmspe:0.848373
[113]	train-rmse:2.

[202]	train-rmse:1.02629	val-rmse:1.07745	train-rmspe:0.598577	val-rmspe:0.61524
[203]	train-rmse:1.01684	val-rmse:1.06789	train-rmspe:0.59538	val-rmspe:0.612155
[204]	train-rmse:1.00737	val-rmse:1.05833	train-rmspe:0.592174	val-rmspe:0.609065
[205]	train-rmse:0.997988	val-rmse:1.04892	train-rmspe:0.588975	val-rmspe:0.605992
[206]	train-rmse:0.988744	val-rmse:1.03964	train-rmspe:0.585775	val-rmspe:0.602922
[207]	train-rmse:0.979622	val-rmse:1.03038	train-rmspe:0.582574	val-rmspe:0.599813
[208]	train-rmse:0.970661	val-rmse:1.02133	train-rmspe:0.579393	val-rmspe:0.596739
[209]	train-rmse:0.961721	val-rmse:1.01231	train-rmspe:0.576204	val-rmspe:0.593649
[210]	train-rmse:0.952853	val-rmse:1.00336	train-rmspe:0.573025	val-rmspe:0.59058
[211]	train-rmse:0.945131	val-rmse:0.996492	train-rmspe:0.57018	val-rmspe:0.588105
[212]	train-rmse:0.936539	val-rmse:0.987837	train-rmspe:0.567026	val-rmspe:0.585062
[213]	train-rmse:0.927929	val-rmse:0.979154	train-rmspe:0.563856	val-rmspe:0.582006
[214]	tr

[301]	train-rmse:0.452982	val-rmse:0.496893	train-rmspe:0.346625	val-rmspe:0.365273
[302]	train-rmse:0.449912	val-rmse:0.493742	train-rmspe:0.345044	val-rmspe:0.363584
[303]	train-rmse:0.44679	val-rmse:0.490516	train-rmspe:0.343438	val-rmspe:0.361858
[304]	train-rmse:0.443816	val-rmse:0.48738	train-rmspe:0.341899	val-rmspe:0.360171
[305]	train-rmse:0.440817	val-rmse:0.484279	train-rmspe:0.34035	val-rmspe:0.358502
[306]	train-rmse:0.437494	val-rmse:0.480897	train-rmspe:0.338649	val-rmspe:0.356706
[307]	train-rmse:0.434615	val-rmse:0.477884	train-rmspe:0.337175	val-rmspe:0.35508
[308]	train-rmse:0.431792	val-rmse:0.474895	train-rmspe:0.335716	val-rmspe:0.353463
[309]	train-rmse:0.428942	val-rmse:0.471928	train-rmspe:0.334257	val-rmspe:0.35187
[310]	train-rmse:0.426108	val-rmse:0.469005	train-rmspe:0.332807	val-rmspe:0.350278
[311]	train-rmse:0.423428	val-rmse:0.466203	train-rmspe:0.331427	val-rmspe:0.348759
[312]	train-rmse:0.420586	val-rmse:0.463264	train-rmspe:0.329974	val-rmspe:0.3471

[400]	train-rmse:0.27808	val-rmse:0.308871	train-rmspe:0.266194	val-rmspe:0.266233
[401]	train-rmse:0.27713	val-rmse:0.307807	train-rmspe:0.265782	val-rmspe:0.265664
[402]	train-rmse:0.27637	val-rmse:0.3069	train-rmspe:0.265607	val-rmspe:0.265281
[403]	train-rmse:0.275535	val-rmse:0.305923	train-rmspe:0.265352	val-rmspe:0.264822
[404]	train-rmse:0.274534	val-rmse:0.304818	train-rmspe:0.264937	val-rmspe:0.264255
[405]	train-rmse:0.273634	val-rmse:0.303804	train-rmspe:0.264595	val-rmspe:0.263741
[406]	train-rmse:0.272824	val-rmse:0.30287	train-rmspe:0.264301	val-rmspe:0.263284
[407]	train-rmse:0.272085	val-rmse:0.301998	train-rmspe:0.264123	val-rmspe:0.262911
[408]	train-rmse:0.270997	val-rmse:0.300838	train-rmspe:0.263663	val-rmspe:0.262269
[409]	train-rmse:0.270237	val-rmse:0.299937	train-rmspe:0.263463	val-rmspe:0.26186
[410]	train-rmse:0.269463	val-rmse:0.299024	train-rmspe:0.263207	val-rmspe:0.26144
[411]	train-rmse:0.268701	val-rmse:0.298134	train-rmspe:0.262995	val-rmspe:0.261032


...

[5366]	train-rmse:0.090618	val-rmse:0.151693	train-rmspe:0.107453	val-rmspe:0.149536
[5367]	train-rmse:0.090612	val-rmse:0.151693	train-rmspe:0.107449	val-rmspe:0.149535
[5368]	train-rmse:0.090606	val-rmse:0.151691	train-rmspe:0.107441	val-rmspe:0.149533
[5369]	train-rmse:0.090601	val-rmse:0.151691	train-rmspe:0.107426	val-rmspe:0.149532
[5370]	train-rmse:0.090598	val-rmse:0.15169	train-rmspe:0.107424	val-rmspe:0.149531
[5371]	train-rmse:0.090595	val-rmse:0.15169	train-rmspe:0.107422	val-rmspe:0.149529
[5372]	train-rmse:0.090583	val-rmse:0.151693	train-rmspe:0.107414	val-rmspe:0.14953
[5373]	train-rmse:0.090576	val-rmse:0.151695	train-rmspe:0.107407	val-rmspe:0.149528
[5374]	train-rmse:0.090574	val-rmse:0.151695	train-rmspe:0.107403	val-rmspe:0.149526
[5375]	train-rmse:0.090569	val-rmse:0.151695	train-rmspe:0.107392	val-rmspe:0.149526
[5376]	train-rmse:0.090562	val-rmse:0.151696	train-rmspe:0.107389	val-rmspe:0.149525
[5377]	train-rmse:0.090559	val-rmse:0.151696	train-rmspe:0.107387	va

[5463]	train-rmse:0.090133	val-rmse:0.15174	train-rmspe:0.106863	val-rmspe:0.149494
[5464]	train-rmse:0.090125	val-rmse:0.151739	train-rmspe:0.106858	val-rmspe:0.149493
[5465]	train-rmse:0.090123	val-rmse:0.151742	train-rmspe:0.106856	val-rmspe:0.149495
[5466]	train-rmse:0.090118	val-rmse:0.151744	train-rmspe:0.106854	val-rmspe:0.149495
[5467]	train-rmse:0.090116	val-rmse:0.151744	train-rmspe:0.106852	val-rmspe:0.149496
[5468]	train-rmse:0.090106	val-rmse:0.151751	train-rmspe:0.106849	val-rmspe:0.149496
[5469]	train-rmse:0.090103	val-rmse:0.151749	train-rmspe:0.106846	val-rmspe:0.149493
[5470]	train-rmse:0.090099	val-rmse:0.151747	train-rmspe:0.106844	val-rmspe:0.149492
[5471]	train-rmse:0.090094	val-rmse:0.151747	train-rmspe:0.106839	val-rmspe:0.149492
[5472]	train-rmse:0.09009	val-rmse:0.151753	train-rmspe:0.106608	val-rmspe:0.149497
[5473]	train-rmse:0.090087	val-rmse:0.151752	train-rmspe:0.106607	val-rmspe:0.149496
[5474]	train-rmse:0.090079	val-rmse:0.151754	train-rmspe:0.106604	v

[5560]	train-rmse:0.089664	val-rmse:0.151783	train-rmspe:0.105969	val-rmspe:0.149467
[5561]	train-rmse:0.089662	val-rmse:0.151783	train-rmspe:0.105966	val-rmspe:0.149466
[5562]	train-rmse:0.08966	val-rmse:0.151781	train-rmspe:0.105965	val-rmspe:0.149465
[5563]	train-rmse:0.089652	val-rmse:0.151784	train-rmspe:0.105961	val-rmspe:0.149467
[5564]	train-rmse:0.089644	val-rmse:0.151782	train-rmspe:0.105949	val-rmspe:0.149466
[5565]	train-rmse:0.089636	val-rmse:0.151782	train-rmspe:0.105937	val-rmspe:0.149467
[5566]	train-rmse:0.089631	val-rmse:0.151782	train-rmspe:0.105923	val-rmspe:0.149466
[5567]	train-rmse:0.089626	val-rmse:0.151786	train-rmspe:0.10592	val-rmspe:0.149468
[5568]	train-rmse:0.089617	val-rmse:0.151792	train-rmspe:0.10591	val-rmspe:0.149471
[5569]	train-rmse:0.089615	val-rmse:0.151793	train-rmspe:0.105906	val-rmspe:0.149471
[5570]	train-rmse:0.089611	val-rmse:0.151791	train-rmspe:0.105904	val-rmspe:0.149469
[5571]	train-rmse:0.08961	val-rmse:0.151791	train-rmspe:0.105902	val

[5657]	train-rmse:0.089222	val-rmse:0.151814	train-rmspe:0.105227	val-rmspe:0.149438
[5658]	train-rmse:0.089214	val-rmse:0.151814	train-rmspe:0.105177	val-rmspe:0.149438
[5659]	train-rmse:0.089212	val-rmse:0.151815	train-rmspe:0.105175	val-rmspe:0.149441
[5660]	train-rmse:0.089203	val-rmse:0.15182	train-rmspe:0.105171	val-rmspe:0.149442
[5661]	train-rmse:0.089199	val-rmse:0.151819	train-rmspe:0.105168	val-rmspe:0.149441
[5662]	train-rmse:0.089194	val-rmse:0.151821	train-rmspe:0.105162	val-rmspe:0.149441
[5663]	train-rmse:0.08919	val-rmse:0.15182	train-rmspe:0.10516	val-rmspe:0.14944
[5664]	train-rmse:0.089183	val-rmse:0.151823	train-rmspe:0.105145	val-rmspe:0.149443
[5665]	train-rmse:0.089176	val-rmse:0.151823	train-rmspe:0.105141	val-rmspe:0.149446
[5666]	train-rmse:0.089174	val-rmse:0.151823	train-rmspe:0.10514	val-rmspe:0.149446
[5667]	train-rmse:0.089167	val-rmse:0.151827	train-rmspe:0.105135	val-rmspe:0.149447
[5668]	train-rmse:0.089165	val-rmse:0.151828	train-rmspe:0.105134	val-r

The training time of the model is: 11457s
The rmspe of the model on validation data set is 0.149460


In [105]:
#设定参数
param = {'max_depth': 10, 'eta': 0.03, 'silent': 0, 'objective': 'reg:linear', 'min_child_weight': 5,'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)



[0]	train-rmse:7.30303	val-rmse:7.34104	train-rmspe:0.910788	val-rmspe:0.91132
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:7.08439	val-rmse:7.12256	train-rmspe:0.910698	val-rmspe:0.911234
[2]	train-rmse:6.87233	val-rmse:6.91063	train-rmspe:0.910588	val-rmspe:0.911129
[3]	train-rmse:6.66662	val-rmse:6.70505	train-rmspe:0.910454	val-rmspe:0.911
[4]	train-rmse:6.46712	val-rmse:6.50558	train-rmspe:0.910291	val-rmspe:0.910845
[5]	train-rmse:6.27359	val-rmse:6.31211	train-rmspe:0.910096	val-rmspe:0.910658
[6]	train-rmse:6.08699	val-rmse:6.12516	train-rmspe:0.909865	val-rmspe:0.910437
[7]	train-rmse:5.90489	val-rmse:5.94285	train-rmspe:0.909589	val-rmspe:0.910172
[8]	train-rmse:5.72827	val-rmse:5.76598	train-rmspe:0.909263	val-rmspe:0.909861
[9]	train-rmse:5.55694	val-rmse:5.59476	train-rmspe:0.908881	val-rmspe:0.909495
[10]	train-rmse:5.39157	val-rmse:5.43114	train-rmspe:0.90843

[100]	train-rmse:0.436603	val-rmse:0.470398	train-rmspe:0.338337	val-rmspe:0.350413
[101]	train-rmse:0.427639	val-rmse:0.461159	train-rmspe:0.333721	val-rmspe:0.345374
[102]	train-rmse:0.419187	val-rmse:0.452172	train-rmspe:0.329282	val-rmspe:0.340401
[103]	train-rmse:0.410865	val-rmse:0.443715	train-rmspe:0.325005	val-rmspe:0.335756
[104]	train-rmse:0.403218	val-rmse:0.43574	train-rmspe:0.321038	val-rmspe:0.331363
[105]	train-rmse:0.395713	val-rmse:0.427955	train-rmspe:0.317144	val-rmspe:0.327054
[106]	train-rmse:0.388286	val-rmse:0.420205	train-rmspe:0.313404	val-rmspe:0.322815
[107]	train-rmse:0.381205	val-rmse:0.412791	train-rmspe:0.309884	val-rmspe:0.318764
[108]	train-rmse:0.374739	val-rmse:0.40593	train-rmspe:0.306676	val-rmspe:0.315012
[109]	train-rmse:0.367665	val-rmse:0.398645	train-rmspe:0.303173	val-rmspe:0.310992
[110]	train-rmse:0.361585	val-rmse:0.392144	train-rmspe:0.300303	val-rmspe:0.307452
[111]	train-rmse:0.355861	val-rmse:0.386088	train-rmspe:0.297597	val-rmspe:0.3

[199]	train-rmse:0.204857	val-rmse:0.214717	train-rmspe:0.243676	val-rmspe:0.219566
[200]	train-rmse:0.204503	val-rmse:0.214335	train-rmspe:0.243539	val-rmspe:0.21938
[201]	train-rmse:0.203983	val-rmse:0.213652	train-rmspe:0.243254	val-rmspe:0.218937
[202]	train-rmse:0.203541	val-rmse:0.213172	train-rmspe:0.243032	val-rmspe:0.218644
[203]	train-rmse:0.203319	val-rmse:0.212919	train-rmspe:0.242967	val-rmspe:0.218554
[204]	train-rmse:0.202999	val-rmse:0.212478	train-rmspe:0.242837	val-rmspe:0.218308
[205]	train-rmse:0.20249	val-rmse:0.211972	train-rmspe:0.242536	val-rmspe:0.218008
[206]	train-rmse:0.202361	val-rmse:0.21183	train-rmspe:0.242584	val-rmspe:0.218015
[207]	train-rmse:0.201526	val-rmse:0.211083	train-rmspe:0.24199	val-rmspe:0.217459
[208]	train-rmse:0.201274	val-rmse:0.210892	train-rmspe:0.241725	val-rmspe:0.217453
[209]	train-rmse:0.200911	val-rmse:0.210474	train-rmspe:0.241465	val-rmspe:0.217001
[210]	train-rmse:0.200744	val-rmse:0.21032	train-rmspe:0.241358	val-rmspe:0.2170

[298]	train-rmse:0.169421	val-rmse:0.181859	train-rmspe:0.212221	val-rmspe:0.190348
[299]	train-rmse:0.169234	val-rmse:0.181694	train-rmspe:0.212184	val-rmspe:0.190013
[300]	train-rmse:0.169125	val-rmse:0.181652	train-rmspe:0.211681	val-rmspe:0.190013
[301]	train-rmse:0.16884	val-rmse:0.181414	train-rmspe:0.211365	val-rmspe:0.189758
[302]	train-rmse:0.168627	val-rmse:0.18123	train-rmspe:0.211159	val-rmspe:0.189562
[303]	train-rmse:0.168465	val-rmse:0.181082	train-rmspe:0.211007	val-rmspe:0.189429
[304]	train-rmse:0.168355	val-rmse:0.181041	train-rmspe:0.210868	val-rmspe:0.189416
[305]	train-rmse:0.168079	val-rmse:0.180803	train-rmspe:0.210592	val-rmspe:0.189163
[306]	train-rmse:0.167397	val-rmse:0.180182	train-rmspe:0.209962	val-rmspe:0.188548
[307]	train-rmse:0.167188	val-rmse:0.180035	train-rmspe:0.209748	val-rmspe:0.188394
[308]	train-rmse:0.167096	val-rmse:0.179997	train-rmspe:0.209651	val-rmspe:0.188372
[309]	train-rmse:0.166963	val-rmse:0.179877	train-rmspe:0.209526	val-rmspe:0.1

[397]	train-rmse:0.148267	val-rmse:0.165109	train-rmspe:0.187586	val-rmspe:0.172916
[398]	train-rmse:0.148196	val-rmse:0.165059	train-rmspe:0.187395	val-rmspe:0.172867
[399]	train-rmse:0.148108	val-rmse:0.165021	train-rmspe:0.187328	val-rmspe:0.172834
[400]	train-rmse:0.147872	val-rmse:0.164847	train-rmspe:0.187258	val-rmspe:0.172699
[401]	train-rmse:0.147658	val-rmse:0.164694	train-rmspe:0.186936	val-rmspe:0.172556
[402]	train-rmse:0.147537	val-rmse:0.164591	train-rmspe:0.186917	val-rmspe:0.172395
[403]	train-rmse:0.147369	val-rmse:0.164436	train-rmspe:0.186771	val-rmspe:0.172249
[404]	train-rmse:0.147027	val-rmse:0.164175	train-rmspe:0.186455	val-rmspe:0.171994
[405]	train-rmse:0.146979	val-rmse:0.164129	train-rmspe:0.186428	val-rmspe:0.17195
[406]	train-rmse:0.146506	val-rmse:0.163759	train-rmspe:0.185848	val-rmspe:0.171526
[407]	train-rmse:0.146398	val-rmse:0.163684	train-rmspe:0.185639	val-rmspe:0.171464
[408]	train-rmse:0.146155	val-rmse:0.163491	train-rmspe:0.185431	val-rmspe:0.

...

[1380]	train-rmse:0.097811	val-rmse:0.140628	train-rmspe:0.116909	val-rmspe:0.14365
[1381]	train-rmse:0.097796	val-rmse:0.140624	train-rmspe:0.116865	val-rmspe:0.143645
[1382]	train-rmse:0.097785	val-rmse:0.140621	train-rmspe:0.116855	val-rmspe:0.143639
[1383]	train-rmse:0.097749	val-rmse:0.140639	train-rmspe:0.116829	val-rmspe:0.143649
[1384]	train-rmse:0.097735	val-rmse:0.140636	train-rmspe:0.116822	val-rmspe:0.143648
[1385]	train-rmse:0.097717	val-rmse:0.140625	train-rmspe:0.116807	val-rmspe:0.14364
[1386]	train-rmse:0.097697	val-rmse:0.140613	train-rmspe:0.116787	val-rmspe:0.143627
[1387]	train-rmse:0.097685	val-rmse:0.140617	train-rmspe:0.116778	val-rmspe:0.143617
[1388]	train-rmse:0.097682	val-rmse:0.140616	train-rmspe:0.116775	val-rmspe:0.143616
[1389]	train-rmse:0.097654	val-rmse:0.140625	train-rmspe:0.116753	val-rmspe:0.14363
[1390]	train-rmse:0.097627	val-rmse:0.140621	train-rmspe:0.116737	val-rmspe:0.143626
[1391]	train-rmse:0.097607	val-rmse:0.140612	train-rmspe:0.116703	va

[1477]	train-rmse:0.096052	val-rmse:0.140539	train-rmspe:0.114474	val-rmspe:0.143403
[1478]	train-rmse:0.096025	val-rmse:0.140548	train-rmspe:0.114407	val-rmspe:0.143403
[1479]	train-rmse:0.096002	val-rmse:0.140551	train-rmspe:0.114376	val-rmspe:0.143402
[1480]	train-rmse:0.095975	val-rmse:0.140551	train-rmspe:0.114356	val-rmspe:0.143394
[1481]	train-rmse:0.095955	val-rmse:0.140549	train-rmspe:0.114342	val-rmspe:0.143391
[1482]	train-rmse:0.095946	val-rmse:0.140548	train-rmspe:0.114445	val-rmspe:0.143378
[1483]	train-rmse:0.09593	val-rmse:0.140544	train-rmspe:0.114434	val-rmspe:0.143374
[1484]	train-rmse:0.095903	val-rmse:0.140563	train-rmspe:0.114417	val-rmspe:0.143379
[1485]	train-rmse:0.095879	val-rmse:0.140573	train-rmspe:0.114407	val-rmspe:0.14338
[1486]	train-rmse:0.095865	val-rmse:0.140576	train-rmspe:0.114385	val-rmspe:0.14338
[1487]	train-rmse:0.095844	val-rmse:0.140577	train-rmspe:0.11437	val-rmspe:0.143377
[1488]	train-rmse:0.095832	val-rmse:0.140588	train-rmspe:0.114361	val

[1574]	train-rmse:0.094392	val-rmse:0.140581	train-rmspe:0.112359	val-rmspe:0.143198
[1575]	train-rmse:0.09437	val-rmse:0.140585	train-rmspe:0.112347	val-rmspe:0.143198
[1576]	train-rmse:0.09435	val-rmse:0.140583	train-rmspe:0.112331	val-rmspe:0.143173
[1577]	train-rmse:0.094335	val-rmse:0.140571	train-rmspe:0.112324	val-rmspe:0.143168
[1578]	train-rmse:0.094316	val-rmse:0.140557	train-rmspe:0.112291	val-rmspe:0.143146
[1579]	train-rmse:0.0943	val-rmse:0.140548	train-rmspe:0.112276	val-rmspe:0.143129
[1580]	train-rmse:0.094284	val-rmse:0.140542	train-rmspe:0.112268	val-rmspe:0.143124
[1581]	train-rmse:0.094265	val-rmse:0.140552	train-rmspe:0.112187	val-rmspe:0.143124
[1582]	train-rmse:0.094254	val-rmse:0.140548	train-rmspe:0.112178	val-rmspe:0.143117
[1583]	train-rmse:0.094233	val-rmse:0.14057	train-rmspe:0.112151	val-rmspe:0.143135
[1584]	train-rmse:0.094216	val-rmse:0.140572	train-rmspe:0.112091	val-rmspe:0.143134
[1585]	train-rmse:0.094211	val-rmse:0.140572	train-rmspe:0.112092	val-

[1671]	train-rmse:0.092686	val-rmse:0.140706	train-rmspe:0.109836	val-rmspe:0.143053
[1672]	train-rmse:0.092667	val-rmse:0.140721	train-rmspe:0.109795	val-rmspe:0.143054
[1673]	train-rmse:0.092652	val-rmse:0.140726	train-rmspe:0.109779	val-rmspe:0.143059
[1674]	train-rmse:0.092637	val-rmse:0.140722	train-rmspe:0.109728	val-rmspe:0.143056
[1675]	train-rmse:0.092621	val-rmse:0.140722	train-rmspe:0.109716	val-rmspe:0.143056
[1676]	train-rmse:0.092592	val-rmse:0.140737	train-rmspe:0.109703	val-rmspe:0.143066
[1677]	train-rmse:0.09258	val-rmse:0.140733	train-rmspe:0.109693	val-rmspe:0.143064
[1678]	train-rmse:0.092545	val-rmse:0.14077	train-rmspe:0.109654	val-rmspe:0.143092
[1679]	train-rmse:0.092534	val-rmse:0.140771	train-rmspe:0.109648	val-rmspe:0.143093
[1680]	train-rmse:0.092526	val-rmse:0.140767	train-rmspe:0.109643	val-rmspe:0.143091
[1681]	train-rmse:0.092513	val-rmse:0.140762	train-rmspe:0.109613	val-rmspe:0.143082
[1682]	train-rmse:0.092484	val-rmse:0.140774	train-rmspe:0.109605	v

[1768]	train-rmse:0.091038	val-rmse:0.140966	train-rmspe:0.106795	val-rmspe:0.143035
[1769]	train-rmse:0.091008	val-rmse:0.140965	train-rmspe:0.106771	val-rmspe:0.143036
[1770]	train-rmse:0.090993	val-rmse:0.140971	train-rmspe:0.106768	val-rmspe:0.143038
[1771]	train-rmse:0.090977	val-rmse:0.140972	train-rmspe:0.106806	val-rmspe:0.143035
[1772]	train-rmse:0.090958	val-rmse:0.140971	train-rmspe:0.106795	val-rmspe:0.143031
[1773]	train-rmse:0.090951	val-rmse:0.140969	train-rmspe:0.10679	val-rmspe:0.143029
[1774]	train-rmse:0.090936	val-rmse:0.140974	train-rmspe:0.106151	val-rmspe:0.143034
[1775]	train-rmse:0.090927	val-rmse:0.140966	train-rmspe:0.106143	val-rmspe:0.143028
[1776]	train-rmse:0.090909	val-rmse:0.140981	train-rmspe:0.106123	val-rmspe:0.143029
[1777]	train-rmse:0.09089	val-rmse:0.141029	train-rmspe:0.10609	val-rmspe:0.143101
[1778]	train-rmse:0.090882	val-rmse:0.141038	train-rmspe:0.10607	val-rmspe:0.143108
[1779]	train-rmse:0.090865	val-rmse:0.141058	train-rmspe:0.10605	val-

In [112]:
#设定参数
param = {'max_depth': 10, 'eta': 0.05, 'silent': 0, 'min_child_weight': 5,'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)




[0]	train-rmse:7.15282	val-rmse:7.19105	train-rmspe:0.910729	val-rmspe:0.911263
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:6.79594	val-rmse:6.83443	train-rmspe:0.910541	val-rmspe:0.911084
[2]	train-rmse:6.45695	val-rmse:6.49567	train-rmspe:0.910282	val-rmspe:0.910836
[3]	train-rmse:6.13493	val-rmse:6.17384	train-rmspe:0.909929	val-rmspe:0.910499
[4]	train-rmse:5.82907	val-rmse:5.86787	train-rmspe:0.909456	val-rmspe:0.910046
[5]	train-rmse:5.5385	val-rmse:5.57718	train-rmspe:0.908835	val-rmspe:0.909452
[6]	train-rmse:5.26413	val-rmse:5.30216	train-rmspe:0.908036	val-rmspe:0.908687
[7]	train-rmse:5.00188	val-rmse:5.03959	train-rmspe:0.907015	val-rmspe:0.907709
[8]	train-rmse:4.75279	val-rmse:4.79009	train-rmspe:0.905733	val-rmspe:0.906481
[9]	train-rmse:4.51616	val-rmse:4.5534	train-rmspe:0.904146	val-rmspe:0.904961
[10]	train-rmse:4.29253	val-rmse:4.3335	train-rmspe:0.9022

[99]	train-rmse:0.229137	val-rmse:0.242177	train-rmspe:0.254419	val-rmspe:0.239359
[100]	train-rmse:0.227365	val-rmse:0.240218	train-rmspe:0.253539	val-rmspe:0.238218
[101]	train-rmse:0.226767	val-rmse:0.239321	train-rmspe:0.253782	val-rmspe:0.238164
[102]	train-rmse:0.224979	val-rmse:0.23738	train-rmspe:0.25289	val-rmspe:0.236758
[103]	train-rmse:0.223605	val-rmse:0.235816	train-rmspe:0.252393	val-rmspe:0.235987
[104]	train-rmse:0.221437	val-rmse:0.233547	train-rmspe:0.250913	val-rmspe:0.234373
[105]	train-rmse:0.22042	val-rmse:0.232334	train-rmspe:0.250485	val-rmspe:0.233764
[106]	train-rmse:0.219874	val-rmse:0.23154	train-rmspe:0.250426	val-rmspe:0.233625
[107]	train-rmse:0.219567	val-rmse:0.231037	train-rmspe:0.250728	val-rmspe:0.233703
[108]	train-rmse:0.218886	val-rmse:0.230196	train-rmspe:0.2506	val-rmspe:0.233457
[109]	train-rmse:0.218234	val-rmse:0.229347	train-rmspe:0.250643	val-rmspe:0.233159
[110]	train-rmse:0.21703	val-rmse:0.228079	train-rmspe:0.249942	val-rmspe:0.232317


[198]	train-rmse:0.163882	val-rmse:0.177959	train-rmspe:0.204698	val-rmspe:0.1893
[199]	train-rmse:0.163667	val-rmse:0.177815	train-rmspe:0.204483	val-rmspe:0.189151
[200]	train-rmse:0.163588	val-rmse:0.177741	train-rmspe:0.204443	val-rmspe:0.189066
[201]	train-rmse:0.163043	val-rmse:0.177109	train-rmspe:0.203922	val-rmspe:0.188468
[202]	train-rmse:0.162548	val-rmse:0.176687	train-rmspe:0.203447	val-rmspe:0.188008
[203]	train-rmse:0.162185	val-rmse:0.176363	train-rmspe:0.203113	val-rmspe:0.187711
[204]	train-rmse:0.161869	val-rmse:0.176083	train-rmspe:0.202807	val-rmspe:0.187455
[205]	train-rmse:0.161753	val-rmse:0.175983	train-rmspe:0.202713	val-rmspe:0.187353
[206]	train-rmse:0.160934	val-rmse:0.175317	train-rmspe:0.202018	val-rmspe:0.186739
[207]	train-rmse:0.160463	val-rmse:0.174918	train-rmspe:0.201612	val-rmspe:0.186352
[208]	train-rmse:0.160241	val-rmse:0.174933	train-rmspe:0.201266	val-rmspe:0.186345
[209]	train-rmse:0.159925	val-rmse:0.174658	train-rmspe:0.200922	val-rmspe:0.1

[296]	train-rmse:0.135742	val-rmse:0.155883	train-rmspe:0.174464	val-rmspe:0.16479
[297]	train-rmse:0.135617	val-rmse:0.155774	train-rmspe:0.174364	val-rmspe:0.164665
[298]	train-rmse:0.135327	val-rmse:0.155604	train-rmspe:0.174052	val-rmspe:0.164487
[299]	train-rmse:0.135162	val-rmse:0.15551	train-rmspe:0.172065	val-rmspe:0.164285
[300]	train-rmse:0.135035	val-rmse:0.155497	train-rmspe:0.17177	val-rmspe:0.164262
[301]	train-rmse:0.134895	val-rmse:0.155374	train-rmspe:0.171586	val-rmspe:0.164192
[302]	train-rmse:0.134805	val-rmse:0.155309	train-rmspe:0.171517	val-rmspe:0.164131
[303]	train-rmse:0.134585	val-rmse:0.155118	train-rmspe:0.171305	val-rmspe:0.163925
[304]	train-rmse:0.134461	val-rmse:0.155119	train-rmspe:0.171222	val-rmspe:0.163949
[305]	train-rmse:0.134316	val-rmse:0.155004	train-rmspe:0.17132	val-rmspe:0.163683
[306]	train-rmse:0.134015	val-rmse:0.15475	train-rmspe:0.171079	val-rmspe:0.163446
[307]	train-rmse:0.133744	val-rmse:0.154525	train-rmspe:0.170848	val-rmspe:0.1632

[395]	train-rmse:0.121529	val-rmse:0.146951	train-rmspe:0.158614	val-rmspe:0.154456
[396]	train-rmse:0.121488	val-rmse:0.146937	train-rmspe:0.158582	val-rmspe:0.154433
[397]	train-rmse:0.121412	val-rmse:0.146883	train-rmspe:0.158544	val-rmspe:0.154337
[398]	train-rmse:0.121342	val-rmse:0.146827	train-rmspe:0.158485	val-rmspe:0.154289
[399]	train-rmse:0.121218	val-rmse:0.146775	train-rmspe:0.158347	val-rmspe:0.154194
[400]	train-rmse:0.121144	val-rmse:0.146733	train-rmspe:0.158286	val-rmspe:0.154154
[401]	train-rmse:0.12092	val-rmse:0.146587	train-rmspe:0.158054	val-rmspe:0.154009
[402]	train-rmse:0.120832	val-rmse:0.146526	train-rmspe:0.157979	val-rmspe:0.153959
[403]	train-rmse:0.120686	val-rmse:0.146402	train-rmspe:0.15786	val-rmspe:0.153832
[404]	train-rmse:0.120597	val-rmse:0.146375	train-rmspe:0.157773	val-rmspe:0.153635
[405]	train-rmse:0.120547	val-rmse:0.146365	train-rmspe:0.157735	val-rmspe:0.153651
[406]	train-rmse:0.120421	val-rmse:0.146298	train-rmspe:0.157625	val-rmspe:0.1

...

[791]	train-rmse:0.099165	val-rmse:0.139084	train-rmspe:0.122834	val-rmspe:0.14369
[792]	train-rmse:0.099143	val-rmse:0.139074	train-rmspe:0.122815	val-rmspe:0.143675
[793]	train-rmse:0.099107	val-rmse:0.139069	train-rmspe:0.122797	val-rmspe:0.143664
[794]	train-rmse:0.09906	val-rmse:0.139009	train-rmspe:0.12247	val-rmspe:0.143627
[795]	train-rmse:0.099021	val-rmse:0.138992	train-rmspe:0.122446	val-rmspe:0.143612
[796]	train-rmse:0.098987	val-rmse:0.138978	train-rmspe:0.122423	val-rmspe:0.143596
[797]	train-rmse:0.098975	val-rmse:0.138969	train-rmspe:0.122412	val-rmspe:0.143586
[798]	train-rmse:0.098919	val-rmse:0.138945	train-rmspe:0.122366	val-rmspe:0.143566
[799]	train-rmse:0.098883	val-rmse:0.138942	train-rmspe:0.122204	val-rmspe:0.143551
[800]	train-rmse:0.098826	val-rmse:0.138929	train-rmspe:0.12213	val-rmspe:0.143524
[801]	train-rmse:0.098785	val-rmse:0.138938	train-rmspe:0.122101	val-rmspe:0.143526
[802]	train-rmse:0.098736	val-rmse:0.138959	train-rmspe:0.122021	val-rmspe:0.143

[890]	train-rmse:0.095879	val-rmse:0.138808	train-rmspe:0.119085	val-rmspe:0.143129
[891]	train-rmse:0.095847	val-rmse:0.138792	train-rmspe:0.119074	val-rmspe:0.143111
[892]	train-rmse:0.095817	val-rmse:0.138776	train-rmspe:0.119053	val-rmspe:0.1431
[893]	train-rmse:0.095802	val-rmse:0.138783	train-rmspe:0.119034	val-rmspe:0.143104
[894]	train-rmse:0.095788	val-rmse:0.138772	train-rmspe:0.119022	val-rmspe:0.143094
[895]	train-rmse:0.095761	val-rmse:0.138747	train-rmspe:0.119015	val-rmspe:0.143063
[896]	train-rmse:0.095735	val-rmse:0.138736	train-rmspe:0.118995	val-rmspe:0.143053
[897]	train-rmse:0.095704	val-rmse:0.138753	train-rmspe:0.118981	val-rmspe:0.143048
[898]	train-rmse:0.095681	val-rmse:0.138743	train-rmspe:0.11894	val-rmspe:0.143023
[899]	train-rmse:0.095657	val-rmse:0.138742	train-rmspe:0.118918	val-rmspe:0.143018
[900]	train-rmse:0.095627	val-rmse:0.138735	train-rmspe:0.118931	val-rmspe:0.143
[901]	train-rmse:0.09561	val-rmse:0.138746	train-rmspe:0.118834	val-rmspe:0.142995

[989]	train-rmse:0.093137	val-rmse:0.138952	train-rmspe:0.114865	val-rmspe:0.142917
[990]	train-rmse:0.093112	val-rmse:0.138947	train-rmspe:0.114849	val-rmspe:0.142912
[991]	train-rmse:0.093084	val-rmse:0.138939	train-rmspe:0.114827	val-rmspe:0.142898
[992]	train-rmse:0.09307	val-rmse:0.138952	train-rmspe:0.114822	val-rmspe:0.1429
[993]	train-rmse:0.09306	val-rmse:0.138954	train-rmspe:0.114812	val-rmspe:0.142902
[994]	train-rmse:0.093023	val-rmse:0.138958	train-rmspe:0.114667	val-rmspe:0.142908
[995]	train-rmse:0.093001	val-rmse:0.138943	train-rmspe:0.11465	val-rmspe:0.142897
[996]	train-rmse:0.092988	val-rmse:0.138927	train-rmspe:0.114643	val-rmspe:0.142889
[997]	train-rmse:0.092961	val-rmse:0.138933	train-rmspe:0.114641	val-rmspe:0.142888
[998]	train-rmse:0.092933	val-rmse:0.138925	train-rmspe:0.114617	val-rmspe:0.142879
[999]	train-rmse:0.092917	val-rmse:0.138928	train-rmspe:0.114603	val-rmspe:0.142882
[1000]	train-rmse:0.092904	val-rmse:0.138924	train-rmspe:0.114697	val-rmspe:0.142

[1086]	train-rmse:0.090674	val-rmse:0.139109	train-rmspe:0.111606	val-rmspe:0.142717
[1087]	train-rmse:0.090653	val-rmse:0.13913	train-rmspe:0.111565	val-rmspe:0.142724
[1088]	train-rmse:0.09063	val-rmse:0.139125	train-rmspe:0.111546	val-rmspe:0.14271
[1089]	train-rmse:0.090608	val-rmse:0.139113	train-rmspe:0.111518	val-rmspe:0.142708
[1090]	train-rmse:0.09058	val-rmse:0.139108	train-rmspe:0.111495	val-rmspe:0.142703
[1091]	train-rmse:0.090557	val-rmse:0.13915	train-rmspe:0.111472	val-rmspe:0.142735
[1092]	train-rmse:0.090535	val-rmse:0.139148	train-rmspe:0.111409	val-rmspe:0.142735
[1093]	train-rmse:0.090504	val-rmse:0.139156	train-rmspe:0.111378	val-rmspe:0.142724
[1094]	train-rmse:0.090487	val-rmse:0.139157	train-rmspe:0.111362	val-rmspe:0.142724
[1095]	train-rmse:0.090454	val-rmse:0.139164	train-rmspe:0.11132	val-rmspe:0.142728
[1096]	train-rmse:0.090429	val-rmse:0.139179	train-rmspe:0.11128	val-rmspe:0.14274
[1097]	train-rmse:0.090398	val-rmse:0.139191	train-rmspe:0.111241	val-rms

[1183]	train-rmse:0.088392	val-rmse:0.139511	train-rmspe:0.108657	val-rmspe:0.142738
[1184]	train-rmse:0.088369	val-rmse:0.139515	train-rmspe:0.108639	val-rmspe:0.142737
[1185]	train-rmse:0.088356	val-rmse:0.139528	train-rmspe:0.108618	val-rmspe:0.142753
[1186]	train-rmse:0.088341	val-rmse:0.139525	train-rmspe:0.108618	val-rmspe:0.142754
[1187]	train-rmse:0.088323	val-rmse:0.139527	train-rmspe:0.108606	val-rmspe:0.142751
[1188]	train-rmse:0.088277	val-rmse:0.13953	train-rmspe:0.10858	val-rmspe:0.142743
[1189]	train-rmse:0.088242	val-rmse:0.13954	train-rmspe:0.108568	val-rmspe:0.142757
[1190]	train-rmse:0.088219	val-rmse:0.139538	train-rmspe:0.108553	val-rmspe:0.142754
Stopping. Best iteration:
[1090]	train-rmse:0.09058	val-rmse:0.139108	train-rmspe:0.111495	val-rmspe:0.142703

The training time of the model is: 2200s
The rmspe of the model on validation data set is 0.142754


In [113]:
#设定参数
param = {'max_depth': 10, 'eta': 0.1, 'silent': 0, 'min_child_weight': 5,'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)



[0]	train-rmse:6.77732	val-rmse:6.81611	train-rmspe:0.910528	val-rmspe:0.911072
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:6.10121	val-rmse:6.14056	train-rmspe:0.909882	val-rmspe:0.910455
[2]	train-rmse:5.49286	val-rmse:5.53167	train-rmspe:0.908717	val-rmspe:0.90934
[3]	train-rmse:4.94547	val-rmse:4.98434	train-rmspe:0.906753	val-rmspe:0.907463
[4]	train-rmse:4.453	val-rmse:4.49196	train-rmspe:0.903645	val-rmspe:0.904493
[5]	train-rmse:4.00992	val-rmse:4.04858	train-rmspe:0.898996	val-rmspe:0.900047
[6]	train-rmse:3.61382	val-rmse:3.65142	train-rmspe:0.892428	val-rmspe:0.893752
[7]	train-rmse:3.25507	val-rmse:3.29201	train-rmspe:0.883476	val-rmspe:0.885169
[8]	train-rmse:2.93242	val-rmse:2.96853	train-rmspe:0.871812	val-rmspe:0.873964
[9]	train-rmse:2.64227	val-rmse:2.67823	train-rmspe:0.857168	val-rmspe:0.859898
[10]	train-rmse:2.38288	val-rmse:2.42488	train-rmspe:0.8394

[99]	train-rmse:0.165819	val-rmse:0.180707	train-rmspe:0.202506	val-rmspe:0.188432
[100]	train-rmse:0.164637	val-rmse:0.179752	train-rmspe:0.201348	val-rmspe:0.187422
[101]	train-rmse:0.16297	val-rmse:0.178409	train-rmspe:0.199781	val-rmspe:0.186152
[102]	train-rmse:0.162165	val-rmse:0.177814	train-rmspe:0.198631	val-rmspe:0.185457
[103]	train-rmse:0.16189	val-rmse:0.177566	train-rmspe:0.198512	val-rmspe:0.185219
[104]	train-rmse:0.160722	val-rmse:0.176629	train-rmspe:0.197322	val-rmspe:0.184193
[105]	train-rmse:0.16023	val-rmse:0.176221	train-rmspe:0.1969	val-rmspe:0.183751
[106]	train-rmse:0.159831	val-rmse:0.175926	train-rmspe:0.196606	val-rmspe:0.183463
[107]	train-rmse:0.15955	val-rmse:0.175759	train-rmspe:0.19638	val-rmspe:0.183066
[108]	train-rmse:0.158807	val-rmse:0.175364	train-rmspe:0.195576	val-rmspe:0.182744
[109]	train-rmse:0.158252	val-rmse:0.174917	train-rmspe:0.19501	val-rmspe:0.182282
[110]	train-rmse:0.157575	val-rmse:0.17441	train-rmspe:0.194361	val-rmspe:0.18169
[11

[198]	train-rmse:0.121693	val-rmse:0.150421	train-rmspe:0.153364	val-rmspe:0.154225
[199]	train-rmse:0.121477	val-rmse:0.150322	train-rmspe:0.153145	val-rmspe:0.154119
[200]	train-rmse:0.121316	val-rmse:0.150226	train-rmspe:0.153012	val-rmspe:0.154026
[201]	train-rmse:0.121135	val-rmse:0.150082	train-rmspe:0.152843	val-rmspe:0.153882
[202]	train-rmse:0.120863	val-rmse:0.149847	train-rmspe:0.152613	val-rmspe:0.15364
[203]	train-rmse:0.12076	val-rmse:0.149784	train-rmspe:0.152521	val-rmspe:0.153579
[204]	train-rmse:0.12054	val-rmse:0.149643	train-rmspe:0.152195	val-rmspe:0.153441
[205]	train-rmse:0.120455	val-rmse:0.149574	train-rmspe:0.152112	val-rmspe:0.153253
[206]	train-rmse:0.120377	val-rmse:0.149541	train-rmspe:0.152044	val-rmspe:0.153229
[207]	train-rmse:0.120313	val-rmse:0.149539	train-rmspe:0.151996	val-rmspe:0.153203
[208]	train-rmse:0.119957	val-rmse:0.149279	train-rmspe:0.151697	val-rmspe:0.152941
[209]	train-rmse:0.119772	val-rmse:0.149149	train-rmspe:0.151547	val-rmspe:0.15

[296]	train-rmse:0.107918	val-rmse:0.145129	train-rmspe:0.139315	val-rmspe:0.147995
[297]	train-rmse:0.107756	val-rmse:0.145046	train-rmspe:0.139132	val-rmspe:0.14791
[298]	train-rmse:0.107587	val-rmse:0.145146	train-rmspe:0.138772	val-rmspe:0.147964
[299]	train-rmse:0.107393	val-rmse:0.145172	train-rmspe:0.13871	val-rmspe:0.147969
[300]	train-rmse:0.10734	val-rmse:0.145196	train-rmspe:0.138687	val-rmspe:0.147922
[301]	train-rmse:0.107293	val-rmse:0.145171	train-rmspe:0.138649	val-rmspe:0.147896
[302]	train-rmse:0.107223	val-rmse:0.145167	train-rmspe:0.138589	val-rmspe:0.147894
[303]	train-rmse:0.107171	val-rmse:0.145158	train-rmspe:0.137959	val-rmspe:0.147898
[304]	train-rmse:0.107088	val-rmse:0.145132	train-rmspe:0.137902	val-rmspe:0.147885
[305]	train-rmse:0.107035	val-rmse:0.145093	train-rmspe:0.137857	val-rmspe:0.147853
[306]	train-rmse:0.106924	val-rmse:0.145029	train-rmspe:0.137734	val-rmspe:0.147781
[307]	train-rmse:0.106836	val-rmse:0.145015	train-rmspe:0.13768	val-rmspe:0.147

[395]	train-rmse:0.100066	val-rmse:0.143985	train-rmspe:0.123688	val-rmspe:0.145751
[396]	train-rmse:0.099995	val-rmse:0.143971	train-rmspe:0.123637	val-rmspe:0.145718
[397]	train-rmse:0.099889	val-rmse:0.14398	train-rmspe:0.123647	val-rmspe:0.145711
[398]	train-rmse:0.099793	val-rmse:0.143937	train-rmspe:0.123576	val-rmspe:0.145677
[399]	train-rmse:0.099726	val-rmse:0.143911	train-rmspe:0.123541	val-rmspe:0.145652
[400]	train-rmse:0.099664	val-rmse:0.143904	train-rmspe:0.12351	val-rmspe:0.145637
[401]	train-rmse:0.099543	val-rmse:0.143873	train-rmspe:0.12341	val-rmspe:0.145599
[402]	train-rmse:0.099489	val-rmse:0.143862	train-rmspe:0.123356	val-rmspe:0.145571
[403]	train-rmse:0.099449	val-rmse:0.143859	train-rmspe:0.12333	val-rmspe:0.145535
[404]	train-rmse:0.099388	val-rmse:0.143873	train-rmspe:0.123296	val-rmspe:0.145558
[405]	train-rmse:0.099318	val-rmse:0.143889	train-rmspe:0.123284	val-rmspe:0.145558
[406]	train-rmse:0.099217	val-rmse:0.14405	train-rmspe:0.123214	val-rmspe:0.1457

[494]	train-rmse:0.09398	val-rmse:0.144056	train-rmspe:0.113692	val-rmspe:0.145126
[495]	train-rmse:0.093916	val-rmse:0.144008	train-rmspe:0.11358	val-rmspe:0.145098
[496]	train-rmse:0.093853	val-rmse:0.143996	train-rmspe:0.113515	val-rmspe:0.145099
[497]	train-rmse:0.093767	val-rmse:0.143975	train-rmspe:0.113514	val-rmspe:0.145068
[498]	train-rmse:0.093716	val-rmse:0.143974	train-rmspe:0.113479	val-rmspe:0.145062
[499]	train-rmse:0.093696	val-rmse:0.143976	train-rmspe:0.11347	val-rmspe:0.145066
[500]	train-rmse:0.093664	val-rmse:0.143964	train-rmspe:0.11332	val-rmspe:0.145052
[501]	train-rmse:0.093626	val-rmse:0.143968	train-rmspe:0.113301	val-rmspe:0.145051
[502]	train-rmse:0.093558	val-rmse:0.143936	train-rmspe:0.11326	val-rmspe:0.145029
[503]	train-rmse:0.093524	val-rmse:0.143908	train-rmspe:0.112473	val-rmspe:0.144955
[504]	train-rmse:0.093459	val-rmse:0.143931	train-rmspe:0.112438	val-rmspe:0.144955
[505]	train-rmse:0.093366	val-rmse:0.143952	train-rmspe:0.112366	val-rmspe:0.1450

[593]	train-rmse:0.089047	val-rmse:0.144596	train-rmspe:0.107427	val-rmspe:0.145085
[594]	train-rmse:0.089003	val-rmse:0.144591	train-rmspe:0.107391	val-rmspe:0.145079
[595]	train-rmse:0.08894	val-rmse:0.144616	train-rmspe:0.107344	val-rmspe:0.145102
[596]	train-rmse:0.088929	val-rmse:0.144586	train-rmspe:0.10733	val-rmspe:0.145081
[597]	train-rmse:0.088888	val-rmse:0.144592	train-rmspe:0.107303	val-rmspe:0.145083
[598]	train-rmse:0.088865	val-rmse:0.144587	train-rmspe:0.106127	val-rmspe:0.145077
[599]	train-rmse:0.08881	val-rmse:0.144593	train-rmspe:0.106098	val-rmspe:0.145071
[600]	train-rmse:0.088758	val-rmse:0.144593	train-rmspe:0.10606	val-rmspe:0.145074
[601]	train-rmse:0.088719	val-rmse:0.144585	train-rmspe:0.106025	val-rmspe:0.145074
[602]	train-rmse:0.088671	val-rmse:0.144604	train-rmspe:0.105987	val-rmspe:0.145092
[603]	train-rmse:0.088639	val-rmse:0.144599	train-rmspe:0.105965	val-rmspe:0.145097
Stopping. Best iteration:
[503]	train-rmse:0.093524	val-rmse:0.143908	train-rmsp

In [114]:
#设定参数
param = {'max_depth': 10, 'eta': 0.07, 'silent': 0, 'min_child_weight': 5,'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)





[0]	train-rmse:7.00261	val-rmse:7.04107	train-rmspe:0.910658	val-rmspe:0.911196
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:6.51353	val-rmse:6.55233	train-rmspe:0.910332	val-rmspe:0.910884
[2]	train-rmse:6.05875	val-rmse:6.09763	train-rmspe:0.909825	val-rmspe:0.910399
[3]	train-rmse:5.63585	val-rmse:5.67481	train-rmspe:0.909065	val-rmspe:0.909673
[4]	train-rmse:5.24266	val-rmse:5.28167	train-rmspe:0.907963	val-rmspe:0.908619
[5]	train-rmse:4.87703	val-rmse:4.91602	train-rmspe:0.906415	val-rmspe:0.90714
[6]	train-rmse:4.53911	val-rmse:4.57726	train-rmspe:0.904315	val-rmspe:0.905128
[7]	train-rmse:4.22289	val-rmse:4.26063	train-rmspe:0.901512	val-rmspe:0.902444
[8]	train-rmse:3.9289	val-rmse:3.96605	train-rmspe:0.897877	val-rmspe:0.898959
[9]	train-rmse:3.65558	val-rmse:3.6924	train-rmspe:0.893271	val-rmspe:0.89454
[10]	train-rmse:3.4028	val-rmse:3.44379	train-rmspe:0.887586

[99]	train-rmse:0.19189	val-rmse:0.201669	train-rmspe:0.230149	val-rmspe:0.211818
[100]	train-rmse:0.191178	val-rmse:0.201048	train-rmspe:0.229501	val-rmspe:0.211171
[101]	train-rmse:0.190268	val-rmse:0.200223	train-rmspe:0.228509	val-rmspe:0.210447
[102]	train-rmse:0.189862	val-rmse:0.199934	train-rmspe:0.228078	val-rmspe:0.210363
[103]	train-rmse:0.187841	val-rmse:0.198055	train-rmspe:0.225948	val-rmspe:0.208487
[104]	train-rmse:0.186664	val-rmse:0.197074	train-rmspe:0.224575	val-rmspe:0.207499
[105]	train-rmse:0.185235	val-rmse:0.195651	train-rmspe:0.223426	val-rmspe:0.206272
[106]	train-rmse:0.184344	val-rmse:0.194865	train-rmspe:0.222633	val-rmspe:0.205611
[107]	train-rmse:0.183069	val-rmse:0.193358	train-rmspe:0.221443	val-rmspe:0.204185
[108]	train-rmse:0.182305	val-rmse:0.19272	train-rmspe:0.220143	val-rmspe:0.203657
[109]	train-rmse:0.182161	val-rmse:0.192575	train-rmspe:0.220012	val-rmspe:0.203562
[110]	train-rmse:0.181728	val-rmse:0.192154	train-rmspe:0.219804	val-rmspe:0.20

[198]	train-rmse:0.136167	val-rmse:0.155322	train-rmspe:0.171822	val-rmspe:0.163135
[199]	train-rmse:0.135931	val-rmse:0.155034	train-rmspe:0.171585	val-rmspe:0.16277
[200]	train-rmse:0.13562	val-rmse:0.154789	train-rmspe:0.171286	val-rmspe:0.162506
[201]	train-rmse:0.135468	val-rmse:0.154672	train-rmspe:0.171004	val-rmspe:0.162368
[202]	train-rmse:0.13523	val-rmse:0.154474	train-rmspe:0.170771	val-rmspe:0.162169
[203]	train-rmse:0.135092	val-rmse:0.154352	train-rmspe:0.17068	val-rmspe:0.162031
[204]	train-rmse:0.135007	val-rmse:0.154264	train-rmspe:0.170614	val-rmspe:0.161953
[205]	train-rmse:0.134664	val-rmse:0.153948	train-rmspe:0.170315	val-rmspe:0.161646
[206]	train-rmse:0.134483	val-rmse:0.153816	train-rmspe:0.170155	val-rmspe:0.161518
[207]	train-rmse:0.134204	val-rmse:0.153647	train-rmspe:0.169967	val-rmspe:0.161326
[208]	train-rmse:0.134166	val-rmse:0.153608	train-rmspe:0.169937	val-rmspe:0.161301
[209]	train-rmse:0.133958	val-rmse:0.153439	train-rmspe:0.16975	val-rmspe:0.1611

[297]	train-rmse:0.118708	val-rmse:0.143821	train-rmspe:0.150153	val-rmspe:0.150914
[298]	train-rmse:0.118533	val-rmse:0.143848	train-rmspe:0.149969	val-rmspe:0.150917
[299]	train-rmse:0.118415	val-rmse:0.143834	train-rmspe:0.149884	val-rmspe:0.150844
[300]	train-rmse:0.118322	val-rmse:0.1438	train-rmspe:0.149602	val-rmspe:0.150777
[301]	train-rmse:0.118299	val-rmse:0.143783	train-rmspe:0.149579	val-rmspe:0.150759
[302]	train-rmse:0.118222	val-rmse:0.143738	train-rmspe:0.149491	val-rmspe:0.150704
[303]	train-rmse:0.118145	val-rmse:0.143712	train-rmspe:0.14941	val-rmspe:0.150678
[304]	train-rmse:0.117971	val-rmse:0.143722	train-rmspe:0.149066	val-rmspe:0.150749
[305]	train-rmse:0.11789	val-rmse:0.143669	train-rmspe:0.148997	val-rmspe:0.150689
[306]	train-rmse:0.117723	val-rmse:0.14354	train-rmspe:0.148862	val-rmspe:0.150264
[307]	train-rmse:0.117601	val-rmse:0.143432	train-rmspe:0.14875	val-rmspe:0.150173
[308]	train-rmse:0.117487	val-rmse:0.143434	train-rmspe:0.148639	val-rmspe:0.15019

[396]	train-rmse:0.109417	val-rmse:0.13974	train-rmspe:0.136917	val-rmspe:0.145466
[397]	train-rmse:0.109336	val-rmse:0.139669	train-rmspe:0.136855	val-rmspe:0.145421
[398]	train-rmse:0.109252	val-rmse:0.13962	train-rmspe:0.136797	val-rmspe:0.145372
[399]	train-rmse:0.109142	val-rmse:0.139542	train-rmspe:0.136709	val-rmspe:0.145299
[400]	train-rmse:0.109101	val-rmse:0.139517	train-rmspe:0.136674	val-rmspe:0.145276
[401]	train-rmse:0.10897	val-rmse:0.139482	train-rmspe:0.136581	val-rmspe:0.145217
[402]	train-rmse:0.108903	val-rmse:0.139451	train-rmspe:0.134919	val-rmspe:0.145103
[403]	train-rmse:0.108849	val-rmse:0.139414	train-rmspe:0.134797	val-rmspe:0.145051
[404]	train-rmse:0.108665	val-rmse:0.139569	train-rmspe:0.134466	val-rmspe:0.145241
[405]	train-rmse:0.10861	val-rmse:0.139561	train-rmspe:0.134417	val-rmspe:0.145227
[406]	train-rmse:0.10851	val-rmse:0.139519	train-rmspe:0.134342	val-rmspe:0.14519
[407]	train-rmse:0.108435	val-rmse:0.139479	train-rmspe:0.134289	val-rmspe:0.14515

[495]	train-rmse:0.102329	val-rmse:0.138211	train-rmspe:0.123735	val-rmspe:0.142811
[496]	train-rmse:0.10228	val-rmse:0.138192	train-rmspe:0.123698	val-rmspe:0.142792
[497]	train-rmse:0.10222	val-rmse:0.138153	train-rmspe:0.123655	val-rmspe:0.142774
[498]	train-rmse:0.102177	val-rmse:0.13813	train-rmspe:0.123622	val-rmspe:0.142743
[499]	train-rmse:0.102122	val-rmse:0.138118	train-rmspe:0.123595	val-rmspe:0.142707
[500]	train-rmse:0.102094	val-rmse:0.13811	train-rmspe:0.123526	val-rmspe:0.142694
[501]	train-rmse:0.102058	val-rmse:0.138121	train-rmspe:0.123511	val-rmspe:0.142698
[502]	train-rmse:0.102031	val-rmse:0.138105	train-rmspe:0.123491	val-rmspe:0.14269
[503]	train-rmse:0.101921	val-rmse:0.138074	train-rmspe:0.123394	val-rmspe:0.142643
[504]	train-rmse:0.101827	val-rmse:0.13802	train-rmspe:0.123289	val-rmspe:0.14259
[505]	train-rmse:0.101702	val-rmse:0.138093	train-rmspe:0.123169	val-rmspe:0.142717
[506]	train-rmse:0.101605	val-rmse:0.138188	train-rmspe:0.12309	val-rmspe:0.142761


[594]	train-rmse:0.097424	val-rmse:0.137568	train-rmspe:0.116489	val-rmspe:0.141575
[595]	train-rmse:0.097383	val-rmse:0.137515	train-rmspe:0.11646	val-rmspe:0.141534
[596]	train-rmse:0.097369	val-rmse:0.137494	train-rmspe:0.116444	val-rmspe:0.141525
[597]	train-rmse:0.09731	val-rmse:0.137502	train-rmspe:0.116408	val-rmspe:0.141528
[598]	train-rmse:0.097265	val-rmse:0.137492	train-rmspe:0.116179	val-rmspe:0.141511
[599]	train-rmse:0.097247	val-rmse:0.137481	train-rmspe:0.11575	val-rmspe:0.141504
[600]	train-rmse:0.097184	val-rmse:0.137481	train-rmspe:0.115715	val-rmspe:0.1415
[601]	train-rmse:0.09715	val-rmse:0.137475	train-rmspe:0.115688	val-rmspe:0.141493
[602]	train-rmse:0.097101	val-rmse:0.13746	train-rmspe:0.115656	val-rmspe:0.141477
[603]	train-rmse:0.097068	val-rmse:0.137458	train-rmspe:0.115633	val-rmspe:0.141465
[604]	train-rmse:0.096976	val-rmse:0.137458	train-rmspe:0.115517	val-rmspe:0.14146
[605]	train-rmse:0.096926	val-rmse:0.137481	train-rmspe:0.115483	val-rmspe:0.141443


[693]	train-rmse:0.093617	val-rmse:0.137226	train-rmspe:0.112408	val-rmspe:0.140781
[694]	train-rmse:0.093595	val-rmse:0.137187	train-rmspe:0.112453	val-rmspe:0.140754
[695]	train-rmse:0.093575	val-rmse:0.137172	train-rmspe:0.112433	val-rmspe:0.140743
[696]	train-rmse:0.09353	val-rmse:0.137201	train-rmspe:0.1124	val-rmspe:0.14078
[697]	train-rmse:0.093489	val-rmse:0.137221	train-rmspe:0.112376	val-rmspe:0.140801
[698]	train-rmse:0.093427	val-rmse:0.137265	train-rmspe:0.112319	val-rmspe:0.140843
[699]	train-rmse:0.093405	val-rmse:0.137267	train-rmspe:0.112277	val-rmspe:0.140828
[700]	train-rmse:0.093355	val-rmse:0.137243	train-rmspe:0.112208	val-rmspe:0.140793
[701]	train-rmse:0.093304	val-rmse:0.137258	train-rmspe:0.112189	val-rmspe:0.140794
[702]	train-rmse:0.093285	val-rmse:0.137261	train-rmspe:0.112177	val-rmspe:0.140789
[703]	train-rmse:0.093259	val-rmse:0.137238	train-rmspe:0.112158	val-rmspe:0.140762
[704]	train-rmse:0.09324	val-rmse:0.137228	train-rmspe:0.112138	val-rmspe:0.1407

[792]	train-rmse:0.090213	val-rmse:0.137348	train-rmspe:0.107676	val-rmspe:0.14032
[793]	train-rmse:0.090181	val-rmse:0.137375	train-rmspe:0.107665	val-rmspe:0.140318
[794]	train-rmse:0.090133	val-rmse:0.137366	train-rmspe:0.107647	val-rmspe:0.14031
[795]	train-rmse:0.090109	val-rmse:0.137351	train-rmspe:0.107632	val-rmspe:0.140298
[796]	train-rmse:0.090075	val-rmse:0.137329	train-rmspe:0.107602	val-rmspe:0.140278
[797]	train-rmse:0.090015	val-rmse:0.137372	train-rmspe:0.107574	val-rmspe:0.140284
[798]	train-rmse:0.089957	val-rmse:0.137416	train-rmspe:0.107547	val-rmspe:0.140289
[799]	train-rmse:0.089929	val-rmse:0.137427	train-rmspe:0.107529	val-rmspe:0.140289
[800]	train-rmse:0.089898	val-rmse:0.137422	train-rmspe:0.107542	val-rmspe:0.14027
[801]	train-rmse:0.089852	val-rmse:0.137437	train-rmspe:0.107297	val-rmspe:0.140313
[802]	train-rmse:0.089819	val-rmse:0.137461	train-rmspe:0.107222	val-rmspe:0.14032
[803]	train-rmse:0.089789	val-rmse:0.137478	train-rmspe:0.107116	val-rmspe:0.140

[891]	train-rmse:0.086878	val-rmse:0.138109	train-rmspe:0.101034	val-rmspe:0.140442
[892]	train-rmse:0.08685	val-rmse:0.138093	train-rmspe:0.101014	val-rmspe:0.140435
[893]	train-rmse:0.086829	val-rmse:0.138098	train-rmspe:0.100996	val-rmspe:0.140438
[894]	train-rmse:0.086815	val-rmse:0.13812	train-rmspe:0.100991	val-rmspe:0.140465
[895]	train-rmse:0.086798	val-rmse:0.138117	train-rmspe:0.100971	val-rmspe:0.140458
[896]	train-rmse:0.086764	val-rmse:0.138129	train-rmspe:0.100984	val-rmspe:0.140465
[897]	train-rmse:0.08673	val-rmse:0.13813	train-rmspe:0.100979	val-rmspe:0.14046
[898]	train-rmse:0.086699	val-rmse:0.138129	train-rmspe:0.100886	val-rmspe:0.14046
[899]	train-rmse:0.086672	val-rmse:0.13813	train-rmspe:0.100862	val-rmspe:0.140467
[900]	train-rmse:0.086649	val-rmse:0.138118	train-rmspe:0.100883	val-rmspe:0.140463
Stopping. Best iteration:
[800]	train-rmse:0.089898	val-rmse:0.137422	train-rmspe:0.107542	val-rmspe:0.14027

The training time of the model is: 1651s
The rmspe of the

In [115]:
#设定参数
param = {'max_depth': 10, 'eta': 0.08, 'silent': 0, 'min_child_weight': 5,'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)






[0]	train-rmse:6.92751	val-rmse:6.96608	train-rmspe:0.910618	val-rmspe:0.911158
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:6.37458	val-rmse:6.41353	train-rmspe:0.910202	val-rmspe:0.91076
[2]	train-rmse:5.86597	val-rmse:5.90501	train-rmspe:0.909521	val-rmspe:0.910109
[3]	train-rmse:5.39812	val-rmse:5.43725	train-rmspe:0.908456	val-rmspe:0.909092
[4]	train-rmse:4.96784	val-rmse:5.00684	train-rmspe:0.906858	val-rmspe:0.907563
[5]	train-rmse:4.57205	val-rmse:4.61057	train-rmspe:0.904555	val-rmspe:0.90536
[6]	train-rmse:4.21022	val-rmse:4.24781	train-rmspe:0.901373	val-rmspe:0.90231
[7]	train-rmse:3.87524	val-rmse:3.91236	train-rmspe:0.897073	val-rmspe:0.89819
[8]	train-rmse:3.56718	val-rmse:3.60373	train-rmspe:0.891463	val-rmspe:0.892808
[9]	train-rmse:3.28386	val-rmse:3.3202	train-rmspe:0.884344	val-rmspe:0.885978
[10]	train-rmse:3.02482	val-rmse:3.06585	train-rmspe:0.875573

[99]	train-rmse:0.179981	val-rmse:0.193358	train-rmspe:0.218691	val-rmspe:0.200776
[100]	train-rmse:0.178731	val-rmse:0.192319	train-rmspe:0.217215	val-rmspe:0.199555
[101]	train-rmse:0.178021	val-rmse:0.191639	train-rmspe:0.216602	val-rmspe:0.198989
[102]	train-rmse:0.176798	val-rmse:0.190653	train-rmspe:0.215114	val-rmspe:0.197935
[103]	train-rmse:0.176345	val-rmse:0.190295	train-rmspe:0.214685	val-rmspe:0.197635
[104]	train-rmse:0.175959	val-rmse:0.190136	train-rmspe:0.214336	val-rmspe:0.19751
[105]	train-rmse:0.175594	val-rmse:0.189859	train-rmspe:0.214029	val-rmspe:0.197246
[106]	train-rmse:0.17449	val-rmse:0.188895	train-rmspe:0.212773	val-rmspe:0.196308
[107]	train-rmse:0.174326	val-rmse:0.188706	train-rmspe:0.212621	val-rmspe:0.196249
[108]	train-rmse:0.172879	val-rmse:0.187419	train-rmspe:0.211352	val-rmspe:0.19494
[109]	train-rmse:0.172364	val-rmse:0.186984	train-rmspe:0.210631	val-rmspe:0.194194
[110]	train-rmse:0.171917	val-rmse:0.186597	train-rmspe:0.210619	val-rmspe:0.193

[198]	train-rmse:0.132192	val-rmse:0.157407	train-rmspe:0.168055	val-rmspe:0.162727
[199]	train-rmse:0.13193	val-rmse:0.157357	train-rmspe:0.167698	val-rmspe:0.162651
[200]	train-rmse:0.13162	val-rmse:0.157127	train-rmspe:0.167394	val-rmspe:0.16246
[201]	train-rmse:0.13139	val-rmse:0.156943	train-rmspe:0.1672	val-rmspe:0.162277
[202]	train-rmse:0.131189	val-rmse:0.156781	train-rmspe:0.166998	val-rmspe:0.161925
[203]	train-rmse:0.131048	val-rmse:0.156672	train-rmspe:0.166866	val-rmspe:0.161779
[204]	train-rmse:0.130785	val-rmse:0.156486	train-rmspe:0.166585	val-rmspe:0.161616
[205]	train-rmse:0.130612	val-rmse:0.156289	train-rmspe:0.166438	val-rmspe:0.161426
[206]	train-rmse:0.130517	val-rmse:0.156235	train-rmspe:0.166223	val-rmspe:0.161368
[207]	train-rmse:0.130019	val-rmse:0.155839	train-rmspe:0.165786	val-rmspe:0.160994
[208]	train-rmse:0.129741	val-rmse:0.155624	train-rmspe:0.165432	val-rmspe:0.160763
[209]	train-rmse:0.129562	val-rmse:0.155503	train-rmspe:0.165279	val-rmspe:0.16065

[296]	train-rmse:0.114961	val-rmse:0.147932	train-rmspe:0.142723	val-rmspe:0.151685
[297]	train-rmse:0.114851	val-rmse:0.147865	train-rmspe:0.142563	val-rmspe:0.15164
[298]	train-rmse:0.114662	val-rmse:0.148018	train-rmspe:0.142245	val-rmspe:0.151746
[299]	train-rmse:0.114543	val-rmse:0.147976	train-rmspe:0.14216	val-rmspe:0.151704
[300]	train-rmse:0.114446	val-rmse:0.147932	train-rmspe:0.142089	val-rmspe:0.15167
[301]	train-rmse:0.114387	val-rmse:0.147886	train-rmspe:0.14206	val-rmspe:0.151621
[302]	train-rmse:0.114341	val-rmse:0.147906	train-rmspe:0.142049	val-rmspe:0.151619
[303]	train-rmse:0.114287	val-rmse:0.147879	train-rmspe:0.141985	val-rmspe:0.151596
[304]	train-rmse:0.114166	val-rmse:0.147895	train-rmspe:0.14183	val-rmspe:0.151634
[305]	train-rmse:0.11398	val-rmse:0.147774	train-rmspe:0.141492	val-rmspe:0.151477
[306]	train-rmse:0.113885	val-rmse:0.14771	train-rmspe:0.141411	val-rmspe:0.151425
[307]	train-rmse:0.113788	val-rmse:0.14761	train-rmspe:0.141101	val-rmspe:0.151363


[395]	train-rmse:0.105923	val-rmse:0.144723	train-rmspe:0.129861	val-rmspe:0.147681
[396]	train-rmse:0.105853	val-rmse:0.144722	train-rmspe:0.129822	val-rmspe:0.147672
[397]	train-rmse:0.105755	val-rmse:0.144721	train-rmspe:0.128961	val-rmspe:0.147677
[398]	train-rmse:0.105682	val-rmse:0.144709	train-rmspe:0.128924	val-rmspe:0.147663
[399]	train-rmse:0.105611	val-rmse:0.144701	train-rmspe:0.128843	val-rmspe:0.147606
[400]	train-rmse:0.105492	val-rmse:0.144654	train-rmspe:0.128775	val-rmspe:0.147547
[401]	train-rmse:0.10532	val-rmse:0.144617	train-rmspe:0.128589	val-rmspe:0.14751
[402]	train-rmse:0.105263	val-rmse:0.144594	train-rmspe:0.128037	val-rmspe:0.147456
[403]	train-rmse:0.105215	val-rmse:0.144568	train-rmspe:0.127992	val-rmspe:0.147423
[404]	train-rmse:0.105143	val-rmse:0.144558	train-rmspe:0.127964	val-rmspe:0.147416
[405]	train-rmse:0.105074	val-rmse:0.144547	train-rmspe:0.127912	val-rmspe:0.147409
[406]	train-rmse:0.104988	val-rmse:0.14454	train-rmspe:0.127862	val-rmspe:0.14

[493]	train-rmse:0.099307	val-rmse:0.14379	train-rmspe:0.117441	val-rmspe:0.145944
[494]	train-rmse:0.099263	val-rmse:0.143786	train-rmspe:0.117399	val-rmspe:0.145943
[495]	train-rmse:0.0992	val-rmse:0.143776	train-rmspe:0.117249	val-rmspe:0.145933
[496]	train-rmse:0.099164	val-rmse:0.143726	train-rmspe:0.117218	val-rmspe:0.145871
[497]	train-rmse:0.099114	val-rmse:0.143721	train-rmspe:0.117158	val-rmspe:0.145866
[498]	train-rmse:0.099071	val-rmse:0.143704	train-rmspe:0.117227	val-rmspe:0.145852
[499]	train-rmse:0.099022	val-rmse:0.143708	train-rmspe:0.117207	val-rmspe:0.14586
[500]	train-rmse:0.098998	val-rmse:0.143695	train-rmspe:0.117103	val-rmspe:0.145847
[501]	train-rmse:0.098955	val-rmse:0.143709	train-rmspe:0.117064	val-rmspe:0.145855
[502]	train-rmse:0.098938	val-rmse:0.1437	train-rmspe:0.116965	val-rmspe:0.145858
[503]	train-rmse:0.098902	val-rmse:0.143677	train-rmspe:0.116287	val-rmspe:0.145728
[504]	train-rmse:0.098827	val-rmse:0.143662	train-rmspe:0.116268	val-rmspe:0.14571

[591]	train-rmse:0.094522	val-rmse:0.14394	train-rmspe:0.11202	val-rmspe:0.145351
[592]	train-rmse:0.094494	val-rmse:0.143936	train-rmspe:0.111981	val-rmspe:0.14534
[593]	train-rmse:0.094441	val-rmse:0.143938	train-rmspe:0.111939	val-rmspe:0.145341
[594]	train-rmse:0.094415	val-rmse:0.143928	train-rmspe:0.111913	val-rmspe:0.145331
[595]	train-rmse:0.094355	val-rmse:0.14395	train-rmspe:0.111837	val-rmspe:0.145327
[596]	train-rmse:0.094339	val-rmse:0.143927	train-rmspe:0.111829	val-rmspe:0.145317
[597]	train-rmse:0.094309	val-rmse:0.143917	train-rmspe:0.111769	val-rmspe:0.145309
[598]	train-rmse:0.094266	val-rmse:0.143947	train-rmspe:0.111731	val-rmspe:0.145322
[599]	train-rmse:0.09422	val-rmse:0.143924	train-rmspe:0.111693	val-rmspe:0.145303
[600]	train-rmse:0.094175	val-rmse:0.14395	train-rmspe:0.111674	val-rmspe:0.145295
[601]	train-rmse:0.09414	val-rmse:0.14395	train-rmspe:0.111656	val-rmspe:0.145301
[602]	train-rmse:0.09408	val-rmse:0.143958	train-rmspe:0.111625	val-rmspe:0.145297
[

[690]	train-rmse:0.090496	val-rmse:0.144384	train-rmspe:0.104308	val-rmspe:0.144907
[691]	train-rmse:0.090455	val-rmse:0.144383	train-rmspe:0.104304	val-rmspe:0.144903
[692]	train-rmse:0.090416	val-rmse:0.144384	train-rmspe:0.104287	val-rmspe:0.144897
[693]	train-rmse:0.090393	val-rmse:0.144397	train-rmspe:0.104285	val-rmspe:0.144907
[694]	train-rmse:0.090356	val-rmse:0.144391	train-rmspe:0.104492	val-rmspe:0.144892
[695]	train-rmse:0.090333	val-rmse:0.14438	train-rmspe:0.104475	val-rmspe:0.144886
[696]	train-rmse:0.090269	val-rmse:0.144402	train-rmspe:0.104407	val-rmspe:0.144907
[697]	train-rmse:0.090234	val-rmse:0.144442	train-rmspe:0.10438	val-rmspe:0.14491
[698]	train-rmse:0.090194	val-rmse:0.144438	train-rmspe:0.104061	val-rmspe:0.144901
[699]	train-rmse:0.090165	val-rmse:0.144407	train-rmspe:0.104055	val-rmspe:0.144853
[700]	train-rmse:0.09012	val-rmse:0.144449	train-rmspe:0.10398	val-rmspe:0.144896
[701]	train-rmse:0.090062	val-rmse:0.144433	train-rmspe:0.103935	val-rmspe:0.1448

In [116]:
#设定参数
param = {'max_depth': 10, 'eta': 0.06, 'silent': 0, 'min_child_weight': 5,'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)







[0]	train-rmse:7.07772	val-rmse:7.11606	train-rmspe:0.910695	val-rmspe:0.911231
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:6.65398	val-rmse:6.69263	train-rmspe:0.910444	val-rmspe:0.910991
[2]	train-rmse:6.25573	val-rmse:6.29465	train-rmspe:0.910076	val-rmspe:0.910639
[3]	train-rmse:5.8814	val-rmse:5.92048	train-rmspe:0.909548	val-rmspe:0.910135
[4]	train-rmse:5.52962	val-rmse:5.56872	train-rmspe:0.908812	val-rmspe:0.909431
[5]	train-rmse:5.19894	val-rmse:5.23776	train-rmspe:0.907809	val-rmspe:0.908472
[6]	train-rmse:4.89002	val-rmse:4.92811	train-rmspe:0.906481	val-rmspe:0.9072
[7]	train-rmse:4.59784	val-rmse:4.63556	train-rmspe:0.904739	val-rmspe:0.905532
[8]	train-rmse:4.32325	val-rmse:4.36061	train-rmspe:0.902511	val-rmspe:0.903397
[9]	train-rmse:4.06517	val-rmse:4.1023	train-rmspe:0.89971	val-rmspe:0.900712
[10]	train-rmse:3.82389	val-rmse:3.86496	train-rmspe:0.896266

[99]	train-rmse:0.212866	val-rmse:0.221935	train-rmspe:0.248832	val-rmspe:0.229079
[100]	train-rmse:0.211847	val-rmse:0.220908	train-rmspe:0.248179	val-rmspe:0.228349
[101]	train-rmse:0.211446	val-rmse:0.220402	train-rmspe:0.247925	val-rmspe:0.228152
[102]	train-rmse:0.210316	val-rmse:0.219331	train-rmspe:0.247109	val-rmspe:0.227454
[103]	train-rmse:0.209144	val-rmse:0.218134	train-rmspe:0.246322	val-rmspe:0.226555
[104]	train-rmse:0.207647	val-rmse:0.216678	train-rmspe:0.244988	val-rmspe:0.225206
[105]	train-rmse:0.206824	val-rmse:0.215824	train-rmspe:0.244418	val-rmspe:0.224521
[106]	train-rmse:0.20663	val-rmse:0.215538	train-rmspe:0.244438	val-rmspe:0.22454
[107]	train-rmse:0.20606	val-rmse:0.21496	train-rmspe:0.244205	val-rmspe:0.224191
[108]	train-rmse:0.205808	val-rmse:0.21467	train-rmspe:0.244088	val-rmspe:0.224125
[109]	train-rmse:0.205605	val-rmse:0.214393	train-rmspe:0.244062	val-rmspe:0.224056
[110]	train-rmse:0.204804	val-rmse:0.21362	train-rmspe:0.243463	val-rmspe:0.223429

[198]	train-rmse:0.153209	val-rmse:0.169896	train-rmspe:0.194392	val-rmspe:0.180174
[199]	train-rmse:0.15301	val-rmse:0.169807	train-rmspe:0.194242	val-rmspe:0.180036
[200]	train-rmse:0.152586	val-rmse:0.169493	train-rmspe:0.193826	val-rmspe:0.17969
[201]	train-rmse:0.152141	val-rmse:0.168931	train-rmspe:0.193397	val-rmspe:0.179159
[202]	train-rmse:0.151547	val-rmse:0.168422	train-rmspe:0.192517	val-rmspe:0.178504
[203]	train-rmse:0.151185	val-rmse:0.168149	train-rmspe:0.19218	val-rmspe:0.178262
[204]	train-rmse:0.150387	val-rmse:0.16745	train-rmspe:0.191456	val-rmspe:0.177571
[205]	train-rmse:0.149847	val-rmse:0.166997	train-rmspe:0.190987	val-rmspe:0.177196
[206]	train-rmse:0.149638	val-rmse:0.166872	train-rmspe:0.190847	val-rmspe:0.177067
[207]	train-rmse:0.149486	val-rmse:0.166783	train-rmspe:0.190755	val-rmspe:0.176979
[208]	train-rmse:0.149296	val-rmse:0.166853	train-rmspe:0.190419	val-rmspe:0.176948
[209]	train-rmse:0.148965	val-rmse:0.166562	train-rmspe:0.190096	val-rmspe:0.176

[297]	train-rmse:0.127494	val-rmse:0.151254	train-rmspe:0.168491	val-rmspe:0.159645
[298]	train-rmse:0.127342	val-rmse:0.151138	train-rmspe:0.168359	val-rmspe:0.159536
[299]	train-rmse:0.127151	val-rmse:0.151013	train-rmspe:0.168222	val-rmspe:0.159433
[300]	train-rmse:0.127104	val-rmse:0.150987	train-rmspe:0.168195	val-rmspe:0.159394
[301]	train-rmse:0.126992	val-rmse:0.150909	train-rmspe:0.168197	val-rmspe:0.159344
[302]	train-rmse:0.126875	val-rmse:0.150843	train-rmspe:0.168097	val-rmspe:0.159121
[303]	train-rmse:0.126721	val-rmse:0.15075	train-rmspe:0.167972	val-rmspe:0.158978
[304]	train-rmse:0.126558	val-rmse:0.150616	train-rmspe:0.167852	val-rmspe:0.158856
[305]	train-rmse:0.126439	val-rmse:0.150522	train-rmspe:0.167746	val-rmspe:0.15876
[306]	train-rmse:0.126265	val-rmse:0.15038	train-rmspe:0.167598	val-rmspe:0.15863
[307]	train-rmse:0.126174	val-rmse:0.15032	train-rmspe:0.167521	val-rmspe:0.158536
[308]	train-rmse:0.125955	val-rmse:0.150254	train-rmspe:0.167229	val-rmspe:0.1585

[396]	train-rmse:0.11625	val-rmse:0.144931	train-rmspe:0.1534	val-rmspe:0.151889
[397]	train-rmse:0.116136	val-rmse:0.144853	train-rmspe:0.15329	val-rmspe:0.151804
[398]	train-rmse:0.116104	val-rmse:0.144835	train-rmspe:0.15327	val-rmspe:0.151789
[399]	train-rmse:0.115999	val-rmse:0.144787	train-rmspe:0.153153	val-rmspe:0.151438
[400]	train-rmse:0.115957	val-rmse:0.144778	train-rmspe:0.153121	val-rmspe:0.151427
[401]	train-rmse:0.115817	val-rmse:0.144781	train-rmspe:0.153041	val-rmspe:0.1514
[402]	train-rmse:0.115732	val-rmse:0.144725	train-rmspe:0.151097	val-rmspe:0.151132
[403]	train-rmse:0.115565	val-rmse:0.144593	train-rmspe:0.15094	val-rmspe:0.150999
[404]	train-rmse:0.115453	val-rmse:0.144611	train-rmspe:0.150842	val-rmspe:0.150982
[405]	train-rmse:0.1154	val-rmse:0.144605	train-rmspe:0.150815	val-rmspe:0.150976
[406]	train-rmse:0.11528	val-rmse:0.144596	train-rmspe:0.150177	val-rmspe:0.150952
[407]	train-rmse:0.115191	val-rmse:0.144534	train-rmspe:0.1501	val-rmspe:0.150887
[408]

...

[692]	train-rmse:0.098254	val-rmse:0.139423	train-rmspe:0.127625	val-rmspe:0.144168
[693]	train-rmse:0.098227	val-rmse:0.139457	train-rmspe:0.127663	val-rmspe:0.144155
[694]	train-rmse:0.098178	val-rmse:0.139442	train-rmspe:0.127636	val-rmspe:0.144142
[695]	train-rmse:0.098156	val-rmse:0.139429	train-rmspe:0.127619	val-rmspe:0.144134
[696]	train-rmse:0.098102	val-rmse:0.139448	train-rmspe:0.127537	val-rmspe:0.144148
[697]	train-rmse:0.098048	val-rmse:0.139472	train-rmspe:0.127461	val-rmspe:0.144169
[698]	train-rmse:0.097991	val-rmse:0.139465	train-rmspe:0.127423	val-rmspe:0.144165
[699]	train-rmse:0.097979	val-rmse:0.139459	train-rmspe:0.127412	val-rmspe:0.144148
[700]	train-rmse:0.097925	val-rmse:0.139463	train-rmspe:0.127333	val-rmspe:0.144156
[701]	train-rmse:0.097851	val-rmse:0.139492	train-rmspe:0.127283	val-rmspe:0.144178
[702]	train-rmse:0.097835	val-rmse:0.139497	train-rmspe:0.127245	val-rmspe:0.144177
[703]	train-rmse:0.097804	val-rmse:0.139482	train-rmspe:0.127214	val-rmspe:0

[791]	train-rmse:0.094531	val-rmse:0.139409	train-rmspe:0.118503	val-rmspe:0.143645
[792]	train-rmse:0.094513	val-rmse:0.139397	train-rmspe:0.118503	val-rmspe:0.143636
[793]	train-rmse:0.094498	val-rmse:0.139405	train-rmspe:0.118513	val-rmspe:0.143632
[794]	train-rmse:0.094454	val-rmse:0.139407	train-rmspe:0.118496	val-rmspe:0.143627
[795]	train-rmse:0.094415	val-rmse:0.139389	train-rmspe:0.118475	val-rmspe:0.14361
[796]	train-rmse:0.094378	val-rmse:0.139372	train-rmspe:0.118449	val-rmspe:0.143588
[797]	train-rmse:0.094364	val-rmse:0.139373	train-rmspe:0.118272	val-rmspe:0.143585
[798]	train-rmse:0.094295	val-rmse:0.139409	train-rmspe:0.118236	val-rmspe:0.14359
[799]	train-rmse:0.094258	val-rmse:0.1394	train-rmspe:0.118213	val-rmspe:0.143524
[800]	train-rmse:0.094217	val-rmse:0.139391	train-rmspe:0.118182	val-rmspe:0.143524
[801]	train-rmse:0.094168	val-rmse:0.139414	train-rmspe:0.118129	val-rmspe:0.143531
[802]	train-rmse:0.09413	val-rmse:0.139423	train-rmspe:0.118112	val-rmspe:0.1435

[890]	train-rmse:0.091353	val-rmse:0.13956	train-rmspe:0.111476	val-rmspe:0.143157
[891]	train-rmse:0.091271	val-rmse:0.139561	train-rmspe:0.111447	val-rmspe:0.143143
[892]	train-rmse:0.091237	val-rmse:0.139554	train-rmspe:0.11113	val-rmspe:0.143137
[893]	train-rmse:0.091223	val-rmse:0.13956	train-rmspe:0.111116	val-rmspe:0.143134
[894]	train-rmse:0.091214	val-rmse:0.139549	train-rmspe:0.111106	val-rmspe:0.143127
[895]	train-rmse:0.09119	val-rmse:0.139536	train-rmspe:0.110884	val-rmspe:0.143111
[896]	train-rmse:0.091166	val-rmse:0.139541	train-rmspe:0.110907	val-rmspe:0.143112
[897]	train-rmse:0.09113	val-rmse:0.139529	train-rmspe:0.110883	val-rmspe:0.143101
[898]	train-rmse:0.091118	val-rmse:0.139525	train-rmspe:0.110876	val-rmspe:0.143097
[899]	train-rmse:0.09108	val-rmse:0.139526	train-rmspe:0.110844	val-rmspe:0.143096
[900]	train-rmse:0.091042	val-rmse:0.139511	train-rmspe:0.110861	val-rmspe:0.143093
[901]	train-rmse:0.091007	val-rmse:0.139496	train-rmspe:0.110841	val-rmspe:0.14306

[989]	train-rmse:0.088418	val-rmse:0.14	train-rmspe:0.103335	val-rmspe:0.142699
[990]	train-rmse:0.0884	val-rmse:0.139993	train-rmspe:0.103317	val-rmspe:0.142695
[991]	train-rmse:0.088376	val-rmse:0.140003	train-rmspe:0.103299	val-rmspe:0.142693
[992]	train-rmse:0.088357	val-rmse:0.140006	train-rmspe:0.103287	val-rmspe:0.142693
[993]	train-rmse:0.088342	val-rmse:0.140009	train-rmspe:0.103276	val-rmspe:0.142707
[994]	train-rmse:0.088321	val-rmse:0.140006	train-rmspe:0.10324	val-rmspe:0.142707
[995]	train-rmse:0.088304	val-rmse:0.140002	train-rmspe:0.103158	val-rmspe:0.142702
[996]	train-rmse:0.088285	val-rmse:0.139998	train-rmspe:0.10319	val-rmspe:0.142697
[997]	train-rmse:0.088255	val-rmse:0.139993	train-rmspe:0.103173	val-rmspe:0.142697
[998]	train-rmse:0.088238	val-rmse:0.139996	train-rmspe:0.103165	val-rmspe:0.142698
[999]	train-rmse:0.088208	val-rmse:0.140003	train-rmspe:0.102966	val-rmspe:0.142697
[1000]	train-rmse:0.088194	val-rmse:0.140001	train-rmspe:0.103068	val-rmspe:0.1427
[

[1087]	train-rmse:0.085858	val-rmse:0.140533	train-rmspe:0.100778	val-rmspe:0.142593
[1088]	train-rmse:0.085833	val-rmse:0.140529	train-rmspe:0.100753	val-rmspe:0.142593
[1089]	train-rmse:0.085809	val-rmse:0.140512	train-rmspe:0.100657	val-rmspe:0.142583
[1090]	train-rmse:0.085777	val-rmse:0.140535	train-rmspe:0.100637	val-rmspe:0.142593
[1091]	train-rmse:0.085751	val-rmse:0.140531	train-rmspe:0.100624	val-rmspe:0.142591
[1092]	train-rmse:0.085722	val-rmse:0.140535	train-rmspe:0.100604	val-rmspe:0.142554
[1093]	train-rmse:0.085697	val-rmse:0.140541	train-rmspe:0.099769	val-rmspe:0.142553
[1094]	train-rmse:0.085681	val-rmse:0.14055	train-rmspe:0.099767	val-rmspe:0.142563
[1095]	train-rmse:0.085656	val-rmse:0.140574	train-rmspe:0.099721	val-rmspe:0.142574
[1096]	train-rmse:0.085631	val-rmse:0.140592	train-rmspe:0.099686	val-rmspe:0.142582
[1097]	train-rmse:0.085612	val-rmse:0.140583	train-rmspe:0.099659	val-rmspe:0.142573
[1098]	train-rmse:0.085581	val-rmse:0.140602	train-rmspe:0.099639	

In [117]:
#设定参数
param = {'max_depth': 10, 'eta': 0.07, 'silent': 0, 'min_child_weight': 5, 'gamma': 0.9, 'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)








[0]	train-rmse:7.00261	val-rmse:7.04107	train-rmspe:0.910658	val-rmspe:0.911196
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:6.51353	val-rmse:6.55233	train-rmspe:0.910332	val-rmspe:0.910884
[2]	train-rmse:6.05875	val-rmse:6.09763	train-rmspe:0.909825	val-rmspe:0.910399
[3]	train-rmse:5.63585	val-rmse:5.67481	train-rmspe:0.909065	val-rmspe:0.909673
[4]	train-rmse:5.24266	val-rmse:5.28167	train-rmspe:0.907963	val-rmspe:0.908619
[5]	train-rmse:4.87703	val-rmse:4.91603	train-rmspe:0.906415	val-rmspe:0.90714
[6]	train-rmse:4.53911	val-rmse:4.57726	train-rmspe:0.904314	val-rmspe:0.905128
[7]	train-rmse:4.22288	val-rmse:4.26062	train-rmspe:0.901512	val-rmspe:0.902444
[8]	train-rmse:3.92889	val-rmse:3.96604	train-rmspe:0.897877	val-rmspe:0.898959
[9]	train-rmse:3.65554	val-rmse:3.69237	train-rmspe:0.893274	val-rmspe:0.894544
[10]	train-rmse:3.40275	val-rmse:3.44376	train-rmspe:0.88

[99]	train-rmse:0.20209	val-rmse:0.209727	train-rmspe:0.242505	val-rmspe:0.222162
[100]	train-rmse:0.201204	val-rmse:0.208937	train-rmspe:0.24161	val-rmspe:0.221525
[101]	train-rmse:0.200441	val-rmse:0.208301	train-rmspe:0.240606	val-rmspe:0.221022
[102]	train-rmse:0.199535	val-rmse:0.207514	train-rmspe:0.239692	val-rmspe:0.220289
[103]	train-rmse:0.199005	val-rmse:0.207087	train-rmspe:0.239349	val-rmspe:0.219966
[104]	train-rmse:0.196399	val-rmse:0.204713	train-rmspe:0.236665	val-rmspe:0.217496
[105]	train-rmse:0.195852	val-rmse:0.204232	train-rmspe:0.236226	val-rmspe:0.217112
[106]	train-rmse:0.195049	val-rmse:0.203493	train-rmspe:0.235572	val-rmspe:0.216451
[107]	train-rmse:0.194385	val-rmse:0.202874	train-rmspe:0.234896	val-rmspe:0.21587
[108]	train-rmse:0.193427	val-rmse:0.202044	train-rmspe:0.234051	val-rmspe:0.215048
[109]	train-rmse:0.192469	val-rmse:0.201162	train-rmspe:0.233199	val-rmspe:0.214232
[110]	train-rmse:0.192024	val-rmse:0.200738	train-rmspe:0.232931	val-rmspe:0.213

[198]	train-rmse:0.145716	val-rmse:0.162217	train-rmspe:0.1853	val-rmspe:0.17101
[199]	train-rmse:0.145353	val-rmse:0.161925	train-rmspe:0.184996	val-rmspe:0.170714
[200]	train-rmse:0.145042	val-rmse:0.161688	train-rmspe:0.18467	val-rmspe:0.170455
[201]	train-rmse:0.144796	val-rmse:0.161501	train-rmspe:0.184462	val-rmspe:0.170253
[202]	train-rmse:0.144505	val-rmse:0.161276	train-rmspe:0.184191	val-rmspe:0.169949
[203]	train-rmse:0.144444	val-rmse:0.161218	train-rmspe:0.18415	val-rmspe:0.169914
[204]	train-rmse:0.144319	val-rmse:0.161139	train-rmspe:0.184058	val-rmspe:0.16984
[205]	train-rmse:0.144097	val-rmse:0.160933	train-rmspe:0.183863	val-rmspe:0.169621
[206]	train-rmse:0.14398	val-rmse:0.160851	train-rmspe:0.183796	val-rmspe:0.169544
[207]	train-rmse:0.143591	val-rmse:0.160588	train-rmspe:0.183479	val-rmspe:0.169218
[208]	train-rmse:0.143344	val-rmse:0.160408	train-rmspe:0.183277	val-rmspe:0.168997
[209]	train-rmse:0.143161	val-rmse:0.160267	train-rmspe:0.183114	val-rmspe:0.168855

[297]	train-rmse:0.128995	val-rmse:0.151107	train-rmspe:0.161833	val-rmspe:0.157528
[298]	train-rmse:0.128893	val-rmse:0.151115	train-rmspe:0.161791	val-rmspe:0.157482
[299]	train-rmse:0.128848	val-rmse:0.151084	train-rmspe:0.162019	val-rmspe:0.157436
[300]	train-rmse:0.128817	val-rmse:0.151076	train-rmspe:0.162008	val-rmspe:0.157426
[301]	train-rmse:0.128796	val-rmse:0.151064	train-rmspe:0.162028	val-rmspe:0.157413
[302]	train-rmse:0.12876	val-rmse:0.151046	train-rmspe:0.162008	val-rmspe:0.157394
[303]	train-rmse:0.128735	val-rmse:0.151033	train-rmspe:0.161992	val-rmspe:0.157383
[304]	train-rmse:0.128643	val-rmse:0.151014	train-rmspe:0.161909	val-rmspe:0.157334
[305]	train-rmse:0.128477	val-rmse:0.150871	train-rmspe:0.161747	val-rmspe:0.157182
[306]	train-rmse:0.128247	val-rmse:0.150679	train-rmspe:0.161546	val-rmspe:0.156999
[307]	train-rmse:0.128052	val-rmse:0.150556	train-rmspe:0.161394	val-rmspe:0.156881
[308]	train-rmse:0.128026	val-rmse:0.150515	train-rmspe:0.161381	val-rmspe:0.

[395]	train-rmse:0.123088	val-rmse:0.148051	train-rmspe:0.157319	val-rmspe:0.153868
[396]	train-rmse:0.123067	val-rmse:0.148015	train-rmspe:0.157283	val-rmspe:0.153883
[397]	train-rmse:0.12302	val-rmse:0.147954	train-rmspe:0.157248	val-rmspe:0.153861
[398]	train-rmse:0.12301	val-rmse:0.147945	train-rmspe:0.156573	val-rmspe:0.153856
[399]	train-rmse:0.122961	val-rmse:0.147912	train-rmspe:0.156535	val-rmspe:0.153816
[400]	train-rmse:0.122935	val-rmse:0.147921	train-rmspe:0.156522	val-rmspe:0.153818
[401]	train-rmse:0.122868	val-rmse:0.147964	train-rmspe:0.156459	val-rmspe:0.153847
[402]	train-rmse:0.122794	val-rmse:0.147907	train-rmspe:0.156401	val-rmspe:0.153793
[403]	train-rmse:0.122751	val-rmse:0.147875	train-rmspe:0.156359	val-rmspe:0.153661
[404]	train-rmse:0.122585	val-rmse:0.147921	train-rmspe:0.156236	val-rmspe:0.153728
[405]	train-rmse:0.122549	val-rmse:0.147914	train-rmspe:0.156224	val-rmspe:0.153718
[406]	train-rmse:0.122515	val-rmse:0.147905	train-rmspe:0.156211	val-rmspe:0.1

...

[2349]	train-rmse:0.107434	val-rmse:0.145015	train-rmspe:0.126491	val-rmspe:0.148202
[2350]	train-rmse:0.107434	val-rmse:0.145015	train-rmspe:0.126492	val-rmspe:0.148202
[2351]	train-rmse:0.107434	val-rmse:0.145016	train-rmspe:0.126491	val-rmspe:0.148202
[2352]	train-rmse:0.107434	val-rmse:0.145015	train-rmspe:0.126491	val-rmspe:0.148202
[2353]	train-rmse:0.107434	val-rmse:0.145015	train-rmspe:0.126492	val-rmspe:0.148202
[2354]	train-rmse:0.107421	val-rmse:0.145013	train-rmspe:0.126492	val-rmspe:0.148201
[2355]	train-rmse:0.107421	val-rmse:0.145013	train-rmspe:0.126491	val-rmspe:0.148201
[2356]	train-rmse:0.10741	val-rmse:0.145028	train-rmspe:0.126492	val-rmspe:0.148203
[2357]	train-rmse:0.10741	val-rmse:0.145021	train-rmspe:0.126491	val-rmspe:0.148202
[2358]	train-rmse:0.10741	val-rmse:0.145022	train-rmspe:0.126491	val-rmspe:0.148202
[2359]	train-rmse:0.107408	val-rmse:0.14501	train-rmspe:0.12649	val-rmspe:0.148199
[2360]	train-rmse:0.107408	val-rmse:0.14501	train-rmspe:0.12649	val-rm

[2447]	train-rmse:0.107215	val-rmse:0.144979	train-rmspe:0.124091	val-rmspe:0.148168
[2448]	train-rmse:0.107213	val-rmse:0.144973	train-rmspe:0.12409	val-rmspe:0.148165
[2449]	train-rmse:0.10721	val-rmse:0.144981	train-rmspe:0.12409	val-rmspe:0.148167
[2450]	train-rmse:0.107208	val-rmse:0.144981	train-rmspe:0.124089	val-rmspe:0.148165
[2451]	train-rmse:0.107208	val-rmse:0.144979	train-rmspe:0.12409	val-rmspe:0.148165
[2452]	train-rmse:0.107207	val-rmse:0.144979	train-rmspe:0.12409	val-rmspe:0.148167
[2453]	train-rmse:0.107207	val-rmse:0.144979	train-rmspe:0.12409	val-rmspe:0.148167
[2454]	train-rmse:0.107205	val-rmse:0.144977	train-rmspe:0.124088	val-rmspe:0.148166
[2455]	train-rmse:0.107204	val-rmse:0.144974	train-rmspe:0.124086	val-rmspe:0.148165
[2456]	train-rmse:0.107198	val-rmse:0.144972	train-rmspe:0.124084	val-rmspe:0.148161
[2457]	train-rmse:0.107198	val-rmse:0.144972	train-rmspe:0.124084	val-rmspe:0.148161
[2458]	train-rmse:0.107198	val-rmse:0.144972	train-rmspe:0.124084	val-r

[2544]	train-rmse:0.107034	val-rmse:0.144974	train-rmspe:0.12379	val-rmspe:0.14811
[2545]	train-rmse:0.107032	val-rmse:0.144979	train-rmspe:0.123791	val-rmspe:0.14811
[2546]	train-rmse:0.107032	val-rmse:0.144979	train-rmspe:0.123791	val-rmspe:0.14811
[2547]	train-rmse:0.107032	val-rmse:0.144979	train-rmspe:0.12379	val-rmspe:0.14811
[2548]	train-rmse:0.107015	val-rmse:0.144996	train-rmspe:0.123785	val-rmspe:0.148113
[2549]	train-rmse:0.107015	val-rmse:0.144995	train-rmspe:0.123786	val-rmspe:0.148113
[2550]	train-rmse:0.107012	val-rmse:0.144993	train-rmspe:0.123786	val-rmspe:0.148113
[2551]	train-rmse:0.107012	val-rmse:0.144993	train-rmspe:0.123786	val-rmspe:0.148113
[2552]	train-rmse:0.107008	val-rmse:0.144992	train-rmspe:0.123718	val-rmspe:0.148112
[2553]	train-rmse:0.107008	val-rmse:0.144992	train-rmspe:0.123718	val-rmspe:0.148112
[2554]	train-rmse:0.107006	val-rmse:0.144993	train-rmspe:0.123716	val-rmspe:0.148111
[2555]	train-rmse:0.107002	val-rmse:0.144997	train-rmspe:0.123715	val-r

[2642]	train-rmse:0.106756	val-rmse:0.145032	train-rmspe:0.123488	val-rmspe:0.148117
[2643]	train-rmse:0.106756	val-rmse:0.145033	train-rmspe:0.123488	val-rmspe:0.148117
[2644]	train-rmse:0.106753	val-rmse:0.145032	train-rmspe:0.123489	val-rmspe:0.148117
[2645]	train-rmse:0.10675	val-rmse:0.145031	train-rmspe:0.123485	val-rmspe:0.148117
[2646]	train-rmse:0.106747	val-rmse:0.145032	train-rmspe:0.123483	val-rmspe:0.148117
[2647]	train-rmse:0.106744	val-rmse:0.145031	train-rmspe:0.123481	val-rmspe:0.148115
[2648]	train-rmse:0.106744	val-rmse:0.14503	train-rmspe:0.123482	val-rmspe:0.148116
[2649]	train-rmse:0.106744	val-rmse:0.14503	train-rmspe:0.123482	val-rmspe:0.148116
[2650]	train-rmse:0.106738	val-rmse:0.145031	train-rmspe:0.123477	val-rmspe:0.148115
[2651]	train-rmse:0.106738	val-rmse:0.14503	train-rmspe:0.123478	val-rmspe:0.148115
[2652]	train-rmse:0.106738	val-rmse:0.14503	train-rmspe:0.123478	val-rmspe:0.148115
[2653]	train-rmse:0.106737	val-rmse:0.145029	train-rmspe:0.123479	val-

The training time of the model is: 4930s
The rmspe of the model on validation data set is 0.148116


In [118]:
#设定参数
param = {'max_depth': 11, 'eta': 0.07, 'silent': 0, 'min_child_weight': 5, 'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)




[0]	train-rmse:7.00258	val-rmse:7.04103	train-rmspe:0.910658	val-rmspe:0.911196
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:6.51347	val-rmse:6.55226	train-rmspe:0.910332	val-rmspe:0.910885
[2]	train-rmse:6.05867	val-rmse:6.09742	train-rmspe:0.909826	val-rmspe:0.910401
[3]	train-rmse:5.63574	val-rmse:5.67469	train-rmspe:0.909068	val-rmspe:0.909676
[4]	train-rmse:5.24253	val-rmse:5.28148	train-rmspe:0.907967	val-rmspe:0.908624
[5]	train-rmse:4.87686	val-rmse:4.91574	train-rmspe:0.906423	val-rmspe:0.907147
[6]	train-rmse:4.53854	val-rmse:4.5769	train-rmspe:0.904325	val-rmspe:0.905139
[7]	train-rmse:4.22228	val-rmse:4.26023	train-rmspe:0.901529	val-rmspe:0.902462
[8]	train-rmse:3.92823	val-rmse:3.96557	train-rmspe:0.897906	val-rmspe:0.898988
[9]	train-rmse:3.65487	val-rmse:3.69192	train-rmspe:0.893313	val-rmspe:0.894582
[10]	train-rmse:3.40193	val-rmse:3.44333	train-rmspe:0.88

[99]	train-rmse:0.175152	val-rmse:0.189594	train-rmspe:0.211899	val-rmspe:0.198142
[100]	train-rmse:0.173937	val-rmse:0.188428	train-rmspe:0.21073	val-rmspe:0.197
[101]	train-rmse:0.173178	val-rmse:0.187703	train-rmspe:0.209098	val-rmspe:0.196379
[102]	train-rmse:0.172781	val-rmse:0.187441	train-rmspe:0.208632	val-rmspe:0.196301
[103]	train-rmse:0.171937	val-rmse:0.186669	train-rmspe:0.207675	val-rmspe:0.195616
[104]	train-rmse:0.170711	val-rmse:0.185569	train-rmspe:0.206238	val-rmspe:0.194554
[105]	train-rmse:0.16931	val-rmse:0.184316	train-rmspe:0.204864	val-rmspe:0.193293
[106]	train-rmse:0.168777	val-rmse:0.183839	train-rmspe:0.204346	val-rmspe:0.192872
[107]	train-rmse:0.168149	val-rmse:0.183311	train-rmspe:0.203694	val-rmspe:0.192413
[108]	train-rmse:0.167855	val-rmse:0.18315	train-rmspe:0.203577	val-rmspe:0.192375
[109]	train-rmse:0.167403	val-rmse:0.182738	train-rmspe:0.202114	val-rmspe:0.191988
[110]	train-rmse:0.166928	val-rmse:0.182327	train-rmspe:0.201976	val-rmspe:0.191604

[198]	train-rmse:0.124519	val-rmse:0.149679	train-rmspe:0.152439	val-rmspe:0.156069
[199]	train-rmse:0.123993	val-rmse:0.149242	train-rmspe:0.151958	val-rmspe:0.155643
[200]	train-rmse:0.123801	val-rmse:0.149076	train-rmspe:0.151781	val-rmspe:0.155477
[201]	train-rmse:0.12349	val-rmse:0.148862	train-rmspe:0.151506	val-rmspe:0.15522
[202]	train-rmse:0.123314	val-rmse:0.148709	train-rmspe:0.151351	val-rmspe:0.155073
[203]	train-rmse:0.123207	val-rmse:0.148748	train-rmspe:0.151249	val-rmspe:0.155069
[204]	train-rmse:0.122817	val-rmse:0.148464	train-rmspe:0.150784	val-rmspe:0.154793
[205]	train-rmse:0.122538	val-rmse:0.148237	train-rmspe:0.150525	val-rmspe:0.154609
[206]	train-rmse:0.122375	val-rmse:0.148124	train-rmspe:0.150377	val-rmspe:0.154489
[207]	train-rmse:0.122089	val-rmse:0.147888	train-rmspe:0.150103	val-rmspe:0.154182
[208]	train-rmse:0.121759	val-rmse:0.147748	train-rmspe:0.149837	val-rmspe:0.153958
[209]	train-rmse:0.121574	val-rmse:0.147605	train-rmspe:0.149618	val-rmspe:0.1

[296]	train-rmse:0.107832	val-rmse:0.141494	train-rmspe:0.132351	val-rmspe:0.145965
[297]	train-rmse:0.107622	val-rmse:0.141371	train-rmspe:0.132456	val-rmspe:0.145815
[298]	train-rmse:0.107422	val-rmse:0.141353	train-rmspe:0.132217	val-rmspe:0.145682
[299]	train-rmse:0.107354	val-rmse:0.141319	train-rmspe:0.130232	val-rmspe:0.145527
[300]	train-rmse:0.107275	val-rmse:0.141295	train-rmspe:0.1302	val-rmspe:0.145484
[301]	train-rmse:0.107208	val-rmse:0.141253	train-rmspe:0.130158	val-rmspe:0.145436
[302]	train-rmse:0.107097	val-rmse:0.141241	train-rmspe:0.13008	val-rmspe:0.145394
[303]	train-rmse:0.107041	val-rmse:0.141217	train-rmspe:0.13003	val-rmspe:0.145381
[304]	train-rmse:0.106845	val-rmse:0.14123	train-rmspe:0.129817	val-rmspe:0.145372
[305]	train-rmse:0.106781	val-rmse:0.141191	train-rmspe:0.129755	val-rmspe:0.145322
[306]	train-rmse:0.106602	val-rmse:0.141099	train-rmspe:0.129746	val-rmspe:0.145223
[307]	train-rmse:0.106513	val-rmse:0.141076	train-rmspe:0.12967	val-rmspe:0.14519

[395]	train-rmse:0.098861	val-rmse:0.139061	train-rmspe:0.116851	val-rmspe:0.142281
[396]	train-rmse:0.098736	val-rmse:0.13901	train-rmspe:0.116751	val-rmspe:0.142235
[397]	train-rmse:0.09868	val-rmse:0.138982	train-rmspe:0.116701	val-rmspe:0.142224
[398]	train-rmse:0.098623	val-rmse:0.138978	train-rmspe:0.11666	val-rmspe:0.142221
[399]	train-rmse:0.098583	val-rmse:0.138903	train-rmspe:0.116606	val-rmspe:0.142151
[400]	train-rmse:0.098518	val-rmse:0.138881	train-rmspe:0.116536	val-rmspe:0.142126
[401]	train-rmse:0.098372	val-rmse:0.138822	train-rmspe:0.116428	val-rmspe:0.142053
[402]	train-rmse:0.098326	val-rmse:0.138804	train-rmspe:0.115982	val-rmspe:0.142022
[403]	train-rmse:0.098281	val-rmse:0.138783	train-rmspe:0.115943	val-rmspe:0.141948
[404]	train-rmse:0.098174	val-rmse:0.138833	train-rmspe:0.11591	val-rmspe:0.141929
[405]	train-rmse:0.098129	val-rmse:0.138834	train-rmspe:0.115884	val-rmspe:0.141928
[406]	train-rmse:0.098013	val-rmse:0.138867	train-rmspe:0.115621	val-rmspe:0.141

[493]	train-rmse:0.091921	val-rmse:0.138463	train-rmspe:0.103802	val-rmspe:0.140789
[494]	train-rmse:0.091871	val-rmse:0.138476	train-rmspe:0.103759	val-rmspe:0.140804
[495]	train-rmse:0.09182	val-rmse:0.138419	train-rmspe:0.103656	val-rmspe:0.140766
[496]	train-rmse:0.091773	val-rmse:0.138409	train-rmspe:0.103618	val-rmspe:0.140755
[497]	train-rmse:0.0917	val-rmse:0.138384	train-rmspe:0.103475	val-rmspe:0.140745
[498]	train-rmse:0.091619	val-rmse:0.138391	train-rmspe:0.103434	val-rmspe:0.140746
[499]	train-rmse:0.091561	val-rmse:0.138411	train-rmspe:0.10341	val-rmspe:0.140743
[500]	train-rmse:0.091517	val-rmse:0.138393	train-rmspe:0.10292	val-rmspe:0.140746
[501]	train-rmse:0.091464	val-rmse:0.13841	train-rmspe:0.10289	val-rmspe:0.14075
[502]	train-rmse:0.091424	val-rmse:0.138395	train-rmspe:0.102852	val-rmspe:0.140734
[503]	train-rmse:0.091388	val-rmse:0.138395	train-rmspe:0.102821	val-rmspe:0.140744
[504]	train-rmse:0.091303	val-rmse:0.138398	train-rmspe:0.102775	val-rmspe:0.140737


[591]	train-rmse:0.08645	val-rmse:0.139076	train-rmspe:0.095201	val-rmspe:0.140759
[592]	train-rmse:0.086414	val-rmse:0.139077	train-rmspe:0.095178	val-rmspe:0.140747
[593]	train-rmse:0.08634	val-rmse:0.139075	train-rmspe:0.095149	val-rmspe:0.140739
[594]	train-rmse:0.0863	val-rmse:0.13907	train-rmspe:0.095126	val-rmspe:0.14073
[595]	train-rmse:0.086231	val-rmse:0.13904	train-rmspe:0.095084	val-rmspe:0.140694
[596]	train-rmse:0.086219	val-rmse:0.139024	train-rmspe:0.095069	val-rmspe:0.140669
[597]	train-rmse:0.086158	val-rmse:0.139077	train-rmspe:0.095007	val-rmspe:0.14069
[598]	train-rmse:0.086121	val-rmse:0.139081	train-rmspe:0.094979	val-rmspe:0.140687
[599]	train-rmse:0.086084	val-rmse:0.139072	train-rmspe:0.094947	val-rmspe:0.140681
[600]	train-rmse:0.086047	val-rmse:0.13909	train-rmspe:0.094926	val-rmspe:0.140697
[601]	train-rmse:0.086017	val-rmse:0.139081	train-rmspe:0.0949	val-rmspe:0.140692
[602]	train-rmse:0.085958	val-rmse:0.139098	train-rmspe:0.094853	val-rmspe:0.140698
[60

[690]	train-rmse:0.082061	val-rmse:0.140105	train-rmspe:0.09036	val-rmspe:0.140693
[691]	train-rmse:0.082017	val-rmse:0.140114	train-rmspe:0.09027	val-rmspe:0.140709
[692]	train-rmse:0.081964	val-rmse:0.140121	train-rmspe:0.090178	val-rmspe:0.140699
[693]	train-rmse:0.081925	val-rmse:0.140149	train-rmspe:0.090179	val-rmspe:0.140706
[694]	train-rmse:0.08189	val-rmse:0.140146	train-rmspe:0.090234	val-rmspe:0.140687
[695]	train-rmse:0.081868	val-rmse:0.140136	train-rmspe:0.090218	val-rmspe:0.140688
[696]	train-rmse:0.08182	val-rmse:0.140141	train-rmspe:0.090176	val-rmspe:0.140674
[697]	train-rmse:0.081786	val-rmse:0.140149	train-rmspe:0.090149	val-rmspe:0.140677
[698]	train-rmse:0.081733	val-rmse:0.140153	train-rmspe:0.090107	val-rmspe:0.140682
[699]	train-rmse:0.081725	val-rmse:0.140157	train-rmspe:0.090099	val-rmspe:0.140669
[700]	train-rmse:0.081672	val-rmse:0.140197	train-rmspe:0.090004	val-rmspe:0.140726
[701]	train-rmse:0.081636	val-rmse:0.140222	train-rmspe:0.089479	val-rmspe:0.140

In [119]:
#设定参数
param = {'max_depth': 9, 'eta': 0.07, 'silent': 0, 'min_child_weight': 5, 'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)





[0]	train-rmse:7.00265	val-rmse:7.0411	train-rmspe:0.910658	val-rmspe:0.911196
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:6.51359	val-rmse:6.55237	train-rmspe:0.910331	val-rmspe:0.910883
[2]	train-rmse:6.05884	val-rmse:6.09792	train-rmspe:0.909823	val-rmspe:0.910398
[3]	train-rmse:5.63597	val-rmse:5.67534	train-rmspe:0.909062	val-rmspe:0.909671
[4]	train-rmse:5.24282	val-rmse:5.28207	train-rmspe:0.907957	val-rmspe:0.908615
[5]	train-rmse:4.87723	val-rmse:4.91649	train-rmspe:0.906406	val-rmspe:0.907133
[6]	train-rmse:4.53959	val-rmse:4.57782	train-rmspe:0.904302	val-rmspe:0.905118
[7]	train-rmse:4.22341	val-rmse:4.26123	train-rmspe:0.901492	val-rmspe:0.902428
[8]	train-rmse:3.92943	val-rmse:3.96675	train-rmspe:0.897849	val-rmspe:0.898938
[9]	train-rmse:3.65615	val-rmse:3.69333	train-rmspe:0.893231	val-rmspe:0.894513
[10]	train-rmse:3.40389	val-rmse:3.44365	train-rmspe:0.88

[99]	train-rmse:0.215308	val-rmse:0.219239	train-rmspe:0.260808	val-rmspe:0.236006
[100]	train-rmse:0.214065	val-rmse:0.218013	train-rmspe:0.259406	val-rmspe:0.234648
[101]	train-rmse:0.213299	val-rmse:0.217358	train-rmspe:0.258463	val-rmspe:0.234054
[102]	train-rmse:0.212917	val-rmse:0.21719	train-rmspe:0.258168	val-rmspe:0.234039
[103]	train-rmse:0.211836	val-rmse:0.216192	train-rmspe:0.257232	val-rmspe:0.233122
[104]	train-rmse:0.210388	val-rmse:0.214783	train-rmspe:0.255556	val-rmspe:0.231435
[105]	train-rmse:0.20962	val-rmse:0.214031	train-rmspe:0.254981	val-rmspe:0.230783
[106]	train-rmse:0.20925	val-rmse:0.213651	train-rmspe:0.254833	val-rmspe:0.23043
[107]	train-rmse:0.208248	val-rmse:0.212792	train-rmspe:0.253938	val-rmspe:0.229721
[108]	train-rmse:0.207975	val-rmse:0.212672	train-rmspe:0.253753	val-rmspe:0.229797
[109]	train-rmse:0.207674	val-rmse:0.212376	train-rmspe:0.253719	val-rmspe:0.229583
[110]	train-rmse:0.206281	val-rmse:0.211083	train-rmspe:0.252672	val-rmspe:0.2283

[197]	train-rmse:0.157797	val-rmse:0.168627	train-rmspe:0.203362	val-rmspe:0.179748
[198]	train-rmse:0.157463	val-rmse:0.168367	train-rmspe:0.202972	val-rmspe:0.179459
[199]	train-rmse:0.157011	val-rmse:0.167988	train-rmspe:0.202569	val-rmspe:0.179028
[200]	train-rmse:0.156769	val-rmse:0.167773	train-rmspe:0.202349	val-rmspe:0.178823
[201]	train-rmse:0.156577	val-rmse:0.1676	train-rmspe:0.202029	val-rmspe:0.178642
[202]	train-rmse:0.156078	val-rmse:0.16717	train-rmspe:0.201575	val-rmspe:0.178178
[203]	train-rmse:0.155785	val-rmse:0.166941	train-rmspe:0.201366	val-rmspe:0.178002
[204]	train-rmse:0.155295	val-rmse:0.166493	train-rmspe:0.200868	val-rmspe:0.17757
[205]	train-rmse:0.155177	val-rmse:0.166374	train-rmspe:0.200738	val-rmspe:0.17746
[206]	train-rmse:0.154992	val-rmse:0.166263	train-rmspe:0.20058	val-rmspe:0.177344
[207]	train-rmse:0.154707	val-rmse:0.16602	train-rmspe:0.200348	val-rmspe:0.177104
[208]	train-rmse:0.154569	val-rmse:0.166014	train-rmspe:0.200185	val-rmspe:0.177087

[295]	train-rmse:0.133946	val-rmse:0.149759	train-rmspe:0.1774	val-rmspe:0.159786
[296]	train-rmse:0.13387	val-rmse:0.149692	train-rmspe:0.177347	val-rmspe:0.159718
[297]	train-rmse:0.133667	val-rmse:0.149519	train-rmspe:0.177135	val-rmspe:0.159553
[298]	train-rmse:0.133573	val-rmse:0.149505	train-rmspe:0.177088	val-rmspe:0.159525
[299]	train-rmse:0.133421	val-rmse:0.149386	train-rmspe:0.177244	val-rmspe:0.159381
[300]	train-rmse:0.133391	val-rmse:0.149366	train-rmspe:0.176918	val-rmspe:0.159367
[301]	train-rmse:0.13326	val-rmse:0.149247	train-rmspe:0.17681	val-rmspe:0.158867
[302]	train-rmse:0.133088	val-rmse:0.149116	train-rmspe:0.176676	val-rmspe:0.158736
[303]	train-rmse:0.13296	val-rmse:0.148992	train-rmspe:0.176527	val-rmspe:0.158643
[304]	train-rmse:0.132817	val-rmse:0.148867	train-rmspe:0.176315	val-rmspe:0.158477
[305]	train-rmse:0.132691	val-rmse:0.148785	train-rmspe:0.176214	val-rmspe:0.158388
[306]	train-rmse:0.132508	val-rmse:0.148653	train-rmspe:0.175978	val-rmspe:0.15825

[394]	train-rmse:0.122758	val-rmse:0.142321	train-rmspe:0.159162	val-rmspe:0.150875
[395]	train-rmse:0.122685	val-rmse:0.142271	train-rmspe:0.15908	val-rmspe:0.150816
[396]	train-rmse:0.122581	val-rmse:0.142338	train-rmspe:0.158982	val-rmspe:0.15083
[397]	train-rmse:0.122507	val-rmse:0.142262	train-rmspe:0.158876	val-rmspe:0.150769
[398]	train-rmse:0.122388	val-rmse:0.142162	train-rmspe:0.158784	val-rmspe:0.150677
[399]	train-rmse:0.122186	val-rmse:0.142081	train-rmspe:0.158607	val-rmspe:0.150582
[400]	train-rmse:0.122073	val-rmse:0.141988	train-rmspe:0.158524	val-rmspe:0.150486
[401]	train-rmse:0.121938	val-rmse:0.141915	train-rmspe:0.158422	val-rmspe:0.150412
[402]	train-rmse:0.121815	val-rmse:0.141765	train-rmspe:0.158326	val-rmspe:0.150287
[403]	train-rmse:0.121728	val-rmse:0.14169	train-rmspe:0.158265	val-rmspe:0.150189
[404]	train-rmse:0.121666	val-rmse:0.141685	train-rmspe:0.158217	val-rmspe:0.15018
[405]	train-rmse:0.12165	val-rmse:0.141675	train-rmspe:0.158204	val-rmspe:0.1501

...

[790]	train-rmse:0.102467	val-rmse:0.135637	train-rmspe:0.134508	val-rmspe:0.141651
[791]	train-rmse:0.102447	val-rmse:0.135661	train-rmspe:0.134489	val-rmspe:0.141708
[792]	train-rmse:0.102417	val-rmse:0.135649	train-rmspe:0.134466	val-rmspe:0.141696
[793]	train-rmse:0.102394	val-rmse:0.135636	train-rmspe:0.134469	val-rmspe:0.141683
[794]	train-rmse:0.102351	val-rmse:0.135579	train-rmspe:0.134427	val-rmspe:0.141659
[795]	train-rmse:0.102306	val-rmse:0.135573	train-rmspe:0.134401	val-rmspe:0.141657
[796]	train-rmse:0.102279	val-rmse:0.13555	train-rmspe:0.134382	val-rmspe:0.141636
[797]	train-rmse:0.102255	val-rmse:0.135555	train-rmspe:0.134369	val-rmspe:0.141636
[798]	train-rmse:0.102216	val-rmse:0.135561	train-rmspe:0.134356	val-rmspe:0.141632
[799]	train-rmse:0.102173	val-rmse:0.135539	train-rmspe:0.134325	val-rmspe:0.141603
[800]	train-rmse:0.102129	val-rmse:0.135522	train-rmspe:0.134284	val-rmspe:0.141587
[801]	train-rmse:0.102081	val-rmse:0.135524	train-rmspe:0.134223	val-rmspe:0.

[888]	train-rmse:0.099398	val-rmse:0.135462	train-rmspe:0.128192	val-rmspe:0.141079
[889]	train-rmse:0.099364	val-rmse:0.135451	train-rmspe:0.128172	val-rmspe:0.141025
[890]	train-rmse:0.099331	val-rmse:0.135445	train-rmspe:0.128156	val-rmspe:0.141013
[891]	train-rmse:0.099309	val-rmse:0.135444	train-rmspe:0.128142	val-rmspe:0.141014
[892]	train-rmse:0.099274	val-rmse:0.13543	train-rmspe:0.128126	val-rmspe:0.141002
[893]	train-rmse:0.099257	val-rmse:0.135427	train-rmspe:0.128122	val-rmspe:0.141004
[894]	train-rmse:0.099247	val-rmse:0.135429	train-rmspe:0.128115	val-rmspe:0.140999
[895]	train-rmse:0.099215	val-rmse:0.135454	train-rmspe:0.128091	val-rmspe:0.14099
[896]	train-rmse:0.099179	val-rmse:0.135462	train-rmspe:0.128145	val-rmspe:0.140976
[897]	train-rmse:0.099162	val-rmse:0.135476	train-rmspe:0.128221	val-rmspe:0.140978
[898]	train-rmse:0.09912	val-rmse:0.135473	train-rmspe:0.128204	val-rmspe:0.140975
[899]	train-rmse:0.099093	val-rmse:0.135467	train-rmspe:0.128183	val-rmspe:0.14

[986]	train-rmse:0.096759	val-rmse:0.135818	train-rmspe:0.123577	val-rmspe:0.140686
[987]	train-rmse:0.096724	val-rmse:0.13583	train-rmspe:0.12356	val-rmspe:0.140714
[988]	train-rmse:0.096691	val-rmse:0.135838	train-rmspe:0.123481	val-rmspe:0.140711
[989]	train-rmse:0.096639	val-rmse:0.135869	train-rmspe:0.123394	val-rmspe:0.140731
[990]	train-rmse:0.096609	val-rmse:0.135865	train-rmspe:0.123358	val-rmspe:0.140727
[991]	train-rmse:0.096559	val-rmse:0.135881	train-rmspe:0.123328	val-rmspe:0.140702
[992]	train-rmse:0.096536	val-rmse:0.1359	train-rmspe:0.123319	val-rmspe:0.140708
[993]	train-rmse:0.096527	val-rmse:0.135908	train-rmspe:0.123316	val-rmspe:0.14071
[994]	train-rmse:0.096495	val-rmse:0.13591	train-rmspe:0.123305	val-rmspe:0.140708
[995]	train-rmse:0.096478	val-rmse:0.135897	train-rmspe:0.123287	val-rmspe:0.140695
[996]	train-rmse:0.096449	val-rmse:0.13588	train-rmspe:0.123265	val-rmspe:0.140675
[997]	train-rmse:0.09642	val-rmse:0.135879	train-rmspe:0.123252	val-rmspe:0.140669


[1084]	train-rmse:0.094432	val-rmse:0.13594	train-rmspe:0.1204	val-rmspe:0.140481
[1085]	train-rmse:0.094405	val-rmse:0.135941	train-rmspe:0.120334	val-rmspe:0.140474
[1086]	train-rmse:0.094376	val-rmse:0.135956	train-rmspe:0.120307	val-rmspe:0.140478
[1087]	train-rmse:0.094362	val-rmse:0.135957	train-rmspe:0.120303	val-rmspe:0.140468
[1088]	train-rmse:0.094331	val-rmse:0.13598	train-rmspe:0.120266	val-rmspe:0.140488
[1089]	train-rmse:0.09431	val-rmse:0.135973	train-rmspe:0.120211	val-rmspe:0.14048
[1090]	train-rmse:0.094294	val-rmse:0.135994	train-rmspe:0.120212	val-rmspe:0.140514
[1091]	train-rmse:0.094276	val-rmse:0.136006	train-rmspe:0.120202	val-rmspe:0.140526
[1092]	train-rmse:0.094248	val-rmse:0.13601	train-rmspe:0.120187	val-rmspe:0.1405
[1093]	train-rmse:0.094219	val-rmse:0.136017	train-rmspe:0.12018	val-rmspe:0.140498
[1094]	train-rmse:0.094208	val-rmse:0.136012	train-rmspe:0.120178	val-rmspe:0.140494
[1095]	train-rmse:0.094181	val-rmse:0.136018	train-rmspe:0.120144	val-rmspe

[1182]	train-rmse:0.092157	val-rmse:0.136584	train-rmspe:0.116425	val-rmspe:0.140577
[1183]	train-rmse:0.092134	val-rmse:0.136581	train-rmspe:0.116403	val-rmspe:0.140567
[1184]	train-rmse:0.092126	val-rmse:0.136581	train-rmspe:0.116391	val-rmspe:0.14057
[1185]	train-rmse:0.092109	val-rmse:0.136621	train-rmspe:0.116373	val-rmspe:0.140612
[1186]	train-rmse:0.092094	val-rmse:0.136599	train-rmspe:0.116368	val-rmspe:0.140604
[1187]	train-rmse:0.092075	val-rmse:0.136598	train-rmspe:0.116347	val-rmspe:0.140603
[1188]	train-rmse:0.092044	val-rmse:0.13662	train-rmspe:0.116335	val-rmspe:0.140606
[1189]	train-rmse:0.092022	val-rmse:0.136617	train-rmspe:0.116315	val-rmspe:0.140601
[1190]	train-rmse:0.092008	val-rmse:0.136614	train-rmspe:0.116307	val-rmspe:0.140602
[1191]	train-rmse:0.091984	val-rmse:0.136616	train-rmspe:0.116298	val-rmspe:0.140601
[1192]	train-rmse:0.091968	val-rmse:0.136615	train-rmspe:0.116046	val-rmspe:0.140598
[1193]	train-rmse:0.091955	val-rmse:0.136615	train-rmspe:0.116051	v

In [120]:
#设定参数
param = {'max_depth': 10, 'eta': 0.07, 'silent': 0, 'gamma': 0.1, 'min_child_weight': 5, 'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)






[0]	train-rmse:7.00261	val-rmse:7.04107	train-rmspe:0.910658	val-rmspe:0.911196
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:6.51353	val-rmse:6.55233	train-rmspe:0.910332	val-rmspe:0.910884
[2]	train-rmse:6.05875	val-rmse:6.09763	train-rmspe:0.909825	val-rmspe:0.910399
[3]	train-rmse:5.63585	val-rmse:5.67481	train-rmspe:0.909065	val-rmspe:0.909673
[4]	train-rmse:5.24266	val-rmse:5.28167	train-rmspe:0.907963	val-rmspe:0.908619
[5]	train-rmse:4.87703	val-rmse:4.91602	train-rmspe:0.906415	val-rmspe:0.90714
[6]	train-rmse:4.53911	val-rmse:4.57726	train-rmspe:0.904315	val-rmspe:0.905128
[7]	train-rmse:4.22289	val-rmse:4.26063	train-rmspe:0.901512	val-rmspe:0.902444
[8]	train-rmse:3.9289	val-rmse:3.96605	train-rmspe:0.897877	val-rmspe:0.898959
[9]	train-rmse:3.65558	val-rmse:3.6924	train-rmspe:0.893271	val-rmspe:0.89454
[10]	train-rmse:3.4028	val-rmse:3.44379	train-rmspe:0.887586

[99]	train-rmse:0.196705	val-rmse:0.205642	train-rmspe:0.235403	val-rmspe:0.215835
[100]	train-rmse:0.195822	val-rmse:0.204792	train-rmspe:0.234626	val-rmspe:0.215089
[101]	train-rmse:0.194853	val-rmse:0.204002	train-rmspe:0.233799	val-rmspe:0.214344
[102]	train-rmse:0.193718	val-rmse:0.202907	train-rmspe:0.232959	val-rmspe:0.213217
[103]	train-rmse:0.192179	val-rmse:0.201453	train-rmspe:0.230626	val-rmspe:0.21176
[104]	train-rmse:0.191932	val-rmse:0.20119	train-rmspe:0.230484	val-rmspe:0.211755
[105]	train-rmse:0.19125	val-rmse:0.20057	train-rmspe:0.229851	val-rmspe:0.211197
[106]	train-rmse:0.190708	val-rmse:0.200058	train-rmspe:0.229394	val-rmspe:0.210725
[107]	train-rmse:0.189783	val-rmse:0.199289	train-rmspe:0.228771	val-rmspe:0.210012
[108]	train-rmse:0.18943	val-rmse:0.199059	train-rmspe:0.228477	val-rmspe:0.209926
[109]	train-rmse:0.187701	val-rmse:0.197576	train-rmspe:0.226513	val-rmspe:0.208451
[110]	train-rmse:0.187216	val-rmse:0.197145	train-rmspe:0.225967	val-rmspe:0.20772

[197]	train-rmse:0.139771	val-rmse:0.158614	train-rmspe:0.173394	val-rmspe:0.166465
[198]	train-rmse:0.139173	val-rmse:0.158124	train-rmspe:0.172836	val-rmspe:0.165977
[199]	train-rmse:0.138974	val-rmse:0.158107	train-rmspe:0.172577	val-rmspe:0.165894
[200]	train-rmse:0.138877	val-rmse:0.158026	train-rmspe:0.17263	val-rmspe:0.16563
[201]	train-rmse:0.138498	val-rmse:0.157753	train-rmspe:0.172316	val-rmspe:0.165351
[202]	train-rmse:0.138032	val-rmse:0.157338	train-rmspe:0.171751	val-rmspe:0.164863
[203]	train-rmse:0.137936	val-rmse:0.157265	train-rmspe:0.170707	val-rmspe:0.164784
[204]	train-rmse:0.137462	val-rmse:0.156918	train-rmspe:0.170273	val-rmspe:0.164448
[205]	train-rmse:0.136947	val-rmse:0.156487	train-rmspe:0.169918	val-rmspe:0.16408
[206]	train-rmse:0.136706	val-rmse:0.156379	train-rmspe:0.169752	val-rmspe:0.163975
[207]	train-rmse:0.136477	val-rmse:0.156209	train-rmspe:0.168838	val-rmspe:0.163815
[208]	train-rmse:0.136177	val-rmse:0.155961	train-rmspe:0.168559	val-rmspe:0.16

[295]	train-rmse:0.121074	val-rmse:0.145871	train-rmspe:0.148003	val-rmspe:0.151958
[296]	train-rmse:0.120937	val-rmse:0.145797	train-rmspe:0.147886	val-rmspe:0.151869
[297]	train-rmse:0.12084	val-rmse:0.145747	train-rmspe:0.147616	val-rmspe:0.151813
[298]	train-rmse:0.120758	val-rmse:0.145688	train-rmspe:0.147534	val-rmspe:0.15174
[299]	train-rmse:0.120571	val-rmse:0.14556	train-rmspe:0.147363	val-rmspe:0.151589
[300]	train-rmse:0.120472	val-rmse:0.145508	train-rmspe:0.147288	val-rmspe:0.15154
[301]	train-rmse:0.120437	val-rmse:0.145476	train-rmspe:0.147256	val-rmspe:0.151502
[302]	train-rmse:0.12034	val-rmse:0.145427	train-rmspe:0.147188	val-rmspe:0.151385
[303]	train-rmse:0.12023	val-rmse:0.145367	train-rmspe:0.146996	val-rmspe:0.151331
[304]	train-rmse:0.120127	val-rmse:0.145336	train-rmspe:0.146832	val-rmspe:0.151322
[305]	train-rmse:0.120055	val-rmse:0.145264	train-rmspe:0.146765	val-rmspe:0.151252
[306]	train-rmse:0.119847	val-rmse:0.145111	train-rmspe:0.146555	val-rmspe:0.15109

[394]	train-rmse:0.111807	val-rmse:0.141268	train-rmspe:0.134204	val-rmspe:0.146563
[395]	train-rmse:0.11171	val-rmse:0.141203	train-rmspe:0.134109	val-rmspe:0.146464
[396]	train-rmse:0.111608	val-rmse:0.141133	train-rmspe:0.13396	val-rmspe:0.146264
[397]	train-rmse:0.111551	val-rmse:0.141105	train-rmspe:0.133919	val-rmspe:0.146161
[398]	train-rmse:0.111503	val-rmse:0.14107	train-rmspe:0.133871	val-rmspe:0.146127
[399]	train-rmse:0.111429	val-rmse:0.141029	train-rmspe:0.133802	val-rmspe:0.146078
[400]	train-rmse:0.111389	val-rmse:0.141016	train-rmspe:0.13377	val-rmspe:0.146063
[401]	train-rmse:0.111179	val-rmse:0.140986	train-rmspe:0.132885	val-rmspe:0.14599
[402]	train-rmse:0.111136	val-rmse:0.140962	train-rmspe:0.132855	val-rmspe:0.145955
[403]	train-rmse:0.111081	val-rmse:0.140929	train-rmspe:0.132806	val-rmspe:0.145935
[404]	train-rmse:0.110952	val-rmse:0.141081	train-rmspe:0.132729	val-rmspe:0.146108
[405]	train-rmse:0.110911	val-rmse:0.141063	train-rmspe:0.132692	val-rmspe:0.1460

[492]	train-rmse:0.106015	val-rmse:0.139451	train-rmspe:0.124947	val-rmspe:0.144033
[493]	train-rmse:0.105998	val-rmse:0.139449	train-rmspe:0.12493	val-rmspe:0.144026
[494]	train-rmse:0.105962	val-rmse:0.139441	train-rmspe:0.124921	val-rmspe:0.144013
[495]	train-rmse:0.105877	val-rmse:0.139495	train-rmspe:0.124884	val-rmspe:0.144055
[496]	train-rmse:0.105828	val-rmse:0.139467	train-rmspe:0.124845	val-rmspe:0.144027
[497]	train-rmse:0.105764	val-rmse:0.139485	train-rmspe:0.124694	val-rmspe:0.144022
[498]	train-rmse:0.105724	val-rmse:0.139496	train-rmspe:0.124672	val-rmspe:0.144038
[499]	train-rmse:0.105707	val-rmse:0.139482	train-rmspe:0.124654	val-rmspe:0.144028
[500]	train-rmse:0.105686	val-rmse:0.139473	train-rmspe:0.124673	val-rmspe:0.14402
[501]	train-rmse:0.105665	val-rmse:0.139486	train-rmspe:0.124658	val-rmspe:0.144028
[502]	train-rmse:0.10563	val-rmse:0.139459	train-rmspe:0.124626	val-rmspe:0.143997
[503]	train-rmse:0.105597	val-rmse:0.139439	train-rmspe:0.124634	val-rmspe:0.14

[590]	train-rmse:0.102363	val-rmse:0.138786	train-rmspe:0.118749	val-rmspe:0.142717
[591]	train-rmse:0.102353	val-rmse:0.138783	train-rmspe:0.118741	val-rmspe:0.14272
[592]	train-rmse:0.102322	val-rmse:0.138779	train-rmspe:0.118717	val-rmspe:0.142703
[593]	train-rmse:0.102295	val-rmse:0.138784	train-rmspe:0.11869	val-rmspe:0.142689
[594]	train-rmse:0.102265	val-rmse:0.138769	train-rmspe:0.118662	val-rmspe:0.142672
[595]	train-rmse:0.102228	val-rmse:0.138751	train-rmspe:0.118638	val-rmspe:0.142649
[596]	train-rmse:0.102223	val-rmse:0.138729	train-rmspe:0.11863	val-rmspe:0.142639
[597]	train-rmse:0.102195	val-rmse:0.138721	train-rmspe:0.118615	val-rmspe:0.142632
[598]	train-rmse:0.10215	val-rmse:0.1387	train-rmspe:0.118585	val-rmspe:0.142609
[599]	train-rmse:0.102128	val-rmse:0.138692	train-rmspe:0.118566	val-rmspe:0.142601
[600]	train-rmse:0.102104	val-rmse:0.138686	train-rmspe:0.118542	val-rmspe:0.142603
[601]	train-rmse:0.102084	val-rmse:0.138674	train-rmspe:0.118516	val-rmspe:0.14258

[689]	train-rmse:0.099598	val-rmse:0.138663	train-rmspe:0.115879	val-rmspe:0.142208
[690]	train-rmse:0.099589	val-rmse:0.138661	train-rmspe:0.115875	val-rmspe:0.142205
[691]	train-rmse:0.099559	val-rmse:0.13865	train-rmspe:0.115848	val-rmspe:0.142199
[692]	train-rmse:0.099521	val-rmse:0.138671	train-rmspe:0.115834	val-rmspe:0.142193
[693]	train-rmse:0.099514	val-rmse:0.138681	train-rmspe:0.115826	val-rmspe:0.142234
[694]	train-rmse:0.099486	val-rmse:0.138665	train-rmspe:0.115805	val-rmspe:0.142216
[695]	train-rmse:0.099476	val-rmse:0.138653	train-rmspe:0.115793	val-rmspe:0.142213
[696]	train-rmse:0.09944	val-rmse:0.138669	train-rmspe:0.115753	val-rmspe:0.142235
[697]	train-rmse:0.09942	val-rmse:0.138666	train-rmspe:0.115714	val-rmspe:0.14223
[698]	train-rmse:0.099361	val-rmse:0.138696	train-rmspe:0.11569	val-rmspe:0.142245
[699]	train-rmse:0.099347	val-rmse:0.138686	train-rmspe:0.115689	val-rmspe:0.142237
[700]	train-rmse:0.099317	val-rmse:0.138697	train-rmspe:0.11562	val-rmspe:0.14224

[788]	train-rmse:0.097357	val-rmse:0.13865	train-rmspe:0.111459	val-rmspe:0.141834
[789]	train-rmse:0.097337	val-rmse:0.138629	train-rmspe:0.111444	val-rmspe:0.141825
[790]	train-rmse:0.097313	val-rmse:0.138632	train-rmspe:0.111436	val-rmspe:0.141823
[791]	train-rmse:0.097298	val-rmse:0.138638	train-rmspe:0.111414	val-rmspe:0.141829
[792]	train-rmse:0.097271	val-rmse:0.138651	train-rmspe:0.111388	val-rmspe:0.141834
[793]	train-rmse:0.09725	val-rmse:0.138662	train-rmspe:0.111381	val-rmspe:0.141834
[794]	train-rmse:0.097206	val-rmse:0.138664	train-rmspe:0.11137	val-rmspe:0.141831
[795]	train-rmse:0.097174	val-rmse:0.138666	train-rmspe:0.11135	val-rmspe:0.141825
[796]	train-rmse:0.097156	val-rmse:0.138656	train-rmspe:0.111334	val-rmspe:0.141814
[797]	train-rmse:0.097124	val-rmse:0.138667	train-rmspe:0.111319	val-rmspe:0.141822
[798]	train-rmse:0.097077	val-rmse:0.138666	train-rmspe:0.111312	val-rmspe:0.141821
[799]	train-rmse:0.097057	val-rmse:0.138661	train-rmspe:0.1113	val-rmspe:0.14181

[887]	train-rmse:0.095528	val-rmse:0.139076	train-rmspe:0.108482	val-rmspe:0.141726
[888]	train-rmse:0.095518	val-rmse:0.139074	train-rmspe:0.108474	val-rmspe:0.141723
[889]	train-rmse:0.095516	val-rmse:0.139078	train-rmspe:0.108476	val-rmspe:0.141728
[890]	train-rmse:0.095499	val-rmse:0.139073	train-rmspe:0.108465	val-rmspe:0.141724
[891]	train-rmse:0.095463	val-rmse:0.139094	train-rmspe:0.108452	val-rmspe:0.141726
[892]	train-rmse:0.095442	val-rmse:0.139114	train-rmspe:0.108438	val-rmspe:0.141722
[893]	train-rmse:0.095427	val-rmse:0.139123	train-rmspe:0.108429	val-rmspe:0.141731
[894]	train-rmse:0.095421	val-rmse:0.139127	train-rmspe:0.108428	val-rmspe:0.141736
[895]	train-rmse:0.095412	val-rmse:0.139137	train-rmspe:0.10844	val-rmspe:0.141735
[896]	train-rmse:0.095365	val-rmse:0.13915	train-rmspe:0.108466	val-rmspe:0.141738
[897]	train-rmse:0.095352	val-rmse:0.139151	train-rmspe:0.108458	val-rmspe:0.141739
[898]	train-rmse:0.09533	val-rmse:0.13914	train-rmspe:0.10843	val-rmspe:0.1417

In [122]:
#设定参数
param = {'max_depth': 10, 'eta': 0.07, 'silent': 0, 'objective': 'reg:linear', 'gamma': 0.01, 'min_child_weight': 5, 'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)







[0]	train-rmse:7.00261	val-rmse:7.04107	train-rmspe:0.910658	val-rmspe:0.911196
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:6.51353	val-rmse:6.55233	train-rmspe:0.910332	val-rmspe:0.910884
[2]	train-rmse:6.05875	val-rmse:6.09763	train-rmspe:0.909825	val-rmspe:0.910399
[3]	train-rmse:5.63585	val-rmse:5.67481	train-rmspe:0.909065	val-rmspe:0.909673
[4]	train-rmse:5.24266	val-rmse:5.28167	train-rmspe:0.907963	val-rmspe:0.908619
[5]	train-rmse:4.87703	val-rmse:4.91602	train-rmspe:0.906415	val-rmspe:0.90714
[6]	train-rmse:4.53911	val-rmse:4.57726	train-rmspe:0.904315	val-rmspe:0.905128
[7]	train-rmse:4.22289	val-rmse:4.26063	train-rmspe:0.901512	val-rmspe:0.902444
[8]	train-rmse:3.9289	val-rmse:3.96605	train-rmspe:0.897877	val-rmspe:0.898959
[9]	train-rmse:3.65558	val-rmse:3.6924	train-rmspe:0.893271	val-rmspe:0.89454
[10]	train-rmse:3.4028	val-rmse:3.44379	train-rmspe:0.887586

[99]	train-rmse:0.194024	val-rmse:0.203687	train-rmspe:0.235036	val-rmspe:0.214834
[100]	train-rmse:0.193908	val-rmse:0.203506	train-rmspe:0.235232	val-rmspe:0.214811
[101]	train-rmse:0.193078	val-rmse:0.202678	train-rmspe:0.233311	val-rmspe:0.214111
[102]	train-rmse:0.192668	val-rmse:0.20236	train-rmspe:0.232658	val-rmspe:0.214015
[103]	train-rmse:0.191599	val-rmse:0.201349	train-rmspe:0.231471	val-rmspe:0.213142
[104]	train-rmse:0.190357	val-rmse:0.200149	train-rmspe:0.230183	val-rmspe:0.211917
[105]	train-rmse:0.188896	val-rmse:0.198825	train-rmspe:0.228893	val-rmspe:0.210674
[106]	train-rmse:0.187646	val-rmse:0.19767	train-rmspe:0.227602	val-rmspe:0.209336
[107]	train-rmse:0.186885	val-rmse:0.19696	train-rmspe:0.226955	val-rmspe:0.208682
[108]	train-rmse:0.186539	val-rmse:0.196867	train-rmspe:0.226063	val-rmspe:0.208797
[109]	train-rmse:0.185673	val-rmse:0.196062	train-rmspe:0.225214	val-rmspe:0.20795
[110]	train-rmse:0.1849	val-rmse:0.195291	train-rmspe:0.224468	val-rmspe:0.207197

[198]	train-rmse:0.141634	val-rmse:0.159878	train-rmspe:0.174796	val-rmspe:0.170487
[199]	train-rmse:0.141011	val-rmse:0.159364	train-rmspe:0.174146	val-rmspe:0.169915
[200]	train-rmse:0.140682	val-rmse:0.159122	train-rmspe:0.173849	val-rmspe:0.169635
[201]	train-rmse:0.140307	val-rmse:0.158809	train-rmspe:0.173509	val-rmspe:0.16933
[202]	train-rmse:0.140035	val-rmse:0.15857	train-rmspe:0.173263	val-rmspe:0.169086
[203]	train-rmse:0.139597	val-rmse:0.158262	train-rmspe:0.172697	val-rmspe:0.168733
[204]	train-rmse:0.139303	val-rmse:0.158023	train-rmspe:0.172435	val-rmspe:0.168507
[205]	train-rmse:0.138803	val-rmse:0.157584	train-rmspe:0.171984	val-rmspe:0.167998
[206]	train-rmse:0.138554	val-rmse:0.157399	train-rmspe:0.171735	val-rmspe:0.167809
[207]	train-rmse:0.138328	val-rmse:0.15721	train-rmspe:0.171487	val-rmspe:0.167492
[208]	train-rmse:0.13813	val-rmse:0.157272	train-rmspe:0.171246	val-rmspe:0.167566
[209]	train-rmse:0.137936	val-rmse:0.157114	train-rmspe:0.171051	val-rmspe:0.167

[297]	train-rmse:0.120806	val-rmse:0.145847	train-rmspe:0.153895	val-rmspe:0.152579
[298]	train-rmse:0.120673	val-rmse:0.145743	train-rmspe:0.153786	val-rmspe:0.152472
[299]	train-rmse:0.120553	val-rmse:0.145647	train-rmspe:0.152133	val-rmspe:0.152282
[300]	train-rmse:0.120523	val-rmse:0.145631	train-rmspe:0.152083	val-rmspe:0.152266
[301]	train-rmse:0.120443	val-rmse:0.145553	train-rmspe:0.152009	val-rmspe:0.152184
[302]	train-rmse:0.120395	val-rmse:0.145535	train-rmspe:0.151995	val-rmspe:0.152153
[303]	train-rmse:0.120285	val-rmse:0.145467	train-rmspe:0.151615	val-rmspe:0.152092
[304]	train-rmse:0.120118	val-rmse:0.145364	train-rmspe:0.151503	val-rmspe:0.152033
[305]	train-rmse:0.119929	val-rmse:0.145225	train-rmspe:0.151205	val-rmspe:0.151888
[306]	train-rmse:0.119797	val-rmse:0.145101	train-rmspe:0.151076	val-rmspe:0.151783
[307]	train-rmse:0.119656	val-rmse:0.14502	train-rmspe:0.150957	val-rmspe:0.151683
[308]	train-rmse:0.119512	val-rmse:0.145093	train-rmspe:0.150852	val-rmspe:0.

[396]	train-rmse:0.110893	val-rmse:0.140917	train-rmspe:0.138344	val-rmspe:0.146774
[397]	train-rmse:0.11082	val-rmse:0.140863	train-rmspe:0.138226	val-rmspe:0.146726
[398]	train-rmse:0.110703	val-rmse:0.140793	train-rmspe:0.138052	val-rmspe:0.146663
[399]	train-rmse:0.110585	val-rmse:0.140703	train-rmspe:0.137925	val-rmspe:0.146567
[400]	train-rmse:0.110491	val-rmse:0.140692	train-rmspe:0.137852	val-rmspe:0.146571
[401]	train-rmse:0.110329	val-rmse:0.140633	train-rmspe:0.13761	val-rmspe:0.146477
[402]	train-rmse:0.110218	val-rmse:0.140468	train-rmspe:0.137444	val-rmspe:0.146317
[403]	train-rmse:0.110148	val-rmse:0.140406	train-rmspe:0.137384	val-rmspe:0.146167
[404]	train-rmse:0.110065	val-rmse:0.14038	train-rmspe:0.137307	val-rmspe:0.146134
[405]	train-rmse:0.11001	val-rmse:0.140382	train-rmspe:0.137288	val-rmspe:0.146132
[406]	train-rmse:0.109881	val-rmse:0.140338	train-rmspe:0.137205	val-rmspe:0.146093
[407]	train-rmse:0.109814	val-rmse:0.140296	train-rmspe:0.137148	val-rmspe:0.146

...

[594]	train-rmse:0.098613	val-rmse:0.137734	train-rmspe:0.116879	val-rmspe:0.141719
[595]	train-rmse:0.098564	val-rmse:0.137718	train-rmspe:0.116877	val-rmspe:0.141702
[596]	train-rmse:0.098555	val-rmse:0.137704	train-rmspe:0.116864	val-rmspe:0.14169
[597]	train-rmse:0.098513	val-rmse:0.137696	train-rmspe:0.116835	val-rmspe:0.141676
[598]	train-rmse:0.098458	val-rmse:0.137689	train-rmspe:0.116812	val-rmspe:0.141669
[599]	train-rmse:0.0984	val-rmse:0.137664	train-rmspe:0.116756	val-rmspe:0.141639
[600]	train-rmse:0.09835	val-rmse:0.137665	train-rmspe:0.116698	val-rmspe:0.141637
[601]	train-rmse:0.09831	val-rmse:0.137663	train-rmspe:0.116286	val-rmspe:0.14163
[602]	train-rmse:0.09827	val-rmse:0.137645	train-rmspe:0.116264	val-rmspe:0.141619
[603]	train-rmse:0.098225	val-rmse:0.137642	train-rmspe:0.116227	val-rmspe:0.141583
[604]	train-rmse:0.098181	val-rmse:0.137627	train-rmspe:0.116202	val-rmspe:0.141577
[605]	train-rmse:0.098125	val-rmse:0.137625	train-rmspe:0.11616	val-rmspe:0.141573


[693]	train-rmse:0.094618	val-rmse:0.137525	train-rmspe:0.108339	val-rmspe:0.141089
[694]	train-rmse:0.094574	val-rmse:0.137516	train-rmspe:0.108312	val-rmspe:0.141063
[695]	train-rmse:0.094555	val-rmse:0.137497	train-rmspe:0.108292	val-rmspe:0.141054
[696]	train-rmse:0.094508	val-rmse:0.137507	train-rmspe:0.108264	val-rmspe:0.14107
[697]	train-rmse:0.09448	val-rmse:0.137514	train-rmspe:0.108238	val-rmspe:0.141066
[698]	train-rmse:0.094431	val-rmse:0.13752	train-rmspe:0.108207	val-rmspe:0.141075
[699]	train-rmse:0.094422	val-rmse:0.137522	train-rmspe:0.108177	val-rmspe:0.141073
[700]	train-rmse:0.09439	val-rmse:0.137512	train-rmspe:0.108117	val-rmspe:0.141062
[701]	train-rmse:0.094274	val-rmse:0.137556	train-rmspe:0.108084	val-rmspe:0.141056
[702]	train-rmse:0.094249	val-rmse:0.137576	train-rmspe:0.108071	val-rmspe:0.141061
[703]	train-rmse:0.094221	val-rmse:0.137563	train-rmspe:0.108022	val-rmspe:0.141007
[704]	train-rmse:0.094211	val-rmse:0.13756	train-rmspe:0.10801	val-rmspe:0.14100

[792]	train-rmse:0.091133	val-rmse:0.137932	train-rmspe:0.104296	val-rmspe:0.140947
[793]	train-rmse:0.091108	val-rmse:0.137939	train-rmspe:0.104286	val-rmspe:0.140964
[794]	train-rmse:0.091075	val-rmse:0.137938	train-rmspe:0.104186	val-rmspe:0.140959
[795]	train-rmse:0.091028	val-rmse:0.137936	train-rmspe:0.104158	val-rmspe:0.140953
[796]	train-rmse:0.090979	val-rmse:0.137912	train-rmspe:0.104119	val-rmspe:0.140928
[797]	train-rmse:0.090967	val-rmse:0.137908	train-rmspe:0.10411	val-rmspe:0.140923
[798]	train-rmse:0.090919	val-rmse:0.137916	train-rmspe:0.104092	val-rmspe:0.140917
[799]	train-rmse:0.090887	val-rmse:0.137943	train-rmspe:0.10399	val-rmspe:0.140915
[800]	train-rmse:0.090839	val-rmse:0.137943	train-rmspe:0.103957	val-rmspe:0.140906
[801]	train-rmse:0.090793	val-rmse:0.137948	train-rmspe:0.103917	val-rmspe:0.140903
[802]	train-rmse:0.090742	val-rmse:0.13796	train-rmspe:0.10386	val-rmspe:0.140905
[803]	train-rmse:0.09071	val-rmse:0.137953	train-rmspe:0.10384	val-rmspe:0.14089

[891]	train-rmse:0.087757	val-rmse:0.138635	train-rmspe:0.099342	val-rmspe:0.140873
[892]	train-rmse:0.087737	val-rmse:0.138628	train-rmspe:0.099329	val-rmspe:0.140867
[893]	train-rmse:0.087719	val-rmse:0.138627	train-rmspe:0.099314	val-rmspe:0.140863
[894]	train-rmse:0.087698	val-rmse:0.138635	train-rmspe:0.099307	val-rmspe:0.140877
[895]	train-rmse:0.08767	val-rmse:0.138647	train-rmspe:0.099326	val-rmspe:0.140881
[896]	train-rmse:0.087638	val-rmse:0.138667	train-rmspe:0.099312	val-rmspe:0.140885
[897]	train-rmse:0.087599	val-rmse:0.13869	train-rmspe:0.099294	val-rmspe:0.140889
[898]	train-rmse:0.087579	val-rmse:0.138679	train-rmspe:0.099281	val-rmspe:0.140882
[899]	train-rmse:0.087556	val-rmse:0.138678	train-rmspe:0.099265	val-rmspe:0.140879
[900]	train-rmse:0.087525	val-rmse:0.138668	train-rmspe:0.099278	val-rmspe:0.140875
[901]	train-rmse:0.087498	val-rmse:0.138673	train-rmspe:0.099125	val-rmspe:0.140873
[902]	train-rmse:0.087475	val-rmse:0.138666	train-rmspe:0.099095	val-rmspe:0.1

[990]	train-rmse:0.084884	val-rmse:0.139468	train-rmspe:0.096186	val-rmspe:0.141037
[991]	train-rmse:0.084852	val-rmse:0.139478	train-rmspe:0.096175	val-rmspe:0.141018
[992]	train-rmse:0.084836	val-rmse:0.139507	train-rmspe:0.096168	val-rmspe:0.141019
[993]	train-rmse:0.084822	val-rmse:0.139521	train-rmspe:0.096156	val-rmspe:0.141028
[994]	train-rmse:0.084803	val-rmse:0.139532	train-rmspe:0.096136	val-rmspe:0.141017
[995]	train-rmse:0.084778	val-rmse:0.139545	train-rmspe:0.096034	val-rmspe:0.141013
[996]	train-rmse:0.084765	val-rmse:0.139537	train-rmspe:0.09602	val-rmspe:0.141006
[997]	train-rmse:0.084745	val-rmse:0.139538	train-rmspe:0.096009	val-rmspe:0.141004
[998]	train-rmse:0.084717	val-rmse:0.139537	train-rmspe:0.096	val-rmspe:0.141004
[999]	train-rmse:0.084691	val-rmse:0.139577	train-rmspe:0.095989	val-rmspe:0.141006
[1000]	train-rmse:0.084655	val-rmse:0.139578	train-rmspe:0.095985	val-rmspe:0.141009
[1001]	train-rmse:0.08464	val-rmse:0.139576	train-rmspe:0.095957	val-rmspe:0.14

In [123]:
#设定参数
param = {'max_depth': 10, 'eta': 0.07, 'silent': 0, 'objective': 'reg:linear', 'min_child_weight': 5, 'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 800
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)








[0]	train-rmse:7.00261	val-rmse:7.04107	train-rmspe:0.910658	val-rmspe:0.911196
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:6.51353	val-rmse:6.55233	train-rmspe:0.910332	val-rmspe:0.910884
[2]	train-rmse:6.05875	val-rmse:6.09763	train-rmspe:0.909825	val-rmspe:0.910399
[3]	train-rmse:5.63585	val-rmse:5.67481	train-rmspe:0.909065	val-rmspe:0.909673
[4]	train-rmse:5.24266	val-rmse:5.28167	train-rmspe:0.907963	val-rmspe:0.908619
[5]	train-rmse:4.87703	val-rmse:4.91602	train-rmspe:0.906415	val-rmspe:0.90714
[6]	train-rmse:4.53911	val-rmse:4.57726	train-rmspe:0.904315	val-rmspe:0.905128
[7]	train-rmse:4.22289	val-rmse:4.26063	train-rmspe:0.901512	val-rmspe:0.902444
[8]	train-rmse:3.9289	val-rmse:3.96605	train-rmspe:0.897877	val-rmspe:0.898959
[9]	train-rmse:3.65558	val-rmse:3.6924	train-rmspe:0.893271	val-rmspe:0.89454
[10]	train-rmse:3.4028	val-rmse:3.44379	train-rmspe:0.887586

[99]	train-rmse:0.19189	val-rmse:0.201669	train-rmspe:0.230149	val-rmspe:0.211818
[100]	train-rmse:0.191178	val-rmse:0.201048	train-rmspe:0.229501	val-rmspe:0.211171
[101]	train-rmse:0.190268	val-rmse:0.200223	train-rmspe:0.228509	val-rmspe:0.210447
[102]	train-rmse:0.189862	val-rmse:0.199934	train-rmspe:0.228078	val-rmspe:0.210363
[103]	train-rmse:0.187841	val-rmse:0.198055	train-rmspe:0.225948	val-rmspe:0.208487
[104]	train-rmse:0.186664	val-rmse:0.197074	train-rmspe:0.224575	val-rmspe:0.207499
[105]	train-rmse:0.185235	val-rmse:0.195651	train-rmspe:0.223426	val-rmspe:0.206272
[106]	train-rmse:0.184344	val-rmse:0.194865	train-rmspe:0.222633	val-rmspe:0.205611
[107]	train-rmse:0.183069	val-rmse:0.193358	train-rmspe:0.221443	val-rmspe:0.204185
[108]	train-rmse:0.182305	val-rmse:0.19272	train-rmspe:0.220143	val-rmspe:0.203657
[109]	train-rmse:0.182161	val-rmse:0.192575	train-rmspe:0.220012	val-rmspe:0.203562
[110]	train-rmse:0.181728	val-rmse:0.192154	train-rmspe:0.219804	val-rmspe:0.20

[198]	train-rmse:0.136167	val-rmse:0.155322	train-rmspe:0.171822	val-rmspe:0.163135
[199]	train-rmse:0.135931	val-rmse:0.155034	train-rmspe:0.171585	val-rmspe:0.16277
[200]	train-rmse:0.13562	val-rmse:0.154789	train-rmspe:0.171286	val-rmspe:0.162506
[201]	train-rmse:0.135468	val-rmse:0.154672	train-rmspe:0.171004	val-rmspe:0.162368
[202]	train-rmse:0.13523	val-rmse:0.154474	train-rmspe:0.170771	val-rmspe:0.162169
[203]	train-rmse:0.135092	val-rmse:0.154352	train-rmspe:0.17068	val-rmspe:0.162031
[204]	train-rmse:0.135007	val-rmse:0.154264	train-rmspe:0.170614	val-rmspe:0.161953
[205]	train-rmse:0.134664	val-rmse:0.153948	train-rmspe:0.170315	val-rmspe:0.161646
[206]	train-rmse:0.134483	val-rmse:0.153816	train-rmspe:0.170155	val-rmspe:0.161518
[207]	train-rmse:0.134204	val-rmse:0.153647	train-rmspe:0.169967	val-rmspe:0.161326
[208]	train-rmse:0.134166	val-rmse:0.153608	train-rmspe:0.169937	val-rmspe:0.161301
[209]	train-rmse:0.133958	val-rmse:0.153439	train-rmspe:0.16975	val-rmspe:0.1611

[297]	train-rmse:0.118708	val-rmse:0.143821	train-rmspe:0.150153	val-rmspe:0.150914
[298]	train-rmse:0.118533	val-rmse:0.143848	train-rmspe:0.149969	val-rmspe:0.150917
[299]	train-rmse:0.118415	val-rmse:0.143834	train-rmspe:0.149884	val-rmspe:0.150844
[300]	train-rmse:0.118322	val-rmse:0.1438	train-rmspe:0.149602	val-rmspe:0.150777
[301]	train-rmse:0.118299	val-rmse:0.143783	train-rmspe:0.149579	val-rmspe:0.150759
[302]	train-rmse:0.118222	val-rmse:0.143738	train-rmspe:0.149491	val-rmspe:0.150704
[303]	train-rmse:0.118145	val-rmse:0.143712	train-rmspe:0.14941	val-rmspe:0.150678
[304]	train-rmse:0.117971	val-rmse:0.143722	train-rmspe:0.149066	val-rmspe:0.150749
[305]	train-rmse:0.11789	val-rmse:0.143669	train-rmspe:0.148997	val-rmspe:0.150689
[306]	train-rmse:0.117723	val-rmse:0.14354	train-rmspe:0.148862	val-rmspe:0.150264
[307]	train-rmse:0.117601	val-rmse:0.143432	train-rmspe:0.14875	val-rmspe:0.150173
[308]	train-rmse:0.117487	val-rmse:0.143434	train-rmspe:0.148639	val-rmspe:0.15019

[396]	train-rmse:0.109417	val-rmse:0.13974	train-rmspe:0.136917	val-rmspe:0.145466
[397]	train-rmse:0.109336	val-rmse:0.139669	train-rmspe:0.136855	val-rmspe:0.145421
[398]	train-rmse:0.109252	val-rmse:0.13962	train-rmspe:0.136797	val-rmspe:0.145372
[399]	train-rmse:0.109142	val-rmse:0.139542	train-rmspe:0.136709	val-rmspe:0.145299
[400]	train-rmse:0.109101	val-rmse:0.139517	train-rmspe:0.136674	val-rmspe:0.145276
[401]	train-rmse:0.10897	val-rmse:0.139482	train-rmspe:0.136581	val-rmspe:0.145217
[402]	train-rmse:0.108903	val-rmse:0.139451	train-rmspe:0.134919	val-rmspe:0.145103
[403]	train-rmse:0.108849	val-rmse:0.139414	train-rmspe:0.134797	val-rmspe:0.145051
[404]	train-rmse:0.108665	val-rmse:0.139569	train-rmspe:0.134466	val-rmspe:0.145241
[405]	train-rmse:0.10861	val-rmse:0.139561	train-rmspe:0.134417	val-rmspe:0.145227
[406]	train-rmse:0.10851	val-rmse:0.139519	train-rmspe:0.134342	val-rmspe:0.14519
[407]	train-rmse:0.108435	val-rmse:0.139479	train-rmspe:0.134289	val-rmspe:0.14515

[495]	train-rmse:0.102329	val-rmse:0.138211	train-rmspe:0.123735	val-rmspe:0.142811
[496]	train-rmse:0.10228	val-rmse:0.138192	train-rmspe:0.123698	val-rmspe:0.142792
[497]	train-rmse:0.10222	val-rmse:0.138153	train-rmspe:0.123655	val-rmspe:0.142774
[498]	train-rmse:0.102177	val-rmse:0.13813	train-rmspe:0.123622	val-rmspe:0.142743
[499]	train-rmse:0.102122	val-rmse:0.138118	train-rmspe:0.123595	val-rmspe:0.142707
[500]	train-rmse:0.102094	val-rmse:0.13811	train-rmspe:0.123526	val-rmspe:0.142694
[501]	train-rmse:0.102058	val-rmse:0.138121	train-rmspe:0.123511	val-rmspe:0.142698
[502]	train-rmse:0.102031	val-rmse:0.138105	train-rmspe:0.123491	val-rmspe:0.14269
[503]	train-rmse:0.101921	val-rmse:0.138074	train-rmspe:0.123394	val-rmspe:0.142643
[504]	train-rmse:0.101827	val-rmse:0.13802	train-rmspe:0.123289	val-rmspe:0.14259
[505]	train-rmse:0.101702	val-rmse:0.138093	train-rmspe:0.123169	val-rmspe:0.142717
[506]	train-rmse:0.101605	val-rmse:0.138188	train-rmspe:0.12309	val-rmspe:0.142761


[594]	train-rmse:0.097424	val-rmse:0.137568	train-rmspe:0.116489	val-rmspe:0.141575
[595]	train-rmse:0.097383	val-rmse:0.137515	train-rmspe:0.11646	val-rmspe:0.141534
[596]	train-rmse:0.097369	val-rmse:0.137494	train-rmspe:0.116444	val-rmspe:0.141525
[597]	train-rmse:0.09731	val-rmse:0.137502	train-rmspe:0.116408	val-rmspe:0.141528
[598]	train-rmse:0.097265	val-rmse:0.137492	train-rmspe:0.116179	val-rmspe:0.141511
[599]	train-rmse:0.097247	val-rmse:0.137481	train-rmspe:0.11575	val-rmspe:0.141504
[600]	train-rmse:0.097184	val-rmse:0.137481	train-rmspe:0.115715	val-rmspe:0.1415
[601]	train-rmse:0.09715	val-rmse:0.137475	train-rmspe:0.115688	val-rmspe:0.141493
[602]	train-rmse:0.097101	val-rmse:0.13746	train-rmspe:0.115656	val-rmspe:0.141477
[603]	train-rmse:0.097068	val-rmse:0.137458	train-rmspe:0.115633	val-rmspe:0.141465
[604]	train-rmse:0.096976	val-rmse:0.137458	train-rmspe:0.115517	val-rmspe:0.14146
[605]	train-rmse:0.096926	val-rmse:0.137481	train-rmspe:0.115483	val-rmspe:0.141443


[693]	train-rmse:0.093617	val-rmse:0.137226	train-rmspe:0.112408	val-rmspe:0.140781
[694]	train-rmse:0.093595	val-rmse:0.137187	train-rmspe:0.112453	val-rmspe:0.140754
[695]	train-rmse:0.093575	val-rmse:0.137172	train-rmspe:0.112433	val-rmspe:0.140743
[696]	train-rmse:0.09353	val-rmse:0.137201	train-rmspe:0.1124	val-rmspe:0.14078
[697]	train-rmse:0.093489	val-rmse:0.137221	train-rmspe:0.112376	val-rmspe:0.140801
[698]	train-rmse:0.093427	val-rmse:0.137265	train-rmspe:0.112319	val-rmspe:0.140843
[699]	train-rmse:0.093405	val-rmse:0.137267	train-rmspe:0.112277	val-rmspe:0.140828
[700]	train-rmse:0.093355	val-rmse:0.137243	train-rmspe:0.112208	val-rmspe:0.140793
[701]	train-rmse:0.093304	val-rmse:0.137258	train-rmspe:0.112189	val-rmspe:0.140794
[702]	train-rmse:0.093285	val-rmse:0.137261	train-rmspe:0.112177	val-rmspe:0.140789
[703]	train-rmse:0.093259	val-rmse:0.137238	train-rmspe:0.112158	val-rmspe:0.140762
[704]	train-rmse:0.09324	val-rmse:0.137228	train-rmspe:0.112138	val-rmspe:0.1407

[792]	train-rmse:0.090213	val-rmse:0.137348	train-rmspe:0.107676	val-rmspe:0.14032
[793]	train-rmse:0.090181	val-rmse:0.137375	train-rmspe:0.107665	val-rmspe:0.140318
[794]	train-rmse:0.090133	val-rmse:0.137366	train-rmspe:0.107647	val-rmspe:0.14031
[795]	train-rmse:0.090109	val-rmse:0.137351	train-rmspe:0.107632	val-rmspe:0.140298
[796]	train-rmse:0.090075	val-rmse:0.137329	train-rmspe:0.107602	val-rmspe:0.140278
[797]	train-rmse:0.090015	val-rmse:0.137372	train-rmspe:0.107574	val-rmspe:0.140284
[798]	train-rmse:0.089957	val-rmse:0.137416	train-rmspe:0.107547	val-rmspe:0.140289
[799]	train-rmse:0.089929	val-rmse:0.137427	train-rmspe:0.107529	val-rmspe:0.140289
The training time of the model is: 1491s
The rmspe of the model on validation data set is 0.140289


似乎调参能够达到的最佳验证集得分是0.140289，这说明在特征工程部分还有提高空间

在报告的可视化分析部分可以看到，'CompetitionDistance'这一项是偏置的，我们先尝试把它取对数

In [125]:
#从头开始处理数据

# 导入训练数据
train_data = pd.read_csv(
    "train.csv", 
    low_memory=False)

store_features = pd.read_csv("store.csv")
# 导入测试数据
test_data = pd.read_csv("test.csv")

#此处增加一步，先将验证集划分出来
#打开数据文件，很容易找到，2015/1/24-2015/7/31时间范围内的数据编号为1 - 210736

val_data = train_data[: 210735]
print(val_data['Store'][210734])


display(val_data.head(n=1))


train_data = train_data[210735:]
display(train_data.head(n=1))

#融合
train_data = pd.merge(train_data, store_features, on = 'Store')
val_data = pd.merge(val_data, store_features, on = 'Store')
test_data = pd.merge(test_data, store_features, on = 'Store')

train_data = train_data.drop('Customers', axis = 1)
sales_train = train_data['Sales']
features_train = train_data.drop('Sales', axis = 1)

val_data = val_data.drop('Customers', axis = 1)
sales_val = val_data['Sales']
features_val = val_data.drop('Sales', axis = 1)

features_test = test_data.drop('Id', axis = 1)

# 对字符串特征进行独热编码
category = ['StoreType', 'Assortment', 'PromoInterval', 'StateHoliday']


#首先将训练集、验证集、测试集合并，然后统一独热编码，然后再拆分为训练集、验证集、测试集

print('合并前：')
print(features_train.shape[0])
print(features_val.shape[0])
print(features_test.shape[0])

data_merge = pd.concat([features_train, features_val], ignore_index = True)
data_merge = pd.concat([data_merge, features_test], ignore_index = True)
data_merge_pd = pd.get_dummies(data_merge, columns = category)

# 需要把NA/NAN的数据转化成0
data_merge_pd.fillna(0, inplace = True)


#增加一步，增加‘Year', 'month', 'day'三个有序分类数据

data_merge_pd['year'] = data_merge_pd['Date'].apply(lambda x: float(x.split('-')[0]))
data_merge_pd['month'] = data_merge_pd['Date'].apply(lambda x: float(x.split('-')[1]))
data_merge_pd['day'] = data_merge_pd['Date'].apply(lambda x: float(x.split('-')[2]))
data_merge_pd = data_merge_pd.drop('Date', axis = 1)


#增加一步，对‘CompetitionDistance’取对数

data_merge_pd['CompetitionDistance'] = np.log(data_merge_pd['CompetitionDistance'] + 1)

#拆分

features_train = data_merge_pd[ : features_train.shape[0]]
features_val = data_merge_pd[features_train.shape[0] : (features_val.shape[0] + features_train.shape[0])]
features_test = data_merge_pd[ (features_val.shape[0] + features_train.shape[0]) : ]

print('合并后：')
print(features_train.shape[0])
print(features_val.shape[0])
print(features_test.shape[0])



#下面将sales做log处理

sales_train_log = np.log(sales_train + 1) #+1是为了避免log（0）的情况同时使得数据从0开始
sales_val_log = np.log(sales_val + 1)

dtrain = xgb.DMatrix(features_train, label = sales_train_log)
dval = xgb.DMatrix(features_val, label = sales_val_log)


1115


Store  DayOfWeek        Date  Sales  Customers  Open  Promo StateHoliday  \
0      1          5  2015-07-31   5263        555     1      1            0   

   SchoolHoliday  
0              1

Store  DayOfWeek        Date  Sales  Customers  Open  Promo  \
210735      1          5  2015-01-23   3586        489     1      0   

       StateHoliday  SchoolHoliday  
210735            0              0

合并前：
806474
210735
41088
合并后：
806474
210735
41088


In [127]:
#设定参数
param = {'max_depth': 10, 'eta': 0.07, 'silent': 0, 'objective': 'reg:linear', 'min_child_weight': 5, 'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)









[0]	train-rmse:7.00261	val-rmse:7.04107	train-rmspe:0.910658	val-rmspe:0.911196
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:6.51353	val-rmse:6.55233	train-rmspe:0.910332	val-rmspe:0.910884
[2]	train-rmse:6.05875	val-rmse:6.09763	train-rmspe:0.909825	val-rmspe:0.910399
[3]	train-rmse:5.63585	val-rmse:5.67481	train-rmspe:0.909065	val-rmspe:0.909673
[4]	train-rmse:5.24266	val-rmse:5.28167	train-rmspe:0.907963	val-rmspe:0.908619
[5]	train-rmse:4.87703	val-rmse:4.91602	train-rmspe:0.906415	val-rmspe:0.90714
[6]	train-rmse:4.53911	val-rmse:4.57726	train-rmspe:0.904315	val-rmspe:0.905128
[7]	train-rmse:4.22289	val-rmse:4.26063	train-rmspe:0.901512	val-rmspe:0.902444
[8]	train-rmse:3.9289	val-rmse:3.96605	train-rmspe:0.897877	val-rmspe:0.898959
[9]	train-rmse:3.65558	val-rmse:3.6924	train-rmspe:0.893271	val-rmspe:0.89454
[10]	train-rmse:3.4028	val-rmse:3.44379	train-rmspe:0.887586

[99]	train-rmse:0.193455	val-rmse:0.203249	train-rmspe:0.231342	val-rmspe:0.213527
[100]	train-rmse:0.193033	val-rmse:0.202811	train-rmspe:0.230923	val-rmspe:0.213235
[101]	train-rmse:0.191482	val-rmse:0.201418	train-rmspe:0.229376	val-rmspe:0.211972
[102]	train-rmse:0.191029	val-rmse:0.201057	train-rmspe:0.22897	val-rmspe:0.21176
[103]	train-rmse:0.189551	val-rmse:0.199672	train-rmspe:0.22746	val-rmspe:0.210438
[104]	train-rmse:0.188418	val-rmse:0.198634	train-rmspe:0.226324	val-rmspe:0.20932
[105]	train-rmse:0.187349	val-rmse:0.197579	train-rmspe:0.225718	val-rmspe:0.208393
[106]	train-rmse:0.186268	val-rmse:0.196651	train-rmspe:0.224813	val-rmspe:0.207621
[107]	train-rmse:0.185377	val-rmse:0.19582	train-rmspe:0.224058	val-rmspe:0.206876
[108]	train-rmse:0.185058	val-rmse:0.195605	train-rmspe:0.223181	val-rmspe:0.206866
[109]	train-rmse:0.18473	val-rmse:0.195246	train-rmspe:0.222911	val-rmspe:0.206568
[110]	train-rmse:0.183719	val-rmse:0.194348	train-rmspe:0.221905	val-rmspe:0.2056
[

[198]	train-rmse:0.136348	val-rmse:0.156146	train-rmspe:0.169829	val-rmspe:0.164419
[199]	train-rmse:0.13572	val-rmse:0.155578	train-rmspe:0.169188	val-rmspe:0.163842
[200]	train-rmse:0.135559	val-rmse:0.155395	train-rmspe:0.169059	val-rmspe:0.16367
[201]	train-rmse:0.135438	val-rmse:0.155311	train-rmspe:0.168426	val-rmspe:0.163575
[202]	train-rmse:0.135174	val-rmse:0.155076	train-rmspe:0.168186	val-rmspe:0.163336
[203]	train-rmse:0.135035	val-rmse:0.154974	train-rmspe:0.168058	val-rmspe:0.16324
[204]	train-rmse:0.134703	val-rmse:0.15465	train-rmspe:0.167722	val-rmspe:0.162838
[205]	train-rmse:0.134271	val-rmse:0.154256	train-rmspe:0.167355	val-rmspe:0.16247
[206]	train-rmse:0.134059	val-rmse:0.154084	train-rmspe:0.167169	val-rmspe:0.162312
[207]	train-rmse:0.133885	val-rmse:0.15394	train-rmspe:0.165805	val-rmspe:0.162107
[208]	train-rmse:0.13372	val-rmse:0.153914	train-rmspe:0.164313	val-rmspe:0.162052
[209]	train-rmse:0.13338	val-rmse:0.153657	train-rmspe:0.163872	val-rmspe:0.16181
[

[297]	train-rmse:0.118386	val-rmse:0.144544	train-rmspe:0.142528	val-rmspe:0.150901
[298]	train-rmse:0.118227	val-rmse:0.144554	train-rmspe:0.142292	val-rmspe:0.150911
[299]	train-rmse:0.118152	val-rmse:0.144506	train-rmspe:0.141621	val-rmspe:0.150857
[300]	train-rmse:0.118047	val-rmse:0.144467	train-rmspe:0.141436	val-rmspe:0.150825
[301]	train-rmse:0.117996	val-rmse:0.144431	train-rmspe:0.141393	val-rmspe:0.150789
[302]	train-rmse:0.117935	val-rmse:0.14439	train-rmspe:0.141348	val-rmspe:0.150763
[303]	train-rmse:0.117859	val-rmse:0.144341	train-rmspe:0.141064	val-rmspe:0.150727
[304]	train-rmse:0.11772	val-rmse:0.144373	train-rmspe:0.140862	val-rmspe:0.150794
[305]	train-rmse:0.117637	val-rmse:0.144322	train-rmspe:0.140785	val-rmspe:0.150737
[306]	train-rmse:0.117526	val-rmse:0.144246	train-rmspe:0.140694	val-rmspe:0.150664
[307]	train-rmse:0.117435	val-rmse:0.144174	train-rmspe:0.140617	val-rmspe:0.150597
[308]	train-rmse:0.117335	val-rmse:0.144287	train-rmspe:0.140546	val-rmspe:0.1

[396]	train-rmse:0.109274	val-rmse:0.14121	train-rmspe:0.132326	val-rmspe:0.146739
[397]	train-rmse:0.109206	val-rmse:0.141154	train-rmspe:0.131672	val-rmspe:0.146694
[398]	train-rmse:0.109132	val-rmse:0.141107	train-rmspe:0.13159	val-rmspe:0.146642
[399]	train-rmse:0.109072	val-rmse:0.14111	train-rmspe:0.131546	val-rmspe:0.146608
[400]	train-rmse:0.109015	val-rmse:0.141121	train-rmspe:0.131507	val-rmspe:0.1466
[401]	train-rmse:0.108887	val-rmse:0.141042	train-rmspe:0.131131	val-rmspe:0.146515
[402]	train-rmse:0.108811	val-rmse:0.141006	train-rmspe:0.130689	val-rmspe:0.146474
[403]	train-rmse:0.108741	val-rmse:0.140946	train-rmspe:0.13062	val-rmspe:0.146357
[404]	train-rmse:0.108671	val-rmse:0.140922	train-rmspe:0.130554	val-rmspe:0.146334
[405]	train-rmse:0.108622	val-rmse:0.140931	train-rmspe:0.130538	val-rmspe:0.146335
[406]	train-rmse:0.108537	val-rmse:0.140905	train-rmspe:0.130452	val-rmspe:0.146303
[407]	train-rmse:0.108486	val-rmse:0.14089	train-rmspe:0.130412	val-rmspe:0.146282

[495]	train-rmse:0.102727	val-rmse:0.139363	train-rmspe:0.121652	val-rmspe:0.144407
[496]	train-rmse:0.102675	val-rmse:0.13933	train-rmspe:0.121618	val-rmspe:0.144383
[497]	train-rmse:0.102624	val-rmse:0.139323	train-rmspe:0.121577	val-rmspe:0.144375
[498]	train-rmse:0.102571	val-rmse:0.139305	train-rmspe:0.121545	val-rmspe:0.144356
[499]	train-rmse:0.10253	val-rmse:0.139184	train-rmspe:0.121518	val-rmspe:0.144243
[500]	train-rmse:0.102498	val-rmse:0.139171	train-rmspe:0.12143	val-rmspe:0.144225
[501]	train-rmse:0.102452	val-rmse:0.139151	train-rmspe:0.121396	val-rmspe:0.144209
[502]	train-rmse:0.102408	val-rmse:0.139125	train-rmspe:0.121357	val-rmspe:0.144159
[503]	train-rmse:0.102322	val-rmse:0.139004	train-rmspe:0.121271	val-rmspe:0.144026
[504]	train-rmse:0.102253	val-rmse:0.138957	train-rmspe:0.121211	val-rmspe:0.143972
[505]	train-rmse:0.102142	val-rmse:0.139051	train-rmspe:0.121004	val-rmspe:0.144116
[506]	train-rmse:0.10203	val-rmse:0.139111	train-rmspe:0.120938	val-rmspe:0.144

[594]	train-rmse:0.097525	val-rmse:0.139088	train-rmspe:0.113474	val-rmspe:0.14354
[595]	train-rmse:0.09748	val-rmse:0.139034	train-rmspe:0.113434	val-rmspe:0.143493
[596]	train-rmse:0.09747	val-rmse:0.139015	train-rmspe:0.113422	val-rmspe:0.143486
[597]	train-rmse:0.097384	val-rmse:0.139061	train-rmspe:0.113353	val-rmspe:0.143509
[598]	train-rmse:0.097324	val-rmse:0.139114	train-rmspe:0.113293	val-rmspe:0.14352
[599]	train-rmse:0.097285	val-rmse:0.1391	train-rmspe:0.113272	val-rmspe:0.143509
[600]	train-rmse:0.097234	val-rmse:0.13908	train-rmspe:0.113239	val-rmspe:0.143492
[601]	train-rmse:0.097194	val-rmse:0.139071	train-rmspe:0.113205	val-rmspe:0.143472
[602]	train-rmse:0.09715	val-rmse:0.13909	train-rmspe:0.113191	val-rmspe:0.143467
[603]	train-rmse:0.097115	val-rmse:0.139084	train-rmspe:0.113171	val-rmspe:0.143455
[604]	train-rmse:0.097058	val-rmse:0.139106	train-rmspe:0.113138	val-rmspe:0.143447
[605]	train-rmse:0.096989	val-rmse:0.13914	train-rmspe:0.113041	val-rmspe:0.143457
[6

[693]	train-rmse:0.093484	val-rmse:0.139005	train-rmspe:0.106748	val-rmspe:0.143008
[694]	train-rmse:0.093453	val-rmse:0.138992	train-rmspe:0.106725	val-rmspe:0.142992
[695]	train-rmse:0.093427	val-rmse:0.138975	train-rmspe:0.106704	val-rmspe:0.142986
[696]	train-rmse:0.093387	val-rmse:0.138999	train-rmspe:0.106639	val-rmspe:0.142986
[697]	train-rmse:0.09335	val-rmse:0.139028	train-rmspe:0.106615	val-rmspe:0.142981
[698]	train-rmse:0.093292	val-rmse:0.139037	train-rmspe:0.106575	val-rmspe:0.142987
[699]	train-rmse:0.093273	val-rmse:0.139051	train-rmspe:0.106567	val-rmspe:0.143005
[700]	train-rmse:0.093224	val-rmse:0.139063	train-rmspe:0.106488	val-rmspe:0.143019
[701]	train-rmse:0.093177	val-rmse:0.139047	train-rmspe:0.10645	val-rmspe:0.143006
[702]	train-rmse:0.09316	val-rmse:0.139058	train-rmspe:0.10644	val-rmspe:0.143009
[703]	train-rmse:0.093139	val-rmse:0.139038	train-rmspe:0.10641	val-rmspe:0.142992
[704]	train-rmse:0.093124	val-rmse:0.139033	train-rmspe:0.106395	val-rmspe:0.1429

[792]	train-rmse:0.089951	val-rmse:0.139362	train-rmspe:0.101704	val-rmspe:0.142764
[793]	train-rmse:0.08993	val-rmse:0.139355	train-rmspe:0.101686	val-rmspe:0.142757
[794]	train-rmse:0.089891	val-rmse:0.139355	train-rmspe:0.101653	val-rmspe:0.14275
[795]	train-rmse:0.089878	val-rmse:0.139354	train-rmspe:0.101638	val-rmspe:0.142745
[796]	train-rmse:0.089846	val-rmse:0.139341	train-rmspe:0.10161	val-rmspe:0.142719
[797]	train-rmse:0.08982	val-rmse:0.139336	train-rmspe:0.10161	val-rmspe:0.142717
[798]	train-rmse:0.08978	val-rmse:0.139329	train-rmspe:0.101582	val-rmspe:0.142714
[799]	train-rmse:0.089739	val-rmse:0.139326	train-rmspe:0.101526	val-rmspe:0.1427
[800]	train-rmse:0.089708	val-rmse:0.139321	train-rmspe:0.101503	val-rmspe:0.142693
[801]	train-rmse:0.089663	val-rmse:0.139341	train-rmspe:0.101758	val-rmspe:0.142697
[802]	train-rmse:0.089608	val-rmse:0.139445	train-rmspe:0.10173	val-rmspe:0.142804
[803]	train-rmse:0.089566	val-rmse:0.139454	train-rmspe:0.101713	val-rmspe:0.142802
[

[891]	train-rmse:0.086859	val-rmse:0.140019	train-rmspe:0.098518	val-rmspe:0.142738
[892]	train-rmse:0.086836	val-rmse:0.140022	train-rmspe:0.098501	val-rmspe:0.142739
[893]	train-rmse:0.086821	val-rmse:0.140038	train-rmspe:0.098493	val-rmspe:0.142737
[894]	train-rmse:0.086805	val-rmse:0.14003	train-rmspe:0.09848	val-rmspe:0.142729
[895]	train-rmse:0.08678	val-rmse:0.140026	train-rmspe:0.098456	val-rmspe:0.142725
[896]	train-rmse:0.086756	val-rmse:0.140041	train-rmspe:0.098494	val-rmspe:0.142724
[897]	train-rmse:0.086724	val-rmse:0.140043	train-rmspe:0.098311	val-rmspe:0.142721
[898]	train-rmse:0.086691	val-rmse:0.140037	train-rmspe:0.098246	val-rmspe:0.142714
[899]	train-rmse:0.086658	val-rmse:0.140026	train-rmspe:0.09822	val-rmspe:0.142686
[900]	train-rmse:0.086618	val-rmse:0.140018	train-rmspe:0.098251	val-rmspe:0.142688
[901]	train-rmse:0.086558	val-rmse:0.140051	train-rmspe:0.098195	val-rmspe:0.142696
[902]	train-rmse:0.086536	val-rmse:0.140037	train-rmspe:0.097677	val-rmspe:0.142

考虑到这是一个时间序列分析问题，并且在可视化部分，我们已经看到‘Day’，‘Month’2个特征的重要性分列1、2位，所以这里把‘Date’特征值转化为一个在一年中的第几天，体现时间序列。同时，只使用sales不为零的数据进行训练、验证。

In [2]:
#从头开始处理数据

# 导入训练数据
train_data = pd.read_csv(
    "train.csv", 
    low_memory=False)

store_features = pd.read_csv("store.csv")
# 导入测试数据
test_data = pd.read_csv("test.csv")

train_data['year'] = train_data['Date'].apply(lambda x: float(x.split('-')[0]))
train_data['month'] = train_data['Date'].apply(lambda x: float(x.split('-')[1]))
train_data['day'] = train_data['Date'].apply(lambda x: float(x.split('-')[2]))

test_data['year'] = test_data['Date'].apply(lambda x: float(x.split('-')[0]))
test_data['month'] = test_data['Date'].apply(lambda x: float(x.split('-')[1]))
test_data['day'] = test_data['Date'].apply(lambda x: float(x.split('-')[2]))



In [3]:
#此处增加一步，先将验证集划分出来
#打开数据文件，很容易找到，2015/1/24-2015/7/31时间范围内的数据编号为1 - 210736

val_data = train_data[: 210735]
train_data = train_data[210735:]

#只使用sales不是0的数据
val_data = val_data[val_data['Sales'] != 0]
train_data = train_data[train_data['Sales'] != 0]


#融合
train_data = pd.merge(train_data, store_features, on = 'Store')
val_data = pd.merge(val_data, store_features, on = 'Store')
test_data = pd.merge(test_data, store_features, on = 'Store')

train_data = train_data.drop('Customers', axis = 1)
sales_train = train_data['Sales']
features_train = train_data.drop('Sales', axis = 1)

val_data = val_data.drop('Customers', axis = 1)
sales_val = val_data['Sales']
features_val = val_data.drop('Sales', axis = 1)

features_test = test_data.drop('Id', axis = 1)

# 对字符串特征进行独热编码
category = ['StoreType', 'Assortment', 'PromoInterval', 'StateHoliday']


#首先将训练集、验证集、测试集合并，然后统一独热编码，然后再拆分为训练集、验证集、测试集

print('合并前：')
print(features_train.shape[0])
print(features_val.shape[0])
print(features_test.shape[0])

data_merge = pd.concat([features_train, features_val], ignore_index = True)
data_merge = pd.concat([data_merge, features_test], ignore_index = True)
data_merge_pd = pd.get_dummies(data_merge, columns = category)

#把时间数据转化为一年中的第几周

data_merge_pd['Date'] = pd.to_datetime(data_merge_pd['Date'])
data_merge_pd['Dayofyear'] = data_merge_pd['Date'].dt.dayofyear


# 需要把NA/NAN的数据转化成0
data_merge_pd.fillna(0, inplace = True)



data_merge_pd = data_merge_pd.drop('Date', axis = 1)



#拆分

features_train = data_merge_pd[ : features_train.shape[0]]
features_val = data_merge_pd[features_train.shape[0] : (features_val.shape[0] + features_train.shape[0])]
features_test = data_merge_pd[ (features_val.shape[0] + features_train.shape[0]) : ]

print('合并后：')
print(features_train.shape[0])
print(features_val.shape[0])
print(features_test.shape[0])



#下面将sales做log处理

sales_train_log = np.log(sales_train) #因为去掉了为0的销售数据，所以不用+1了
sales_val_log = np.log(sales_val)

dtrain = xgb.DMatrix(features_train, label = sales_train_log)
dval = xgb.DMatrix(features_val, label = sales_val_log)




合并前：
669257
175081
41088
合并后：
669257
175081
41088


In [4]:
def rmspe(y, y_hat):
    #由于sales取了对数，这里要还原
    y = np.exp(y)
    y_hat = np.exp(y_hat)
    
    #由于有yi=0的情况，直接计算会得出无穷大的结果，所以需要处理一下
    #定义一个y_rev来表示y的倒数，y为0时y_rev也赋值为0（因为在项目中提到“ Any day and store with 0 sales is ignored in scoring.“）
    y_rev = np.zeros(y.shape, dtype = float)
    n_zero = y != 0
    y_rev[n_zero] = 1./y[n_zero]

    rmspe = np.sqrt(np.mean(((y - y_hat)*y_rev)**2))
    return rmspe


#自定义一个评价函数

def rmspe_feval(y_hat, dy):
    y = dy.get_label()
    rmspe_score = rmspe(y, y_hat)
    return 'rmspe', rmspe_score
#定义训练函数
def train(param, dtrain, dval, num_round, feval_c):
    train_time = time.clock()

    model = xgb.train(
        param, dtrain, num_round, feval = feval_c, 
        evals = [(dtrain, 'train'), (dval, 'val')], early_stopping_rounds = 100, 
        verbose_eval = True
    )

    train_time = time.clock() - train_time

    print('The training time of the model is: {:.0f}s'.format(train_time))
    
    return model

#定义一个打分函数
def score(bst, dval):
    y_pred = bst.predict(dval)
#print(y_pred)
    y_val = dval.get_label()
    score = rmspe(y_val, y_pred)
#print(score)
    print('The rmspe of the model on validation data set is {:.6f}'.format(score))
    pass

In [5]:
#设定参数
param = {'max_depth': 5, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear', 'min_child_weight': 5, 'colsample_bytree': 0.8, 'subsample':0.9}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)










[0]	train-rmse:5.78965	val-rmse:5.82862	train-rmspe:0.996618	val-rmspe:0.99677
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:4.06091	val-rmse:4.1005	train-rmspe:0.981108	val-rmspe:0.981956
[2]	train-rmse:2.85382	val-rmse:2.8954	train-rmspe:0.937143	val-rmspe:0.939987
[3]	train-rmse:2.01324	val-rmse:2.05217	train-rmspe:0.854884	val-rmspe:0.860899
[4]	train-rmse:1.4307	val-rmse:1.47067	train-rmspe:0.741818	val-rmspe:0.752176
[5]	train-rmse:1.0311	val-rmse:1.06977	train-rmspe:0.618798	val-rmspe:0.632306
[6]	train-rmse:0.761519	val-rmse:0.799344	train-rmspe:0.509147	val-rmspe:0.523601
[7]	train-rmse:0.584357	val-rmse:0.618141	train-rmspe:0.429143	val-rmspe:0.439015
[8]	train-rmse:0.47131	val-rmse:0.50044	train-rmspe:0.382186	val-rmspe:0.383404
[9]	train-rmse:0.404432	val-rmse:0.428187	train-rmspe:0.36307	val-rmspe:0.353723
[10]	train-rmse:0.364483	val-rmse:0.382727	train-rmspe:0

[98]	train-rmse:0.187167	val-rmse:0.200947	train-rmspe:0.259757	val-rmspe:0.226303
[99]	train-rmse:0.185889	val-rmse:0.199736	train-rmspe:0.25812	val-rmspe:0.224789
[100]	train-rmse:0.185138	val-rmse:0.199136	train-rmspe:0.257376	val-rmspe:0.224216
[101]	train-rmse:0.184424	val-rmse:0.198623	train-rmspe:0.256581	val-rmspe:0.223819
[102]	train-rmse:0.184365	val-rmse:0.198563	train-rmspe:0.256534	val-rmspe:0.223761
[103]	train-rmse:0.183751	val-rmse:0.198101	train-rmspe:0.255909	val-rmspe:0.22303
[104]	train-rmse:0.183522	val-rmse:0.198065	train-rmspe:0.255788	val-rmspe:0.223016
[105]	train-rmse:0.18307	val-rmse:0.197664	train-rmspe:0.25546	val-rmspe:0.222803
[106]	train-rmse:0.182317	val-rmse:0.19711	train-rmspe:0.254414	val-rmspe:0.222559
[107]	train-rmse:0.181716	val-rmse:0.196561	train-rmspe:0.253702	val-rmspe:0.221955
[108]	train-rmse:0.180873	val-rmse:0.195884	train-rmspe:0.252988	val-rmspe:0.22167
[109]	train-rmse:0.179929	val-rmse:0.194998	train-rmspe:0.252164	val-rmspe:0.220783


[197]	train-rmse:0.146175	val-rmse:0.171057	train-rmspe:0.213231	val-rmspe:0.191859
[198]	train-rmse:0.145837	val-rmse:0.17091	train-rmspe:0.212855	val-rmspe:0.191437
[199]	train-rmse:0.145596	val-rmse:0.170787	train-rmspe:0.212463	val-rmspe:0.191363
[200]	train-rmse:0.145446	val-rmse:0.170777	train-rmspe:0.212203	val-rmspe:0.191409
[201]	train-rmse:0.145388	val-rmse:0.170751	train-rmspe:0.212152	val-rmspe:0.191389
[202]	train-rmse:0.145027	val-rmse:0.170415	train-rmspe:0.211611	val-rmspe:0.190997
[203]	train-rmse:0.144678	val-rmse:0.170199	train-rmspe:0.211319	val-rmspe:0.19068
[204]	train-rmse:0.144579	val-rmse:0.170091	train-rmspe:0.211236	val-rmspe:0.190914
[205]	train-rmse:0.144362	val-rmse:0.169919	train-rmspe:0.21085	val-rmspe:0.190571
[206]	train-rmse:0.144114	val-rmse:0.169639	train-rmspe:0.210515	val-rmspe:0.1904
[207]	train-rmse:0.143807	val-rmse:0.169814	train-rmspe:0.210378	val-rmspe:0.190583
[208]	train-rmse:0.14363	val-rmse:0.169715	train-rmspe:0.210215	val-rmspe:0.19056

[296]	train-rmse:0.130492	val-rmse:0.161039	train-rmspe:0.198359	val-rmspe:0.180731
[297]	train-rmse:0.130342	val-rmse:0.160925	train-rmspe:0.198257	val-rmspe:0.180648
[298]	train-rmse:0.130239	val-rmse:0.160812	train-rmspe:0.198094	val-rmspe:0.180546
[299]	train-rmse:0.130141	val-rmse:0.160725	train-rmspe:0.198019	val-rmspe:0.180468
[300]	train-rmse:0.130114	val-rmse:0.160706	train-rmspe:0.197958	val-rmspe:0.180445
[301]	train-rmse:0.129932	val-rmse:0.160588	train-rmspe:0.197665	val-rmspe:0.1803
[302]	train-rmse:0.129783	val-rmse:0.160462	train-rmspe:0.197598	val-rmspe:0.180207
[303]	train-rmse:0.129741	val-rmse:0.160386	train-rmspe:0.197506	val-rmspe:0.180117
[304]	train-rmse:0.129673	val-rmse:0.160322	train-rmspe:0.19764	val-rmspe:0.180065
[305]	train-rmse:0.129468	val-rmse:0.160186	train-rmspe:0.197426	val-rmspe:0.179932
[306]	train-rmse:0.129384	val-rmse:0.160126	train-rmspe:0.197271	val-rmspe:0.179873
[307]	train-rmse:0.129268	val-rmse:0.160052	train-rmspe:0.197164	val-rmspe:0.17

[395]	train-rmse:0.121052	val-rmse:0.155542	train-rmspe:0.190239	val-rmspe:0.172834
[396]	train-rmse:0.121021	val-rmse:0.155533	train-rmspe:0.190207	val-rmspe:0.172834
[397]	train-rmse:0.120961	val-rmse:0.155535	train-rmspe:0.19022	val-rmspe:0.172834
[398]	train-rmse:0.120919	val-rmse:0.15555	train-rmspe:0.190196	val-rmspe:0.172818
[399]	train-rmse:0.120878	val-rmse:0.155541	train-rmspe:0.190187	val-rmspe:0.172697
[400]	train-rmse:0.120855	val-rmse:0.155489	train-rmspe:0.190165	val-rmspe:0.173027
[401]	train-rmse:0.12076	val-rmse:0.155427	train-rmspe:0.190104	val-rmspe:0.172982
[402]	train-rmse:0.120601	val-rmse:0.155318	train-rmspe:0.189997	val-rmspe:0.172867
[403]	train-rmse:0.12053	val-rmse:0.155266	train-rmspe:0.189944	val-rmspe:0.172767
[404]	train-rmse:0.120476	val-rmse:0.155405	train-rmspe:0.189905	val-rmspe:0.172872
[405]	train-rmse:0.120455	val-rmse:0.15539	train-rmspe:0.189891	val-rmspe:0.17285
[406]	train-rmse:0.120347	val-rmse:0.155333	train-rmspe:0.189739	val-rmspe:0.17278

...

[1668]	train-rmse:0.09303	val-rmse:0.144272	train-rmspe:0.140578	val-rmspe:0.158419
[1669]	train-rmse:0.093021	val-rmse:0.14428	train-rmspe:0.140571	val-rmspe:0.158428
[1670]	train-rmse:0.093018	val-rmse:0.144274	train-rmspe:0.140568	val-rmspe:0.158429
[1671]	train-rmse:0.093014	val-rmse:0.144337	train-rmspe:0.140557	val-rmspe:0.15846
[1672]	train-rmse:0.093009	val-rmse:0.144346	train-rmspe:0.140551	val-rmspe:0.15846
[1673]	train-rmse:0.092999	val-rmse:0.144338	train-rmspe:0.140541	val-rmspe:0.158459
[1674]	train-rmse:0.092986	val-rmse:0.14434	train-rmspe:0.140519	val-rmspe:0.158466
[1675]	train-rmse:0.092982	val-rmse:0.144335	train-rmspe:0.140518	val-rmspe:0.158461
[1676]	train-rmse:0.092977	val-rmse:0.14433	train-rmspe:0.140524	val-rmspe:0.158449
[1677]	train-rmse:0.092973	val-rmse:0.14433	train-rmspe:0.140465	val-rmspe:0.158432
[1678]	train-rmse:0.092969	val-rmse:0.144338	train-rmspe:0.140462	val-rmspe:0.158434
[1679]	train-rmse:0.092958	val-rmse:0.144317	train-rmspe:0.140446	val-rm

[1765]	train-rmse:0.092342	val-rmse:0.144202	train-rmspe:0.131937	val-rmspe:0.158382
[1766]	train-rmse:0.092336	val-rmse:0.144202	train-rmspe:0.131946	val-rmspe:0.158379
[1767]	train-rmse:0.092332	val-rmse:0.144197	train-rmspe:0.131947	val-rmspe:0.158383
[1768]	train-rmse:0.092328	val-rmse:0.144192	train-rmspe:0.132796	val-rmspe:0.158371
[1769]	train-rmse:0.092323	val-rmse:0.144179	train-rmspe:0.132811	val-rmspe:0.158364
[1770]	train-rmse:0.092317	val-rmse:0.144183	train-rmspe:0.132802	val-rmspe:0.15836
[1771]	train-rmse:0.092308	val-rmse:0.144182	train-rmspe:0.132794	val-rmspe:0.158369
[1772]	train-rmse:0.092298	val-rmse:0.144174	train-rmspe:0.132774	val-rmspe:0.158369
[1773]	train-rmse:0.092288	val-rmse:0.144153	train-rmspe:0.132766	val-rmspe:0.158356
[1774]	train-rmse:0.092283	val-rmse:0.144164	train-rmspe:0.132772	val-rmspe:0.158356
[1775]	train-rmse:0.092277	val-rmse:0.14416	train-rmspe:0.132777	val-rmspe:0.158359
[1776]	train-rmse:0.09227	val-rmse:0.144165	train-rmspe:0.132772	va

[1862]	train-rmse:0.091699	val-rmse:0.144055	train-rmspe:0.13161	val-rmspe:0.15817
[1863]	train-rmse:0.091694	val-rmse:0.144047	train-rmspe:0.131613	val-rmspe:0.158165
[1864]	train-rmse:0.091689	val-rmse:0.144045	train-rmspe:0.131612	val-rmspe:0.158165
[1865]	train-rmse:0.091681	val-rmse:0.144041	train-rmspe:0.131561	val-rmspe:0.15816
[1866]	train-rmse:0.091673	val-rmse:0.144027	train-rmspe:0.131538	val-rmspe:0.158147
[1867]	train-rmse:0.091662	val-rmse:0.144032	train-rmspe:0.131535	val-rmspe:0.158154
[1868]	train-rmse:0.091656	val-rmse:0.144018	train-rmspe:0.131531	val-rmspe:0.158153
[1869]	train-rmse:0.091652	val-rmse:0.144016	train-rmspe:0.131528	val-rmspe:0.15815
[1870]	train-rmse:0.091639	val-rmse:0.144018	train-rmspe:0.131512	val-rmspe:0.158119
[1871]	train-rmse:0.091636	val-rmse:0.144016	train-rmspe:0.131514	val-rmspe:0.158124
[1872]	train-rmse:0.091629	val-rmse:0.144011	train-rmspe:0.131289	val-rmspe:0.158117
[1873]	train-rmse:0.091624	val-rmse:0.144008	train-rmspe:0.131273	val

[1959]	train-rmse:0.091076	val-rmse:0.143902	train-rmspe:0.130591	val-rmspe:0.158048
[1960]	train-rmse:0.091064	val-rmse:0.143916	train-rmspe:0.130585	val-rmspe:0.158042
[1961]	train-rmse:0.091062	val-rmse:0.143908	train-rmspe:0.130582	val-rmspe:0.15804
[1962]	train-rmse:0.091056	val-rmse:0.143932	train-rmspe:0.130579	val-rmspe:0.158062
[1963]	train-rmse:0.091051	val-rmse:0.143926	train-rmspe:0.130572	val-rmspe:0.158051
[1964]	train-rmse:0.091046	val-rmse:0.143927	train-rmspe:0.130476	val-rmspe:0.158055
[1965]	train-rmse:0.091044	val-rmse:0.143931	train-rmspe:0.130479	val-rmspe:0.158057
[1966]	train-rmse:0.091041	val-rmse:0.143933	train-rmspe:0.130476	val-rmspe:0.15806
[1967]	train-rmse:0.091033	val-rmse:0.143919	train-rmspe:0.130472	val-rmspe:0.158056
[1968]	train-rmse:0.09103	val-rmse:0.143926	train-rmspe:0.13047	val-rmspe:0.158064
[1969]	train-rmse:0.091025	val-rmse:0.14393	train-rmspe:0.130468	val-rmspe:0.158063
[1970]	train-rmse:0.091024	val-rmse:0.143928	train-rmspe:0.131246	val-

[2056]	train-rmse:0.090466	val-rmse:0.143866	train-rmspe:0.12844	val-rmspe:0.158195
[2057]	train-rmse:0.090456	val-rmse:0.143862	train-rmspe:0.128427	val-rmspe:0.158183
[2058]	train-rmse:0.09045	val-rmse:0.143865	train-rmspe:0.128421	val-rmspe:0.158189
[2059]	train-rmse:0.090446	val-rmse:0.143872	train-rmspe:0.128425	val-rmspe:0.158185
[2060]	train-rmse:0.090429	val-rmse:0.143864	train-rmspe:0.128418	val-rmspe:0.158184
[2061]	train-rmse:0.090422	val-rmse:0.143872	train-rmspe:0.128407	val-rmspe:0.158194
[2062]	train-rmse:0.090413	val-rmse:0.143872	train-rmspe:0.1284	val-rmspe:0.158194
[2063]	train-rmse:0.09041	val-rmse:0.143869	train-rmspe:0.1284	val-rmspe:0.158197
[2064]	train-rmse:0.090405	val-rmse:0.143865	train-rmspe:0.129182	val-rmspe:0.158189
[2065]	train-rmse:0.090394	val-rmse:0.143865	train-rmspe:0.129176	val-rmspe:0.158192
[2066]	train-rmse:0.090391	val-rmse:0.143865	train-rmspe:0.128916	val-rmspe:0.158198
[2067]	train-rmse:0.090386	val-rmse:0.143866	train-rmspe:0.128906	val-rm

还是有点过拟合，但是已经没有之前严重了

In [6]:
#设定参数
param = {'max_depth': 5, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear', 'min_child_weight': 5, 'colsample_bytree': 0.8, 'subsample':0.7}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)


[0]	train-rmse:5.7896	val-rmse:5.82858	train-rmspe:0.996618	val-rmspe:0.99677
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:4.06087	val-rmse:4.10016	train-rmspe:0.981103	val-rmspe:0.981947
[2]	train-rmse:2.85388	val-rmse:2.89549	train-rmspe:0.937128	val-rmspe:0.939976
[3]	train-rmse:2.01292	val-rmse:2.0535	train-rmspe:0.85488	val-rmspe:0.861121
[4]	train-rmse:1.43059	val-rmse:1.47095	train-rmspe:0.741775	val-rmspe:0.752172
[5]	train-rmse:1.03103	val-rmse:1.07096	train-rmspe:0.618918	val-rmspe:0.632716
[6]	train-rmse:0.761245	val-rmse:0.798486	train-rmspe:0.509611	val-rmspe:0.523461
[7]	train-rmse:0.584805	val-rmse:0.619766	train-rmspe:0.429789	val-rmspe:0.440088
[8]	train-rmse:0.472267	val-rmse:0.502545	train-rmspe:0.383746	val-rmspe:0.384653
[9]	train-rmse:0.405145	val-rmse:0.429792	train-rmspe:0.363357	val-rmspe:0.353759
[10]	train-rmse:0.366341	val-rmse:0.386114	train-rms

[98]	train-rmse:0.186606	val-rmse:0.199701	train-rmspe:0.258034	val-rmspe:0.227946
[99]	train-rmse:0.185464	val-rmse:0.198729	train-rmspe:0.257098	val-rmspe:0.226785
[100]	train-rmse:0.184774	val-rmse:0.19798	train-rmspe:0.25651	val-rmspe:0.226158
[101]	train-rmse:0.183893	val-rmse:0.197326	train-rmspe:0.255765	val-rmspe:0.2256
[102]	train-rmse:0.182531	val-rmse:0.19616	train-rmspe:0.254518	val-rmspe:0.224592
[103]	train-rmse:0.181909	val-rmse:0.195625	train-rmspe:0.253758	val-rmspe:0.223939
[104]	train-rmse:0.181523	val-rmse:0.195576	train-rmspe:0.253808	val-rmspe:0.223852
[105]	train-rmse:0.180599	val-rmse:0.194619	train-rmspe:0.252831	val-rmspe:0.222789
[106]	train-rmse:0.180197	val-rmse:0.194234	train-rmspe:0.252588	val-rmspe:0.222541
[107]	train-rmse:0.179505	val-rmse:0.193593	train-rmspe:0.251869	val-rmspe:0.221869
[108]	train-rmse:0.179291	val-rmse:0.193511	train-rmspe:0.251498	val-rmspe:0.221797
[109]	train-rmse:0.178641	val-rmse:0.192937	train-rmspe:0.250943	val-rmspe:0.221164

[197]	train-rmse:0.146126	val-rmse:0.168877	train-rmspe:0.217588	val-rmspe:0.186772
[198]	train-rmse:0.145851	val-rmse:0.168531	train-rmspe:0.217431	val-rmspe:0.186271
[199]	train-rmse:0.145648	val-rmse:0.168302	train-rmspe:0.217287	val-rmspe:0.186068
[200]	train-rmse:0.145401	val-rmse:0.168134	train-rmspe:0.217575	val-rmspe:0.185867
[201]	train-rmse:0.145221	val-rmse:0.168023	train-rmspe:0.217341	val-rmspe:0.185856
[202]	train-rmse:0.145	val-rmse:0.167834	train-rmspe:0.217181	val-rmspe:0.185711
[203]	train-rmse:0.144818	val-rmse:0.167764	train-rmspe:0.216861	val-rmspe:0.185579
[204]	train-rmse:0.144457	val-rmse:0.167473	train-rmspe:0.216388	val-rmspe:0.185206
[205]	train-rmse:0.14429	val-rmse:0.167319	train-rmspe:0.216288	val-rmspe:0.185072
[206]	train-rmse:0.143916	val-rmse:0.167028	train-rmspe:0.216091	val-rmspe:0.184847
[207]	train-rmse:0.143641	val-rmse:0.166813	train-rmspe:0.215876	val-rmspe:0.184576
[208]	train-rmse:0.143348	val-rmse:0.166599	train-rmspe:0.21564	val-rmspe:0.1843

[295]	train-rmse:0.130921	val-rmse:0.158898	train-rmspe:0.202782	val-rmspe:0.176266
[296]	train-rmse:0.130857	val-rmse:0.158851	train-rmspe:0.202672	val-rmspe:0.176218
[297]	train-rmse:0.130678	val-rmse:0.158637	train-rmspe:0.202539	val-rmspe:0.176055
[298]	train-rmse:0.130494	val-rmse:0.158487	train-rmspe:0.202696	val-rmspe:0.175973
[299]	train-rmse:0.130424	val-rmse:0.158425	train-rmspe:0.202653	val-rmspe:0.175911
[300]	train-rmse:0.13036	val-rmse:0.15838	train-rmspe:0.202611	val-rmspe:0.175875
[301]	train-rmse:0.130289	val-rmse:0.158371	train-rmspe:0.202759	val-rmspe:0.17581
[302]	train-rmse:0.130152	val-rmse:0.158269	train-rmspe:0.202671	val-rmspe:0.175726
[303]	train-rmse:0.130086	val-rmse:0.158202	train-rmspe:0.202666	val-rmspe:0.175687
[304]	train-rmse:0.12993	val-rmse:0.158084	train-rmspe:0.20257	val-rmspe:0.175578
[305]	train-rmse:0.129664	val-rmse:0.157835	train-rmspe:0.202147	val-rmspe:0.175326
[306]	train-rmse:0.129609	val-rmse:0.15784	train-rmspe:0.202127	val-rmspe:0.17530

[393]	train-rmse:0.122083	val-rmse:0.153558	train-rmspe:0.196258	val-rmspe:0.16987
[394]	train-rmse:0.122036	val-rmse:0.153584	train-rmspe:0.196218	val-rmspe:0.169847
[395]	train-rmse:0.121934	val-rmse:0.153496	train-rmspe:0.196122	val-rmspe:0.16973
[396]	train-rmse:0.121823	val-rmse:0.153431	train-rmspe:0.196003	val-rmspe:0.169672
[397]	train-rmse:0.121746	val-rmse:0.153461	train-rmspe:0.195952	val-rmspe:0.169758
[398]	train-rmse:0.121711	val-rmse:0.153444	train-rmspe:0.195919	val-rmspe:0.169725
[399]	train-rmse:0.121654	val-rmse:0.153334	train-rmspe:0.195883	val-rmspe:0.169865
[400]	train-rmse:0.121542	val-rmse:0.153314	train-rmspe:0.195816	val-rmspe:0.169878
[401]	train-rmse:0.121468	val-rmse:0.153324	train-rmspe:0.195766	val-rmspe:0.169803
[402]	train-rmse:0.121401	val-rmse:0.153293	train-rmspe:0.195729	val-rmspe:0.169785
[403]	train-rmse:0.12132	val-rmse:0.153469	train-rmspe:0.195549	val-rmspe:0.169943
[404]	train-rmse:0.12125	val-rmse:0.153408	train-rmspe:0.195504	val-rmspe:0.169

...

[984]	train-rmse:0.101784	val-rmse:0.143206	train-rmspe:0.161841	val-rmspe:0.159014
[985]	train-rmse:0.101777	val-rmse:0.143209	train-rmspe:0.161822	val-rmspe:0.159008
[986]	train-rmse:0.101771	val-rmse:0.143161	train-rmspe:0.161843	val-rmspe:0.159041
[987]	train-rmse:0.101731	val-rmse:0.143164	train-rmspe:0.161809	val-rmspe:0.159052
[988]	train-rmse:0.101717	val-rmse:0.143185	train-rmspe:0.161797	val-rmspe:0.158978
[989]	train-rmse:0.101697	val-rmse:0.143177	train-rmspe:0.161791	val-rmspe:0.158938
[990]	train-rmse:0.101679	val-rmse:0.143071	train-rmspe:0.161785	val-rmspe:0.158874
[991]	train-rmse:0.101634	val-rmse:0.143036	train-rmspe:0.161664	val-rmspe:0.158856
[992]	train-rmse:0.10162	val-rmse:0.143045	train-rmspe:0.161664	val-rmspe:0.158862
[993]	train-rmse:0.101606	val-rmse:0.143043	train-rmspe:0.161629	val-rmspe:0.158821
[994]	train-rmse:0.10159	val-rmse:0.143029	train-rmspe:0.161695	val-rmspe:0.158827
[995]	train-rmse:0.101574	val-rmse:0.14302	train-rmspe:0.161692	val-rmspe:0.15

[1082]	train-rmse:0.100266	val-rmse:0.142614	train-rmspe:0.154972	val-rmspe:0.158218
[1083]	train-rmse:0.100258	val-rmse:0.142623	train-rmspe:0.154973	val-rmspe:0.158247
[1084]	train-rmse:0.100249	val-rmse:0.142544	train-rmspe:0.154952	val-rmspe:0.158215
[1085]	train-rmse:0.10023	val-rmse:0.142549	train-rmspe:0.154742	val-rmspe:0.158214
[1086]	train-rmse:0.100221	val-rmse:0.142537	train-rmspe:0.154732	val-rmspe:0.158196
[1087]	train-rmse:0.100213	val-rmse:0.142514	train-rmspe:0.154731	val-rmspe:0.158174
[1088]	train-rmse:0.100195	val-rmse:0.14251	train-rmspe:0.154673	val-rmspe:0.158163
[1089]	train-rmse:0.100142	val-rmse:0.142486	train-rmspe:0.154631	val-rmspe:0.158161
[1090]	train-rmse:0.10013	val-rmse:0.142475	train-rmspe:0.154618	val-rmspe:0.158151
[1091]	train-rmse:0.100121	val-rmse:0.142463	train-rmspe:0.154617	val-rmspe:0.158152
[1092]	train-rmse:0.100114	val-rmse:0.142462	train-rmspe:0.154607	val-rmspe:0.158147
[1093]	train-rmse:0.100103	val-rmse:0.142456	train-rmspe:0.154587	va

[1179]	train-rmse:0.098981	val-rmse:0.141621	train-rmspe:0.152977	val-rmspe:0.15748
[1180]	train-rmse:0.098971	val-rmse:0.141605	train-rmspe:0.152978	val-rmspe:0.157502
[1181]	train-rmse:0.098965	val-rmse:0.141639	train-rmspe:0.153005	val-rmspe:0.157521
[1182]	train-rmse:0.098959	val-rmse:0.141655	train-rmspe:0.152995	val-rmspe:0.15754
[1183]	train-rmse:0.098957	val-rmse:0.141646	train-rmspe:0.153038	val-rmspe:0.15754
[1184]	train-rmse:0.098944	val-rmse:0.141615	train-rmspe:0.153024	val-rmspe:0.157529
[1185]	train-rmse:0.098933	val-rmse:0.141619	train-rmspe:0.153027	val-rmspe:0.157534
[1186]	train-rmse:0.098927	val-rmse:0.141626	train-rmspe:0.153018	val-rmspe:0.157557
[1187]	train-rmse:0.098913	val-rmse:0.141618	train-rmspe:0.153014	val-rmspe:0.157588
[1188]	train-rmse:0.098907	val-rmse:0.141621	train-rmspe:0.153009	val-rmspe:0.157581
[1189]	train-rmse:0.098892	val-rmse:0.141588	train-rmspe:0.152958	val-rmspe:0.157579
[1190]	train-rmse:0.098864	val-rmse:0.141562	train-rmspe:0.152949	va

[1276]	train-rmse:0.097785	val-rmse:0.141387	train-rmspe:0.151574	val-rmspe:0.157478
[1277]	train-rmse:0.097781	val-rmse:0.141395	train-rmspe:0.15155	val-rmspe:0.157466
[1278]	train-rmse:0.097771	val-rmse:0.141407	train-rmspe:0.151552	val-rmspe:0.157475
[1279]	train-rmse:0.097762	val-rmse:0.141408	train-rmspe:0.151588	val-rmspe:0.157472
[1280]	train-rmse:0.097751	val-rmse:0.141402	train-rmspe:0.15158	val-rmspe:0.157473
[1281]	train-rmse:0.097745	val-rmse:0.141381	train-rmspe:0.151571	val-rmspe:0.157372
[1282]	train-rmse:0.097736	val-rmse:0.141399	train-rmspe:0.151561	val-rmspe:0.157376
[1283]	train-rmse:0.09773	val-rmse:0.141396	train-rmspe:0.151586	val-rmspe:0.157369
[1284]	train-rmse:0.09772	val-rmse:0.14144	train-rmspe:0.15161	val-rmspe:0.157393
[1285]	train-rmse:0.097707	val-rmse:0.141426	train-rmspe:0.151605	val-rmspe:0.157401
[1286]	train-rmse:0.097681	val-rmse:0.141405	train-rmspe:0.151562	val-rmspe:0.157377
[1287]	train-rmse:0.097675	val-rmse:0.141395	train-rmspe:0.151564	val-r

[1373]	train-rmse:0.096687	val-rmse:0.14171	train-rmspe:0.148339	val-rmspe:0.15792
[1374]	train-rmse:0.096676	val-rmse:0.141704	train-rmspe:0.14832	val-rmspe:0.157891
[1375]	train-rmse:0.09667	val-rmse:0.14173	train-rmspe:0.148299	val-rmspe:0.157896
[1376]	train-rmse:0.096659	val-rmse:0.141724	train-rmspe:0.148238	val-rmspe:0.157886
[1377]	train-rmse:0.09665	val-rmse:0.141757	train-rmspe:0.148236	val-rmspe:0.157885
[1378]	train-rmse:0.096642	val-rmse:0.141812	train-rmspe:0.148244	val-rmspe:0.157912
[1379]	train-rmse:0.096637	val-rmse:0.141807	train-rmspe:0.14813	val-rmspe:0.157896
[1380]	train-rmse:0.096634	val-rmse:0.141809	train-rmspe:0.14821	val-rmspe:0.157897
[1381]	train-rmse:0.096619	val-rmse:0.141813	train-rmspe:0.148197	val-rmspe:0.157907
[1382]	train-rmse:0.096612	val-rmse:0.14182	train-rmspe:0.1482	val-rmspe:0.157926
[1383]	train-rmse:0.096605	val-rmse:0.141817	train-rmspe:0.148178	val-rmspe:0.15793
[1384]	train-rmse:0.096597	val-rmse:0.141764	train-rmspe:0.148153	val-rmspe:0

In [7]:
#设定参数
param = {'max_depth': 5, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear', 'min_child_weight': 5, 'colsample_bytree': 0.7, 'subsample':0.7}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)

[0]	train-rmse:5.78961	val-rmse:5.82945	train-rmspe:0.996617	val-rmspe:0.996772
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:4.06089	val-rmse:4.10231	train-rmspe:0.981101	val-rmspe:0.981978
[2]	train-rmse:2.85393	val-rmse:2.89797	train-rmspe:0.937119	val-rmspe:0.940093
[3]	train-rmse:2.013	val-rmse:2.0538	train-rmspe:0.854875	val-rmspe:0.861109
[4]	train-rmse:1.43054	val-rmse:1.47179	train-rmspe:0.741768	val-rmspe:0.752377
[5]	train-rmse:1.03084	val-rmse:1.06975	train-rmspe:0.618841	val-rmspe:0.63232
[6]	train-rmse:0.761761	val-rmse:0.79912	train-rmspe:0.509478	val-rmspe:0.523245
[7]	train-rmse:0.584144	val-rmse:0.617892	train-rmspe:0.429415	val-rmspe:0.438568
[8]	train-rmse:0.471743	val-rmse:0.500804	train-rmspe:0.383007	val-rmspe:0.383322
[9]	train-rmse:0.405497	val-rmse:0.429758	train-rmspe:0.364639	val-rmspe:0.354463
[10]	train-rmse:0.365968	val-rmse:0.384869	train-rmsp

[98]	train-rmse:0.188982	val-rmse:0.201645	train-rmspe:0.262492	val-rmspe:0.225629
[99]	train-rmse:0.187669	val-rmse:0.200544	train-rmspe:0.26133	val-rmspe:0.224542
[100]	train-rmse:0.187421	val-rmse:0.200282	train-rmspe:0.260392	val-rmspe:0.224324
[101]	train-rmse:0.187255	val-rmse:0.200291	train-rmspe:0.260354	val-rmspe:0.224311
[102]	train-rmse:0.187157	val-rmse:0.200146	train-rmspe:0.260271	val-rmspe:0.224147
[103]	train-rmse:0.186536	val-rmse:0.199832	train-rmspe:0.259514	val-rmspe:0.22377
[104]	train-rmse:0.185682	val-rmse:0.198983	train-rmspe:0.258593	val-rmspe:0.222657
[105]	train-rmse:0.184607	val-rmse:0.197895	train-rmspe:0.257578	val-rmspe:0.221397
[106]	train-rmse:0.183315	val-rmse:0.196697	train-rmspe:0.256207	val-rmspe:0.219556
[107]	train-rmse:0.182906	val-rmse:0.196402	train-rmspe:0.255656	val-rmspe:0.220383
[108]	train-rmse:0.18219	val-rmse:0.195717	train-rmspe:0.254869	val-rmspe:0.219565
[109]	train-rmse:0.181494	val-rmse:0.195019	train-rmspe:0.253338	val-rmspe:0.2188

[197]	train-rmse:0.147159	val-rmse:0.169165	train-rmspe:0.220444	val-rmspe:0.191859
[198]	train-rmse:0.146715	val-rmse:0.168818	train-rmspe:0.219709	val-rmspe:0.191493
[199]	train-rmse:0.146502	val-rmse:0.168678	train-rmspe:0.219544	val-rmspe:0.191362
[200]	train-rmse:0.146389	val-rmse:0.168766	train-rmspe:0.219447	val-rmspe:0.191255
[201]	train-rmse:0.146282	val-rmse:0.168618	train-rmspe:0.2193	val-rmspe:0.191199
[202]	train-rmse:0.145885	val-rmse:0.168306	train-rmspe:0.218969	val-rmspe:0.190865
[203]	train-rmse:0.145644	val-rmse:0.16797	train-rmspe:0.218891	val-rmspe:0.190314
[204]	train-rmse:0.145433	val-rmse:0.167776	train-rmspe:0.218747	val-rmspe:0.190121
[205]	train-rmse:0.145229	val-rmse:0.167753	train-rmspe:0.218501	val-rmspe:0.190009
[206]	train-rmse:0.145029	val-rmse:0.167755	train-rmspe:0.218317	val-rmspe:0.189772
[207]	train-rmse:0.144971	val-rmse:0.167761	train-rmspe:0.218208	val-rmspe:0.189813
[208]	train-rmse:0.14483	val-rmse:0.167725	train-rmspe:0.218158	val-rmspe:0.189

[296]	train-rmse:0.132269	val-rmse:0.160607	train-rmspe:0.209903	val-rmspe:0.181338
[297]	train-rmse:0.132204	val-rmse:0.160552	train-rmspe:0.20987	val-rmspe:0.181279
[298]	train-rmse:0.132014	val-rmse:0.160401	train-rmspe:0.209801	val-rmspe:0.181057
[299]	train-rmse:0.131891	val-rmse:0.160277	train-rmspe:0.209737	val-rmspe:0.180969
[300]	train-rmse:0.131844	val-rmse:0.16026	train-rmspe:0.209742	val-rmspe:0.180987
[301]	train-rmse:0.131746	val-rmse:0.160189	train-rmspe:0.209699	val-rmspe:0.180898
[302]	train-rmse:0.131677	val-rmse:0.160171	train-rmspe:0.209665	val-rmspe:0.180894
[303]	train-rmse:0.131627	val-rmse:0.160248	train-rmspe:0.209564	val-rmspe:0.180969
[304]	train-rmse:0.131593	val-rmse:0.160203	train-rmspe:0.209559	val-rmspe:0.180925
[305]	train-rmse:0.131568	val-rmse:0.160196	train-rmspe:0.209536	val-rmspe:0.180906
[306]	train-rmse:0.131446	val-rmse:0.160101	train-rmspe:0.209475	val-rmspe:0.180832
[307]	train-rmse:0.131261	val-rmse:0.159906	train-rmspe:0.209585	val-rmspe:0.1

[395]	train-rmse:0.124024	val-rmse:0.157292	train-rmspe:0.202295	val-rmspe:0.176812
[396]	train-rmse:0.123831	val-rmse:0.157209	train-rmspe:0.202328	val-rmspe:0.176758
[397]	train-rmse:0.123545	val-rmse:0.157009	train-rmspe:0.202078	val-rmspe:0.176496
[398]	train-rmse:0.123522	val-rmse:0.157002	train-rmspe:0.202056	val-rmspe:0.176476
[399]	train-rmse:0.123515	val-rmse:0.156991	train-rmspe:0.201944	val-rmspe:0.176468
[400]	train-rmse:0.123482	val-rmse:0.156953	train-rmspe:0.201919	val-rmspe:0.176456
[401]	train-rmse:0.123382	val-rmse:0.156876	train-rmspe:0.203304	val-rmspe:0.176243
[402]	train-rmse:0.123277	val-rmse:0.15684	train-rmspe:0.202868	val-rmspe:0.176196
[403]	train-rmse:0.123239	val-rmse:0.156817	train-rmspe:0.202816	val-rmspe:0.176179
[404]	train-rmse:0.123186	val-rmse:0.156748	train-rmspe:0.202766	val-rmspe:0.176138
[405]	train-rmse:0.123149	val-rmse:0.15682	train-rmspe:0.202689	val-rmspe:0.17628
[406]	train-rmse:0.123086	val-rmse:0.156798	train-rmspe:0.2025	val-rmspe:0.1762

...

[1473]	train-rmse:0.096946	val-rmse:0.145018	train-rmspe:0.143113	val-rmspe:0.160611
[1474]	train-rmse:0.096939	val-rmse:0.145009	train-rmspe:0.143117	val-rmspe:0.16062
[1475]	train-rmse:0.09693	val-rmse:0.145006	train-rmspe:0.1431	val-rmspe:0.160621
[1476]	train-rmse:0.096911	val-rmse:0.14499	train-rmspe:0.1431	val-rmspe:0.160628
[1477]	train-rmse:0.096903	val-rmse:0.145007	train-rmspe:0.143115	val-rmspe:0.16062
[1478]	train-rmse:0.096893	val-rmse:0.145008	train-rmspe:0.143124	val-rmspe:0.160613
[1479]	train-rmse:0.096876	val-rmse:0.145021	train-rmspe:0.143102	val-rmspe:0.160613
[1480]	train-rmse:0.09687	val-rmse:0.145031	train-rmspe:0.143101	val-rmspe:0.16066
[1481]	train-rmse:0.096856	val-rmse:0.145015	train-rmspe:0.143091	val-rmspe:0.160636
[1482]	train-rmse:0.096844	val-rmse:0.144982	train-rmspe:0.143402	val-rmspe:0.160626
[1483]	train-rmse:0.096838	val-rmse:0.144979	train-rmspe:0.143396	val-rmspe:0.16061
[1484]	train-rmse:0.09683	val-rmse:0.144957	train-rmspe:0.143388	val-rmspe:0

[1570]	train-rmse:0.096097	val-rmse:0.144848	train-rmspe:0.137969	val-rmspe:0.160263
[1571]	train-rmse:0.09609	val-rmse:0.144831	train-rmspe:0.137972	val-rmspe:0.160261
[1572]	train-rmse:0.096087	val-rmse:0.144827	train-rmspe:0.137985	val-rmspe:0.160258
[1573]	train-rmse:0.096069	val-rmse:0.144818	train-rmspe:0.137966	val-rmspe:0.16024
[1574]	train-rmse:0.096062	val-rmse:0.144828	train-rmspe:0.137965	val-rmspe:0.160249
[1575]	train-rmse:0.096047	val-rmse:0.144831	train-rmspe:0.137943	val-rmspe:0.160252
[1576]	train-rmse:0.096043	val-rmse:0.144821	train-rmspe:0.137963	val-rmspe:0.16025
[1577]	train-rmse:0.096032	val-rmse:0.144815	train-rmspe:0.137972	val-rmspe:0.160261
[1578]	train-rmse:0.096016	val-rmse:0.144831	train-rmspe:0.137956	val-rmspe:0.160242
[1579]	train-rmse:0.096001	val-rmse:0.144818	train-rmspe:0.137956	val-rmspe:0.160236
[1580]	train-rmse:0.09599	val-rmse:0.144778	train-rmspe:0.137958	val-rmspe:0.160251
[1581]	train-rmse:0.095975	val-rmse:0.144779	train-rmspe:0.137949	val

[1667]	train-rmse:0.095231	val-rmse:0.144619	train-rmspe:0.136883	val-rmspe:0.160206
[1668]	train-rmse:0.095223	val-rmse:0.144612	train-rmspe:0.136895	val-rmspe:0.160197
[1669]	train-rmse:0.095217	val-rmse:0.144622	train-rmspe:0.13684	val-rmspe:0.160194
[1670]	train-rmse:0.095212	val-rmse:0.144615	train-rmspe:0.136775	val-rmspe:0.160162
[1671]	train-rmse:0.095205	val-rmse:0.144608	train-rmspe:0.132866	val-rmspe:0.160156
[1672]	train-rmse:0.095195	val-rmse:0.144621	train-rmspe:0.132853	val-rmspe:0.160157
[1673]	train-rmse:0.09519	val-rmse:0.144616	train-rmspe:0.132841	val-rmspe:0.160162
[1674]	train-rmse:0.095176	val-rmse:0.144609	train-rmspe:0.132762	val-rmspe:0.160156
[1675]	train-rmse:0.095168	val-rmse:0.144593	train-rmspe:0.13277	val-rmspe:0.160135
[1676]	train-rmse:0.095161	val-rmse:0.144581	train-rmspe:0.132776	val-rmspe:0.160129
[1677]	train-rmse:0.095146	val-rmse:0.144568	train-rmspe:0.132764	val-rmspe:0.160133
[1678]	train-rmse:0.095116	val-rmse:0.144512	train-rmspe:0.132732	va

[1764]	train-rmse:0.09449	val-rmse:0.144468	train-rmspe:0.127961	val-rmspe:0.160068
[1765]	train-rmse:0.094486	val-rmse:0.144463	train-rmspe:0.127953	val-rmspe:0.160071
[1766]	train-rmse:0.094477	val-rmse:0.144533	train-rmspe:0.127951	val-rmspe:0.160123
[1767]	train-rmse:0.094466	val-rmse:0.14453	train-rmspe:0.127941	val-rmspe:0.160134
[1768]	train-rmse:0.09446	val-rmse:0.144532	train-rmspe:0.127986	val-rmspe:0.16012
[1769]	train-rmse:0.094453	val-rmse:0.144524	train-rmspe:0.127969	val-rmspe:0.160111
[1770]	train-rmse:0.09445	val-rmse:0.144525	train-rmspe:0.127972	val-rmspe:0.160112
[1771]	train-rmse:0.094446	val-rmse:0.144533	train-rmspe:0.128021	val-rmspe:0.160126
[1772]	train-rmse:0.094442	val-rmse:0.144538	train-rmspe:0.128011	val-rmspe:0.160135
[1773]	train-rmse:0.094437	val-rmse:0.144527	train-rmspe:0.128013	val-rmspe:0.160126
[1774]	train-rmse:0.094429	val-rmse:0.144552	train-rmspe:0.127993	val-rmspe:0.160125
[1775]	train-rmse:0.094426	val-rmse:0.144553	train-rmspe:0.127982	val-

[1861]	train-rmse:0.093878	val-rmse:0.144296	train-rmspe:0.127116	val-rmspe:0.159831
[1862]	train-rmse:0.093873	val-rmse:0.144299	train-rmspe:0.127119	val-rmspe:0.159858
[1863]	train-rmse:0.093865	val-rmse:0.144314	train-rmspe:0.127112	val-rmspe:0.159866
[1864]	train-rmse:0.093859	val-rmse:0.144307	train-rmspe:0.127117	val-rmspe:0.159868
[1865]	train-rmse:0.093852	val-rmse:0.144308	train-rmspe:0.127112	val-rmspe:0.159865
[1866]	train-rmse:0.093847	val-rmse:0.144315	train-rmspe:0.127079	val-rmspe:0.159845
[1867]	train-rmse:0.093841	val-rmse:0.144332	train-rmspe:0.127069	val-rmspe:0.159848
[1868]	train-rmse:0.093837	val-rmse:0.144331	train-rmspe:0.127068	val-rmspe:0.159861
[1869]	train-rmse:0.093829	val-rmse:0.144326	train-rmspe:0.127063	val-rmspe:0.15986
[1870]	train-rmse:0.093819	val-rmse:0.144329	train-rmspe:0.127042	val-rmspe:0.159849
[1871]	train-rmse:0.09381	val-rmse:0.144355	train-rmspe:0.127003	val-rmspe:0.159869
[1872]	train-rmse:0.093801	val-rmse:0.144374	train-rmspe:0.126969	v

In [8]:
#设定参数
param = {'max_depth': 5, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear', 'min_child_weight': 5, 'colsample_bytree': 0.8, 'subsample':0.6}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)

[0]	train-rmse:5.78959	val-rmse:5.82859	train-rmspe:0.996617	val-rmspe:0.99677
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:4.06086	val-rmse:4.10033	train-rmspe:0.981104	val-rmspe:0.98195
[2]	train-rmse:2.8539	val-rmse:2.89568	train-rmspe:0.937132	val-rmspe:0.939986
[3]	train-rmse:2.01309	val-rmse:2.05382	train-rmspe:0.854861	val-rmspe:0.861119
[4]	train-rmse:1.43082	val-rmse:1.47133	train-rmspe:0.74179	val-rmspe:0.752228
[5]	train-rmse:1.0311	val-rmse:1.06946	train-rmspe:0.618981	val-rmspe:0.632222
[6]	train-rmse:0.761452	val-rmse:0.799075	train-rmspe:0.509642	val-rmspe:0.523874
[7]	train-rmse:0.583946	val-rmse:0.617792	train-rmspe:0.430024	val-rmspe:0.439736
[8]	train-rmse:0.471265	val-rmse:0.500493	train-rmspe:0.384033	val-rmspe:0.384141
[9]	train-rmse:0.404451	val-rmse:0.428312	train-rmspe:0.364097	val-rmspe:0.353722
[10]	train-rmse:0.366758	val-rmse:0.385776	train-rmsp

[98]	train-rmse:0.186568	val-rmse:0.201212	train-rmspe:0.258863	val-rmspe:0.227906
[99]	train-rmse:0.186257	val-rmse:0.200952	train-rmspe:0.258106	val-rmspe:0.227727
[100]	train-rmse:0.185183	val-rmse:0.200047	train-rmspe:0.256161	val-rmspe:0.22654
[101]	train-rmse:0.184066	val-rmse:0.19908	train-rmspe:0.256253	val-rmspe:0.225543
[102]	train-rmse:0.183146	val-rmse:0.198324	train-rmspe:0.254946	val-rmspe:0.224516
[103]	train-rmse:0.182693	val-rmse:0.198034	train-rmspe:0.254592	val-rmspe:0.224259
[104]	train-rmse:0.181827	val-rmse:0.197406	train-rmspe:0.253895	val-rmspe:0.223583
[105]	train-rmse:0.180642	val-rmse:0.196407	train-rmspe:0.252897	val-rmspe:0.222643
[106]	train-rmse:0.180129	val-rmse:0.196068	train-rmspe:0.25253	val-rmspe:0.222328
[107]	train-rmse:0.179762	val-rmse:0.195793	train-rmspe:0.252228	val-rmspe:0.222107
[108]	train-rmse:0.179437	val-rmse:0.195548	train-rmspe:0.251912	val-rmspe:0.221884
[109]	train-rmse:0.179169	val-rmse:0.195329	train-rmspe:0.251949	val-rmspe:0.2214

[196]	train-rmse:0.146035	val-rmse:0.169621	train-rmspe:0.224119	val-rmspe:0.193833
[197]	train-rmse:0.145859	val-rmse:0.169462	train-rmspe:0.22398	val-rmspe:0.193662
[198]	train-rmse:0.145731	val-rmse:0.169411	train-rmspe:0.223747	val-rmspe:0.193636
[199]	train-rmse:0.145613	val-rmse:0.169379	train-rmspe:0.223732	val-rmspe:0.193604
[200]	train-rmse:0.145337	val-rmse:0.169204	train-rmspe:0.223506	val-rmspe:0.193396
[201]	train-rmse:0.144989	val-rmse:0.16893	train-rmspe:0.223122	val-rmspe:0.192959
[202]	train-rmse:0.144755	val-rmse:0.168705	train-rmspe:0.223076	val-rmspe:0.192763
[203]	train-rmse:0.144595	val-rmse:0.168635	train-rmspe:0.222964	val-rmspe:0.192614
[204]	train-rmse:0.144206	val-rmse:0.168269	train-rmspe:0.222717	val-rmspe:0.192301
[205]	train-rmse:0.144078	val-rmse:0.168198	train-rmspe:0.222535	val-rmspe:0.192208
[206]	train-rmse:0.143963	val-rmse:0.167755	train-rmspe:0.222577	val-rmspe:0.192057
[207]	train-rmse:0.143823	val-rmse:0.167663	train-rmspe:0.22248	val-rmspe:0.19

[295]	train-rmse:0.131053	val-rmse:0.161167	train-rmspe:0.209484	val-rmspe:0.184081
[296]	train-rmse:0.130968	val-rmse:0.161053	train-rmspe:0.209468	val-rmspe:0.183994
[297]	train-rmse:0.130823	val-rmse:0.161072	train-rmspe:0.209075	val-rmspe:0.184221
[298]	train-rmse:0.130729	val-rmse:0.161051	train-rmspe:0.208976	val-rmspe:0.184158
[299]	train-rmse:0.130635	val-rmse:0.160975	train-rmspe:0.208915	val-rmspe:0.184087
[300]	train-rmse:0.130505	val-rmse:0.160884	train-rmspe:0.208782	val-rmspe:0.18402
[301]	train-rmse:0.130284	val-rmse:0.16078	train-rmspe:0.208616	val-rmspe:0.183687
[302]	train-rmse:0.130187	val-rmse:0.160896	train-rmspe:0.208365	val-rmspe:0.18383
[303]	train-rmse:0.130114	val-rmse:0.160801	train-rmspe:0.208301	val-rmspe:0.183725
[304]	train-rmse:0.130059	val-rmse:0.160777	train-rmspe:0.20826	val-rmspe:0.183698
[305]	train-rmse:0.13	val-rmse:0.160729	train-rmspe:0.208289	val-rmspe:0.183674
[306]	train-rmse:0.1299	val-rmse:0.160798	train-rmspe:0.208158	val-rmspe:0.183746
[3

[394]	train-rmse:0.122386	val-rmse:0.156801	train-rmspe:0.200378	val-rmspe:0.175983
[395]	train-rmse:0.122282	val-rmse:0.156724	train-rmspe:0.200337	val-rmspe:0.175925
[396]	train-rmse:0.122224	val-rmse:0.156834	train-rmspe:0.200186	val-rmspe:0.175928
[397]	train-rmse:0.122099	val-rmse:0.156725	train-rmspe:0.199688	val-rmspe:0.175772
[398]	train-rmse:0.122042	val-rmse:0.156707	train-rmspe:0.199661	val-rmspe:0.175782
[399]	train-rmse:0.121962	val-rmse:0.156614	train-rmspe:0.199308	val-rmspe:0.175834
[400]	train-rmse:0.121935	val-rmse:0.15661	train-rmspe:0.199341	val-rmspe:0.175795
[401]	train-rmse:0.121665	val-rmse:0.156393	train-rmspe:0.199096	val-rmspe:0.175526
[402]	train-rmse:0.121649	val-rmse:0.156384	train-rmspe:0.199108	val-rmspe:0.17551
[403]	train-rmse:0.12154	val-rmse:0.156323	train-rmspe:0.199045	val-rmspe:0.175441
[404]	train-rmse:0.121504	val-rmse:0.156246	train-rmspe:0.199036	val-rmspe:0.175377
[405]	train-rmse:0.121429	val-rmse:0.15622	train-rmspe:0.198997	val-rmspe:0.175

...

[1375]	train-rmse:0.097363	val-rmse:0.145406	train-rmspe:0.160951	val-rmspe:0.158649
[1376]	train-rmse:0.097355	val-rmse:0.145405	train-rmspe:0.160955	val-rmspe:0.158657
[1377]	train-rmse:0.097339	val-rmse:0.145385	train-rmspe:0.160954	val-rmspe:0.158624
[1378]	train-rmse:0.097328	val-rmse:0.145403	train-rmspe:0.160935	val-rmspe:0.158644
[1379]	train-rmse:0.09732	val-rmse:0.145477	train-rmspe:0.160923	val-rmspe:0.15866
[1380]	train-rmse:0.097314	val-rmse:0.145482	train-rmspe:0.160943	val-rmspe:0.158656
[1381]	train-rmse:0.097309	val-rmse:0.145496	train-rmspe:0.16089	val-rmspe:0.158645
[1382]	train-rmse:0.097294	val-rmse:0.145482	train-rmspe:0.160902	val-rmspe:0.158649
[1383]	train-rmse:0.097286	val-rmse:0.145499	train-rmspe:0.160897	val-rmspe:0.158648
[1384]	train-rmse:0.09726	val-rmse:0.145454	train-rmspe:0.160849	val-rmspe:0.158631
[1385]	train-rmse:0.097238	val-rmse:0.145432	train-rmspe:0.160864	val-rmspe:0.158614
[1386]	train-rmse:0.09723	val-rmse:0.145451	train-rmspe:0.160865	val-

[1472]	train-rmse:0.096426	val-rmse:0.145332	train-rmspe:0.159129	val-rmspe:0.158575
[1473]	train-rmse:0.096405	val-rmse:0.14537	train-rmspe:0.159055	val-rmspe:0.158583
[1474]	train-rmse:0.096395	val-rmse:0.145353	train-rmspe:0.159076	val-rmspe:0.158587
[1475]	train-rmse:0.096385	val-rmse:0.145332	train-rmspe:0.159044	val-rmspe:0.158587
[1476]	train-rmse:0.096382	val-rmse:0.145294	train-rmspe:0.159056	val-rmspe:0.158578
[1477]	train-rmse:0.096377	val-rmse:0.145203	train-rmspe:0.159066	val-rmspe:0.158567
[1478]	train-rmse:0.09637	val-rmse:0.145202	train-rmspe:0.159073	val-rmspe:0.158575
[1479]	train-rmse:0.096361	val-rmse:0.145196	train-rmspe:0.159078	val-rmspe:0.158572
[1480]	train-rmse:0.096352	val-rmse:0.145163	train-rmspe:0.159065	val-rmspe:0.158585
[1481]	train-rmse:0.096343	val-rmse:0.145161	train-rmspe:0.159049	val-rmspe:0.158595
[1482]	train-rmse:0.096319	val-rmse:0.145137	train-rmspe:0.159012	val-rmspe:0.158576
[1483]	train-rmse:0.096313	val-rmse:0.145145	train-rmspe:0.159009	v

[1569]	train-rmse:0.095591	val-rmse:0.145238	train-rmspe:0.154601	val-rmspe:0.158448
[1570]	train-rmse:0.09558	val-rmse:0.145223	train-rmspe:0.154603	val-rmspe:0.158436
[1571]	train-rmse:0.095574	val-rmse:0.145224	train-rmspe:0.154604	val-rmspe:0.158433
[1572]	train-rmse:0.095572	val-rmse:0.145228	train-rmspe:0.15461	val-rmspe:0.158436
[1573]	train-rmse:0.095557	val-rmse:0.145249	train-rmspe:0.154601	val-rmspe:0.158451
[1574]	train-rmse:0.095551	val-rmse:0.145215	train-rmspe:0.154716	val-rmspe:0.158453
[1575]	train-rmse:0.095547	val-rmse:0.145225	train-rmspe:0.15474	val-rmspe:0.158452
[1576]	train-rmse:0.095541	val-rmse:0.145165	train-rmspe:0.154738	val-rmspe:0.158426
[1577]	train-rmse:0.095531	val-rmse:0.145152	train-rmspe:0.149913	val-rmspe:0.158433
[1578]	train-rmse:0.095515	val-rmse:0.145175	train-rmspe:0.149886	val-rmspe:0.158401
[1579]	train-rmse:0.095503	val-rmse:0.145158	train-rmspe:0.149882	val-rmspe:0.158396
[1580]	train-rmse:0.0955	val-rmse:0.145153	train-rmspe:0.149898	val-

[1666]	train-rmse:0.094817	val-rmse:0.144904	train-rmspe:0.149296	val-rmspe:0.158288
[1667]	train-rmse:0.094814	val-rmse:0.144881	train-rmspe:0.149279	val-rmspe:0.158284
[1668]	train-rmse:0.094806	val-rmse:0.144909	train-rmspe:0.149262	val-rmspe:0.158278
[1669]	train-rmse:0.094804	val-rmse:0.14491	train-rmspe:0.149441	val-rmspe:0.158259
[1670]	train-rmse:0.094793	val-rmse:0.144893	train-rmspe:0.149444	val-rmspe:0.15826
[1671]	train-rmse:0.09479	val-rmse:0.144887	train-rmspe:0.149432	val-rmspe:0.158261
[1672]	train-rmse:0.094783	val-rmse:0.14486	train-rmspe:0.149505	val-rmspe:0.158249
[1673]	train-rmse:0.094777	val-rmse:0.144843	train-rmspe:0.14951	val-rmspe:0.158238
[1674]	train-rmse:0.094772	val-rmse:0.144852	train-rmspe:0.14945	val-rmspe:0.158237
[1675]	train-rmse:0.094768	val-rmse:0.144877	train-rmspe:0.149365	val-rmspe:0.15823
[1676]	train-rmse:0.094759	val-rmse:0.144849	train-rmspe:0.149384	val-rmspe:0.158235
[1677]	train-rmse:0.094753	val-rmse:0.144854	train-rmspe:0.149362	val-rm

[1764]	train-rmse:0.094144	val-rmse:0.144797	train-rmspe:0.138118	val-rmspe:0.158464
[1765]	train-rmse:0.094135	val-rmse:0.144802	train-rmspe:0.138112	val-rmspe:0.158459
[1766]	train-rmse:0.094133	val-rmse:0.144795	train-rmspe:0.138127	val-rmspe:0.158459
[1767]	train-rmse:0.094128	val-rmse:0.144781	train-rmspe:0.138119	val-rmspe:0.158428
[1768]	train-rmse:0.09412	val-rmse:0.144773	train-rmspe:0.138207	val-rmspe:0.158417
[1769]	train-rmse:0.094115	val-rmse:0.144804	train-rmspe:0.13822	val-rmspe:0.158409
[1770]	train-rmse:0.094111	val-rmse:0.144771	train-rmspe:0.138216	val-rmspe:0.158424
[1771]	train-rmse:0.094099	val-rmse:0.144764	train-rmspe:0.138211	val-rmspe:0.15843
[1772]	train-rmse:0.094092	val-rmse:0.144742	train-rmspe:0.138213	val-rmspe:0.15842
[1773]	train-rmse:0.09408	val-rmse:0.144728	train-rmspe:0.138223	val-rmspe:0.158409
[1774]	train-rmse:0.094076	val-rmse:0.144742	train-rmspe:0.138214	val-rmspe:0.158412
[1775]	train-rmse:0.094073	val-rmse:0.144747	train-rmspe:0.138204	val-

In [9]:
#设定参数
param = {'max_depth': 5, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear', 'min_child_weight': 5, 'colsample_bytree': 0.9, 'subsample':0.7}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)



[0]	train-rmse:5.78947	val-rmse:5.82709	train-rmspe:0.99662	val-rmspe:0.996769
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:4.06077	val-rmse:4.10031	train-rmspe:0.981107	val-rmspe:0.981953
[2]	train-rmse:2.85377	val-rmse:2.89335	train-rmspe:0.937129	val-rmspe:0.939879
[3]	train-rmse:2.0131	val-rmse:2.05438	train-rmspe:0.854827	val-rmspe:0.861199
[4]	train-rmse:1.43056	val-rmse:1.47201	train-rmspe:0.741622	val-rmspe:0.752436
[5]	train-rmse:1.03068	val-rmse:1.07101	train-rmspe:0.618363	val-rmspe:0.632807
[6]	train-rmse:0.761142	val-rmse:0.800883	train-rmspe:0.508416	val-rmspe:0.524197
[7]	train-rmse:0.584495	val-rmse:0.619317	train-rmspe:0.42767	val-rmspe:0.439084
[8]	train-rmse:0.472015	val-rmse:0.502171	train-rmspe:0.379194	val-rmspe:0.382618
[9]	train-rmse:0.405193	val-rmse:0.428035	train-rmspe:0.359272	val-rmspe:0.35212
[10]	train-rmse:0.368098	val-rmse:0.386126	train-rms

[98]	train-rmse:0.183671	val-rmse:0.197985	train-rmspe:0.25275	val-rmspe:0.22074
[99]	train-rmse:0.183211	val-rmse:0.1976	train-rmspe:0.25242	val-rmspe:0.220518
[100]	train-rmse:0.182429	val-rmse:0.196931	train-rmspe:0.250935	val-rmspe:0.219521
[101]	train-rmse:0.18174	val-rmse:0.196904	train-rmspe:0.25042	val-rmspe:0.220279
[102]	train-rmse:0.181015	val-rmse:0.196182	train-rmspe:0.249772	val-rmspe:0.219445
[103]	train-rmse:0.180579	val-rmse:0.195764	train-rmspe:0.249339	val-rmspe:0.219027
[104]	train-rmse:0.179905	val-rmse:0.195164	train-rmspe:0.248631	val-rmspe:0.21835
[105]	train-rmse:0.179506	val-rmse:0.194808	train-rmspe:0.248296	val-rmspe:0.217911
[106]	train-rmse:0.178958	val-rmse:0.194598	train-rmspe:0.247581	val-rmspe:0.216719
[107]	train-rmse:0.178593	val-rmse:0.194321	train-rmspe:0.247232	val-rmspe:0.21626
[108]	train-rmse:0.17811	val-rmse:0.193807	train-rmspe:0.246845	val-rmspe:0.215822
[109]	train-rmse:0.177962	val-rmse:0.193635	train-rmspe:0.246643	val-rmspe:0.215654
[110

[197]	train-rmse:0.144536	val-rmse:0.166833	train-rmspe:0.213684	val-rmspe:0.18336
[198]	train-rmse:0.144351	val-rmse:0.166678	train-rmspe:0.21355	val-rmspe:0.183201
[199]	train-rmse:0.144263	val-rmse:0.166598	train-rmspe:0.213787	val-rmspe:0.183097
[200]	train-rmse:0.144042	val-rmse:0.166443	train-rmspe:0.213519	val-rmspe:0.182874
[201]	train-rmse:0.143952	val-rmse:0.166358	train-rmspe:0.213477	val-rmspe:0.182798
[202]	train-rmse:0.143634	val-rmse:0.166126	train-rmspe:0.213216	val-rmspe:0.182609
[203]	train-rmse:0.143519	val-rmse:0.166097	train-rmspe:0.212978	val-rmspe:0.182557
[204]	train-rmse:0.14338	val-rmse:0.165998	train-rmspe:0.21289	val-rmspe:0.182482
[205]	train-rmse:0.142981	val-rmse:0.165657	train-rmspe:0.211969	val-rmspe:0.182015
[206]	train-rmse:0.142734	val-rmse:0.165503	train-rmspe:0.211699	val-rmspe:0.181779
[207]	train-rmse:0.142352	val-rmse:0.165647	train-rmspe:0.211529	val-rmspe:0.181707
[208]	train-rmse:0.142093	val-rmse:0.165417	train-rmspe:0.21134	val-rmspe:0.1815

[296]	train-rmse:0.129163	val-rmse:0.158806	train-rmspe:0.200029	val-rmspe:0.174091
[297]	train-rmse:0.129053	val-rmse:0.15872	train-rmspe:0.202305	val-rmspe:0.174006
[298]	train-rmse:0.12894	val-rmse:0.158629	train-rmspe:0.202229	val-rmspe:0.17389
[299]	train-rmse:0.12887	val-rmse:0.158589	train-rmspe:0.202172	val-rmspe:0.173855
[300]	train-rmse:0.1287	val-rmse:0.158458	train-rmspe:0.202034	val-rmspe:0.173401
[301]	train-rmse:0.128485	val-rmse:0.158278	train-rmspe:0.201893	val-rmspe:0.17318
[302]	train-rmse:0.128371	val-rmse:0.158218	train-rmspe:0.201813	val-rmspe:0.173127
[303]	train-rmse:0.128342	val-rmse:0.158192	train-rmspe:0.201775	val-rmspe:0.173087
[304]	train-rmse:0.128224	val-rmse:0.158041	train-rmspe:0.201701	val-rmspe:0.172996
[305]	train-rmse:0.128119	val-rmse:0.157952	train-rmspe:0.203173	val-rmspe:0.172917
[306]	train-rmse:0.128046	val-rmse:0.15789	train-rmspe:0.203151	val-rmspe:0.172896
[307]	train-rmse:0.127937	val-rmse:0.158023	train-rmspe:0.203111	val-rmspe:0.172964


[395]	train-rmse:0.120632	val-rmse:0.15534	train-rmspe:0.193931	val-rmspe:0.169019
[396]	train-rmse:0.120487	val-rmse:0.15524	train-rmspe:0.193758	val-rmspe:0.168908
[397]	train-rmse:0.120455	val-rmse:0.155224	train-rmspe:0.193752	val-rmspe:0.168886
[398]	train-rmse:0.120413	val-rmse:0.155205	train-rmspe:0.193713	val-rmspe:0.16886
[399]	train-rmse:0.120364	val-rmse:0.155202	train-rmspe:0.193853	val-rmspe:0.168765
[400]	train-rmse:0.120327	val-rmse:0.15516	train-rmspe:0.193829	val-rmspe:0.168737
[401]	train-rmse:0.12025	val-rmse:0.155165	train-rmspe:0.193643	val-rmspe:0.168757
[402]	train-rmse:0.120206	val-rmse:0.155177	train-rmspe:0.193452	val-rmspe:0.168756
[403]	train-rmse:0.120177	val-rmse:0.155196	train-rmspe:0.193435	val-rmspe:0.168715
[404]	train-rmse:0.120135	val-rmse:0.155148	train-rmspe:0.193426	val-rmspe:0.168683
[405]	train-rmse:0.120096	val-rmse:0.155121	train-rmspe:0.193404	val-rmspe:0.168676
[406]	train-rmse:0.120025	val-rmse:0.155024	train-rmspe:0.19335	val-rmspe:0.16858

...

[1667]	train-rmse:0.093707	val-rmse:0.143788	train-rmspe:0.153665	val-rmspe:0.156631
[1668]	train-rmse:0.093699	val-rmse:0.143782	train-rmspe:0.153673	val-rmspe:0.15662
[1669]	train-rmse:0.093693	val-rmse:0.143781	train-rmspe:0.153664	val-rmspe:0.156611
[1670]	train-rmse:0.093688	val-rmse:0.143777	train-rmspe:0.153671	val-rmspe:0.156605
[1671]	train-rmse:0.093681	val-rmse:0.143798	train-rmspe:0.153636	val-rmspe:0.156613
[1672]	train-rmse:0.093676	val-rmse:0.143803	train-rmspe:0.153732	val-rmspe:0.156609
[1673]	train-rmse:0.093673	val-rmse:0.1438	train-rmspe:0.153735	val-rmspe:0.156613
[1674]	train-rmse:0.093666	val-rmse:0.143812	train-rmspe:0.153719	val-rmspe:0.156632
[1675]	train-rmse:0.093658	val-rmse:0.143787	train-rmspe:0.153704	val-rmspe:0.156625
[1676]	train-rmse:0.093653	val-rmse:0.143802	train-rmspe:0.153706	val-rmspe:0.156634
[1677]	train-rmse:0.093647	val-rmse:0.143803	train-rmspe:0.153698	val-rmspe:0.156633
[1678]	train-rmse:0.093637	val-rmse:0.143794	train-rmspe:0.153692	va

[1764]	train-rmse:0.093012	val-rmse:0.143514	train-rmspe:0.1517	val-rmspe:0.156378
[1765]	train-rmse:0.093006	val-rmse:0.143509	train-rmspe:0.151693	val-rmspe:0.156377
[1766]	train-rmse:0.093	val-rmse:0.143505	train-rmspe:0.151684	val-rmspe:0.156378
[1767]	train-rmse:0.092994	val-rmse:0.143515	train-rmspe:0.151674	val-rmspe:0.156375
[1768]	train-rmse:0.092991	val-rmse:0.143538	train-rmspe:0.151667	val-rmspe:0.156391
[1769]	train-rmse:0.09298	val-rmse:0.143538	train-rmspe:0.151411	val-rmspe:0.156397
[1770]	train-rmse:0.092973	val-rmse:0.143534	train-rmspe:0.151405	val-rmspe:0.156366
[1771]	train-rmse:0.092965	val-rmse:0.143431	train-rmspe:0.15139	val-rmspe:0.156322
[1772]	train-rmse:0.092963	val-rmse:0.143485	train-rmspe:0.151357	val-rmspe:0.1563
[1773]	train-rmse:0.092957	val-rmse:0.143476	train-rmspe:0.151334	val-rmspe:0.156295
[1774]	train-rmse:0.092953	val-rmse:0.143496	train-rmspe:0.15133	val-rmspe:0.156298
[1775]	train-rmse:0.092946	val-rmse:0.143424	train-rmspe:0.151256	val-rmspe

[1862]	train-rmse:0.09234	val-rmse:0.143176	train-rmspe:0.150913	val-rmspe:0.156236
[1863]	train-rmse:0.092334	val-rmse:0.143189	train-rmspe:0.150909	val-rmspe:0.156242
[1864]	train-rmse:0.09233	val-rmse:0.143177	train-rmspe:0.150915	val-rmspe:0.15624
[1865]	train-rmse:0.092327	val-rmse:0.143181	train-rmspe:0.150833	val-rmspe:0.15627
[1866]	train-rmse:0.09232	val-rmse:0.14317	train-rmspe:0.150825	val-rmspe:0.156254
[1867]	train-rmse:0.092316	val-rmse:0.143111	train-rmspe:0.150825	val-rmspe:0.156221
[1868]	train-rmse:0.092312	val-rmse:0.143099	train-rmspe:0.150833	val-rmspe:0.156217
[1869]	train-rmse:0.092307	val-rmse:0.143079	train-rmspe:0.15083	val-rmspe:0.15622
[1870]	train-rmse:0.092303	val-rmse:0.143084	train-rmspe:0.150821	val-rmspe:0.156213
[1871]	train-rmse:0.092295	val-rmse:0.143072	train-rmspe:0.150812	val-rmspe:0.156214
[1872]	train-rmse:0.092286	val-rmse:0.143071	train-rmspe:0.150759	val-rmspe:0.156213
[1873]	train-rmse:0.092279	val-rmse:0.143071	train-rmspe:0.150781	val-rms

[1960]	train-rmse:0.091726	val-rmse:0.143122	train-rmspe:0.150334	val-rmspe:0.155944
[1961]	train-rmse:0.091714	val-rmse:0.14309	train-rmspe:0.150343	val-rmspe:0.15594
[1962]	train-rmse:0.09171	val-rmse:0.143094	train-rmspe:0.150333	val-rmspe:0.155948
[1963]	train-rmse:0.091704	val-rmse:0.143103	train-rmspe:0.150295	val-rmspe:0.15594
[1964]	train-rmse:0.0917	val-rmse:0.143099	train-rmspe:0.150314	val-rmspe:0.155938
[1965]	train-rmse:0.0917	val-rmse:0.143098	train-rmspe:0.151012	val-rmspe:0.155931
[1966]	train-rmse:0.091687	val-rmse:0.143106	train-rmspe:0.150992	val-rmspe:0.155931
[1967]	train-rmse:0.091683	val-rmse:0.143095	train-rmspe:0.151002	val-rmspe:0.155935
[1968]	train-rmse:0.091681	val-rmse:0.143103	train-rmspe:0.150993	val-rmspe:0.155936
[1969]	train-rmse:0.091669	val-rmse:0.143109	train-rmspe:0.150978	val-rmspe:0.155894
[1970]	train-rmse:0.091663	val-rmse:0.143102	train-rmspe:0.150966	val-rmspe:0.155867
[1971]	train-rmse:0.091659	val-rmse:0.143093	train-rmspe:0.150973	val-rms

[2057]	train-rmse:0.091173	val-rmse:0.142753	train-rmspe:0.141038	val-rmspe:0.155624
[2058]	train-rmse:0.091168	val-rmse:0.142719	train-rmspe:0.141026	val-rmspe:0.155616
[2059]	train-rmse:0.091162	val-rmse:0.142764	train-rmspe:0.141034	val-rmspe:0.155677
[2060]	train-rmse:0.091153	val-rmse:0.142753	train-rmspe:0.141057	val-rmspe:0.155669
[2061]	train-rmse:0.09115	val-rmse:0.142742	train-rmspe:0.141052	val-rmspe:0.155669
[2062]	train-rmse:0.091138	val-rmse:0.142746	train-rmspe:0.141053	val-rmspe:0.155662
[2063]	train-rmse:0.091132	val-rmse:0.142735	train-rmspe:0.14102	val-rmspe:0.155648
[2064]	train-rmse:0.091126	val-rmse:0.142735	train-rmspe:0.141021	val-rmspe:0.15565
[2065]	train-rmse:0.091122	val-rmse:0.142732	train-rmspe:0.141044	val-rmspe:0.155658
[2066]	train-rmse:0.09112	val-rmse:0.142744	train-rmspe:0.141107	val-rmspe:0.155658
[2067]	train-rmse:0.091115	val-rmse:0.142754	train-rmspe:0.141095	val-rmspe:0.155642
[2068]	train-rmse:0.091111	val-rmse:0.142761	train-rmspe:0.141106	val

In [10]:
#设定参数
param = {'max_depth': 5, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear', 'min_child_weight': 5, 'colsample_bytree': 0.8, 'subsample':0.8}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)

[0]	train-rmse:5.78964	val-rmse:5.8286	train-rmspe:0.996618	val-rmspe:0.99677
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:4.06093	val-rmse:4.10037	train-rmspe:0.981109	val-rmspe:0.981955
[2]	train-rmse:2.85389	val-rmse:2.89651	train-rmspe:0.937131	val-rmspe:0.940053
[3]	train-rmse:2.01324	val-rmse:2.05485	train-rmspe:0.854868	val-rmspe:0.861297
[4]	train-rmse:1.43068	val-rmse:1.46992	train-rmspe:0.741761	val-rmspe:0.752053
[5]	train-rmse:1.03059	val-rmse:1.06965	train-rmspe:0.618927	val-rmspe:0.632688
[6]	train-rmse:0.760935	val-rmse:0.798712	train-rmspe:0.509082	val-rmspe:0.523568
[7]	train-rmse:0.583222	val-rmse:0.617251	train-rmspe:0.428579	val-rmspe:0.43893
[8]	train-rmse:0.471275	val-rmse:0.500229	train-rmspe:0.380886	val-rmspe:0.383137
[9]	train-rmse:0.403761	val-rmse:0.428429	train-rmspe:0.361364	val-rmspe:0.353942
[10]	train-rmse:0.364178	val-rmse:0.383478	train-rm

[98]	train-rmse:0.186654	val-rmse:0.200194	train-rmspe:0.256097	val-rmspe:0.221857
[99]	train-rmse:0.185458	val-rmse:0.199284	train-rmspe:0.254924	val-rmspe:0.220825
[100]	train-rmse:0.185001	val-rmse:0.199003	train-rmspe:0.254309	val-rmspe:0.22024
[101]	train-rmse:0.184789	val-rmse:0.198931	train-rmspe:0.254242	val-rmspe:0.220214
[102]	train-rmse:0.183898	val-rmse:0.198065	train-rmspe:0.253236	val-rmspe:0.219324
[103]	train-rmse:0.183629	val-rmse:0.19806	train-rmspe:0.253008	val-rmspe:0.219149
[104]	train-rmse:0.183489	val-rmse:0.197956	train-rmspe:0.252905	val-rmspe:0.219036
[105]	train-rmse:0.183272	val-rmse:0.197907	train-rmspe:0.252631	val-rmspe:0.218948
[106]	train-rmse:0.182764	val-rmse:0.19745	train-rmspe:0.2522	val-rmspe:0.218508
[107]	train-rmse:0.181917	val-rmse:0.196701	train-rmspe:0.251167	val-rmspe:0.217594
[108]	train-rmse:0.181286	val-rmse:0.196161	train-rmspe:0.250715	val-rmspe:0.217104
[109]	train-rmse:0.180373	val-rmse:0.195453	train-rmspe:0.249885	val-rmspe:0.216134

[197]	train-rmse:0.145048	val-rmse:0.170734	train-rmspe:0.221384	val-rmspe:0.187826
[198]	train-rmse:0.144992	val-rmse:0.170712	train-rmspe:0.221343	val-rmspe:0.187803
[199]	train-rmse:0.144605	val-rmse:0.170423	train-rmspe:0.220921	val-rmspe:0.187499
[200]	train-rmse:0.144334	val-rmse:0.169987	train-rmspe:0.220489	val-rmspe:0.187056
[201]	train-rmse:0.144175	val-rmse:0.169879	train-rmspe:0.22035	val-rmspe:0.186928
[202]	train-rmse:0.144041	val-rmse:0.169763	train-rmspe:0.220267	val-rmspe:0.186827
[203]	train-rmse:0.144004	val-rmse:0.169752	train-rmspe:0.220224	val-rmspe:0.186802
[204]	train-rmse:0.143677	val-rmse:0.16948	train-rmspe:0.220297	val-rmspe:0.186592
[205]	train-rmse:0.143508	val-rmse:0.169331	train-rmspe:0.220303	val-rmspe:0.18646
[206]	train-rmse:0.143225	val-rmse:0.169096	train-rmspe:0.220129	val-rmspe:0.186262
[207]	train-rmse:0.142969	val-rmse:0.168942	train-rmspe:0.219754	val-rmspe:0.186027
[208]	train-rmse:0.142885	val-rmse:0.168907	train-rmspe:0.21981	val-rmspe:0.185

[295]	train-rmse:0.130518	val-rmse:0.162069	train-rmspe:0.205589	val-rmspe:0.178137
[296]	train-rmse:0.130467	val-rmse:0.161956	train-rmspe:0.205508	val-rmspe:0.178097
[297]	train-rmse:0.130407	val-rmse:0.161943	train-rmspe:0.205525	val-rmspe:0.178103
[298]	train-rmse:0.130339	val-rmse:0.1619	train-rmspe:0.205473	val-rmspe:0.178002
[299]	train-rmse:0.13025	val-rmse:0.161826	train-rmspe:0.205701	val-rmspe:0.177681
[300]	train-rmse:0.13018	val-rmse:0.161609	train-rmspe:0.205664	val-rmspe:0.177664
[301]	train-rmse:0.129965	val-rmse:0.161457	train-rmspe:0.205473	val-rmspe:0.177494
[302]	train-rmse:0.129909	val-rmse:0.161414	train-rmspe:0.20527	val-rmspe:0.177108
[303]	train-rmse:0.129819	val-rmse:0.161375	train-rmspe:0.205218	val-rmspe:0.177056
[304]	train-rmse:0.12978	val-rmse:0.161378	train-rmspe:0.205183	val-rmspe:0.177064
[305]	train-rmse:0.129685	val-rmse:0.161283	train-rmspe:0.205056	val-rmspe:0.177001
[306]	train-rmse:0.129574	val-rmse:0.161209	train-rmspe:0.204963	val-rmspe:0.17694

[394]	train-rmse:0.122408	val-rmse:0.157615	train-rmspe:0.197742	val-rmspe:0.172646
[395]	train-rmse:0.12233	val-rmse:0.157532	train-rmspe:0.19769	val-rmspe:0.172548
[396]	train-rmse:0.122209	val-rmse:0.157451	train-rmspe:0.197672	val-rmspe:0.172471
[397]	train-rmse:0.122175	val-rmse:0.157444	train-rmspe:0.197655	val-rmspe:0.172468
[398]	train-rmse:0.122148	val-rmse:0.157451	train-rmspe:0.197581	val-rmspe:0.172429
[399]	train-rmse:0.122122	val-rmse:0.157406	train-rmspe:0.196538	val-rmspe:0.172384
[400]	train-rmse:0.122083	val-rmse:0.157374	train-rmspe:0.196501	val-rmspe:0.17235
[401]	train-rmse:0.122047	val-rmse:0.157321	train-rmspe:0.196466	val-rmspe:0.172339
[402]	train-rmse:0.121984	val-rmse:0.157288	train-rmspe:0.19668	val-rmspe:0.172314
[403]	train-rmse:0.121888	val-rmse:0.157196	train-rmspe:0.196604	val-rmspe:0.172223
[404]	train-rmse:0.121871	val-rmse:0.1572	train-rmspe:0.196624	val-rmspe:0.172241
[405]	train-rmse:0.121794	val-rmse:0.157168	train-rmspe:0.196636	val-rmspe:0.1721


...

[1084]	train-rmse:0.099635	val-rmse:0.147385	train-rmspe:0.173443	val-rmspe:0.160648
[1085]	train-rmse:0.099622	val-rmse:0.147376	train-rmspe:0.173426	val-rmspe:0.160634
[1086]	train-rmse:0.09961	val-rmse:0.147361	train-rmspe:0.173424	val-rmspe:0.160619
[1087]	train-rmse:0.099582	val-rmse:0.147256	train-rmspe:0.173313	val-rmspe:0.160686
[1088]	train-rmse:0.09957	val-rmse:0.147246	train-rmspe:0.173295	val-rmspe:0.160683
[1089]	train-rmse:0.09956	val-rmse:0.147239	train-rmspe:0.173493	val-rmspe:0.160671
[1090]	train-rmse:0.099546	val-rmse:0.147247	train-rmspe:0.173482	val-rmspe:0.160699
[1091]	train-rmse:0.099538	val-rmse:0.147231	train-rmspe:0.173482	val-rmspe:0.160704
[1092]	train-rmse:0.099521	val-rmse:0.147214	train-rmspe:0.173476	val-rmspe:0.16069
[1093]	train-rmse:0.099509	val-rmse:0.147212	train-rmspe:0.173468	val-rmspe:0.160672
[1094]	train-rmse:0.099498	val-rmse:0.147238	train-rmspe:0.173449	val-rmspe:0.160699
[1095]	train-rmse:0.099493	val-rmse:0.147248	train-rmspe:0.173425	val

[1181]	train-rmse:0.098273	val-rmse:0.146899	train-rmspe:0.172671	val-rmspe:0.160591
[1182]	train-rmse:0.098267	val-rmse:0.14687	train-rmspe:0.172677	val-rmspe:0.160561
[1183]	train-rmse:0.098239	val-rmse:0.146892	train-rmspe:0.172671	val-rmspe:0.160574
[1184]	train-rmse:0.098226	val-rmse:0.14688	train-rmspe:0.172666	val-rmspe:0.160568
[1185]	train-rmse:0.098218	val-rmse:0.146883	train-rmspe:0.172659	val-rmspe:0.160564
[1186]	train-rmse:0.098194	val-rmse:0.14681	train-rmspe:0.17264	val-rmspe:0.160521
[1187]	train-rmse:0.098178	val-rmse:0.146803	train-rmspe:0.172617	val-rmspe:0.160523
[1188]	train-rmse:0.098172	val-rmse:0.146804	train-rmspe:0.172599	val-rmspe:0.16052
[1189]	train-rmse:0.098165	val-rmse:0.146798	train-rmspe:0.172658	val-rmspe:0.16051
[1190]	train-rmse:0.098119	val-rmse:0.146749	train-rmspe:0.172743	val-rmspe:0.160483
[1191]	train-rmse:0.098107	val-rmse:0.14674	train-rmspe:0.172733	val-rmspe:0.160469
[1192]	train-rmse:0.098089	val-rmse:0.146736	train-rmspe:0.172736	val-rm

[1279]	train-rmse:0.09694	val-rmse:0.146596	train-rmspe:0.170897	val-rmspe:0.160084
[1280]	train-rmse:0.096933	val-rmse:0.146601	train-rmspe:0.170896	val-rmspe:0.160086
[1281]	train-rmse:0.096925	val-rmse:0.146597	train-rmspe:0.170894	val-rmspe:0.16007
[1282]	train-rmse:0.096916	val-rmse:0.146583	train-rmspe:0.170908	val-rmspe:0.160058
[1283]	train-rmse:0.096876	val-rmse:0.146533	train-rmspe:0.17091	val-rmspe:0.160008
[1284]	train-rmse:0.096869	val-rmse:0.14653	train-rmspe:0.170907	val-rmspe:0.160009
[1285]	train-rmse:0.096861	val-rmse:0.14653	train-rmspe:0.170898	val-rmspe:0.160004
[1286]	train-rmse:0.096843	val-rmse:0.146523	train-rmspe:0.170618	val-rmspe:0.16001
[1287]	train-rmse:0.096832	val-rmse:0.146517	train-rmspe:0.170631	val-rmspe:0.160012
[1288]	train-rmse:0.096819	val-rmse:0.146498	train-rmspe:0.170627	val-rmspe:0.160006
[1289]	train-rmse:0.096809	val-rmse:0.146516	train-rmspe:0.170611	val-rmspe:0.159994
[1290]	train-rmse:0.096801	val-rmse:0.146508	train-rmspe:0.170596	val-r

[1376]	train-rmse:0.095917	val-rmse:0.146231	train-rmspe:0.171188	val-rmspe:0.15987
[1377]	train-rmse:0.095908	val-rmse:0.146242	train-rmspe:0.171171	val-rmspe:0.159844
[1378]	train-rmse:0.095898	val-rmse:0.146258	train-rmspe:0.171041	val-rmspe:0.159853
[1379]	train-rmse:0.095892	val-rmse:0.14624	train-rmspe:0.17103	val-rmspe:0.159852
[1380]	train-rmse:0.09588	val-rmse:0.146243	train-rmspe:0.170865	val-rmspe:0.159858
[1381]	train-rmse:0.095873	val-rmse:0.146239	train-rmspe:0.170858	val-rmspe:0.159871
[1382]	train-rmse:0.095868	val-rmse:0.146233	train-rmspe:0.170861	val-rmspe:0.159872
[1383]	train-rmse:0.095861	val-rmse:0.146225	train-rmspe:0.170876	val-rmspe:0.159857
[1384]	train-rmse:0.095843	val-rmse:0.146228	train-rmspe:0.170857	val-rmspe:0.159856
[1385]	train-rmse:0.095835	val-rmse:0.146233	train-rmspe:0.170838	val-rmspe:0.159849
[1386]	train-rmse:0.095824	val-rmse:0.146224	train-rmspe:0.170691	val-rmspe:0.159849
[1387]	train-rmse:0.09582	val-rmse:0.146222	train-rmspe:0.170634	val-

[1473]	train-rmse:0.094946	val-rmse:0.146332	train-rmspe:0.165367	val-rmspe:0.160027
[1474]	train-rmse:0.094937	val-rmse:0.146336	train-rmspe:0.165367	val-rmspe:0.160025
[1475]	train-rmse:0.094928	val-rmse:0.146335	train-rmspe:0.165353	val-rmspe:0.160031
[1476]	train-rmse:0.094923	val-rmse:0.1463	train-rmspe:0.165355	val-rmspe:0.160015
[1477]	train-rmse:0.094914	val-rmse:0.146301	train-rmspe:0.165354	val-rmspe:0.160025
[1478]	train-rmse:0.094903	val-rmse:0.146292	train-rmspe:0.165417	val-rmspe:0.160018
[1479]	train-rmse:0.094898	val-rmse:0.146293	train-rmspe:0.165369	val-rmspe:0.160017
[1480]	train-rmse:0.094892	val-rmse:0.146293	train-rmspe:0.165358	val-rmspe:0.160016
[1481]	train-rmse:0.094885	val-rmse:0.146293	train-rmspe:0.165365	val-rmspe:0.160005
[1482]	train-rmse:0.094878	val-rmse:0.14627	train-rmspe:0.164485	val-rmspe:0.159998
[1483]	train-rmse:0.094872	val-rmse:0.146283	train-rmspe:0.164474	val-rmspe:0.159995
[1484]	train-rmse:0.094863	val-rmse:0.146279	train-rmspe:0.164477	va

In [11]:
#设定参数
param = {'max_depth': 5, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear', 'min_child_weight': 6, 'colsample_bytree': 0.8, 'subsample':0.7}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)



[0]	train-rmse:5.7896	val-rmse:5.82858	train-rmspe:0.996618	val-rmspe:0.99677
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:4.06087	val-rmse:4.10016	train-rmspe:0.981103	val-rmspe:0.981947
[2]	train-rmse:2.85388	val-rmse:2.89549	train-rmspe:0.937128	val-rmspe:0.939976
[3]	train-rmse:2.01292	val-rmse:2.0535	train-rmspe:0.85488	val-rmspe:0.861121
[4]	train-rmse:1.43059	val-rmse:1.47095	train-rmspe:0.741775	val-rmspe:0.752172
[5]	train-rmse:1.03103	val-rmse:1.07096	train-rmspe:0.618918	val-rmspe:0.632716
[6]	train-rmse:0.761245	val-rmse:0.798486	train-rmspe:0.509611	val-rmspe:0.523461
[7]	train-rmse:0.584805	val-rmse:0.61977	train-rmspe:0.429794	val-rmspe:0.44009
[8]	train-rmse:0.472267	val-rmse:0.502549	train-rmspe:0.383754	val-rmspe:0.384655
[9]	train-rmse:0.405142	val-rmse:0.429793	train-rmspe:0.363366	val-rmspe:0.353761
[10]	train-rmse:0.366341	val-rmse:0.386118	train-rmspe

[98]	train-rmse:0.189987	val-rmse:0.203715	train-rmspe:0.260737	val-rmspe:0.229808
[99]	train-rmse:0.189835	val-rmse:0.203611	train-rmspe:0.261401	val-rmspe:0.229737
[100]	train-rmse:0.189361	val-rmse:0.203221	train-rmspe:0.261189	val-rmspe:0.229432
[101]	train-rmse:0.189197	val-rmse:0.203068	train-rmspe:0.261122	val-rmspe:0.229343
[102]	train-rmse:0.18849	val-rmse:0.202503	train-rmspe:0.260562	val-rmspe:0.228766
[103]	train-rmse:0.188034	val-rmse:0.202079	train-rmspe:0.260133	val-rmspe:0.228348
[104]	train-rmse:0.186337	val-rmse:0.200578	train-rmspe:0.258419	val-rmspe:0.226617
[105]	train-rmse:0.185211	val-rmse:0.199645	train-rmspe:0.25721	val-rmspe:0.225561
[106]	train-rmse:0.184168	val-rmse:0.198717	train-rmspe:0.255634	val-rmspe:0.224491
[107]	train-rmse:0.182966	val-rmse:0.197793	train-rmspe:0.254164	val-rmspe:0.223682
[108]	train-rmse:0.181857	val-rmse:0.197364	train-rmspe:0.252897	val-rmspe:0.223245
[109]	train-rmse:0.181612	val-rmse:0.197135	train-rmspe:0.252716	val-rmspe:0.223

[197]	train-rmse:0.147361	val-rmse:0.170685	train-rmspe:0.222583	val-rmspe:0.194182
[198]	train-rmse:0.147084	val-rmse:0.170454	train-rmspe:0.222352	val-rmspe:0.193944
[199]	train-rmse:0.146895	val-rmse:0.170282	train-rmspe:0.222026	val-rmspe:0.193821
[200]	train-rmse:0.146793	val-rmse:0.170179	train-rmspe:0.221939	val-rmspe:0.193714
[201]	train-rmse:0.146441	val-rmse:0.169875	train-rmspe:0.221577	val-rmspe:0.193369
[202]	train-rmse:0.146134	val-rmse:0.169563	train-rmspe:0.221258	val-rmspe:0.193026
[203]	train-rmse:0.146084	val-rmse:0.169596	train-rmspe:0.221188	val-rmspe:0.193078
[204]	train-rmse:0.145772	val-rmse:0.169369	train-rmspe:0.220949	val-rmspe:0.192893
[205]	train-rmse:0.145504	val-rmse:0.169195	train-rmspe:0.220735	val-rmspe:0.19278
[206]	train-rmse:0.145228	val-rmse:0.169012	train-rmspe:0.220657	val-rmspe:0.192571
[207]	train-rmse:0.145103	val-rmse:0.168904	train-rmspe:0.220548	val-rmspe:0.192441
[208]	train-rmse:0.144912	val-rmse:0.168809	train-rmspe:0.220375	val-rmspe:0.

[295]	train-rmse:0.131228	val-rmse:0.160915	train-rmspe:0.211655	val-rmspe:0.183789
[296]	train-rmse:0.131169	val-rmse:0.160894	train-rmspe:0.211612	val-rmspe:0.183741
[297]	train-rmse:0.131132	val-rmse:0.160864	train-rmspe:0.211643	val-rmspe:0.183741
[298]	train-rmse:0.131084	val-rmse:0.160867	train-rmspe:0.211723	val-rmspe:0.183883
[299]	train-rmse:0.13097	val-rmse:0.160788	train-rmspe:0.211645	val-rmspe:0.183827
[300]	train-rmse:0.130881	val-rmse:0.160734	train-rmspe:0.211575	val-rmspe:0.183775
[301]	train-rmse:0.130524	val-rmse:0.160478	train-rmspe:0.209538	val-rmspe:0.183383
[302]	train-rmse:0.130401	val-rmse:0.160457	train-rmspe:0.209741	val-rmspe:0.183316
[303]	train-rmse:0.130364	val-rmse:0.160452	train-rmspe:0.209709	val-rmspe:0.183315
[304]	train-rmse:0.13026	val-rmse:0.160357	train-rmspe:0.209668	val-rmspe:0.183246
[305]	train-rmse:0.130064	val-rmse:0.160218	train-rmspe:0.209511	val-rmspe:0.183105
[306]	train-rmse:0.129969	val-rmse:0.160132	train-rmspe:0.20957	val-rmspe:0.18

[393]	train-rmse:0.122499	val-rmse:0.155851	train-rmspe:0.202395	val-rmspe:0.174016
[394]	train-rmse:0.122395	val-rmse:0.155838	train-rmspe:0.202263	val-rmspe:0.174007
[395]	train-rmse:0.122336	val-rmse:0.15575	train-rmspe:0.202228	val-rmspe:0.173781
[396]	train-rmse:0.122245	val-rmse:0.15565	train-rmspe:0.202162	val-rmspe:0.173693
[397]	train-rmse:0.122151	val-rmse:0.15563	train-rmspe:0.202224	val-rmspe:0.173702
[398]	train-rmse:0.122108	val-rmse:0.155625	train-rmspe:0.202158	val-rmspe:0.173707
[399]	train-rmse:0.121995	val-rmse:0.155527	train-rmspe:0.202124	val-rmspe:0.173633
[400]	train-rmse:0.121935	val-rmse:0.155491	train-rmspe:0.201953	val-rmspe:0.173535
[401]	train-rmse:0.121917	val-rmse:0.155464	train-rmspe:0.201929	val-rmspe:0.173503
[402]	train-rmse:0.12189	val-rmse:0.155457	train-rmspe:0.201911	val-rmspe:0.173495
[403]	train-rmse:0.121866	val-rmse:0.155464	train-rmspe:0.201591	val-rmspe:0.173526
[404]	train-rmse:0.12182	val-rmse:0.155503	train-rmspe:0.201546	val-rmspe:0.1735

...

[984]	train-rmse:0.102065	val-rmse:0.146633	train-rmspe:0.166885	val-rmspe:0.161779
[985]	train-rmse:0.102056	val-rmse:0.146647	train-rmspe:0.166868	val-rmspe:0.161777
[986]	train-rmse:0.10205	val-rmse:0.146661	train-rmspe:0.166874	val-rmspe:0.161777
[987]	train-rmse:0.10203	val-rmse:0.146675	train-rmspe:0.166873	val-rmspe:0.161798
[988]	train-rmse:0.102015	val-rmse:0.146665	train-rmspe:0.166817	val-rmspe:0.161795
[989]	train-rmse:0.101991	val-rmse:0.146652	train-rmspe:0.166357	val-rmspe:0.161778
[990]	train-rmse:0.10198	val-rmse:0.146666	train-rmspe:0.166356	val-rmspe:0.16179
[991]	train-rmse:0.101944	val-rmse:0.146664	train-rmspe:0.166327	val-rmspe:0.161765
[992]	train-rmse:0.101933	val-rmse:0.146664	train-rmspe:0.166345	val-rmspe:0.161755
[993]	train-rmse:0.101918	val-rmse:0.146677	train-rmspe:0.166317	val-rmspe:0.161756
[994]	train-rmse:0.101904	val-rmse:0.146687	train-rmspe:0.166293	val-rmspe:0.161757
[995]	train-rmse:0.101886	val-rmse:0.146662	train-rmspe:0.166283	val-rmspe:0.161

[1081]	train-rmse:0.100539	val-rmse:0.146098	train-rmspe:0.160688	val-rmspe:0.161033
[1082]	train-rmse:0.100532	val-rmse:0.146113	train-rmspe:0.160673	val-rmspe:0.161036
[1083]	train-rmse:0.100524	val-rmse:0.146112	train-rmspe:0.160676	val-rmspe:0.161042
[1084]	train-rmse:0.100496	val-rmse:0.14608	train-rmspe:0.160535	val-rmspe:0.161008
[1085]	train-rmse:0.100486	val-rmse:0.146089	train-rmspe:0.160513	val-rmspe:0.16101
[1086]	train-rmse:0.100476	val-rmse:0.146075	train-rmspe:0.160504	val-rmspe:0.160998
[1087]	train-rmse:0.100471	val-rmse:0.146083	train-rmspe:0.160518	val-rmspe:0.161
[1088]	train-rmse:0.100405	val-rmse:0.146034	train-rmspe:0.160466	val-rmspe:0.160952
[1089]	train-rmse:0.100396	val-rmse:0.146063	train-rmspe:0.160442	val-rmspe:0.16097
[1090]	train-rmse:0.100357	val-rmse:0.146022	train-rmspe:0.160429	val-rmspe:0.160942
[1091]	train-rmse:0.100346	val-rmse:0.146006	train-rmspe:0.160406	val-rmspe:0.160919
[1092]	train-rmse:0.100338	val-rmse:0.146007	train-rmspe:0.160423	val-r

[1178]	train-rmse:0.099122	val-rmse:0.145439	train-rmspe:0.15848	val-rmspe:0.160638
[1179]	train-rmse:0.099109	val-rmse:0.145438	train-rmspe:0.158474	val-rmspe:0.16063
[1180]	train-rmse:0.0991	val-rmse:0.145747	train-rmspe:0.158465	val-rmspe:0.160554
[1181]	train-rmse:0.099096	val-rmse:0.145767	train-rmspe:0.158472	val-rmspe:0.160563
[1182]	train-rmse:0.099061	val-rmse:0.145743	train-rmspe:0.158477	val-rmspe:0.16055
[1183]	train-rmse:0.09905	val-rmse:0.145766	train-rmspe:0.15848	val-rmspe:0.160531
[1184]	train-rmse:0.09904	val-rmse:0.145751	train-rmspe:0.158472	val-rmspe:0.160569
[1185]	train-rmse:0.09903	val-rmse:0.145756	train-rmspe:0.158458	val-rmspe:0.160584
[1186]	train-rmse:0.099019	val-rmse:0.145773	train-rmspe:0.158458	val-rmspe:0.160609
[1187]	train-rmse:0.09899	val-rmse:0.145751	train-rmspe:0.158429	val-rmspe:0.160577
[1188]	train-rmse:0.098982	val-rmse:0.145756	train-rmspe:0.158422	val-rmspe:0.160578
[1189]	train-rmse:0.098974	val-rmse:0.145755	train-rmspe:0.158408	val-rmspe

[1275]	train-rmse:0.097948	val-rmse:0.145481	train-rmspe:0.156947	val-rmspe:0.160107
[1276]	train-rmse:0.097943	val-rmse:0.145441	train-rmspe:0.156956	val-rmspe:0.160068
[1277]	train-rmse:0.097933	val-rmse:0.145454	train-rmspe:0.156911	val-rmspe:0.160059
[1278]	train-rmse:0.097917	val-rmse:0.145508	train-rmspe:0.156871	val-rmspe:0.160087
[1279]	train-rmse:0.097911	val-rmse:0.145519	train-rmspe:0.156867	val-rmspe:0.160096
[1280]	train-rmse:0.097902	val-rmse:0.145531	train-rmspe:0.156866	val-rmspe:0.160113
[1281]	train-rmse:0.097885	val-rmse:0.145522	train-rmspe:0.156856	val-rmspe:0.16011
[1282]	train-rmse:0.097865	val-rmse:0.145482	train-rmspe:0.156837	val-rmspe:0.160091
[1283]	train-rmse:0.097839	val-rmse:0.145477	train-rmspe:0.156832	val-rmspe:0.160088
[1284]	train-rmse:0.097833	val-rmse:0.145475	train-rmspe:0.156839	val-rmspe:0.160089
[1285]	train-rmse:0.097825	val-rmse:0.145493	train-rmspe:0.156872	val-rmspe:0.160147
[1286]	train-rmse:0.097808	val-rmse:0.145508	train-rmspe:0.156846	

[1372]	train-rmse:0.09679	val-rmse:0.145561	train-rmspe:0.155511	val-rmspe:0.160285
[1373]	train-rmse:0.096772	val-rmse:0.145544	train-rmspe:0.155433	val-rmspe:0.160287
[1374]	train-rmse:0.096765	val-rmse:0.145554	train-rmspe:0.155426	val-rmspe:0.160282
[1375]	train-rmse:0.096754	val-rmse:0.145561	train-rmspe:0.155365	val-rmspe:0.160279
[1376]	train-rmse:0.096746	val-rmse:0.145555	train-rmspe:0.155367	val-rmspe:0.160274
[1377]	train-rmse:0.09674	val-rmse:0.145553	train-rmspe:0.155356	val-rmspe:0.160265
[1378]	train-rmse:0.096727	val-rmse:0.145571	train-rmspe:0.155397	val-rmspe:0.160252
[1379]	train-rmse:0.096713	val-rmse:0.145548	train-rmspe:0.155384	val-rmspe:0.160226
[1380]	train-rmse:0.096709	val-rmse:0.145544	train-rmspe:0.155405	val-rmspe:0.16023
[1381]	train-rmse:0.096701	val-rmse:0.145542	train-rmspe:0.155402	val-rmspe:0.160231
[1382]	train-rmse:0.096685	val-rmse:0.145522	train-rmspe:0.155407	val-rmspe:0.160229
[1383]	train-rmse:0.096678	val-rmse:0.145526	train-rmspe:0.155402	va

In [12]:
#设定参数
param = {'max_depth': 5, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear', 'min_child_weight': 4, 'colsample_bytree': 0.8, 'subsample':0.7}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)



[0]	train-rmse:5.7896	val-rmse:5.82858	train-rmspe:0.996618	val-rmspe:0.99677
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:4.06087	val-rmse:4.10016	train-rmspe:0.981103	val-rmspe:0.981947
[2]	train-rmse:2.85388	val-rmse:2.89549	train-rmspe:0.937128	val-rmspe:0.939976
[3]	train-rmse:2.01292	val-rmse:2.0535	train-rmspe:0.85488	val-rmspe:0.861121
[4]	train-rmse:1.43059	val-rmse:1.47095	train-rmspe:0.741775	val-rmspe:0.752172
[5]	train-rmse:1.03103	val-rmse:1.07096	train-rmspe:0.618918	val-rmspe:0.632716
[6]	train-rmse:0.761245	val-rmse:0.798486	train-rmspe:0.509611	val-rmspe:0.523461
[7]	train-rmse:0.584805	val-rmse:0.619766	train-rmspe:0.429789	val-rmspe:0.440088
[8]	train-rmse:0.472267	val-rmse:0.502545	train-rmspe:0.383746	val-rmspe:0.384653
[9]	train-rmse:0.405145	val-rmse:0.429792	train-rmspe:0.363357	val-rmspe:0.353759
[10]	train-rmse:0.366341	val-rmse:0.386114	train-rms

[98]	train-rmse:0.186604	val-rmse:0.199698	train-rmspe:0.258031	val-rmspe:0.227944
[99]	train-rmse:0.185462	val-rmse:0.198726	train-rmspe:0.257095	val-rmspe:0.226783
[100]	train-rmse:0.184772	val-rmse:0.197977	train-rmspe:0.256508	val-rmspe:0.226156
[101]	train-rmse:0.183891	val-rmse:0.197323	train-rmspe:0.255762	val-rmspe:0.225598
[102]	train-rmse:0.182529	val-rmse:0.196157	train-rmspe:0.254515	val-rmspe:0.22459
[103]	train-rmse:0.181904	val-rmse:0.195623	train-rmspe:0.253773	val-rmspe:0.22398
[104]	train-rmse:0.181517	val-rmse:0.195574	train-rmspe:0.253823	val-rmspe:0.223893
[105]	train-rmse:0.180592	val-rmse:0.194617	train-rmspe:0.252845	val-rmspe:0.222829
[106]	train-rmse:0.18019	val-rmse:0.194231	train-rmspe:0.252602	val-rmspe:0.222581
[107]	train-rmse:0.179498	val-rmse:0.193589	train-rmspe:0.251882	val-rmspe:0.221909
[108]	train-rmse:0.179284	val-rmse:0.193508	train-rmspe:0.251512	val-rmspe:0.221837
[109]	train-rmse:0.178635	val-rmse:0.192934	train-rmspe:0.250957	val-rmspe:0.2212

[197]	train-rmse:0.145998	val-rmse:0.169697	train-rmspe:0.219961	val-rmspe:0.190208
[198]	train-rmse:0.145786	val-rmse:0.169509	train-rmspe:0.219745	val-rmspe:0.190043
[199]	train-rmse:0.145453	val-rmse:0.17018	train-rmspe:0.219559	val-rmspe:0.190834
[200]	train-rmse:0.145347	val-rmse:0.170119	train-rmspe:0.219457	val-rmspe:0.190749
[201]	train-rmse:0.145196	val-rmse:0.170047	train-rmspe:0.219308	val-rmspe:0.19064
[202]	train-rmse:0.144805	val-rmse:0.169712	train-rmspe:0.218786	val-rmspe:0.190358
[203]	train-rmse:0.144637	val-rmse:0.169551	train-rmspe:0.218714	val-rmspe:0.190231
[204]	train-rmse:0.144561	val-rmse:0.169458	train-rmspe:0.218645	val-rmspe:0.1902
[205]	train-rmse:0.144257	val-rmse:0.1692	train-rmspe:0.218445	val-rmspe:0.189933
[206]	train-rmse:0.143736	val-rmse:0.168852	train-rmspe:0.218028	val-rmspe:0.189476
[207]	train-rmse:0.143526	val-rmse:0.168674	train-rmspe:0.21745	val-rmspe:0.189263
[208]	train-rmse:0.143304	val-rmse:0.16846	train-rmspe:0.217258	val-rmspe:0.189029


[296]	train-rmse:0.132081	val-rmse:0.161935	train-rmspe:0.205512	val-rmspe:0.179397
[297]	train-rmse:0.131904	val-rmse:0.161757	train-rmspe:0.205409	val-rmspe:0.179287
[298]	train-rmse:0.131767	val-rmse:0.161554	train-rmspe:0.205359	val-rmspe:0.179042
[299]	train-rmse:0.131631	val-rmse:0.161466	train-rmspe:0.205261	val-rmspe:0.178959
[300]	train-rmse:0.131583	val-rmse:0.161443	train-rmspe:0.205218	val-rmspe:0.178934
[301]	train-rmse:0.131516	val-rmse:0.161409	train-rmspe:0.205146	val-rmspe:0.17889
[302]	train-rmse:0.131336	val-rmse:0.161298	train-rmspe:0.205	val-rmspe:0.178764
[303]	train-rmse:0.13129	val-rmse:0.161346	train-rmspe:0.204963	val-rmspe:0.178842
[304]	train-rmse:0.131216	val-rmse:0.161279	train-rmspe:0.204906	val-rmspe:0.178779
[305]	train-rmse:0.13115	val-rmse:0.161294	train-rmspe:0.204876	val-rmspe:0.178802
[306]	train-rmse:0.130902	val-rmse:0.161113	train-rmspe:0.204555	val-rmspe:0.178497
[307]	train-rmse:0.130833	val-rmse:0.161061	train-rmspe:0.204523	val-rmspe:0.17845

[395]	train-rmse:0.122567	val-rmse:0.15547	train-rmspe:0.19691	val-rmspe:0.169842
[396]	train-rmse:0.12249	val-rmse:0.15549	train-rmspe:0.197108	val-rmspe:0.170067
[397]	train-rmse:0.122431	val-rmse:0.155473	train-rmspe:0.197037	val-rmspe:0.170061
[398]	train-rmse:0.122424	val-rmse:0.155463	train-rmspe:0.197018	val-rmspe:0.170031
[399]	train-rmse:0.122334	val-rmse:0.155396	train-rmspe:0.196929	val-rmspe:0.169981
[400]	train-rmse:0.122297	val-rmse:0.155384	train-rmspe:0.196969	val-rmspe:0.169929
[401]	train-rmse:0.122275	val-rmse:0.155456	train-rmspe:0.196944	val-rmspe:0.169933
[402]	train-rmse:0.122226	val-rmse:0.155436	train-rmspe:0.196727	val-rmspe:0.169801
[403]	train-rmse:0.122189	val-rmse:0.155447	train-rmspe:0.196715	val-rmspe:0.169762
[404]	train-rmse:0.122131	val-rmse:0.155424	train-rmspe:0.196661	val-rmspe:0.169762
[405]	train-rmse:0.122103	val-rmse:0.155402	train-rmspe:0.196613	val-rmspe:0.169736
[406]	train-rmse:0.121988	val-rmse:0.155618	train-rmspe:0.196532	val-rmspe:0.169

[494]	train-rmse:0.116717	val-rmse:0.152493	train-rmspe:0.19159	val-rmspe:0.167157
[495]	train-rmse:0.116655	val-rmse:0.152448	train-rmspe:0.19152	val-rmspe:0.167124
[496]	train-rmse:0.116619	val-rmse:0.152427	train-rmspe:0.191507	val-rmspe:0.16706
[497]	train-rmse:0.116574	val-rmse:0.152393	train-rmspe:0.191475	val-rmspe:0.166994
[498]	train-rmse:0.116502	val-rmse:0.152373	train-rmspe:0.191435	val-rmspe:0.166944
[499]	train-rmse:0.116473	val-rmse:0.152218	train-rmspe:0.191428	val-rmspe:0.166685
[500]	train-rmse:0.11643	val-rmse:0.152209	train-rmspe:0.191387	val-rmspe:0.166684
[501]	train-rmse:0.116411	val-rmse:0.152199	train-rmspe:0.191383	val-rmspe:0.166688
[502]	train-rmse:0.116395	val-rmse:0.152235	train-rmspe:0.191373	val-rmspe:0.166762
[503]	train-rmse:0.116342	val-rmse:0.152199	train-rmspe:0.191141	val-rmspe:0.166756
[504]	train-rmse:0.116319	val-rmse:0.152177	train-rmspe:0.191154	val-rmspe:0.166753
[505]	train-rmse:0.116291	val-rmse:0.152189	train-rmspe:0.191119	val-rmspe:0.166

[593]	train-rmse:0.112438	val-rmse:0.149991	train-rmspe:0.187771	val-rmspe:0.163801
[594]	train-rmse:0.112413	val-rmse:0.150174	train-rmspe:0.187731	val-rmspe:0.164032
[595]	train-rmse:0.112356	val-rmse:0.150163	train-rmspe:0.18769	val-rmspe:0.164014
[596]	train-rmse:0.112337	val-rmse:0.150173	train-rmspe:0.18766	val-rmspe:0.164012
[597]	train-rmse:0.11229	val-rmse:0.150129	train-rmspe:0.187616	val-rmspe:0.164002
[598]	train-rmse:0.112252	val-rmse:0.150196	train-rmspe:0.187582	val-rmspe:0.164098
[599]	train-rmse:0.112188	val-rmse:0.150148	train-rmspe:0.187554	val-rmspe:0.164031
[600]	train-rmse:0.112163	val-rmse:0.150124	train-rmspe:0.187487	val-rmspe:0.164021
[601]	train-rmse:0.112144	val-rmse:0.1501	train-rmspe:0.187517	val-rmspe:0.164019
[602]	train-rmse:0.112109	val-rmse:0.15012	train-rmspe:0.187545	val-rmspe:0.163992
[603]	train-rmse:0.112095	val-rmse:0.15011	train-rmspe:0.187543	val-rmspe:0.163961
[604]	train-rmse:0.11206	val-rmse:0.150087	train-rmspe:0.18753	val-rmspe:0.16393
[6

[692]	train-rmse:0.108862	val-rmse:0.149328	train-rmspe:0.184854	val-rmspe:0.163362
[693]	train-rmse:0.108832	val-rmse:0.149303	train-rmspe:0.184831	val-rmspe:0.163258
[694]	train-rmse:0.108822	val-rmse:0.149306	train-rmspe:0.184835	val-rmspe:0.163254
[695]	train-rmse:0.108806	val-rmse:0.149306	train-rmspe:0.184837	val-rmspe:0.163259
[696]	train-rmse:0.108794	val-rmse:0.149	train-rmspe:0.184836	val-rmspe:0.163211
[697]	train-rmse:0.108778	val-rmse:0.149055	train-rmspe:0.184822	val-rmspe:0.163214
[698]	train-rmse:0.108759	val-rmse:0.149057	train-rmspe:0.184777	val-rmspe:0.163225
[699]	train-rmse:0.10867	val-rmse:0.149007	train-rmspe:0.184665	val-rmspe:0.163171
[700]	train-rmse:0.108629	val-rmse:0.148983	train-rmspe:0.18471	val-rmspe:0.163126
[701]	train-rmse:0.108599	val-rmse:0.148997	train-rmspe:0.184616	val-rmspe:0.163224
[702]	train-rmse:0.108585	val-rmse:0.149004	train-rmspe:0.1846	val-rmspe:0.163186
[703]	train-rmse:0.108567	val-rmse:0.148984	train-rmspe:0.18459	val-rmspe:0.163177


In [13]:
#设定参数
param = {'max_depth': 6, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear', 'min_child_weight': 5, 'colsample_bytree': 0.8, 'subsample':0.7}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)



[0]	train-rmse:5.78943	val-rmse:5.82649	train-rmspe:0.996622	val-rmspe:0.996768
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:4.06056	val-rmse:4.09801	train-rmspe:0.981135	val-rmspe:0.981939
[2]	train-rmse:2.85327	val-rmse:2.89223	train-rmspe:0.937239	val-rmspe:0.939931
[3]	train-rmse:2.01196	val-rmse:2.04924	train-rmspe:0.855181	val-rmspe:0.86091
[4]	train-rmse:1.42874	val-rmse:1.46511	train-rmspe:0.742218	val-rmspe:0.751562
[5]	train-rmse:1.02782	val-rmse:1.06424	train-rmspe:0.619189	val-rmspe:0.631559
[6]	train-rmse:0.756654	val-rmse:0.791473	train-rmspe:0.508847	val-rmspe:0.521356
[7]	train-rmse:0.578949	val-rmse:0.611494	train-rmspe:0.427234	val-rmspe:0.43637
[8]	train-rmse:0.464676	val-rmse:0.492982	train-rmspe:0.376223	val-rmspe:0.378304
[9]	train-rmse:0.391079	val-rmse:0.414784	train-rmspe:0.350894	val-rmspe:0.343694
[10]	train-rmse:0.349813	val-rmse:0.368546	train-r

[98]	train-rmse:0.155886	val-rmse:0.177306	train-rmspe:0.227589	val-rmspe:0.197381
[99]	train-rmse:0.155647	val-rmse:0.177047	train-rmspe:0.227481	val-rmspe:0.197155
[100]	train-rmse:0.155353	val-rmse:0.17675	train-rmspe:0.229258	val-rmspe:0.196863
[101]	train-rmse:0.154747	val-rmse:0.176307	train-rmspe:0.228625	val-rmspe:0.196369
[102]	train-rmse:0.154481	val-rmse:0.176055	train-rmspe:0.228435	val-rmspe:0.196137
[103]	train-rmse:0.154064	val-rmse:0.175872	train-rmspe:0.228091	val-rmspe:0.195963
[104]	train-rmse:0.152971	val-rmse:0.175089	train-rmspe:0.227253	val-rmspe:0.195189
[105]	train-rmse:0.152339	val-rmse:0.174629	train-rmspe:0.226727	val-rmspe:0.194666
[106]	train-rmse:0.151428	val-rmse:0.173968	train-rmspe:0.226589	val-rmspe:0.194099
[107]	train-rmse:0.150904	val-rmse:0.173574	train-rmspe:0.22607	val-rmspe:0.193564
[108]	train-rmse:0.15005	val-rmse:0.172907	train-rmspe:0.225941	val-rmspe:0.193004
[109]	train-rmse:0.149305	val-rmse:0.172374	train-rmspe:0.225247	val-rmspe:0.1925

[197]	train-rmse:0.126263	val-rmse:0.159253	train-rmspe:0.203303	val-rmspe:0.178379
[198]	train-rmse:0.126007	val-rmse:0.15923	train-rmspe:0.203183	val-rmspe:0.178342
[199]	train-rmse:0.125736	val-rmse:0.159073	train-rmspe:0.202985	val-rmspe:0.178202
[200]	train-rmse:0.125621	val-rmse:0.159019	train-rmspe:0.202739	val-rmspe:0.178175
[201]	train-rmse:0.1255	val-rmse:0.158975	train-rmspe:0.201993	val-rmspe:0.178094
[202]	train-rmse:0.125246	val-rmse:0.158763	train-rmspe:0.201471	val-rmspe:0.177571
[203]	train-rmse:0.125023	val-rmse:0.158717	train-rmspe:0.201166	val-rmspe:0.177468
[204]	train-rmse:0.124895	val-rmse:0.158677	train-rmspe:0.200978	val-rmspe:0.177363
[205]	train-rmse:0.124581	val-rmse:0.158433	train-rmspe:0.200767	val-rmspe:0.177169
[206]	train-rmse:0.124531	val-rmse:0.158316	train-rmspe:0.200847	val-rmspe:0.177009
[207]	train-rmse:0.124305	val-rmse:0.158207	train-rmspe:0.200386	val-rmspe:0.176891
[208]	train-rmse:0.123954	val-rmse:0.157977	train-rmspe:0.199929	val-rmspe:0.17

[296]	train-rmse:0.113859	val-rmse:0.152813	train-rmspe:0.188139	val-rmspe:0.167872
[297]	train-rmse:0.113725	val-rmse:0.152459	train-rmspe:0.188082	val-rmspe:0.167707
[298]	train-rmse:0.113695	val-rmse:0.152467	train-rmspe:0.188034	val-rmspe:0.167707
[299]	train-rmse:0.113655	val-rmse:0.152455	train-rmspe:0.188007	val-rmspe:0.167712
[300]	train-rmse:0.113557	val-rmse:0.152371	train-rmspe:0.187917	val-rmspe:0.167646
[301]	train-rmse:0.113332	val-rmse:0.152176	train-rmspe:0.186863	val-rmspe:0.167573
[302]	train-rmse:0.113211	val-rmse:0.152067	train-rmspe:0.186801	val-rmspe:0.167486
[303]	train-rmse:0.113109	val-rmse:0.152012	train-rmspe:0.186694	val-rmspe:0.167416
[304]	train-rmse:0.113069	val-rmse:0.152005	train-rmspe:0.186597	val-rmspe:0.167385
[305]	train-rmse:0.112989	val-rmse:0.151925	train-rmspe:0.186549	val-rmspe:0.167313
[306]	train-rmse:0.112939	val-rmse:0.151903	train-rmspe:0.186529	val-rmspe:0.167308
[307]	train-rmse:0.112803	val-rmse:0.15198	train-rmspe:0.186431	val-rmspe:0.

[394]	train-rmse:0.106057	val-rmse:0.149633	train-rmspe:0.177297	val-rmspe:0.163374
[395]	train-rmse:0.106015	val-rmse:0.149627	train-rmspe:0.177274	val-rmspe:0.163376
[396]	train-rmse:0.105924	val-rmse:0.14961	train-rmspe:0.177246	val-rmspe:0.163364
[397]	train-rmse:0.105873	val-rmse:0.149382	train-rmspe:0.177167	val-rmspe:0.163343
[398]	train-rmse:0.105842	val-rmse:0.149454	train-rmspe:0.177129	val-rmspe:0.163407
[399]	train-rmse:0.1058	val-rmse:0.149425	train-rmspe:0.176658	val-rmspe:0.1634
[400]	train-rmse:0.105769	val-rmse:0.149441	train-rmspe:0.17664	val-rmspe:0.163409
[401]	train-rmse:0.105736	val-rmse:0.149413	train-rmspe:0.176638	val-rmspe:0.163385
[402]	train-rmse:0.105679	val-rmse:0.149401	train-rmspe:0.176466	val-rmspe:0.16337
[403]	train-rmse:0.105621	val-rmse:0.149331	train-rmspe:0.176416	val-rmspe:0.163306
[404]	train-rmse:0.105603	val-rmse:0.149323	train-rmspe:0.176413	val-rmspe:0.163312
[405]	train-rmse:0.105517	val-rmse:0.149172	train-rmspe:0.176302	val-rmspe:0.163204

...

[984]	train-rmse:0.09027	val-rmse:0.144365	train-rmspe:0.12502	val-rmspe:0.157418
[985]	train-rmse:0.090261	val-rmse:0.144373	train-rmspe:0.125008	val-rmspe:0.157416
[986]	train-rmse:0.090245	val-rmse:0.144374	train-rmspe:0.124974	val-rmspe:0.157414
[987]	train-rmse:0.09023	val-rmse:0.144367	train-rmspe:0.124967	val-rmspe:0.157404
[988]	train-rmse:0.090213	val-rmse:0.144382	train-rmspe:0.124954	val-rmspe:0.15737
[989]	train-rmse:0.090195	val-rmse:0.14439	train-rmspe:0.12493	val-rmspe:0.15736
[990]	train-rmse:0.090184	val-rmse:0.144417	train-rmspe:0.124904	val-rmspe:0.1574
[991]	train-rmse:0.09017	val-rmse:0.144405	train-rmspe:0.124981	val-rmspe:0.157386
[992]	train-rmse:0.090161	val-rmse:0.144322	train-rmspe:0.124979	val-rmspe:0.157413
[993]	train-rmse:0.090145	val-rmse:0.144358	train-rmspe:0.12496	val-rmspe:0.157413
[994]	train-rmse:0.090136	val-rmse:0.144333	train-rmspe:0.125019	val-rmspe:0.157408
[995]	train-rmse:0.090121	val-rmse:0.144357	train-rmspe:0.125003	val-rmspe:0.157401
[99

[1082]	train-rmse:0.089044	val-rmse:0.144083	train-rmspe:0.120103	val-rmspe:0.157097
[1083]	train-rmse:0.089037	val-rmse:0.144086	train-rmspe:0.120098	val-rmspe:0.157112
[1084]	train-rmse:0.089034	val-rmse:0.144096	train-rmspe:0.120094	val-rmspe:0.15711
[1085]	train-rmse:0.089023	val-rmse:0.144076	train-rmspe:0.120084	val-rmspe:0.157091
[1086]	train-rmse:0.089015	val-rmse:0.144062	train-rmspe:0.12008	val-rmspe:0.157088
[1087]	train-rmse:0.089007	val-rmse:0.144035	train-rmspe:0.120102	val-rmspe:0.157086
[1088]	train-rmse:0.088991	val-rmse:0.144031	train-rmspe:0.120089	val-rmspe:0.15708
[1089]	train-rmse:0.088982	val-rmse:0.144023	train-rmspe:0.120035	val-rmspe:0.157084
[1090]	train-rmse:0.088973	val-rmse:0.144022	train-rmspe:0.12003	val-rmspe:0.157087
[1091]	train-rmse:0.088965	val-rmse:0.144009	train-rmspe:0.120021	val-rmspe:0.157085
[1092]	train-rmse:0.088959	val-rmse:0.144007	train-rmspe:0.12	val-rmspe:0.15708
[1093]	train-rmse:0.088948	val-rmse:0.144033	train-rmspe:0.119986	val-rmsp

[1179]	train-rmse:0.087952	val-rmse:0.14402	train-rmspe:0.113451	val-rmspe:0.156882
[1180]	train-rmse:0.087935	val-rmse:0.144027	train-rmspe:0.113471	val-rmspe:0.156907
[1181]	train-rmse:0.087928	val-rmse:0.144035	train-rmspe:0.113461	val-rmspe:0.156865
[1182]	train-rmse:0.087919	val-rmse:0.144067	train-rmspe:0.113456	val-rmspe:0.156883
[1183]	train-rmse:0.087907	val-rmse:0.144046	train-rmspe:0.113451	val-rmspe:0.156867
[1184]	train-rmse:0.087898	val-rmse:0.144043	train-rmspe:0.113433	val-rmspe:0.156864
[1185]	train-rmse:0.087887	val-rmse:0.144117	train-rmspe:0.11343	val-rmspe:0.156886
[1186]	train-rmse:0.087873	val-rmse:0.144101	train-rmspe:0.113425	val-rmspe:0.156882
[1187]	train-rmse:0.087858	val-rmse:0.144115	train-rmspe:0.113404	val-rmspe:0.156882
[1188]	train-rmse:0.08785	val-rmse:0.144115	train-rmspe:0.113393	val-rmspe:0.156876
[1189]	train-rmse:0.087844	val-rmse:0.144122	train-rmspe:0.113374	val-rmspe:0.156882
[1190]	train-rmse:0.087834	val-rmse:0.144129	train-rmspe:0.113372	va

[1276]	train-rmse:0.086961	val-rmse:0.143904	train-rmspe:0.112441	val-rmspe:0.156778
[1277]	train-rmse:0.086952	val-rmse:0.143921	train-rmspe:0.112421	val-rmspe:0.15679
[1278]	train-rmse:0.086941	val-rmse:0.143917	train-rmspe:0.112407	val-rmspe:0.156778
[1279]	train-rmse:0.086928	val-rmse:0.143943	train-rmspe:0.112357	val-rmspe:0.156789
[1280]	train-rmse:0.086918	val-rmse:0.143935	train-rmspe:0.112344	val-rmspe:0.156793
[1281]	train-rmse:0.08691	val-rmse:0.143905	train-rmspe:0.112312	val-rmspe:0.156778
[1282]	train-rmse:0.0869	val-rmse:0.143891	train-rmspe:0.112301	val-rmspe:0.156781
[1283]	train-rmse:0.086895	val-rmse:0.143891	train-rmspe:0.112297	val-rmspe:0.156784
[1284]	train-rmse:0.08689	val-rmse:0.143874	train-rmspe:0.112297	val-rmspe:0.156781
[1285]	train-rmse:0.08688	val-rmse:0.143889	train-rmspe:0.112283	val-rmspe:0.156814
[1286]	train-rmse:0.086868	val-rmse:0.143905	train-rmspe:0.112269	val-rmspe:0.156814
[1287]	train-rmse:0.086851	val-rmse:0.143897	train-rmspe:0.112252	val-r

[1373]	train-rmse:0.086043	val-rmse:0.143761	train-rmspe:0.111414	val-rmspe:0.157014
[1374]	train-rmse:0.08604	val-rmse:0.143761	train-rmspe:0.111407	val-rmspe:0.157009
[1375]	train-rmse:0.086028	val-rmse:0.14375	train-rmspe:0.111398	val-rmspe:0.157004
[1376]	train-rmse:0.086025	val-rmse:0.143743	train-rmspe:0.111396	val-rmspe:0.157006
[1377]	train-rmse:0.086016	val-rmse:0.14374	train-rmspe:0.111345	val-rmspe:0.156997
[1378]	train-rmse:0.085994	val-rmse:0.143767	train-rmspe:0.111296	val-rmspe:0.157002
[1379]	train-rmse:0.085986	val-rmse:0.143803	train-rmspe:0.111289	val-rmspe:0.156978
[1380]	train-rmse:0.085981	val-rmse:0.14377	train-rmspe:0.111286	val-rmspe:0.156975
[1381]	train-rmse:0.085967	val-rmse:0.143766	train-rmspe:0.111272	val-rmspe:0.156972
[1382]	train-rmse:0.085963	val-rmse:0.143756	train-rmspe:0.111291	val-rmspe:0.156971
[1383]	train-rmse:0.085957	val-rmse:0.143753	train-rmspe:0.111288	val-rmspe:0.156968
[1384]	train-rmse:0.085949	val-rmse:0.143761	train-rmspe:0.111295	val

In [14]:
#设定参数
param = {'max_depth': 4, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear', 'min_child_weight': 5, 'colsample_bytree': 0.8, 'subsample':0.7}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)



[0]	train-rmse:5.78974	val-rmse:5.82842	train-rmspe:0.996614	val-rmspe:0.996766
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:4.06128	val-rmse:4.10294	train-rmspe:0.981067	val-rmspe:0.981953
[2]	train-rmse:2.85477	val-rmse:2.89616	train-rmspe:0.936969	val-rmspe:0.939837
[3]	train-rmse:2.01466	val-rmse:2.05448	train-rmspe:0.85452	val-rmspe:0.860789
[4]	train-rmse:1.4328	val-rmse:1.47405	train-rmspe:0.741388	val-rmspe:0.752235
[5]	train-rmse:1.03411	val-rmse:1.07147	train-rmspe:0.618816	val-rmspe:0.632022
[6]	train-rmse:0.766024	val-rmse:0.803494	train-rmspe:0.510515	val-rmspe:0.524661
[7]	train-rmse:0.59069	val-rmse:0.624031	train-rmspe:0.433024	val-rmspe:0.442314
[8]	train-rmse:0.480727	val-rmse:0.508972	train-rmspe:0.389443	val-rmspe:0.389478
[9]	train-rmse:0.415095	val-rmse:0.437037	train-rmspe:0.373263	val-rmspe:0.362069
[10]	train-rmse:0.377942	val-rmse:0.394166	train-rm

[98]	train-rmse:0.232247	val-rmse:0.239249	train-rmspe:0.302842	val-rmspe:0.27083
[99]	train-rmse:0.231341	val-rmse:0.238309	train-rmspe:0.300995	val-rmspe:0.268992
[100]	train-rmse:0.230775	val-rmse:0.237879	train-rmspe:0.300543	val-rmspe:0.26865
[101]	train-rmse:0.230591	val-rmse:0.237696	train-rmspe:0.300262	val-rmspe:0.268831
[102]	train-rmse:0.229351	val-rmse:0.236639	train-rmspe:0.298966	val-rmspe:0.267671
[103]	train-rmse:0.228793	val-rmse:0.236057	train-rmspe:0.298376	val-rmspe:0.266997
[104]	train-rmse:0.22863	val-rmse:0.236081	train-rmspe:0.298146	val-rmspe:0.267002
[105]	train-rmse:0.227876	val-rmse:0.235466	train-rmspe:0.297707	val-rmspe:0.266548
[106]	train-rmse:0.227642	val-rmse:0.23544	train-rmspe:0.297866	val-rmspe:0.266604
[107]	train-rmse:0.226756	val-rmse:0.234666	train-rmspe:0.296855	val-rmspe:0.265706
[108]	train-rmse:0.224835	val-rmse:0.23298	train-rmspe:0.294536	val-rmspe:0.263356
[109]	train-rmse:0.223699	val-rmse:0.231874	train-rmspe:0.293737	val-rmspe:0.262488

[197]	train-rmse:0.180454	val-rmse:0.195422	train-rmspe:0.251064	val-rmspe:0.218022
[198]	train-rmse:0.180097	val-rmse:0.195106	train-rmspe:0.250803	val-rmspe:0.217723
[199]	train-rmse:0.179936	val-rmse:0.195008	train-rmspe:0.250621	val-rmspe:0.217598
[200]	train-rmse:0.179791	val-rmse:0.194851	train-rmspe:0.250492	val-rmspe:0.217437
[201]	train-rmse:0.179374	val-rmse:0.194489	train-rmspe:0.250095	val-rmspe:0.216975
[202]	train-rmse:0.179301	val-rmse:0.194451	train-rmspe:0.250082	val-rmspe:0.21701
[203]	train-rmse:0.179204	val-rmse:0.194437	train-rmspe:0.250032	val-rmspe:0.217015
[204]	train-rmse:0.178936	val-rmse:0.194215	train-rmspe:0.249925	val-rmspe:0.21676
[205]	train-rmse:0.178654	val-rmse:0.194004	train-rmspe:0.249523	val-rmspe:0.216457
[206]	train-rmse:0.178324	val-rmse:0.193723	train-rmspe:0.251767	val-rmspe:0.215721
[207]	train-rmse:0.178088	val-rmse:0.193689	train-rmspe:0.251525	val-rmspe:0.215794
[208]	train-rmse:0.177671	val-rmse:0.193289	train-rmspe:0.251481	val-rmspe:0.2

[296]	train-rmse:0.158062	val-rmse:0.178384	train-rmspe:0.232441	val-rmspe:0.198581
[297]	train-rmse:0.158007	val-rmse:0.178332	train-rmspe:0.232399	val-rmspe:0.198541
[298]	train-rmse:0.157943	val-rmse:0.178257	train-rmspe:0.232404	val-rmspe:0.198364
[299]	train-rmse:0.157875	val-rmse:0.178258	train-rmspe:0.232364	val-rmspe:0.198364
[300]	train-rmse:0.157701	val-rmse:0.178107	train-rmspe:0.232184	val-rmspe:0.198401
[301]	train-rmse:0.157569	val-rmse:0.17772	train-rmspe:0.232205	val-rmspe:0.197587
[302]	train-rmse:0.157352	val-rmse:0.177545	train-rmspe:0.232048	val-rmspe:0.197441
[303]	train-rmse:0.157292	val-rmse:0.177544	train-rmspe:0.231986	val-rmspe:0.197436
[304]	train-rmse:0.157155	val-rmse:0.177414	train-rmspe:0.231858	val-rmspe:0.197299
[305]	train-rmse:0.156931	val-rmse:0.177245	train-rmspe:0.231683	val-rmspe:0.197173
[306]	train-rmse:0.156825	val-rmse:0.177163	train-rmspe:0.231615	val-rmspe:0.197115
[307]	train-rmse:0.156765	val-rmse:0.177592	train-rmspe:0.231591	val-rmspe:0.

[395]	train-rmse:0.146699	val-rmse:0.17114	train-rmspe:0.223961	val-rmspe:0.190381
[396]	train-rmse:0.146628	val-rmse:0.1712	train-rmspe:0.223851	val-rmspe:0.190462
[397]	train-rmse:0.146567	val-rmse:0.171183	train-rmspe:0.223811	val-rmspe:0.190468
[398]	train-rmse:0.146493	val-rmse:0.171203	train-rmspe:0.223822	val-rmspe:0.190433
[399]	train-rmse:0.146456	val-rmse:0.171389	train-rmspe:0.223856	val-rmspe:0.19046
[400]	train-rmse:0.146372	val-rmse:0.171317	train-rmspe:0.223799	val-rmspe:0.190379
[401]	train-rmse:0.146336	val-rmse:0.171252	train-rmspe:0.223624	val-rmspe:0.190301
[402]	train-rmse:0.146188	val-rmse:0.171148	train-rmspe:0.223534	val-rmspe:0.190066
[403]	train-rmse:0.145995	val-rmse:0.170959	train-rmspe:0.223355	val-rmspe:0.189863
[404]	train-rmse:0.145875	val-rmse:0.170848	train-rmspe:0.22325	val-rmspe:0.18974
[405]	train-rmse:0.145781	val-rmse:0.170771	train-rmspe:0.223137	val-rmspe:0.189675
[406]	train-rmse:0.145582	val-rmse:0.170636	train-rmspe:0.222861	val-rmspe:0.18936

...

[2347]	train-rmse:0.103451	val-rmse:0.148861	train-rmspe:0.159221	val-rmspe:0.160971
[2348]	train-rmse:0.103446	val-rmse:0.14885	train-rmspe:0.159431	val-rmspe:0.16098
[2349]	train-rmse:0.103438	val-rmse:0.148853	train-rmspe:0.159386	val-rmspe:0.160984
[2350]	train-rmse:0.103436	val-rmse:0.148853	train-rmspe:0.159368	val-rmspe:0.160981
[2351]	train-rmse:0.10342	val-rmse:0.148827	train-rmspe:0.1594	val-rmspe:0.160971
[2352]	train-rmse:0.103399	val-rmse:0.148816	train-rmspe:0.159398	val-rmspe:0.160963
[2353]	train-rmse:0.103398	val-rmse:0.148825	train-rmspe:0.159381	val-rmspe:0.160975
[2354]	train-rmse:0.103397	val-rmse:0.148835	train-rmspe:0.159363	val-rmspe:0.160976
[2355]	train-rmse:0.103394	val-rmse:0.148837	train-rmspe:0.159361	val-rmspe:0.160976
[2356]	train-rmse:0.103392	val-rmse:0.148844	train-rmspe:0.159364	val-rmspe:0.160989
[2357]	train-rmse:0.103384	val-rmse:0.148824	train-rmspe:0.159389	val-rmspe:0.160981
[2358]	train-rmse:0.103382	val-rmse:0.148827	train-rmspe:0.159379	val-

[2444]	train-rmse:0.10288	val-rmse:0.148558	train-rmspe:0.158627	val-rmspe:0.160746
[2445]	train-rmse:0.102876	val-rmse:0.148568	train-rmspe:0.158629	val-rmspe:0.160761
[2446]	train-rmse:0.102872	val-rmse:0.148577	train-rmspe:0.15864	val-rmspe:0.160773
[2447]	train-rmse:0.102862	val-rmse:0.148559	train-rmspe:0.158634	val-rmspe:0.160766
[2448]	train-rmse:0.102855	val-rmse:0.148546	train-rmspe:0.158678	val-rmspe:0.160766
[2449]	train-rmse:0.10285	val-rmse:0.148563	train-rmspe:0.158742	val-rmspe:0.160772
[2450]	train-rmse:0.102843	val-rmse:0.148602	train-rmspe:0.158737	val-rmspe:0.160792
[2451]	train-rmse:0.102832	val-rmse:0.148582	train-rmspe:0.158726	val-rmspe:0.160792
[2452]	train-rmse:0.102828	val-rmse:0.148579	train-rmspe:0.158729	val-rmspe:0.160804
[2453]	train-rmse:0.102824	val-rmse:0.148575	train-rmspe:0.158656	val-rmspe:0.160779
[2454]	train-rmse:0.102821	val-rmse:0.148558	train-rmspe:0.158604	val-rmspe:0.16078
[2455]	train-rmse:0.102808	val-rmse:0.14858	train-rmspe:0.158599	val-

[2541]	train-rmse:0.102277	val-rmse:0.148262	train-rmspe:0.157935	val-rmspe:0.16042
[2542]	train-rmse:0.102274	val-rmse:0.148282	train-rmspe:0.157922	val-rmspe:0.160421
[2543]	train-rmse:0.10227	val-rmse:0.148278	train-rmspe:0.157918	val-rmspe:0.160403
[2544]	train-rmse:0.102269	val-rmse:0.14826	train-rmspe:0.157921	val-rmspe:0.160403
[2545]	train-rmse:0.102262	val-rmse:0.14828	train-rmspe:0.157896	val-rmspe:0.160406
[2546]	train-rmse:0.102257	val-rmse:0.148292	train-rmspe:0.157898	val-rmspe:0.160406
[2547]	train-rmse:0.102251	val-rmse:0.14829	train-rmspe:0.157893	val-rmspe:0.160403
[2548]	train-rmse:0.102244	val-rmse:0.14828	train-rmspe:0.157892	val-rmspe:0.160408
[2549]	train-rmse:0.102243	val-rmse:0.148266	train-rmspe:0.157892	val-rmspe:0.160398
[2550]	train-rmse:0.102241	val-rmse:0.148277	train-rmspe:0.157892	val-rmspe:0.160399
[2551]	train-rmse:0.102237	val-rmse:0.14828	train-rmspe:0.157886	val-rmspe:0.160397
[2552]	train-rmse:0.102233	val-rmse:0.148286	train-rmspe:0.15788	val-rms

[2638]	train-rmse:0.101806	val-rmse:0.147872	train-rmspe:0.157605	val-rmspe:0.160299
[2639]	train-rmse:0.101805	val-rmse:0.147875	train-rmspe:0.157597	val-rmspe:0.160306
[2640]	train-rmse:0.1018	val-rmse:0.147881	train-rmspe:0.15759	val-rmspe:0.160299
[2641]	train-rmse:0.101797	val-rmse:0.147899	train-rmspe:0.157569	val-rmspe:0.160314
[2642]	train-rmse:0.101794	val-rmse:0.14789	train-rmspe:0.157574	val-rmspe:0.160316
[2643]	train-rmse:0.101775	val-rmse:0.147888	train-rmspe:0.157475	val-rmspe:0.160308
[2644]	train-rmse:0.101773	val-rmse:0.147896	train-rmspe:0.157474	val-rmspe:0.160298
[2645]	train-rmse:0.101766	val-rmse:0.147895	train-rmspe:0.157474	val-rmspe:0.160307
[2646]	train-rmse:0.101764	val-rmse:0.14789	train-rmspe:0.157479	val-rmspe:0.160313
[2647]	train-rmse:0.101762	val-rmse:0.147891	train-rmspe:0.157453	val-rmspe:0.160315
[2648]	train-rmse:0.101757	val-rmse:0.147887	train-rmspe:0.157461	val-rmspe:0.160338
[2649]	train-rmse:0.101753	val-rmse:0.147937	train-rmspe:0.157426	val-

[2735]	train-rmse:0.101316	val-rmse:0.147892	train-rmspe:0.156455	val-rmspe:0.160469
[2736]	train-rmse:0.10131	val-rmse:0.147871	train-rmspe:0.156449	val-rmspe:0.160469
[2737]	train-rmse:0.101304	val-rmse:0.147858	train-rmspe:0.156441	val-rmspe:0.160464
[2738]	train-rmse:0.101293	val-rmse:0.147829	train-rmspe:0.15635	val-rmspe:0.160441
[2739]	train-rmse:0.101288	val-rmse:0.147845	train-rmspe:0.156352	val-rmspe:0.160433
[2740]	train-rmse:0.101284	val-rmse:0.147846	train-rmspe:0.15635	val-rmspe:0.160435
[2741]	train-rmse:0.101279	val-rmse:0.147834	train-rmspe:0.15634	val-rmspe:0.160433
[2742]	train-rmse:0.101276	val-rmse:0.147847	train-rmspe:0.156319	val-rmspe:0.160436
[2743]	train-rmse:0.101274	val-rmse:0.147848	train-rmspe:0.156309	val-rmspe:0.160431
[2744]	train-rmse:0.101268	val-rmse:0.14785	train-rmspe:0.156294	val-rmspe:0.160442
[2745]	train-rmse:0.101265	val-rmse:0.147832	train-rmspe:0.1563	val-rmspe:0.160431
[2746]	train-rmse:0.101261	val-rmse:0.147846	train-rmspe:0.156347	val-rm

In [17]:
#设定参数
param = {'max_depth': 5, 'eta': 0.1, 'silent': 0, 'objective': 'reg:linear', 'min_child_weight': 5, 'colsample_bytree': 0.8, 'subsample':0.7}

#设定迭代次数

num_round = 100000
#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval)
score(model, dval)



[0]	train-rmse:7.43684	val-rmse:7.47426	train-rmspe:0.999347	val-rmspe:0.999375
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:6.69507	val-rmse:6.73379	train-rmspe:0.998634	val-rmspe:0.998695
[2]	train-rmse:6.02769	val-rmse:6.067	train-rmspe:0.997345	val-rmspe:0.997464
[3]	train-rmse:5.42717	val-rmse:5.4666	train-rmspe:0.995172	val-rmspe:0.995388
[4]	train-rmse:4.88698	val-rmse:4.9275	train-rmspe:0.991729	val-rmspe:0.992103
[5]	train-rmse:4.40103	val-rmse:4.44186	train-rmspe:0.986574	val-rmspe:0.987182
[6]	train-rmse:3.96407	val-rmse:4.00509	train-rmspe:0.979241	val-rmspe:0.980178
[7]	train-rmse:3.57114	val-rmse:3.61223	train-rmspe:0.969271	val-rmspe:0.970661
[8]	train-rmse:3.21777	val-rmse:3.25853	train-rmspe:0.956295	val-rmspe:0.958248
[9]	train-rmse:2.90006	val-rmse:2.94179	train-rmspe:0.940008	val-rmspe:0.942726
[10]	train-rmse:2.61459	val-rmse:2.6562	train-rmspe:0.920275

[99]	train-rmse:0.275245	val-rmse:0.279139	train-rmspe:0.347118	val-rmspe:0.313517
[100]	train-rmse:0.275008	val-rmse:0.278934	train-rmspe:0.346854	val-rmspe:0.313262
[101]	train-rmse:0.27378	val-rmse:0.277822	train-rmspe:0.345912	val-rmspe:0.312117
[102]	train-rmse:0.272521	val-rmse:0.276678	train-rmspe:0.344667	val-rmspe:0.310925
[103]	train-rmse:0.27135	val-rmse:0.275499	train-rmspe:0.34352	val-rmspe:0.309692
[104]	train-rmse:0.271216	val-rmse:0.275474	train-rmspe:0.343316	val-rmspe:0.309448
[105]	train-rmse:0.270402	val-rmse:0.274763	train-rmspe:0.342612	val-rmspe:0.308761
[106]	train-rmse:0.269982	val-rmse:0.2744	train-rmspe:0.342504	val-rmspe:0.308513
[107]	train-rmse:0.269659	val-rmse:0.274128	train-rmspe:0.342086	val-rmspe:0.308226
[108]	train-rmse:0.268784	val-rmse:0.273339	train-rmspe:0.341313	val-rmspe:0.307454
[109]	train-rmse:0.267913	val-rmse:0.272571	train-rmspe:0.340189	val-rmspe:0.306772
[110]	train-rmse:0.267548	val-rmse:0.27205	train-rmspe:0.339746	val-rmspe:0.306512

[198]	train-rmse:0.222404	val-rmse:0.231713	train-rmspe:0.291169	val-rmspe:0.259591
[199]	train-rmse:0.222022	val-rmse:0.231418	train-rmspe:0.290694	val-rmspe:0.259253
[200]	train-rmse:0.221768	val-rmse:0.231217	train-rmspe:0.290436	val-rmspe:0.259064
[201]	train-rmse:0.221071	val-rmse:0.2306	train-rmspe:0.289906	val-rmspe:0.257967
[202]	train-rmse:0.220456	val-rmse:0.229994	train-rmspe:0.289445	val-rmspe:0.257355
[203]	train-rmse:0.22037	val-rmse:0.229955	train-rmspe:0.289402	val-rmspe:0.257226
[204]	train-rmse:0.220243	val-rmse:0.229803	train-rmspe:0.289289	val-rmspe:0.257171
[205]	train-rmse:0.219879	val-rmse:0.229458	train-rmspe:0.288988	val-rmspe:0.256912
[206]	train-rmse:0.219461	val-rmse:0.229053	train-rmspe:0.288485	val-rmspe:0.256478
[207]	train-rmse:0.218681	val-rmse:0.228349	train-rmspe:0.28771	val-rmspe:0.255731
[208]	train-rmse:0.217862	val-rmse:0.227723	train-rmspe:0.28761	val-rmspe:0.255113
[209]	train-rmse:0.216909	val-rmse:0.226845	train-rmspe:0.286449	val-rmspe:0.2539

[297]	train-rmse:0.188854	val-rmse:0.203175	train-rmspe:0.259937	val-rmspe:0.227068
[298]	train-rmse:0.188731	val-rmse:0.20312	train-rmspe:0.259813	val-rmspe:0.226919
[299]	train-rmse:0.188519	val-rmse:0.202919	train-rmspe:0.259519	val-rmspe:0.226421
[300]	train-rmse:0.188194	val-rmse:0.202641	train-rmspe:0.259244	val-rmspe:0.226142
[301]	train-rmse:0.188053	val-rmse:0.202539	train-rmspe:0.259219	val-rmspe:0.226022
[302]	train-rmse:0.187743	val-rmse:0.202235	train-rmspe:0.258674	val-rmspe:0.22557
[303]	train-rmse:0.187669	val-rmse:0.202155	train-rmspe:0.258612	val-rmspe:0.225511
[304]	train-rmse:0.18734	val-rmse:0.201898	train-rmspe:0.258226	val-rmspe:0.225184
[305]	train-rmse:0.187093	val-rmse:0.201696	train-rmspe:0.257973	val-rmspe:0.224957
[306]	train-rmse:0.1867	val-rmse:0.201361	train-rmspe:0.2576	val-rmspe:0.224599
[307]	train-rmse:0.186554	val-rmse:0.201214	train-rmspe:0.257508	val-rmspe:0.224462
[308]	train-rmse:0.186284	val-rmse:0.200966	train-rmspe:0.257265	val-rmspe:0.224181

[396]	train-rmse:0.168082	val-rmse:0.18672	train-rmspe:0.240012	val-rmspe:0.208086
[397]	train-rmse:0.168042	val-rmse:0.186687	train-rmspe:0.239982	val-rmspe:0.208056
[398]	train-rmse:0.167864	val-rmse:0.186568	train-rmspe:0.239773	val-rmspe:0.207909
[399]	train-rmse:0.167768	val-rmse:0.186522	train-rmspe:0.239689	val-rmspe:0.207874
[400]	train-rmse:0.167741	val-rmse:0.186475	train-rmspe:0.239552	val-rmspe:0.207808
[401]	train-rmse:0.167612	val-rmse:0.186399	train-rmspe:0.239406	val-rmspe:0.207683
[402]	train-rmse:0.167419	val-rmse:0.186239	train-rmspe:0.239155	val-rmspe:0.207535
[403]	train-rmse:0.16732	val-rmse:0.186132	train-rmspe:0.23904	val-rmspe:0.207457
[404]	train-rmse:0.167175	val-rmse:0.185948	train-rmspe:0.238926	val-rmspe:0.207253
[405]	train-rmse:0.166778	val-rmse:0.185647	train-rmspe:0.23861	val-rmspe:0.206947
[406]	train-rmse:0.166689	val-rmse:0.18563	train-rmspe:0.238517	val-rmspe:0.206964
[407]	train-rmse:0.166615	val-rmse:0.185564	train-rmspe:0.238603	val-rmspe:0.2069

...

[2251]	train-rmse:0.105716	val-rmse:0.149633	train-rmspe:0.175686	val-rmspe:0.164516
[2252]	train-rmse:0.105711	val-rmse:0.149634	train-rmspe:0.175678	val-rmspe:0.164514
[2253]	train-rmse:0.105706	val-rmse:0.149636	train-rmspe:0.175695	val-rmspe:0.164508
[2254]	train-rmse:0.105698	val-rmse:0.149641	train-rmspe:0.175689	val-rmspe:0.164523
[2255]	train-rmse:0.10569	val-rmse:0.149664	train-rmspe:0.175679	val-rmspe:0.164545
[2256]	train-rmse:0.105685	val-rmse:0.149668	train-rmspe:0.175678	val-rmspe:0.164555
[2257]	train-rmse:0.10568	val-rmse:0.149664	train-rmspe:0.175674	val-rmspe:0.164547
[2258]	train-rmse:0.10567	val-rmse:0.149663	train-rmspe:0.175665	val-rmspe:0.164545
[2259]	train-rmse:0.105659	val-rmse:0.149654	train-rmspe:0.175654	val-rmspe:0.164541
[2260]	train-rmse:0.105657	val-rmse:0.149661	train-rmspe:0.175648	val-rmspe:0.164542
[2261]	train-rmse:0.105652	val-rmse:0.149665	train-rmspe:0.175619	val-rmspe:0.164544
[2262]	train-rmse:0.105647	val-rmse:0.149664	train-rmspe:0.175619	va

[2348]	train-rmse:0.104825	val-rmse:0.14914	train-rmspe:0.175208	val-rmspe:0.163946
[2349]	train-rmse:0.104822	val-rmse:0.149137	train-rmspe:0.175191	val-rmspe:0.163949
[2350]	train-rmse:0.104818	val-rmse:0.149138	train-rmspe:0.175177	val-rmspe:0.163947
[2351]	train-rmse:0.10481	val-rmse:0.149136	train-rmspe:0.175179	val-rmspe:0.16393
[2352]	train-rmse:0.104806	val-rmse:0.149144	train-rmspe:0.175189	val-rmspe:0.163938
[2353]	train-rmse:0.104801	val-rmse:0.149139	train-rmspe:0.175176	val-rmspe:0.163929
[2354]	train-rmse:0.104794	val-rmse:0.149142	train-rmspe:0.175167	val-rmspe:0.163927
[2355]	train-rmse:0.104787	val-rmse:0.149143	train-rmspe:0.175168	val-rmspe:0.163925
[2356]	train-rmse:0.10478	val-rmse:0.149146	train-rmspe:0.175178	val-rmspe:0.163938
[2357]	train-rmse:0.104773	val-rmse:0.149151	train-rmspe:0.175174	val-rmspe:0.163936
[2358]	train-rmse:0.104766	val-rmse:0.14915	train-rmspe:0.175167	val-rmspe:0.163936
[2359]	train-rmse:0.10475	val-rmse:0.149142	train-rmspe:0.175156	val-r

[2445]	train-rmse:0.104086	val-rmse:0.148971	train-rmspe:0.174084	val-rmspe:0.163794
[2446]	train-rmse:0.104079	val-rmse:0.148962	train-rmspe:0.174064	val-rmspe:0.163779
[2447]	train-rmse:0.104066	val-rmse:0.148951	train-rmspe:0.174023	val-rmspe:0.163774
[2448]	train-rmse:0.104053	val-rmse:0.148944	train-rmspe:0.173987	val-rmspe:0.163769
[2449]	train-rmse:0.104037	val-rmse:0.148935	train-rmspe:0.173971	val-rmspe:0.16376
[2450]	train-rmse:0.104031	val-rmse:0.148948	train-rmspe:0.173963	val-rmspe:0.16377
[2451]	train-rmse:0.104023	val-rmse:0.148967	train-rmspe:0.173959	val-rmspe:0.163784
[2452]	train-rmse:0.104017	val-rmse:0.148969	train-rmspe:0.173965	val-rmspe:0.163791
[2453]	train-rmse:0.10401	val-rmse:0.148963	train-rmspe:0.173958	val-rmspe:0.163785
[2454]	train-rmse:0.104006	val-rmse:0.148959	train-rmspe:0.173962	val-rmspe:0.163787
[2455]	train-rmse:0.104003	val-rmse:0.148953	train-rmspe:0.173951	val-rmspe:0.163782
[2456]	train-rmse:0.104	val-rmse:0.148949	train-rmspe:0.173954	val-r

[2542]	train-rmse:0.103297	val-rmse:0.148732	train-rmspe:0.174648	val-rmspe:0.163548
[2543]	train-rmse:0.103286	val-rmse:0.148732	train-rmspe:0.174592	val-rmspe:0.163547
[2544]	train-rmse:0.10328	val-rmse:0.148738	train-rmspe:0.174594	val-rmspe:0.163574
[2545]	train-rmse:0.103275	val-rmse:0.148736	train-rmspe:0.174601	val-rmspe:0.163569
[2546]	train-rmse:0.103271	val-rmse:0.148735	train-rmspe:0.174596	val-rmspe:0.163571
[2547]	train-rmse:0.103268	val-rmse:0.148737	train-rmspe:0.174592	val-rmspe:0.163572
[2548]	train-rmse:0.103258	val-rmse:0.148729	train-rmspe:0.174578	val-rmspe:0.163569
[2549]	train-rmse:0.103256	val-rmse:0.148721	train-rmspe:0.174562	val-rmspe:0.163566
[2550]	train-rmse:0.103251	val-rmse:0.148716	train-rmspe:0.174559	val-rmspe:0.16356
[2551]	train-rmse:0.103238	val-rmse:0.148715	train-rmspe:0.17455	val-rmspe:0.163554
[2552]	train-rmse:0.103229	val-rmse:0.148652	train-rmspe:0.174545	val-rmspe:0.16352
[2553]	train-rmse:0.103224	val-rmse:0.148646	train-rmspe:0.174549	val

[2639]	train-rmse:0.102604	val-rmse:0.148547	train-rmspe:0.173769	val-rmspe:0.163608
[2640]	train-rmse:0.102599	val-rmse:0.148542	train-rmspe:0.173744	val-rmspe:0.163602
[2641]	train-rmse:0.102594	val-rmse:0.14855	train-rmspe:0.173735	val-rmspe:0.16361
[2642]	train-rmse:0.10259	val-rmse:0.14855	train-rmspe:0.173736	val-rmspe:0.163616
[2643]	train-rmse:0.102581	val-rmse:0.148545	train-rmspe:0.173703	val-rmspe:0.163596
[2644]	train-rmse:0.102575	val-rmse:0.148572	train-rmspe:0.17369	val-rmspe:0.163614
[2645]	train-rmse:0.102565	val-rmse:0.148577	train-rmspe:0.173688	val-rmspe:0.163614
[2646]	train-rmse:0.102562	val-rmse:0.148572	train-rmspe:0.173683	val-rmspe:0.16361
[2647]	train-rmse:0.102559	val-rmse:0.148573	train-rmspe:0.173682	val-rmspe:0.163613
[2648]	train-rmse:0.102555	val-rmse:0.148575	train-rmspe:0.173682	val-rmspe:0.163619
[2649]	train-rmse:0.10254	val-rmse:0.148571	train-rmspe:0.173665	val-rmspe:0.163611
[2650]	train-rmse:0.102522	val-rmse:0.148562	train-rmspe:0.173653	val-rm

In [18]:
#定义训练函数
def train(param, dtrain, dval, num_round, feval_c, stopping):
    train_time = time.clock()

    model = xgb.train(
        param, dtrain, num_round, feval = feval_c, 
        evals = [(dtrain, 'train'), (dval, 'val')], early_stopping_rounds = stopping, 
        verbose_eval = True
    )

    train_time = time.clock() - train_time

    print('The training time of the model is: {:.0f}s'.format(train_time))
    
    return model

In [19]:
#设定参数
param = {'max_depth': 5, 'eta': 0.1, 'silent': 0, 'objective': 'reg:linear', 'min_child_weight': 5, 'colsample_bytree': 0.8, 'subsample':0.7}

#设定迭代次数

num_round = 100000
stopping = 10000

#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval, stopping)
score(model, dval)

[0]	train-rmse:7.43684	val-rmse:7.47426	train-rmspe:0.999347	val-rmspe:0.999375
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 10000 rounds.
[1]	train-rmse:6.69507	val-rmse:6.73379	train-rmspe:0.998634	val-rmspe:0.998695
[2]	train-rmse:6.02769	val-rmse:6.067	train-rmspe:0.997345	val-rmspe:0.997464
[3]	train-rmse:5.42717	val-rmse:5.4666	train-rmspe:0.995172	val-rmspe:0.995388
[4]	train-rmse:4.88698	val-rmse:4.9275	train-rmspe:0.991729	val-rmspe:0.992103
[5]	train-rmse:4.40103	val-rmse:4.44186	train-rmspe:0.986574	val-rmspe:0.987182
[6]	train-rmse:3.96407	val-rmse:4.00509	train-rmspe:0.979241	val-rmspe:0.980178
[7]	train-rmse:3.57114	val-rmse:3.61223	train-rmspe:0.969271	val-rmspe:0.970661
[8]	train-rmse:3.21777	val-rmse:3.25853	train-rmspe:0.956295	val-rmspe:0.958248
[9]	train-rmse:2.90006	val-rmse:2.94179	train-rmspe:0.940008	val-rmspe:0.942726
[10]	train-rmse:2.61459	val-rmse:2.6562	train-rmspe:0.9202

[99]	train-rmse:0.275245	val-rmse:0.279139	train-rmspe:0.347118	val-rmspe:0.313517
[100]	train-rmse:0.275008	val-rmse:0.278934	train-rmspe:0.346854	val-rmspe:0.313262
[101]	train-rmse:0.27378	val-rmse:0.277822	train-rmspe:0.345912	val-rmspe:0.312117
[102]	train-rmse:0.272521	val-rmse:0.276678	train-rmspe:0.344667	val-rmspe:0.310925
[103]	train-rmse:0.27135	val-rmse:0.275499	train-rmspe:0.34352	val-rmspe:0.309692
[104]	train-rmse:0.271216	val-rmse:0.275474	train-rmspe:0.343316	val-rmspe:0.309448
[105]	train-rmse:0.270402	val-rmse:0.274763	train-rmspe:0.342612	val-rmspe:0.308761
[106]	train-rmse:0.269982	val-rmse:0.2744	train-rmspe:0.342504	val-rmspe:0.308513
[107]	train-rmse:0.269659	val-rmse:0.274128	train-rmspe:0.342086	val-rmspe:0.308226
[108]	train-rmse:0.268784	val-rmse:0.273339	train-rmspe:0.341313	val-rmspe:0.307454
[109]	train-rmse:0.267913	val-rmse:0.272571	train-rmspe:0.340189	val-rmspe:0.306772
[110]	train-rmse:0.267548	val-rmse:0.27205	train-rmspe:0.339746	val-rmspe:0.306512

[198]	train-rmse:0.222404	val-rmse:0.231713	train-rmspe:0.291169	val-rmspe:0.259591
[199]	train-rmse:0.222022	val-rmse:0.231418	train-rmspe:0.290694	val-rmspe:0.259253
[200]	train-rmse:0.221768	val-rmse:0.231217	train-rmspe:0.290436	val-rmspe:0.259064
[201]	train-rmse:0.221071	val-rmse:0.2306	train-rmspe:0.289906	val-rmspe:0.257967
[202]	train-rmse:0.220456	val-rmse:0.229994	train-rmspe:0.289445	val-rmspe:0.257355
[203]	train-rmse:0.22037	val-rmse:0.229955	train-rmspe:0.289402	val-rmspe:0.257226
[204]	train-rmse:0.220243	val-rmse:0.229803	train-rmspe:0.289289	val-rmspe:0.257171
[205]	train-rmse:0.219879	val-rmse:0.229458	train-rmspe:0.288988	val-rmspe:0.256912
[206]	train-rmse:0.219461	val-rmse:0.229053	train-rmspe:0.288485	val-rmspe:0.256478
[207]	train-rmse:0.218681	val-rmse:0.228349	train-rmspe:0.28771	val-rmspe:0.255731
[208]	train-rmse:0.217862	val-rmse:0.227723	train-rmspe:0.28761	val-rmspe:0.255113
[209]	train-rmse:0.216909	val-rmse:0.226845	train-rmspe:0.286449	val-rmspe:0.2539

[297]	train-rmse:0.188854	val-rmse:0.203175	train-rmspe:0.259937	val-rmspe:0.227068
[298]	train-rmse:0.188731	val-rmse:0.20312	train-rmspe:0.259813	val-rmspe:0.226919
[299]	train-rmse:0.188519	val-rmse:0.202919	train-rmspe:0.259519	val-rmspe:0.226421
[300]	train-rmse:0.188194	val-rmse:0.202641	train-rmspe:0.259244	val-rmspe:0.226142
[301]	train-rmse:0.188053	val-rmse:0.202539	train-rmspe:0.259219	val-rmspe:0.226022
[302]	train-rmse:0.187743	val-rmse:0.202235	train-rmspe:0.258674	val-rmspe:0.22557
[303]	train-rmse:0.187669	val-rmse:0.202155	train-rmspe:0.258612	val-rmspe:0.225511
[304]	train-rmse:0.18734	val-rmse:0.201898	train-rmspe:0.258226	val-rmspe:0.225184
[305]	train-rmse:0.187093	val-rmse:0.201696	train-rmspe:0.257973	val-rmspe:0.224957
[306]	train-rmse:0.1867	val-rmse:0.201361	train-rmspe:0.2576	val-rmspe:0.224599
[307]	train-rmse:0.186554	val-rmse:0.201214	train-rmspe:0.257508	val-rmspe:0.224462
[308]	train-rmse:0.186284	val-rmse:0.200966	train-rmspe:0.257265	val-rmspe:0.224181

[396]	train-rmse:0.168082	val-rmse:0.18672	train-rmspe:0.240012	val-rmspe:0.208086
[397]	train-rmse:0.168042	val-rmse:0.186687	train-rmspe:0.239982	val-rmspe:0.208056
[398]	train-rmse:0.167864	val-rmse:0.186568	train-rmspe:0.239773	val-rmspe:0.207909
[399]	train-rmse:0.167768	val-rmse:0.186522	train-rmspe:0.239689	val-rmspe:0.207874
[400]	train-rmse:0.167741	val-rmse:0.186475	train-rmspe:0.239552	val-rmspe:0.207808
[401]	train-rmse:0.167612	val-rmse:0.186399	train-rmspe:0.239406	val-rmspe:0.207683
[402]	train-rmse:0.167419	val-rmse:0.186239	train-rmspe:0.239155	val-rmspe:0.207535
[403]	train-rmse:0.16732	val-rmse:0.186132	train-rmspe:0.23904	val-rmspe:0.207457
[404]	train-rmse:0.167175	val-rmse:0.185948	train-rmspe:0.238926	val-rmspe:0.207253
[405]	train-rmse:0.166778	val-rmse:0.185647	train-rmspe:0.23861	val-rmspe:0.206947
[406]	train-rmse:0.166689	val-rmse:0.18563	train-rmspe:0.238517	val-rmspe:0.206964
[407]	train-rmse:0.166615	val-rmse:0.185564	train-rmspe:0.238603	val-rmspe:0.2069

...

[17512]	train-rmse:0.079277	val-rmse:0.144795	train-rmspe:0.094229	val-rmspe:0.159801
[17513]	train-rmse:0.079276	val-rmse:0.144792	train-rmspe:0.094228	val-rmspe:0.159796
[17514]	train-rmse:0.079276	val-rmse:0.144791	train-rmspe:0.094229	val-rmspe:0.159797
[17515]	train-rmse:0.079275	val-rmse:0.144793	train-rmspe:0.094228	val-rmspe:0.159796
[17516]	train-rmse:0.079275	val-rmse:0.144791	train-rmspe:0.094229	val-rmspe:0.159798
[17517]	train-rmse:0.079275	val-rmse:0.144793	train-rmspe:0.094227	val-rmspe:0.159796
[17518]	train-rmse:0.079273	val-rmse:0.144794	train-rmspe:0.094226	val-rmspe:0.159799
[17519]	train-rmse:0.079272	val-rmse:0.144797	train-rmspe:0.094217	val-rmspe:0.159801
[17520]	train-rmse:0.079272	val-rmse:0.144797	train-rmspe:0.094216	val-rmspe:0.159803
[17521]	train-rmse:0.079272	val-rmse:0.144796	train-rmspe:0.094215	val-rmspe:0.159801
[17522]	train-rmse:0.079271	val-rmse:0.144803	train-rmspe:0.094214	val-rmspe:0.1598
[17523]	train-rmse:0.07927	val-rmse:0.144809	train-rmspe

[17608]	train-rmse:0.079224	val-rmse:0.144836	train-rmspe:0.094202	val-rmspe:0.15983
[17609]	train-rmse:0.079223	val-rmse:0.144823	train-rmspe:0.094202	val-rmspe:0.159827
[17610]	train-rmse:0.079219	val-rmse:0.144824	train-rmspe:0.0942	val-rmspe:0.159828
[17611]	train-rmse:0.079219	val-rmse:0.144822	train-rmspe:0.094201	val-rmspe:0.159828
[17612]	train-rmse:0.079218	val-rmse:0.144824	train-rmspe:0.094198	val-rmspe:0.159828
[17613]	train-rmse:0.079218	val-rmse:0.144823	train-rmspe:0.0942	val-rmspe:0.159825
[17614]	train-rmse:0.079218	val-rmse:0.144824	train-rmspe:0.094199	val-rmspe:0.159823
[17615]	train-rmse:0.079217	val-rmse:0.144826	train-rmspe:0.094199	val-rmspe:0.159825
[17616]	train-rmse:0.079217	val-rmse:0.144823	train-rmspe:0.0942	val-rmspe:0.159827
[17617]	train-rmse:0.079216	val-rmse:0.144828	train-rmspe:0.094197	val-rmspe:0.159831
[17618]	train-rmse:0.079216	val-rmse:0.144823	train-rmspe:0.094195	val-rmspe:0.159827
[17619]	train-rmse:0.079215	val-rmse:0.144822	train-rmspe:0.0

[17704]	train-rmse:0.079166	val-rmse:0.144865	train-rmspe:0.093598	val-rmspe:0.159856
[17705]	train-rmse:0.079166	val-rmse:0.144858	train-rmspe:0.093597	val-rmspe:0.159853
[17706]	train-rmse:0.079165	val-rmse:0.144859	train-rmspe:0.093595	val-rmspe:0.159853
[17707]	train-rmse:0.079164	val-rmse:0.144857	train-rmspe:0.093598	val-rmspe:0.159853
[17708]	train-rmse:0.079164	val-rmse:0.144854	train-rmspe:0.093598	val-rmspe:0.159851
[17709]	train-rmse:0.079164	val-rmse:0.14486	train-rmspe:0.093596	val-rmspe:0.159854
[17710]	train-rmse:0.079164	val-rmse:0.144859	train-rmspe:0.093595	val-rmspe:0.159853
[17711]	train-rmse:0.079163	val-rmse:0.144854	train-rmspe:0.093595	val-rmspe:0.159853
[17712]	train-rmse:0.079163	val-rmse:0.144852	train-rmspe:0.093596	val-rmspe:0.159854
[17713]	train-rmse:0.079163	val-rmse:0.144851	train-rmspe:0.093599	val-rmspe:0.159854
[17714]	train-rmse:0.079162	val-rmse:0.14484	train-rmspe:0.093605	val-rmspe:0.159849
[17715]	train-rmse:0.079161	val-rmse:0.14484	train-rmspe

[17800]	train-rmse:0.079119	val-rmse:0.144867	train-rmspe:0.093546	val-rmspe:0.159865
[17801]	train-rmse:0.079118	val-rmse:0.144854	train-rmspe:0.093545	val-rmspe:0.15987
[17802]	train-rmse:0.079117	val-rmse:0.144852	train-rmspe:0.093499	val-rmspe:0.159872
[17803]	train-rmse:0.079116	val-rmse:0.144855	train-rmspe:0.09344	val-rmspe:0.159872
[17804]	train-rmse:0.079115	val-rmse:0.144852	train-rmspe:0.093442	val-rmspe:0.159872
[17805]	train-rmse:0.079114	val-rmse:0.14486	train-rmspe:0.093441	val-rmspe:0.159872
[17806]	train-rmse:0.079114	val-rmse:0.144858	train-rmspe:0.093439	val-rmspe:0.159867
[17807]	train-rmse:0.079114	val-rmse:0.144859	train-rmspe:0.093438	val-rmspe:0.159866
[17808]	train-rmse:0.079113	val-rmse:0.144861	train-rmspe:0.093438	val-rmspe:0.159869
[17809]	train-rmse:0.079113	val-rmse:0.144862	train-rmspe:0.093436	val-rmspe:0.159866
[17810]	train-rmse:0.079113	val-rmse:0.14486	train-rmspe:0.093441	val-rmspe:0.159866
[17811]	train-rmse:0.079112	val-rmse:0.144855	train-rmspe:

[17896]	train-rmse:0.079075	val-rmse:0.144842	train-rmspe:0.09329	val-rmspe:0.159858
[17897]	train-rmse:0.079074	val-rmse:0.14485	train-rmspe:0.09329	val-rmspe:0.159855
[17898]	train-rmse:0.079074	val-rmse:0.144852	train-rmspe:0.09329	val-rmspe:0.159856
[17899]	train-rmse:0.079074	val-rmse:0.144856	train-rmspe:0.093294	val-rmspe:0.159866
[17900]	train-rmse:0.079073	val-rmse:0.144853	train-rmspe:0.093295	val-rmspe:0.159869
[17901]	train-rmse:0.079073	val-rmse:0.144853	train-rmspe:0.093292	val-rmspe:0.159869
[17902]	train-rmse:0.079072	val-rmse:0.144856	train-rmspe:0.093286	val-rmspe:0.159867
[17903]	train-rmse:0.079071	val-rmse:0.144856	train-rmspe:0.093287	val-rmspe:0.159869
[17904]	train-rmse:0.079071	val-rmse:0.144855	train-rmspe:0.093288	val-rmspe:0.159869
[17905]	train-rmse:0.079071	val-rmse:0.14486	train-rmspe:0.093286	val-rmspe:0.159876
[17906]	train-rmse:0.07907	val-rmse:0.144859	train-rmspe:0.093286	val-rmspe:0.159878
[17907]	train-rmse:0.079069	val-rmse:0.144861	train-rmspe:0.

In [20]:
#设定参数
param = {'max_depth': 8, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear', 'min_child_weight': 5, 'colsample_bytree': 0.8, 'subsample':0.7}

#设定迭代次数

num_round = 100000
stopping = 100

#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval, stopping)
score(model, dval)

[0]	train-rmse:5.78925	val-rmse:5.82623	train-rmspe:0.996629	val-rmspe:0.996772
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:4.05998	val-rmse:4.1	train-rmspe:0.981199	val-rmspe:0.98203
[2]	train-rmse:2.85193	val-rmse:2.89384	train-rmspe:0.937547	val-rmspe:0.940353
[3]	train-rmse:2.00966	val-rmse:2.04797	train-rmspe:0.855851	val-rmspe:0.861603
[4]	train-rmse:1.42511	val-rmse:1.46381	train-rmspe:0.743126	val-rmspe:0.752749
[5]	train-rmse:1.02238	val-rmse:1.06091	train-rmspe:0.619553	val-rmspe:0.632528
[6]	train-rmse:0.749575	val-rmse:0.782136	train-rmspe:0.50728	val-rmspe:0.518821
[7]	train-rmse:0.567248	val-rmse:0.597493	train-rmspe:0.42226	val-rmspe:0.430345
[8]	train-rmse:0.447964	val-rmse:0.475561	train-rmspe:0.36686	val-rmspe:0.368605
[9]	train-rmse:0.370551	val-rmse:0.395122	train-rmspe:0.335091	val-rmspe:0.329664
[10]	train-rmse:0.323323	val-rmse:0.344994	train-rmspe:0

[98]	train-rmse:0.118434	val-rmse:0.156732	train-rmspe:0.176969	val-rmspe:0.173393
[99]	train-rmse:0.118059	val-rmse:0.156468	train-rmspe:0.176354	val-rmspe:0.173095
[100]	train-rmse:0.117546	val-rmse:0.15629	train-rmspe:0.176006	val-rmspe:0.172959
[101]	train-rmse:0.117162	val-rmse:0.156014	train-rmspe:0.175781	val-rmspe:0.171456
[102]	train-rmse:0.116516	val-rmse:0.155568	train-rmspe:0.175297	val-rmspe:0.17102
[103]	train-rmse:0.116222	val-rmse:0.155404	train-rmspe:0.174553	val-rmspe:0.170939
[104]	train-rmse:0.116067	val-rmse:0.155474	train-rmspe:0.174463	val-rmspe:0.170961
[105]	train-rmse:0.115408	val-rmse:0.155163	train-rmspe:0.173637	val-rmspe:0.170605
[106]	train-rmse:0.115155	val-rmse:0.154899	train-rmspe:0.17292	val-rmspe:0.170398
[107]	train-rmse:0.115047	val-rmse:0.154869	train-rmspe:0.169245	val-rmspe:0.170354
[108]	train-rmse:0.114784	val-rmse:0.154709	train-rmspe:0.169061	val-rmspe:0.170197
[109]	train-rmse:0.114319	val-rmse:0.154439	train-rmspe:0.168568	val-rmspe:0.1699

[197]	train-rmse:0.099165	val-rmse:0.149722	train-rmspe:0.14556	val-rmspe:0.163325
[198]	train-rmse:0.099065	val-rmse:0.149757	train-rmspe:0.145478	val-rmspe:0.163351
[199]	train-rmse:0.0989	val-rmse:0.149704	train-rmspe:0.145368	val-rmspe:0.163346
[200]	train-rmse:0.098786	val-rmse:0.149637	train-rmspe:0.145232	val-rmspe:0.163287
[201]	train-rmse:0.098685	val-rmse:0.149569	train-rmspe:0.145128	val-rmspe:0.163238
[202]	train-rmse:0.098568	val-rmse:0.149519	train-rmspe:0.145049	val-rmspe:0.163203
[203]	train-rmse:0.098451	val-rmse:0.149516	train-rmspe:0.14481	val-rmspe:0.163046
[204]	train-rmse:0.09833	val-rmse:0.149463	train-rmspe:0.144718	val-rmspe:0.162952
[205]	train-rmse:0.0982	val-rmse:0.149359	train-rmspe:0.144631	val-rmspe:0.162847
[206]	train-rmse:0.098136	val-rmse:0.149368	train-rmspe:0.144563	val-rmspe:0.162869
[207]	train-rmse:0.09797	val-rmse:0.149306	train-rmspe:0.144455	val-rmspe:0.162799
[208]	train-rmse:0.097873	val-rmse:0.149275	train-rmspe:0.144378	val-rmspe:0.162758


[296]	train-rmse:0.090999	val-rmse:0.147509	train-rmspe:0.121097	val-rmspe:0.161384
[297]	train-rmse:0.090951	val-rmse:0.147509	train-rmspe:0.120997	val-rmspe:0.1614
[298]	train-rmse:0.090876	val-rmse:0.147536	train-rmspe:0.120933	val-rmspe:0.161434
[299]	train-rmse:0.090794	val-rmse:0.14751	train-rmspe:0.120869	val-rmspe:0.16143
[300]	train-rmse:0.090697	val-rmse:0.147427	train-rmspe:0.120799	val-rmspe:0.161357
[301]	train-rmse:0.090651	val-rmse:0.14741	train-rmspe:0.120752	val-rmspe:0.161327
[302]	train-rmse:0.090583	val-rmse:0.147397	train-rmspe:0.120697	val-rmspe:0.161338
[303]	train-rmse:0.09055	val-rmse:0.147385	train-rmspe:0.120872	val-rmspe:0.161321
[304]	train-rmse:0.09048	val-rmse:0.14734	train-rmspe:0.121028	val-rmspe:0.161229
[305]	train-rmse:0.090402	val-rmse:0.147313	train-rmspe:0.120968	val-rmspe:0.161201
[306]	train-rmse:0.090358	val-rmse:0.147312	train-rmspe:0.120933	val-rmspe:0.161181
[307]	train-rmse:0.090302	val-rmse:0.147317	train-rmspe:0.120956	val-rmspe:0.161165


[395]	train-rmse:0.085954	val-rmse:0.146304	train-rmspe:0.112604	val-rmspe:0.159974
[396]	train-rmse:0.085895	val-rmse:0.146231	train-rmspe:0.112529	val-rmspe:0.159901
[397]	train-rmse:0.085867	val-rmse:0.146235	train-rmspe:0.112508	val-rmspe:0.159904
[398]	train-rmse:0.085818	val-rmse:0.146244	train-rmspe:0.112337	val-rmspe:0.159924
[399]	train-rmse:0.085798	val-rmse:0.146228	train-rmspe:0.112316	val-rmspe:0.159917
[400]	train-rmse:0.085766	val-rmse:0.14622	train-rmspe:0.112298	val-rmspe:0.159917
[401]	train-rmse:0.085711	val-rmse:0.146167	train-rmspe:0.112039	val-rmspe:0.159895
[402]	train-rmse:0.085691	val-rmse:0.14616	train-rmspe:0.112003	val-rmspe:0.159883
[403]	train-rmse:0.085649	val-rmse:0.146168	train-rmspe:0.111957	val-rmspe:0.159871
[404]	train-rmse:0.085629	val-rmse:0.146164	train-rmspe:0.111952	val-rmspe:0.159872
[405]	train-rmse:0.08559	val-rmse:0.14618	train-rmspe:0.111912	val-rmspe:0.159876
[406]	train-rmse:0.085545	val-rmse:0.146162	train-rmspe:0.11187	val-rmspe:0.1598

[494]	train-rmse:0.082198	val-rmse:0.145839	train-rmspe:0.102297	val-rmspe:0.160078
[495]	train-rmse:0.082162	val-rmse:0.145825	train-rmspe:0.102267	val-rmspe:0.159996
[496]	train-rmse:0.082134	val-rmse:0.145836	train-rmspe:0.102258	val-rmspe:0.159995
[497]	train-rmse:0.082091	val-rmse:0.145837	train-rmspe:0.10222	val-rmspe:0.160009
[498]	train-rmse:0.082057	val-rmse:0.145845	train-rmspe:0.101844	val-rmspe:0.159998
[499]	train-rmse:0.082023	val-rmse:0.145875	train-rmspe:0.101825	val-rmspe:0.160012
[500]	train-rmse:0.081985	val-rmse:0.145902	train-rmspe:0.101781	val-rmspe:0.160037
[501]	train-rmse:0.081972	val-rmse:0.145899	train-rmspe:0.101778	val-rmspe:0.160034
[502]	train-rmse:0.081945	val-rmse:0.145969	train-rmspe:0.101749	val-rmspe:0.160065
[503]	train-rmse:0.081909	val-rmse:0.145979	train-rmspe:0.101711	val-rmspe:0.160046
[504]	train-rmse:0.081892	val-rmse:0.145973	train-rmspe:0.101694	val-rmspe:0.16005
[505]	train-rmse:0.081862	val-rmse:0.145957	train-rmspe:0.101673	val-rmspe:0.1

In [21]:
#设定参数
param = {'max_depth': 8, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear', 'min_child_weight': 5, 'colsample_bytree': 0.8, 'subsample':0.5}

#设定迭代次数

num_round = 100000
stopping = 100

#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval, stopping)
score(model, dval)

[0]	train-rmse:5.78928	val-rmse:5.8279	train-rmspe:0.996627	val-rmspe:0.996775
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:4.06026	val-rmse:4.09947	train-rmspe:0.981185	val-rmspe:0.982009
[2]	train-rmse:2.85219	val-rmse:2.89122	train-rmspe:0.937524	val-rmspe:0.94018
[3]	train-rmse:2.00996	val-rmse:2.0503	train-rmspe:0.855826	val-rmspe:0.861878
[4]	train-rmse:1.42567	val-rmse:1.46541	train-rmspe:0.743065	val-rmspe:0.75297
[5]	train-rmse:1.02199	val-rmse:1.05907	train-rmspe:0.619844	val-rmspe:0.631997
[6]	train-rmse:0.748497	val-rmse:0.783806	train-rmspe:0.507873	val-rmspe:0.520211
[7]	train-rmse:0.567146	val-rmse:0.599993	train-rmspe:0.423072	val-rmspe:0.43198
[8]	train-rmse:0.446178	val-rmse:0.476564	train-rmspe:0.367061	val-rmspe:0.369733
[9]	train-rmse:0.372527	val-rmse:0.397476	train-rmspe:0.337433	val-rmspe:0.330638
[10]	train-rmse:0.329383	val-rmse:0.349767	train-rmsp

[98]	train-rmse:0.119982	val-rmse:0.158324	train-rmspe:0.194751	val-rmspe:0.171025
[99]	train-rmse:0.119858	val-rmse:0.158168	train-rmspe:0.194717	val-rmspe:0.170826
[100]	train-rmse:0.119224	val-rmse:0.157732	train-rmspe:0.194186	val-rmspe:0.170408
[101]	train-rmse:0.118789	val-rmse:0.15748	train-rmspe:0.193844	val-rmspe:0.170173
[102]	train-rmse:0.118275	val-rmse:0.157088	train-rmspe:0.193449	val-rmspe:0.16973
[103]	train-rmse:0.118134	val-rmse:0.157123	train-rmspe:0.193314	val-rmspe:0.169559
[104]	train-rmse:0.117963	val-rmse:0.157104	train-rmspe:0.193207	val-rmspe:0.169661
[105]	train-rmse:0.117833	val-rmse:0.157038	train-rmspe:0.19302	val-rmspe:0.16956
[106]	train-rmse:0.117674	val-rmse:0.157013	train-rmspe:0.193029	val-rmspe:0.169507
[107]	train-rmse:0.117524	val-rmse:0.156947	train-rmspe:0.192929	val-rmspe:0.169424
[108]	train-rmse:0.117296	val-rmse:0.156853	train-rmspe:0.192746	val-rmspe:0.169264
[109]	train-rmse:0.116761	val-rmse:0.156435	train-rmspe:0.192399	val-rmspe:0.16889

[197]	train-rmse:0.100656	val-rmse:0.150355	train-rmspe:0.146152	val-rmspe:0.163599
[198]	train-rmse:0.100577	val-rmse:0.150432	train-rmspe:0.146131	val-rmspe:0.163679
[199]	train-rmse:0.100444	val-rmse:0.15036	train-rmspe:0.146031	val-rmspe:0.163584
[200]	train-rmse:0.100266	val-rmse:0.150262	train-rmspe:0.145799	val-rmspe:0.16348
[201]	train-rmse:0.100169	val-rmse:0.150199	train-rmspe:0.145744	val-rmspe:0.163414
[202]	train-rmse:0.100023	val-rmse:0.15015	train-rmspe:0.145588	val-rmspe:0.163388
[203]	train-rmse:0.099955	val-rmse:0.150118	train-rmspe:0.145489	val-rmspe:0.163362
[204]	train-rmse:0.099792	val-rmse:0.150027	train-rmspe:0.14538	val-rmspe:0.163281
[205]	train-rmse:0.099757	val-rmse:0.150057	train-rmspe:0.145367	val-rmspe:0.163335
[206]	train-rmse:0.099644	val-rmse:0.149965	train-rmspe:0.145301	val-rmspe:0.163228
[207]	train-rmse:0.099542	val-rmse:0.149943	train-rmspe:0.145231	val-rmspe:0.163209
[208]	train-rmse:0.099433	val-rmse:0.149889	train-rmspe:0.145134	val-rmspe:0.163

[295]	train-rmse:0.092743	val-rmse:0.148534	train-rmspe:0.127399	val-rmspe:0.161613
[296]	train-rmse:0.092692	val-rmse:0.148525	train-rmspe:0.127143	val-rmspe:0.161584
[297]	train-rmse:0.092629	val-rmse:0.148486	train-rmspe:0.127051	val-rmspe:0.161561
[298]	train-rmse:0.092581	val-rmse:0.148493	train-rmspe:0.126962	val-rmspe:0.161585
[299]	train-rmse:0.092495	val-rmse:0.148427	train-rmspe:0.126914	val-rmspe:0.161532
[300]	train-rmse:0.092391	val-rmse:0.148357	train-rmspe:0.126793	val-rmspe:0.161487
[301]	train-rmse:0.09231	val-rmse:0.148323	train-rmspe:0.126636	val-rmspe:0.161412
[302]	train-rmse:0.092252	val-rmse:0.148292	train-rmspe:0.126627	val-rmspe:0.161375
[303]	train-rmse:0.09217	val-rmse:0.148267	train-rmspe:0.126558	val-rmspe:0.161359
[304]	train-rmse:0.092116	val-rmse:0.148264	train-rmspe:0.126514	val-rmspe:0.161361
[305]	train-rmse:0.092017	val-rmse:0.148229	train-rmspe:0.126484	val-rmspe:0.161317
[306]	train-rmse:0.091935	val-rmse:0.148225	train-rmspe:0.126385	val-rmspe:0.1

[394]	train-rmse:0.087791	val-rmse:0.147917	train-rmspe:0.109495	val-rmspe:0.161108
[395]	train-rmse:0.087746	val-rmse:0.147963	train-rmspe:0.109453	val-rmspe:0.161144
[396]	train-rmse:0.08773	val-rmse:0.148011	train-rmspe:0.109404	val-rmspe:0.161196
[397]	train-rmse:0.087678	val-rmse:0.148027	train-rmspe:0.109347	val-rmspe:0.161201
[398]	train-rmse:0.087639	val-rmse:0.148024	train-rmspe:0.1093	val-rmspe:0.161208
[399]	train-rmse:0.087607	val-rmse:0.148	train-rmspe:0.109275	val-rmspe:0.161162
[400]	train-rmse:0.087575	val-rmse:0.147986	train-rmspe:0.109253	val-rmspe:0.161151
[401]	train-rmse:0.087534	val-rmse:0.147914	train-rmspe:0.109212	val-rmspe:0.161113
[402]	train-rmse:0.087469	val-rmse:0.147915	train-rmspe:0.109172	val-rmspe:0.161119
[403]	train-rmse:0.087413	val-rmse:0.14792	train-rmspe:0.105526	val-rmspe:0.161115
[404]	train-rmse:0.087362	val-rmse:0.147892	train-rmspe:0.105513	val-rmspe:0.161089
[405]	train-rmse:0.087342	val-rmse:0.147886	train-rmspe:0.105675	val-rmspe:0.161083

[493]	train-rmse:0.084313	val-rmse:0.148061	train-rmspe:0.101006	val-rmspe:0.160999
[494]	train-rmse:0.08429	val-rmse:0.148046	train-rmspe:0.100955	val-rmspe:0.161009
[495]	train-rmse:0.084235	val-rmse:0.148029	train-rmspe:0.100923	val-rmspe:0.161005
[496]	train-rmse:0.084206	val-rmse:0.148021	train-rmspe:0.1009	val-rmspe:0.16097
[497]	train-rmse:0.084182	val-rmse:0.148033	train-rmspe:0.100912	val-rmspe:0.160961
[498]	train-rmse:0.084125	val-rmse:0.148029	train-rmspe:0.100856	val-rmspe:0.160933
[499]	train-rmse:0.084109	val-rmse:0.148267	train-rmspe:0.100844	val-rmspe:0.160975
[500]	train-rmse:0.084077	val-rmse:0.148258	train-rmspe:0.100763	val-rmspe:0.160965
[501]	train-rmse:0.084047	val-rmse:0.148247	train-rmspe:0.10072	val-rmspe:0.160955
[502]	train-rmse:0.084021	val-rmse:0.148219	train-rmspe:0.100649	val-rmspe:0.160913
[503]	train-rmse:0.083977	val-rmse:0.148221	train-rmspe:0.100375	val-rmspe:0.160913
[504]	train-rmse:0.083952	val-rmse:0.148213	train-rmspe:0.100365	val-rmspe:0.1608

In [22]:
#设定参数
param = {'max_depth': 8, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear', 'min_child_weight': 5, 'colsample_bytree': 0.5, 'subsample':0.5}

#设定迭代次数

num_round = 100000
stopping = 100

#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval, stopping)
score(model, dval)

[0]	train-rmse:5.78957	val-rmse:5.83113	train-rmspe:0.996622	val-rmspe:0.996779
Multiple eval metrics have been passed: 'val-rmspe' will be used for early stopping.

Will train until val-rmspe hasn't improved in 100 rounds.
[1]	train-rmse:4.06064	val-rmse:4.10372	train-rmspe:0.981159	val-rmspe:0.98205
[2]	train-rmse:2.85316	val-rmse:2.89931	train-rmspe:0.937337	val-rmspe:0.940412
[3]	train-rmse:2.01073	val-rmse:2.0553	train-rmspe:0.855575	val-rmspe:0.86228
[4]	train-rmse:1.42619	val-rmse:1.47202	train-rmspe:0.742708	val-rmspe:0.754389
[5]	train-rmse:1.02364	val-rmse:1.06598	train-rmspe:0.618988	val-rmspe:0.633856
[6]	train-rmse:0.751115	val-rmse:0.78593	train-rmspe:0.506699	val-rmspe:0.520067
[7]	train-rmse:0.571515	val-rmse:0.602786	train-rmspe:0.421619	val-rmspe:0.432007
[8]	train-rmse:0.453393	val-rmse:0.481505	train-rmspe:0.366755	val-rmspe:0.371128
[9]	train-rmse:0.382217	val-rmse:0.406824	train-rmspe:0.340418	val-rmspe:0.336671
[10]	train-rmse:0.336462	val-rmse:0.355598	train-rms

[98]	train-rmse:0.128069	val-rmse:0.159531	train-rmspe:0.192451	val-rmspe:0.179342
[99]	train-rmse:0.127705	val-rmse:0.159276	train-rmspe:0.1922	val-rmspe:0.178721
[100]	train-rmse:0.127052	val-rmse:0.15886	train-rmspe:0.190771	val-rmspe:0.17824
[101]	train-rmse:0.126859	val-rmse:0.158315	train-rmspe:0.190699	val-rmspe:0.178231
[102]	train-rmse:0.126562	val-rmse:0.158053	train-rmspe:0.190448	val-rmspe:0.178033
[103]	train-rmse:0.125972	val-rmse:0.157648	train-rmspe:0.189941	val-rmspe:0.177598
[104]	train-rmse:0.125479	val-rmse:0.157295	train-rmspe:0.189566	val-rmspe:0.177259
[105]	train-rmse:0.12459	val-rmse:0.156755	train-rmspe:0.188571	val-rmspe:0.17677
[106]	train-rmse:0.124304	val-rmse:0.15674	train-rmspe:0.188304	val-rmspe:0.177242
[107]	train-rmse:0.123896	val-rmse:0.156548	train-rmspe:0.188303	val-rmspe:0.177041
[108]	train-rmse:0.123805	val-rmse:0.156561	train-rmspe:0.188151	val-rmspe:0.177071
[109]	train-rmse:0.123496	val-rmse:0.156291	train-rmspe:0.188028	val-rmspe:0.176826
[

[197]	train-rmse:0.107149	val-rmse:0.149523	train-rmspe:0.16741	val-rmspe:0.168791
[198]	train-rmse:0.107126	val-rmse:0.149483	train-rmspe:0.167086	val-rmspe:0.168732
[199]	train-rmse:0.107029	val-rmse:0.149528	train-rmspe:0.167552	val-rmspe:0.168766
[200]	train-rmse:0.106996	val-rmse:0.149509	train-rmspe:0.167518	val-rmspe:0.16877
[201]	train-rmse:0.106825	val-rmse:0.149584	train-rmspe:0.16735	val-rmspe:0.168653
[202]	train-rmse:0.106727	val-rmse:0.149561	train-rmspe:0.167292	val-rmspe:0.168644
[203]	train-rmse:0.106348	val-rmse:0.149308	train-rmspe:0.167338	val-rmspe:0.168049
[204]	train-rmse:0.106168	val-rmse:0.149175	train-rmspe:0.167263	val-rmspe:0.1679
[205]	train-rmse:0.105801	val-rmse:0.148915	train-rmspe:0.166965	val-rmspe:0.167637
[206]	train-rmse:0.105685	val-rmse:0.148881	train-rmspe:0.166774	val-rmspe:0.167584
[207]	train-rmse:0.105571	val-rmse:0.1488	train-rmspe:0.1667	val-rmspe:0.167523
[208]	train-rmse:0.105307	val-rmse:0.148628	train-rmspe:0.166564	val-rmspe:0.167358
[

[296]	train-rmse:0.097647	val-rmse:0.145567	train-rmspe:0.140492	val-rmspe:0.163875
[297]	train-rmse:0.097579	val-rmse:0.145657	train-rmspe:0.140281	val-rmspe:0.163923
[298]	train-rmse:0.097462	val-rmse:0.145637	train-rmspe:0.1402	val-rmspe:0.163916
[299]	train-rmse:0.097421	val-rmse:0.145618	train-rmspe:0.13169	val-rmspe:0.163918
[300]	train-rmse:0.097365	val-rmse:0.145601	train-rmspe:0.131612	val-rmspe:0.1639
[301]	train-rmse:0.097237	val-rmse:0.145424	train-rmspe:0.131221	val-rmspe:0.163767
[302]	train-rmse:0.09718	val-rmse:0.145424	train-rmspe:0.131146	val-rmspe:0.163768
[303]	train-rmse:0.097031	val-rmse:0.145346	train-rmspe:0.131014	val-rmspe:0.163657
[304]	train-rmse:0.096984	val-rmse:0.145314	train-rmspe:0.130993	val-rmspe:0.163717
[305]	train-rmse:0.096906	val-rmse:0.145307	train-rmspe:0.130934	val-rmspe:0.163709
[306]	train-rmse:0.096851	val-rmse:0.145275	train-rmspe:0.130889	val-rmspe:0.163674
[307]	train-rmse:0.096767	val-rmse:0.145194	train-rmspe:0.130863	val-rmspe:0.16352

[395]	train-rmse:0.092125	val-rmse:0.144058	train-rmspe:0.123902	val-rmspe:0.161572
[396]	train-rmse:0.092023	val-rmse:0.143987	train-rmspe:0.123836	val-rmspe:0.161562
[397]	train-rmse:0.091904	val-rmse:0.143946	train-rmspe:0.123639	val-rmspe:0.161504
[398]	train-rmse:0.091852	val-rmse:0.14396	train-rmspe:0.123545	val-rmspe:0.161467
[399]	train-rmse:0.091804	val-rmse:0.143842	train-rmspe:0.123488	val-rmspe:0.161338
[400]	train-rmse:0.09177	val-rmse:0.143857	train-rmspe:0.123427	val-rmspe:0.161365
[401]	train-rmse:0.091735	val-rmse:0.143694	train-rmspe:0.123417	val-rmspe:0.16122
[402]	train-rmse:0.091662	val-rmse:0.143685	train-rmspe:0.123331	val-rmspe:0.161215
[403]	train-rmse:0.091619	val-rmse:0.143684	train-rmspe:0.123118	val-rmspe:0.161212
[404]	train-rmse:0.091561	val-rmse:0.143628	train-rmspe:0.123089	val-rmspe:0.161182
[405]	train-rmse:0.091514	val-rmse:0.143623	train-rmspe:0.123041	val-rmspe:0.16114
[406]	train-rmse:0.091477	val-rmse:0.143706	train-rmspe:0.123023	val-rmspe:0.161

[494]	train-rmse:0.088182	val-rmse:0.143471	train-rmspe:0.114873	val-rmspe:0.160398
[495]	train-rmse:0.088156	val-rmse:0.143425	train-rmspe:0.114848	val-rmspe:0.160344
[496]	train-rmse:0.088141	val-rmse:0.14345	train-rmspe:0.11483	val-rmspe:0.160346
[497]	train-rmse:0.088107	val-rmse:0.143461	train-rmspe:0.114853	val-rmspe:0.160383
[498]	train-rmse:0.087994	val-rmse:0.143393	train-rmspe:0.11471	val-rmspe:0.160381
[499]	train-rmse:0.087975	val-rmse:0.143572	train-rmspe:0.114654	val-rmspe:0.160393
[500]	train-rmse:0.087939	val-rmse:0.143569	train-rmspe:0.114607	val-rmspe:0.16031
[501]	train-rmse:0.087918	val-rmse:0.143554	train-rmspe:0.114568	val-rmspe:0.160287
[502]	train-rmse:0.087879	val-rmse:0.143536	train-rmspe:0.114525	val-rmspe:0.160271
[503]	train-rmse:0.087844	val-rmse:0.143546	train-rmspe:0.114569	val-rmspe:0.160269
[504]	train-rmse:0.087818	val-rmse:0.143527	train-rmspe:0.114536	val-rmspe:0.160223
[505]	train-rmse:0.087804	val-rmse:0.143544	train-rmspe:0.11453	val-rmspe:0.1602

[593]	train-rmse:0.085379	val-rmse:0.143012	train-rmspe:0.111251	val-rmspe:0.159352
[594]	train-rmse:0.085361	val-rmse:0.143004	train-rmspe:0.111233	val-rmspe:0.159351
[595]	train-rmse:0.08534	val-rmse:0.142863	train-rmspe:0.111213	val-rmspe:0.159335
[596]	train-rmse:0.085314	val-rmse:0.142889	train-rmspe:0.110972	val-rmspe:0.159333
[597]	train-rmse:0.085285	val-rmse:0.142917	train-rmspe:0.110938	val-rmspe:0.159364
[598]	train-rmse:0.085235	val-rmse:0.14289	train-rmspe:0.110902	val-rmspe:0.159337
[599]	train-rmse:0.085223	val-rmse:0.142898	train-rmspe:0.110879	val-rmspe:0.159324
[600]	train-rmse:0.085204	val-rmse:0.142925	train-rmspe:0.110883	val-rmspe:0.159377
[601]	train-rmse:0.085167	val-rmse:0.142917	train-rmspe:0.105989	val-rmspe:0.159357
[602]	train-rmse:0.085142	val-rmse:0.142909	train-rmspe:0.105964	val-rmspe:0.159339
[603]	train-rmse:0.085111	val-rmse:0.142897	train-rmspe:0.105943	val-rmspe:0.159328
[604]	train-rmse:0.085092	val-rmse:0.142914	train-rmspe:0.105911	val-rmspe:0.1

[692]	train-rmse:0.083289	val-rmse:0.143251	train-rmspe:0.103076	val-rmspe:0.159248
[693]	train-rmse:0.083268	val-rmse:0.143257	train-rmspe:0.103047	val-rmspe:0.15925
[694]	train-rmse:0.083237	val-rmse:0.143306	train-rmspe:0.102861	val-rmspe:0.159325
[695]	train-rmse:0.0832	val-rmse:0.143365	train-rmspe:0.102762	val-rmspe:0.159334
[696]	train-rmse:0.083174	val-rmse:0.143375	train-rmspe:0.102714	val-rmspe:0.159361
[697]	train-rmse:0.083156	val-rmse:0.143372	train-rmspe:0.102681	val-rmspe:0.159399
[698]	train-rmse:0.083145	val-rmse:0.143415	train-rmspe:0.102699	val-rmspe:0.159396
[699]	train-rmse:0.083122	val-rmse:0.143359	train-rmspe:0.102633	val-rmspe:0.159349
[700]	train-rmse:0.0831	val-rmse:0.143299	train-rmspe:0.10263	val-rmspe:0.159362
[701]	train-rmse:0.083083	val-rmse:0.143316	train-rmspe:0.102617	val-rmspe:0.159414
[702]	train-rmse:0.083069	val-rmse:0.143305	train-rmspe:0.102312	val-rmspe:0.159387
[703]	train-rmse:0.083037	val-rmse:0.143318	train-rmspe:0.100755	val-rmspe:0.15939

In [ ]:
#设定参数
param = {'max_depth': 8, 'eta': 0.3, 'silent': 0, 'objective': 'reg:linear', 'min_child_weight': 7, 'colsample_bytree': 0.5, 'subsample':0.5}

#设定迭代次数

num_round = 100000
stopping = 100

#训练并打分
model = train(param, dtrain, dval, num_round, rmspe_feval, stopping)
score(model, dval)

调参完毕后输出结果

In [103]:
dtest = xgb.DMatrix(features_test_pd)
sales_pred = model.predict(dtest)
sales_pred = np.exp(sales_pred) - 1
closed = (features_test_pd['Open'] == 0).values
sales_pred[closed] = 0
submission = pd.DataFrame({'Id':test_data['Id'], 'Sales': sales_pred})
submission = submission.sort_values(by = 'Id')
submission.to_csv('submit-final.csv', index = False)